This notebook contains the entire ETL pipeline executed to generate the county data required for subsequent model training. In short, data is retrieved/imported from xlsx files via the U.S. Census Bureau, cleaned/transformed, enriched with segmentation labels via the unsupervised learning algorithm 'KMeans' and finally joined with the target/labeled outcome binary classifier column. Model composition, training and optimization occur within another repository notebook.

In [1]:
import pandas as pd
import numpy as np
import hvplot.pandas
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from sklearn.cluster import KMeans
from sklearn.impute import SimpleImputer

**Demographic Data Extraction, Transformation & Loading (2012, 2016 & 2019)**
-
-----------

**2012**
-

In [2]:
# Reading in 2012 U.S. Census Bureau demographic dataset
initial_pa_demographic_2012 = pd.read_excel("Resources/PA_Demographics_2012.xlsx")
initial_pa_demographic_2012


Unnamed: 0  \
0                                               Label   
1                                         SEX AND AGE   
2                                    Total population   
3                                                Male   
4                                              Female   
..                                                ...   
81                              Some other race alone   
82                                  Two or more races   
83                Two races including Some other race   
84  Two races excluding Some other race, and Three...   
85                                Total housing units   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
0                     Percent                        Percent   
1                         NaN                            NaN   
2                     101,482                      1,229,338   
3                       49.2%                          48.0%   
4                       50.8%                          52.0%   
..                        ...                            ...   
81                       0.0%                           0.1%   
82                       1.7%                           2.1%   
83                       0.1%                           0.1%   
84                       1.6%                           2.0%   
85                        (X)                            (X)   

   Armstrong County, Pennsylvania Beaver County, Pennsylvania  \
0                         Percent                     Percent   
1                             NaN                         NaN   
2                          68,409                     170,245   
3                           49.6%                       48.3%   
4                           50.4%                       51.7%   
..                            ...                         ...   
81                           0.0%                        0.1%   
82                           0.9%                        1.6%   
83                           0.0%                        0.0%   
84                           0.9%                        1.6%   
85                            (X)                         (X)   

   Berks County, Pennsylvania Blair County, Pennsylvania  \
0                     Percent                    Percent   
1                         NaN                        NaN   
2                     413,491                    127,121   
3                       49.1%                      48.8%   
4                       50.9%                      51.2%   
..                        ...                        ...   
81                       0.0%                       0.0%   
82                       1.2%                       1.6%   
83                       0.0%                       0.0%   
84                       1.2%                       1.6%   
85                        (X)                        (X)   

   Bucks County, Pennsylvania Butler County, Pennsylvania  \
0                     Percent                     Percent   
1                         NaN                         NaN   
2                     627,053                     184,970   
3                       49.0%                       49.6%   
4                       51.0%                       50.4%   
..                        ...                         ...   
81                       0.1%                        0.0%   
82                       1.5%                        1.2%   
83                       0.1%                        0.0%   
84                       1.4%                        1.2%   
85                        (X)                         (X)   

   Cambria County, Pennsylvania  ... Monroe County, Pennsylvania  \
0                       Percent  ...                     Percent   
1                           NaN  ...                         NaN   
2                       141,584  ...                     168,798   
3                         49.6%  ...                       49.0%   
4             

In [3]:
# Retrieving only rows that contain the desired county summary demographic statistics
# % Male, % Female, % Male > 18 Years Old, % Female > 18 Years Old, % White, % Black or African American, % American Indian and Alaska Native, % Asian
initial_pa_demographic_2012 = initial_pa_demographic_2012.iloc[[3, 4, 24, 25, 62, 63, 64, 65], :]
initial_pa_demographic_2012.head(8)


Unnamed: 0 Adams County, Pennsylvania  \
3                                Male                      49.2%   
4                              Female                      50.8%   
24                               Male                      48.6%   
25                             Female                      51.4%   
62                              White                      94.4%   
63          Black or African American                       2.0%   
64  American Indian and Alaska Native                       0.5%   
65                              Asian                       1.0%   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
3                           48.0%                          49.6%   
4                           52.0%                          50.4%   
24                          47.3%                          49.3%   
25                          52.7%                          50.7%   
62                          83.1%                          98.6%   
63                          14.5%                           1.4%   
64                           0.7%                           0.6%   
65                           3.6%                           0.3%   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
3                        48.3%                      49.1%   
4                        51.7%                      50.9%   
24                       47.7%                      48.4%   
25                       52.3%                      51.6%   
62                       92.7%                      87.5%   
63                        7.6%                       6.1%   
64                        0.5%                       1.0%   
65                        0.7%                       1.8%   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
3                       48.8%                      49.0%   
4                       51.2%                      51.0%   
24                      48.0%                      48.4%   
25                      52.0%                      51.6%   
62                      97.7%                      90.9%   
63                       2.4%                       4.5%   
64                       0.7%                       0.5%   
65                       1.2%                       4.8%   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
3                        49.6%                        49.6%  ...   
4                        50.4%                        50.4%  ...   
24                       48.8%                        49.2%  ...   
25                       51.2%                        50.8%  ...   
62                       97.6%                        95.7%  ...   
63                        1.7%                         3.8%  ...   
64                        0.4%                         1.2%  ...   
65                        1.3%                         0.8%  ...   

   Monroe County, Pennsylvania Montgomery County, Pennsylvania  \
3                        49.0%                           48.5%   
4                        51.0%                           51.5%   
24                       48.9%                           47.8%   
25                       51.1%                           52.2%   
62                       82.1%                           83.4%   
63                       15.0%                            9.9%   
64                        0.6%                            0.4%   
65                        2.7%                            7.4%   

   Northampton County, Pennsylvania Northumberland County, Pennsylvania  \
3                             49.2%                               51.0%   
4                             50.8%                               49.0%   
24                            48.4%                               50.7%   
25                            51.6%                               49.3%   
62                            89.3%                               95.2%   
63                             7.0%                 

In [4]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_demographic_2012 = initial_pa_demographic_2012.T
initial_pa_demographic_2012.head()


3       4      24      25     62  \
Unnamed: 0                       Male  Female   Male  Female  White   
Adams County, Pennsylvania      49.2%   50.8%  48.6%   51.4%  94.4%   
Allegheny County, Pennsylvania  48.0%   52.0%  47.3%   52.7%  83.1%   
Armstrong County, Pennsylvania  49.6%   50.4%  49.3%   50.7%  98.6%   
Beaver County, Pennsylvania     48.3%   51.7%  47.7%   52.3%  92.7%   

                                                       63  \
Unnamed: 0                      Black or African American   
Adams County, Pennsylvania                           2.0%   
Allegheny County, Pennsylvania                      14.5%   
Armstrong County, Pennsylvania                       1.4%   
Beaver County, Pennsylvania                          7.6%   

                                                               64     65  
Unnamed: 0                      American Indian and Alaska Native  Asian  
Adams County, Pennsylvania                                   0.5%   1.0%  
Allegheny County, Pennsylvania                               0.7%   3.6%  
Armstrong County, Pennsylvania                               0.6%   0.3%  
Beaver County, Pennsylvania                                  0.5%   0.7%

In [5]:
# Resetting index and renaming to create a 'County' column
initial_pa_demographic_2012 = initial_pa_demographic_2012.reset_index()
initial_pa_demographic_2012.rename(columns={'index': 'County'}, inplace=True)
initial_pa_demographic_2012.head()


County      3       4     24      25     62  \
0                      Unnamed: 0   Male  Female   Male  Female  White   
1      Adams County, Pennsylvania  49.2%   50.8%  48.6%   51.4%  94.4%   
2  Allegheny County, Pennsylvania  48.0%   52.0%  47.3%   52.7%  83.1%   
3  Armstrong County, Pennsylvania  49.6%   50.4%  49.3%   50.7%  98.6%   
4     Beaver County, Pennsylvania  48.3%   51.7%  47.7%   52.3%  92.7%   

                          63                                 64     65  
0  Black or African American  American Indian and Alaska Native  Asian  
1                       2.0%                               0.5%   1.0%  
2                      14.5%                               0.7%   3.6%  
3                       1.4%                               0.6%   0.3%  
4                       7.6%                               0.5%   0.7%

In [6]:
# Confirming column data types prior to renaming
print(initial_pa_demographic_2012.columns)


Index(['County', 3, 4, 24, 25, 62, 63, 64, 65], dtype='object')


In [7]:
# Converting column data types from integers to strings for renaming
initial_pa_demographic_2012.columns = initial_pa_demographic_2012.columns.astype(str)
print(initial_pa_demographic_2012.columns)


Index(['County', '3', '4', '24', '25', '62', '63', '64', '65'], dtype='object')


In [8]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_demographic_2012.replace('N', np.nan, inplace=True)


In [9]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_demographic_2012 = initial_pa_demographic_2012.rename(columns={'3': '% Male', '4': '% Female', '24': '% Male > 18 Years Old',
                                                                         '25': '% Female > 18 Years Old', '62': '% White', '63': '% Black or African American',
                                                                         '64': '% American Indian and Alaska Native', '65': '% Asian'})
initial_pa_demographic_2012 = initial_pa_demographic_2012.drop(0)
initial_pa_demographic_2012 = initial_pa_demographic_2012.reset_index(drop=True)
initial_pa_demographic_2012['County'] = initial_pa_demographic_2012['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_demographic_2012['County'] = initial_pa_demographic_2012['County'].apply(lambda x: x.upper())
initial_pa_demographic_2012.insert(0, 'Year', 2012)
initial_pa_demographic_2012['% Male'] = initial_pa_demographic_2012['% Male'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2012['% Female'] = initial_pa_demographic_2012['% Female'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2012['% Male > 18 Years Old'] = initial_pa_demographic_2012['% Male > 18 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2012['% Female > 18 Years Old'] = initial_pa_demographic_2012['% Female > 18 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2012['% White'] = initial_pa_demographic_2012['% White'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2012['% Black or African American'] = initial_pa_demographic_2012['% Black or African American'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2012['% American Indian and Alaska Native'] = initial_pa_demographic_2012['% American Indian and Alaska Native'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2012['% Asian'] = initial_pa_demographic_2012['% Asian'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2012


Year          County  % Male  % Female  % Male > 18 Years Old  \
0   2012           ADAMS   0.492     0.508                  0.486   
1   2012       ALLEGHENY   0.480     0.520                  0.473   
2   2012       ARMSTRONG   0.496     0.504                  0.493   
3   2012          BEAVER   0.483     0.517                  0.477   
4   2012           BERKS   0.491     0.509                  0.484   
5   2012           BLAIR   0.488     0.512                  0.480   
6   2012           BUCKS   0.490     0.510                  0.484   
7   2012          BUTLER   0.496     0.504                  0.488   
8   2012         CAMBRIA   0.496     0.504                  0.492   
9   2012          CARBON   0.489     0.511                  0.481   
10  2012          CENTRE   0.518     0.482                  0.521   
11  2012         CHESTER   0.491     0.509                  0.485   
12  2012      CLEARFIELD   0.516     0.484                  0.513   
13  2012        COLUMBIA   0.478     0.522                  0.474   
14  2012        CRAWFORD   0.487     0.513                  0.479   
15  2012      CUMBERLAND   0.497     0.503                  0.489   
16  2012         DAUPHIN   0.483     0.517                  0.475   
17  2012        DELAWARE   0.480     0.520                  0.471   
18  2012            ERIE   0.491     0.509                  0.486   
19  2012         FAYETTE   0.494     0.506                  0.490   
20  2012        FRANKLIN   0.487     0.513                  0.481   
21  2012         INDIANA   0.499     0.501                  0.495   
22  2012      LACKAWANNA   0.480     0.520                  0.473   
23  2012       LANCASTER   0.489     0.511                  0.482   
24  2012        LAWRENCE   0.485     0.515                  0.476   
25  2012         LEBANON   0.484     0.516                  0.479   
26  2012          LEHIGH   0.484     0.516                  0.475   
27  2012         LUZERNE   0.493     0.507                  0.486   
28  2012        LYCOMING   0.488     0.512                  0.485   
29  2012          MERCER   0.491     0.509                  0.482   
30  2012          MONROE   0.490     0.510                  0.489   
31  2012      MONTGOMERY   0.485     0.515                  0.478   
32  2012     NORTHAMPTON   0.492     0.508                  0.484   
33  2012  NORTHUMBERLAND   0.510     0.490                  0.507   
34  2012    PHILADELPHIA   0.473     0.527                  0.462   
35  2012      SCHUYLKILL   0.505     0.495                  0.505   
36  2012        SOMERSET   0.517     0.483                  0.518   
37  2012      WASHINGTON   0.488     0.512                  0.483   
38  2012    WESTMORELAND   0.488     0.512                  0.484   
39  2012            YORK   0.493     0.507                  0.488   

    % Female > 18 Years Old  % White  % Black or African American  \
0                     0.514    0.944                        0.020   
1                     0.527    0.831                        0.145   
2                     0.507    0.986                        0.014   
3                     0.523    0.927                        0.076   
4                     0.516    0.875                        0.061   
5                     0.520    0.977                        0.024   
6                     0.516    0.909                        0.045   
7                     0.512    0.976                        0.017   
8                     0.508    0.957                        0.038   
9                     0.519    0.968                        0.030   
10                    0.479    0.907                        0.044   
11                    0.515    0.886                        0.070   
12                    0.487    0.968                        0.027   
13                    0.526    0.976                        0.019   
14                    0.521    0.974                        0.027   
15                    0.511    0.917                        0.044   
1

**2016**
-

In [10]:
# Reading in 2016 U.S. Census Bureau demographic dataset
initial_pa_demographic_2016 = pd.read_excel("Resources/PA_Demographics_2016.xlsx")
initial_pa_demographic_2016


Unnamed: 0 Adams County, Pennsylvania  \
0                             Label                    Percent   
1                       SEX AND AGE                        NaN   
2                  Total population                    102,180   
3                              Male                      49.3%   
4                            Female                      50.7%   
..                              ...                        ...   
85              Total housing units                        (X)   
86   CITIZEN, VOTING AGE POPULATION                        NaN   
87  Citizen, 18 and over population                     79,061   
88                             Male                      48.6%   
89                           Female                      51.4%   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
0                         Percent                        Percent   
1                             NaN                            NaN   
2                       1,225,365                         66,486   
3                           48.3%                          49.7%   
4                           51.7%                          50.3%   
..                            ...                            ...   
85                            (X)                            (X)   
86                            NaN                            NaN   
87                        959,493                         53,519   
88                          47.5%                          49.3%   
89                          52.5%                          50.7%   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
0                      Percent                    Percent   
1                          NaN                        NaN   
2                      167,429                    414,812   
3                        48.7%                      49.3%   
4                        51.3%                      50.7%   
..                         ...                        ...   
85                         (X)                        (X)   
86                         NaN                        NaN   
87                     133,884                    307,577   
88                       48.3%                      49.0%   
89                       51.7%                      51.0%   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
0                     Percent                    Percent   
1                         NaN                        NaN   
2                     124,650                    626,399   
3                       49.0%                      49.1%   
4                       51.0%                      50.9%   
..                        ...                        ...   
85                        (X)                        (X)   
86                        NaN                        NaN   
87                     98,678                    473,185   
88                      48.0%                      48.5%   
89                      52.0%                      51.5%   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
0                      Percent                      Percent  ...   
1                          NaN                          NaN  ...   
2                      186,847                      134,732  ...   
3                        49.7%                        49.1%  ...   
4                        50.3%                        50.9%  ...   
..                         ...                          ...  ...   
85                         (X)                          (X)  ...   
86                         NaN                          NaN  ...   
87                     146,228                      108,117  ...   
88                       48.9%                        48.4%  ...   
89                       51.1%                        51.6%  ...   

   Monroe County, Pennsylvania Montgomery County, Pennsylvania  \
0                      Percent                         Percent   
1           

In [11]:
# Retrieving only rows that contain the desired county summary demographic statistics
# % Male, % Female, % Male > 18 Years Old, % Female > 18 Years Old, % White, % Black or African American, % American Indian and Alaska Native, % Asian
initial_pa_demographic_2016 = initial_pa_demographic_2016.iloc[[3, 4, 24, 25, 62, 63, 64, 65], :]
initial_pa_demographic_2016.head(8)


Unnamed: 0 Adams County, Pennsylvania  \
3                                Male                      49.3%   
4                              Female                      50.7%   
24                               Male                      49.0%   
25                             Female                      51.0%   
62                              White                      94.8%   
63          Black or African American                       1.9%   
64  American Indian and Alaska Native                       1.0%   
65                              Asian                       1.1%   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
3                           48.3%                          49.7%   
4                           51.7%                          50.3%   
24                          47.7%                          49.3%   
25                          52.3%                          50.7%   
62                          82.8%                          98.8%   
63                          14.7%                           0.5%   
64                           0.8%                           0.6%   
65                           4.3%                           1.0%   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
3                        48.7%                      49.3%   
4                        51.3%                      50.7%   
24                       48.2%                      48.6%   
25                       51.8%                      51.4%   
62                       93.5%                      89.2%   
63                        7.4%                       8.6%   
64                        0.5%                       4.0%   
65                        0.8%                       1.8%   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
3                       49.0%                      49.1%   
4                       51.0%                      50.9%   
24                      48.0%                      48.5%   
25                      52.0%                      51.5%   
62                      96.8%                      90.0%   
63                       2.6%                       4.9%   
64                       0.3%                       0.6%   
65                       1.0%                       5.4%   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
3                        49.7%                        49.1%  ...   
4                        50.3%                        50.9%  ...   
24                       49.0%                        48.6%  ...   
25                       51.0%                        51.4%  ...   
62                       96.9%                        96.4%  ...   
63                        1.6%                         4.0%  ...   
64                        0.3%                         1.2%  ...   
65                        1.8%                         0.8%  ...   

   Monroe County, Pennsylvania Montgomery County, Pennsylvania  \
3                        49.6%                           48.6%   
4                        50.4%                           51.4%   
24                       49.0%                           47.9%   
25                       51.0%                           52.1%   
62                       77.8%                           81.9%   
63                       15.9%                           10.4%   
64                        0.8%                            0.7%   
65                        2.9%                            8.3%   

   Northampton County, Pennsylvania Northumberland County, Pennsylvania  \
3                             49.4%                               51.1%   
4                             50.6%                               48.9%   
24                            48.6%                               50.7%   
25                            51.4%                               49.3%   
62                            89.9%                               95.8%   
63                             7.4%                 

In [12]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_demographic_2016 = initial_pa_demographic_2016.T
initial_pa_demographic_2016.head()


3       4      24      25     62  \
Unnamed: 0                       Male  Female   Male  Female  White   
Adams County, Pennsylvania      49.3%   50.7%  49.0%   51.0%  94.8%   
Allegheny County, Pennsylvania  48.3%   51.7%  47.7%   52.3%  82.8%   
Armstrong County, Pennsylvania  49.7%   50.3%  49.3%   50.7%  98.8%   
Beaver County, Pennsylvania     48.7%   51.3%  48.2%   51.8%  93.5%   

                                                       63  \
Unnamed: 0                      Black or African American   
Adams County, Pennsylvania                           1.9%   
Allegheny County, Pennsylvania                      14.7%   
Armstrong County, Pennsylvania                       0.5%   
Beaver County, Pennsylvania                          7.4%   

                                                               64     65  
Unnamed: 0                      American Indian and Alaska Native  Asian  
Adams County, Pennsylvania                                   1.0%   1.1%  
Allegheny County, Pennsylvania                               0.8%   4.3%  
Armstrong County, Pennsylvania                               0.6%   1.0%  
Beaver County, Pennsylvania                                  0.5%   0.8%

In [13]:
# Resetting index and renaming to create a 'County' column
initial_pa_demographic_2016 = initial_pa_demographic_2016.reset_index()
initial_pa_demographic_2016.rename(columns={'index': 'County'}, inplace=True)
initial_pa_demographic_2016.head()


County      3       4     24      25     62  \
0                      Unnamed: 0   Male  Female   Male  Female  White   
1      Adams County, Pennsylvania  49.3%   50.7%  49.0%   51.0%  94.8%   
2  Allegheny County, Pennsylvania  48.3%   51.7%  47.7%   52.3%  82.8%   
3  Armstrong County, Pennsylvania  49.7%   50.3%  49.3%   50.7%  98.8%   
4     Beaver County, Pennsylvania  48.7%   51.3%  48.2%   51.8%  93.5%   

                          63                                 64     65  
0  Black or African American  American Indian and Alaska Native  Asian  
1                       1.9%                               1.0%   1.1%  
2                      14.7%                               0.8%   4.3%  
3                       0.5%                               0.6%   1.0%  
4                       7.4%                               0.5%   0.8%

In [14]:
# Confirming column data types prior to renaming
print(initial_pa_demographic_2016.columns)


Index(['County', 3, 4, 24, 25, 62, 63, 64, 65], dtype='object')


In [15]:
# Converting column data types from integers to strings for renaming
initial_pa_demographic_2016.columns = initial_pa_demographic_2016.columns.astype(str)
print(initial_pa_demographic_2016.columns)


Index(['County', '3', '4', '24', '25', '62', '63', '64', '65'], dtype='object')


In [16]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_demographic_2016.replace('N', np.nan, inplace=True)


In [17]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_demographic_2016 = initial_pa_demographic_2016.rename(columns={'3': '% Male', '4': '% Female', '24': '% Male > 18 Years Old',
                                                                         '25': '% Female > 18 Years Old', '62': '% White', '63': '% Black or African American',
                                                                         '64': '% American Indian and Alaska Native', '65': '% Asian'})
initial_pa_demographic_2016 = initial_pa_demographic_2016.drop(0)
initial_pa_demographic_2016 = initial_pa_demographic_2016.reset_index(drop=True)
initial_pa_demographic_2016['County'] = initial_pa_demographic_2016['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_demographic_2016['County'] = initial_pa_demographic_2016['County'].apply(lambda x: x.upper())
initial_pa_demographic_2016.insert(0, 'Year', 2016)
initial_pa_demographic_2016['% Male'] = initial_pa_demographic_2016['% Male'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2016['% Female'] = initial_pa_demographic_2016['% Female'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2016['% Male > 18 Years Old'] = initial_pa_demographic_2016['% Male > 18 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2016['% Female > 18 Years Old'] = initial_pa_demographic_2016['% Female > 18 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2016['% White'] = initial_pa_demographic_2016['% White'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2016['% Black or African American'] = initial_pa_demographic_2016['% Black or African American'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2016['% American Indian and Alaska Native'] = initial_pa_demographic_2016['% American Indian and Alaska Native'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2016['% Asian'] = initial_pa_demographic_2016['% Asian'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2016


Year          County  % Male  % Female  % Male > 18 Years Old  \
0   2016           ADAMS   0.493     0.507                  0.490   
1   2016       ALLEGHENY   0.483     0.517                  0.477   
2   2016       ARMSTRONG   0.497     0.503                  0.493   
3   2016          BEAVER   0.487     0.513                  0.482   
4   2016           BERKS   0.493     0.507                  0.486   
5   2016           BLAIR   0.490     0.510                  0.480   
6   2016           BUCKS   0.491     0.509                  0.485   
7   2016          BUTLER   0.497     0.503                  0.490   
8   2016         CAMBRIA   0.491     0.509                  0.486   
9   2016          CARBON   0.505     0.495                  0.500   
10  2016          CENTRE   0.528     0.472                  0.535   
11  2016         CHESTER   0.492     0.508                  0.487   
12  2016      CLEARFIELD   0.524     0.476                  0.526   
13  2016        COLUMBIA   0.477     0.523                  0.470   
14  2016        CRAWFORD   0.488     0.512                  0.483   
15  2016      CUMBERLAND   0.495     0.505                  0.489   
16  2016         DAUPHIN   0.482     0.518                  0.475   
17  2016        DELAWARE   0.481     0.519                  0.472   
18  2016            ERIE   0.494     0.506                  0.489   
19  2016         FAYETTE   0.493     0.507                  0.488   
20  2016        FRANKLIN   0.498     0.502                  0.487   
21  2016         INDIANA   0.505     0.495                  0.505   
22  2016      LACKAWANNA   0.482     0.518                  0.477   
23  2016       LANCASTER   0.490     0.510                  0.483   
24  2016        LAWRENCE   0.490     0.510                  0.482   
25  2016         LEBANON   0.487     0.513                  0.479   
26  2016          LEHIGH   0.489     0.511                  0.480   
27  2016         LUZERNE   0.491     0.509                  0.489   
28  2016        LYCOMING   0.488     0.512                  0.481   
29  2016          MERCER   0.493     0.507                  0.492   
30  2016          MONROE   0.496     0.504                  0.490   
31  2016      MONTGOMERY   0.486     0.514                  0.479   
32  2016     NORTHAMPTON   0.494     0.506                  0.486   
33  2016  NORTHUMBERLAND   0.511     0.489                  0.507   
34  2016    PHILADELPHIA   0.474     0.526                  0.463   
35  2016      SCHUYLKILL   0.512     0.488                  0.513   
36  2016        SOMERSET   0.516     0.484                  0.519   
37  2016      WASHINGTON   0.489     0.511                  0.483   
38  2016    WESTMORELAND   0.488     0.512                  0.483   
39  2016            YORK   0.493     0.507                  0.488   

    % Female > 18 Years Old  % White  % Black or African American  \
0                     0.510    0.948                        0.019   
1                     0.523    0.828                        0.147   
2                     0.507    0.988                        0.005   
3                     0.518    0.935                        0.074   
4                     0.514    0.892                        0.086   
5                     0.520    0.968                        0.026   
6                     0.515    0.900                        0.049   
7                     0.510    0.969                        0.016   
8                     0.514    0.964                        0.040   
9                     0.500    0.963                        0.031   
10                    0.465    0.898                        0.042   
11                    0.513    0.875                        0.069   
12                    0.474    0.953                        0.034   
13                    0.530    0.951                        0.027   
14                    0.517    0.972                        0.025   
15                    0.511    0.897                        0.049   
1

**2019**
-
Please note: 2020 United States Census Bureau was unavailable and as such the closest year prior to the election (2019) was utilized

In [18]:
# Reading in 2019 U.S. Census Bureau demographic dataset
initial_pa_demographic_2019 = pd.read_excel("Resources/PA_Demographics_2019.xlsx")
initial_pa_demographic_2019


Unnamed: 0 Adams County, Pennsylvania  \
0                             Label                    Percent   
1                       SEX AND AGE                        NaN   
2                  Total population                    103,009   
3                              Male                      49.4%   
4                            Female                      50.6%   
..                              ...                        ...   
90              Total housing units                        (X)   
91   CITIZEN, VOTING AGE POPULATION                        NaN   
92  Citizen, 18 and over population                     81,064   
93                             Male                      48.5%   
94                           Female                      51.5%   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
0                         Percent                        Percent   
1                             NaN                            NaN   
2                       1,216,045                         64,735   
3                           48.4%                          50.1%   
4                           51.6%                          49.9%   
..                            ...                            ...   
90                            (X)                            (X)   
91                            NaN                            NaN   
92                        953,365                         52,096   
93                          47.5%                          49.9%   
94                          52.5%                          50.1%   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
0                      Percent                    Percent   
1                          NaN                        NaN   
2                      163,929                    421,164   
3                        48.3%                      49.2%   
4                        51.7%                      50.8%   
..                         ...                        ...   
90                         (X)                        (X)   
91                         NaN                        NaN   
92                     131,153                    316,613   
93                       47.8%                      48.9%   
94                       52.2%                      51.1%   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
0                     Percent                    Percent   
1                         NaN                        NaN   
2                     121,829                    628,270   
3                       49.1%                      49.1%   
4                       50.9%                      50.9%   
..                        ...                        ...   
90                        (X)                        (X)   
91                        NaN                        NaN   
92                     96,704                    479,735   
93                      48.3%                      48.3%   
94                      51.7%                      51.7%   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
0                      Percent                      Percent  ...   
1                          NaN                          NaN  ...   
2                      187,853                      130,192  ...   
3                        49.1%                        49.0%  ...   
4                        50.9%                        51.0%  ...   
..                         ...                          ...  ...   
90                         (X)                          (X)  ...   
91                         NaN                          NaN  ...   
92                     149,363                      105,148  ...   
93                       48.6%                        48.5%  ...   
94                       51.4%                        51.5%  ...   

   Monroe County, Pennsylvania Montgomery County, Pennsylvania  \
0                      Percent                         Percent   
1           

In [19]:
# Retrieving only rows that contain the desired county summary demographic statistics
# % Male, % Female, % Male > 18 Years Old, % Female > 18 Years Old, % White, % Black or African American, % American Indian and Alaska Native, % Asian
initial_pa_demographic_2019 = initial_pa_demographic_2019.iloc[[3, 4, 27, 28, 67, 68, 69, 70], :]
initial_pa_demographic_2019.head(8)


Unnamed: 0 Adams County, Pennsylvania  \
3                                Male                      49.4%   
4                              Female                      50.6%   
27                               Male                      48.7%   
28                             Female                      51.3%   
67                              White                      94.4%   
68          Black or African American                       3.0%   
69  American Indian and Alaska Native                       0.7%   
70                              Asian                       1.2%   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
3                           48.4%                          50.1%   
4                           51.6%                          49.9%   
27                          47.8%                          49.8%   
28                          52.2%                          50.2%   
67                          82.1%                          98.1%   
68                          14.7%                           2.1%   
69                           0.6%                              N   
70                           4.8%                           0.4%   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
3                        48.3%                      49.2%   
4                        51.7%                      50.8%   
27                       47.9%                      48.7%   
28                       52.1%                      51.3%   
67                       92.9%                      82.4%   
68                        8.4%                       7.5%   
69                        0.5%                       0.5%   
70                        0.9%                       1.7%   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
3                       49.1%                      49.1%   
4                       50.9%                      50.9%   
27                      48.2%                      48.6%   
28                      51.8%                      51.4%   
67                      97.5%                      88.6%   
68                       3.3%                       5.1%   
69                          N                       0.4%   
70                       0.4%                       5.9%   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
3                        49.1%                        49.0%  ...   
4                        50.9%                        51.0%  ...   
27                       48.6%                        48.4%  ...   
28                       51.4%                        51.6%  ...   
67                       97.6%                        94.9%  ...   
68                        1.7%                         5.4%  ...   
69                        0.4%                         0.2%  ...   
70                        1.9%                         0.7%  ...   

   Monroe County, Pennsylvania Montgomery County, Pennsylvania  \
3                        49.5%                           48.6%   
4                        50.5%                           51.4%   
27                       49.2%                           48.0%   
28                       50.8%                           52.0%   
67                       80.4%                           81.3%   
68                       15.8%                           10.9%   
69                        1.3%                            0.5%   
70                        3.5%                            8.8%   

   Northampton County, Pennsylvania Northumberland County, Pennsylvania  \
3                             49.3%                               50.6%   
4                             50.7%                               49.4%   
27                            48.6%                               50.4%   
28                            51.4%                               49.6%   
67                            86.5%                               96.0%   
68                             7.5%                 

In [20]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_demographic_2019 = initial_pa_demographic_2019.T
initial_pa_demographic_2019.head()


3       4      27      28     67  \
Unnamed: 0                       Male  Female   Male  Female  White   
Adams County, Pennsylvania      49.4%   50.6%  48.7%   51.3%  94.4%   
Allegheny County, Pennsylvania  48.4%   51.6%  47.8%   52.2%  82.1%   
Armstrong County, Pennsylvania  50.1%   49.9%  49.8%   50.2%  98.1%   
Beaver County, Pennsylvania     48.3%   51.7%  47.9%   52.1%  92.9%   

                                                       68  \
Unnamed: 0                      Black or African American   
Adams County, Pennsylvania                           3.0%   
Allegheny County, Pennsylvania                      14.7%   
Armstrong County, Pennsylvania                       2.1%   
Beaver County, Pennsylvania                          8.4%   

                                                               69     70  
Unnamed: 0                      American Indian and Alaska Native  Asian  
Adams County, Pennsylvania                                   0.7%   1.2%  
Allegheny County, Pennsylvania                               0.6%   4.8%  
Armstrong County, Pennsylvania                                  N   0.4%  
Beaver County, Pennsylvania                                  0.5%   0.9%

In [21]:
# Resetting index and renaming to create a 'County' column
initial_pa_demographic_2019 = initial_pa_demographic_2019.reset_index()
initial_pa_demographic_2019.rename(columns={'index': 'County'}, inplace=True)
initial_pa_demographic_2019.head()


County      3       4     27      28     67  \
0                      Unnamed: 0   Male  Female   Male  Female  White   
1      Adams County, Pennsylvania  49.4%   50.6%  48.7%   51.3%  94.4%   
2  Allegheny County, Pennsylvania  48.4%   51.6%  47.8%   52.2%  82.1%   
3  Armstrong County, Pennsylvania  50.1%   49.9%  49.8%   50.2%  98.1%   
4     Beaver County, Pennsylvania  48.3%   51.7%  47.9%   52.1%  92.9%   

                          68                                 69     70  
0  Black or African American  American Indian and Alaska Native  Asian  
1                       3.0%                               0.7%   1.2%  
2                      14.7%                               0.6%   4.8%  
3                       2.1%                                  N   0.4%  
4                       8.4%                               0.5%   0.9%

In [22]:
# Confirming column data types prior to renaming
print(initial_pa_demographic_2019.columns)


Index(['County', 3, 4, 27, 28, 67, 68, 69, 70], dtype='object')


In [23]:
# Converting column data types from integers to strings for renaming
initial_pa_demographic_2019.columns = initial_pa_demographic_2019.columns.astype(str)
print(initial_pa_demographic_2019.columns)


Index(['County', '3', '4', '27', '28', '67', '68', '69', '70'], dtype='object')


In [24]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_demographic_2019.replace('N', np.nan, inplace=True)


In [25]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_demographic_2019 = initial_pa_demographic_2019.rename(columns={'3': '% Male', '4': '% Female', '27': '% Male > 18 Years Old',
                                                                         '28': '% Female > 18 Years Old', '67': '% White', '68': '% Black or African American',
                                                                         '69': '% American Indian and Alaska Native', '70': '% Asian'})
initial_pa_demographic_2019 = initial_pa_demographic_2019.drop(0)
initial_pa_demographic_2019 = initial_pa_demographic_2019.reset_index(drop=True)
initial_pa_demographic_2019['County'] = initial_pa_demographic_2019['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_demographic_2019['County'] = initial_pa_demographic_2019['County'].apply(lambda x: x.upper())
initial_pa_demographic_2019.insert(0, 'Year', 2020)
initial_pa_demographic_2019['% Male'] = initial_pa_demographic_2019['% Male'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2019['% Female'] = initial_pa_demographic_2019['% Female'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2019['% Male > 18 Years Old'] = initial_pa_demographic_2019['% Male > 18 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2019['% Female > 18 Years Old'] = initial_pa_demographic_2019['% Female > 18 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2019['% White'] = initial_pa_demographic_2019['% White'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2019['% Black or African American'] = initial_pa_demographic_2019['% Black or African American'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2019['% American Indian and Alaska Native'] = initial_pa_demographic_2019['% American Indian and Alaska Native'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2019['% Asian'] = initial_pa_demographic_2019['% Asian'].str.rstrip('%').astype(float) / 100
initial_pa_demographic_2019


Year          County  % Male  % Female  % Male > 18 Years Old  \
0   2020           ADAMS   0.494     0.506                  0.487   
1   2020       ALLEGHENY   0.484     0.516                  0.478   
2   2020       ARMSTRONG   0.501     0.499                  0.498   
3   2020          BEAVER   0.483     0.517                  0.479   
4   2020           BERKS   0.492     0.508                  0.487   
5   2020           BLAIR   0.491     0.509                  0.482   
6   2020           BUCKS   0.491     0.509                  0.486   
7   2020          BUTLER   0.491     0.509                  0.486   
8   2020         CAMBRIA   0.490     0.510                  0.484   
9   2020          CARBON   0.499     0.501                  0.498   
10  2020          CENTRE   0.523     0.477                  0.525   
11  2020         CHESTER   0.494     0.506                  0.488   
12  2020      CLEARFIELD   0.532     0.468                  0.534   
13  2020        COLUMBIA   0.484     0.516                  0.479   
14  2020        CRAWFORD   0.486     0.514                  0.479   
15  2020      CUMBERLAND   0.495     0.505                  0.491   
16  2020         DAUPHIN   0.487     0.513                  0.478   
17  2020        DELAWARE   0.482     0.518                  0.473   
18  2020            ERIE   0.489     0.511                  0.487   
19  2020         FAYETTE   0.493     0.507                  0.494   
20  2020        FRANKLIN   0.492     0.508                  0.485   
21  2020         INDIANA   0.500     0.500                  0.498   
22  2020      LACKAWANNA   0.485     0.515                  0.478   
23  2020       LANCASTER   0.489     0.511                  0.483   
24  2020        LAWRENCE   0.486     0.514                  0.483   
25  2020         LEBANON   0.493     0.507                  0.489   
26  2020          LEHIGH   0.490     0.510                  0.483   
27  2020         LUZERNE   0.494     0.506                  0.491   
28  2020        LYCOMING   0.493     0.507                  0.487   
29  2020          MERCER   0.490     0.510                  0.483   
30  2020          MONROE   0.495     0.505                  0.492   
31  2020      MONTGOMERY   0.486     0.514                  0.480   
32  2020     NORTHAMPTON   0.493     0.507                  0.486   
33  2020  NORTHUMBERLAND   0.506     0.494                  0.504   
34  2020    PHILADELPHIA   0.473     0.527                  0.463   
35  2020      SCHUYLKILL   0.515     0.485                  0.513   
36  2020        SOMERSET   0.522     0.478                  0.524   
37  2020      WASHINGTON   0.491     0.509                  0.486   
38  2020    WESTMORELAND   0.491     0.509                  0.485   
39  2020            YORK   0.496     0.504                  0.488   

    % Female > 18 Years Old  % White  % Black or African American  \
0                     0.513    0.944                        0.030   
1                     0.522    0.821                        0.147   
2                     0.502    0.981                        0.021   
3                     0.521    0.929                        0.084   
4                     0.513    0.824                        0.075   
5                     0.518    0.975                        0.033   
6                     0.514    0.886                        0.051   
7                     0.514    0.976                        0.017   
8                     0.516    0.949                        0.054   
9                     0.502    0.942                        0.029   
10                    0.475    0.898                        0.044   
11                    0.512    0.851                        0.072   
12                    0.466    0.945                        0.039   
13                    0.521    0.960                        0.014   
14                    0.521    0.968                        0.026   
15                    0.509    0.894                        0.061   
1

**Education Data Extraction, Transformation & Loading (2012, 2016 & 2019)**
-
-----------

**2012**
-

In [26]:
# Reading in 2012 U.S. Census Bureau education dataset
initial_pa_education_2012 = pd.read_excel("Resources/PA_Education_2012.xlsx")
initial_pa_education_2012


Unnamed: 0  \
0                                                 NaN   
1                                               Label   
2                           Population 18 to 24 years   
3                      Less than high school graduate   
4         High school graduate (includes equivalency)   
5                  Some college or associate's degree   
6                         Bachelor's degree or higher   
7                        Population 25 years and over   
8                                 Less than 9th grade   
9                       9th to 12th grade, no diploma   
10        High school graduate (includes equivalency)   
11                            Some college, no degree   
12                                 Associate's degree   
13                                  Bachelor's degree   
14                    Graduate or professional degree   
15             Percent high school graduate or higher   
16                Percent bachelor's degree or higher   
17                          Population 25 to 34 years   
18                     High school graduate or higher   
19                        Bachelor's degree or higher   
20                          Population 35 to 44 years   
21                     High school graduate or higher   
22                        Bachelor's degree or higher   
23                          Population 45 to 64 years   
24                     High school graduate or higher   
25                        Bachelor's degree or higher   
26                       Population 65 years and over   
27                     High school graduate or higher   
28                        Bachelor's degree or higher   
29  POVERTY RATE FOR THE POPULATION 25 YEARS AND O...   
30                     Less than high school graduate   
31        High school graduate (includes equivalency)   
32                 Some college or associate's degree   
33                        Bachelor's degree or higher   
34  MEDIAN EARNINGS IN THE PAST 12 MONTHS (IN 2012...   
35         Population 25 years and over with earnings   
36                     Less than high school graduate   
37        High school graduate (includes equivalency)   
38                 Some college or associate's degree   
39                                  Bachelor's degree   
40                    Graduate or professional degree   
41                                    PERCENT IMPUTED   
42                             Educational attainment   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
0                       Total                          Total   
1                    Estimate                       Estimate   
2                      10,743                        120,782   
3                       11.4%                          10.6%   
4                       36.1%                          25.7%   
5                       47.5%                          44.1%   
6                        4.9%                          19.5%   
7                      69,168                        871,384   
8                        6.0%                           2.0%   
9                        9.2%                           4.5%   
10                      40.8%                          29.8%   
11                      16.0%                          17.2%   
12                       7.3%                           9.8%   
13                      12.5%                          21.6%   
14                       8.3%                          15.2%   
15                      84.9%                          93.6%   
16                      20.8%                          36.8%   
17                      9,906                        171,622   
18                      91.9%                          96.7%   
19                      21.9%                          51.5%   
20                     12,130                        141,804   
21                      86.9%                          96.2%   
22                      20.7%                          45.3%  

In [27]:
# Retrieving only rows that contain the desired county summary demographic statistics
# % High School Graduate & % Bachelor's degree or higher for 18 to 24 years old and % High School Graduate or Higher and % Bachelor's degree or higher for the remaining age groups:
# 25 to 34, 35 to 44, 45 to 64 and 65 & older
initial_pa_education_2012 = initial_pa_education_2012.iloc[[4, 6, 18, 19, 21, 22, 24, 25, 27, 28], :]
initial_pa_education_2012


Unnamed: 0 Adams County, Pennsylvania  \
4   High school graduate (includes equivalency)                      36.1%   
6                   Bachelor's degree or higher                       4.9%   
18               High school graduate or higher                      91.9%   
19                  Bachelor's degree or higher                      21.9%   
21               High school graduate or higher                      86.9%   
22                  Bachelor's degree or higher                      20.7%   
24               High school graduate or higher                      88.3%   
25                  Bachelor's degree or higher                      22.3%   
27               High school graduate or higher                      73.4%   
28                  Bachelor's degree or higher                      17.7%   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
4                           25.7%                          47.9%   
6                           19.5%                          10.4%   
18                          96.7%                          95.1%   
19                          51.5%                          25.0%   
21                          96.2%                          93.3%   
22                          45.3%                          18.6%   
24                          95.4%                          93.0%   
25                          34.8%                          14.7%   
27                          86.2%                          75.4%   
28                          22.4%                          11.6%   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
4                        29.1%                      36.7%   
6                        12.6%                       5.8%   
18                       93.5%                      84.6%   
19                       33.7%                      27.5%   
21                       95.6%                      87.3%   
22                       24.5%                      26.5%   
24                       95.1%                      89.1%   
25                       21.4%                      22.9%   
27                       80.4%                      72.5%   
28                       12.3%                      13.0%   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
4                       47.2%                      34.2%   
6                        7.0%                      14.9%   
18                      92.8%                      94.9%   
19                      22.9%                      38.8%   
21                      95.4%                      96.3%   
22                      25.8%                      45.9%   
24                      93.0%                      95.4%   
25                      17.9%                      36.7%   
27                      82.0%                      85.6%   
28                       9.2%                      26.1%   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
4                        29.7%                        31.8%  ...   
6                         9.9%                         6.5%  ...   
18                       96.9%                        94.7%  ...   
19                       38.7%                        27.1%  ...   
21                       95.8%                        93.2%  ...   
22                       39.3%                        23.2%  ...   
24                       94.0%                        94.1%  ...   
25                       27.7%                        19.0%  ...   
27                       81.9%                        79.0%  ...   
28                       20.7%                         9.4%  ...   

   Monroe County, Pennsylvania Montgomery County, Pennsylvania  \
4                        34.5%                           33.6%   
6                         5.2%                           16.1%   
18                       93.5%                           96.4%   
19                       24.1%                           54.8%   
21               

In [28]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_education_2012 = initial_pa_education_2012.T
initial_pa_education_2012.head()


4   \
Unnamed: 0                      High school graduate (includes equivalency)   
Adams County, Pennsylvania                                            36.1%   
Allegheny County, Pennsylvania                                        25.7%   
Armstrong County, Pennsylvania                                        47.9%   
Beaver County, Pennsylvania                                           29.1%   

                                                         6   \
Unnamed: 0                      Bachelor's degree or higher   
Adams County, Pennsylvania                             4.9%   
Allegheny County, Pennsylvania                        19.5%   
Armstrong County, Pennsylvania                        10.4%   
Beaver County, Pennsylvania                           12.6%   

                                                            18  \
Unnamed: 0                      High school graduate or higher   
Adams County, Pennsylvania                               91.9%   
Allegheny County, Pennsylvania                           96.7%   
Armstrong County, Pennsylvania                           95.1%   
Beaver County, Pennsylvania                              93.5%   

                                                         19  \
Unnamed: 0                      Bachelor's degree or higher   
Adams County, Pennsylvania                            21.9%   
Allegheny County, Pennsylvania                        51.5%   
Armstrong County, Pennsylvania                        25.0%   
Beaver County, Pennsylvania                           33.7%   

                                                            21  \
Unnamed: 0                      High school graduate or higher   
Adams County, Pennsylvania                               86.9%   
Allegheny County, Pennsylvania                           96.2%   
Armstrong County, Pennsylvania                           93.3%   
Beaver County, Pennsylvania                              95.6%   

                                                         22  \
Unnamed: 0                      Bachelor's degree or higher   
Adams County, Pennsylvania                            20.7%   
Allegheny County, Pennsylvania                        45.3%   
Armstrong County, Pennsylvania                        18.6%   
Beaver County, Pennsylvania                           24.5%   

                                                            24  \
Unnamed: 0                      High school graduate or higher   
Adams County, Pennsylvania                               88.3%   
Allegheny County, Pennsylvania                           95.4%   
Armstrong County, Pennsylvania                           93.0%   
Beaver County, Pennsylvania                              95.1%   

                                                         25  \
Unnamed: 0                      Bachelor's degree or higher   
Adams County, Pennsylvania                            22.3%   
Allegheny County, Pennsylvania                        34.8%   
Armstrong County, Pennsylvania                        14.7%   
Beaver County, Pennsylvania                           21.4%   

                                                            27  \
Unnamed: 0                      High school graduate or higher   
Adams County, Pennsylvania                               73.4%   
Allegheny County, Pennsylvania                           86.2%   
Armstrong County, Pennsylvania                           75.4%   
Beaver County, Pennsylvania                              80.4%   

                                                         28  
Unnamed: 0                      Bachelor's degree or higher  
Adams County, Pennsylvania                            17.7%  
Allegheny County, Pennsylvania                        22.4%  
Armstrong County, Pennsylvania                        11.6%  
Beaver County, Pennsylvania                           12.3%

In [29]:
# Resetting index and renaming to create a 'County' column
initial_pa_education_2012 = initial_pa_education_2012.reset_index()
initial_pa_education_2012.rename(columns={'index': 'County'}, inplace=True)
initial_pa_education_2012.head()


County  \
0                      Unnamed: 0   
1      Adams County, Pennsylvania   
2  Allegheny County, Pennsylvania   
3  Armstrong County, Pennsylvania   
4     Beaver County, Pennsylvania   

                                             4                            6  \
0  High school graduate (includes equivalency)  Bachelor's degree or higher   
1                                        36.1%                         4.9%   
2                                        25.7%                        19.5%   
3                                        47.9%                        10.4%   
4                                        29.1%                        12.6%   

                               18                           19  \
0  High school graduate or higher  Bachelor's degree or higher   
1                           91.9%                        21.9%   
2                           96.7%                        51.5%   
3                           95.1%                        25.0%   
4                           93.5%                        33.7%   

                               21                           22  \
0  High school graduate or higher  Bachelor's degree or higher   
1                           86.9%                        20.7%   
2                           96.2%                        45.3%   
3                           93.3%                        18.6%   
4                           95.6%                        24.5%   

                               24                           25  \
0  High school graduate or higher  Bachelor's degree or higher   
1                           88.3%                        22.3%   
2                           95.4%                        34.8%   
3                           93.0%                        14.7%   
4                           95.1%                        21.4%   

                               27                           28  
0  High school graduate or higher  Bachelor's degree or higher  
1                           73.4%                        17.7%  
2                           86.2%                        22.4%  
3                           75.4%                        11.6%  
4                           80.4%                        12.3%

In [30]:
# Confirming column data types prior to renaming
print(initial_pa_education_2012.columns)


Index(['County', 4, 6, 18, 19, 21, 22, 24, 25, 27, 28], dtype='object')


In [31]:
# Converting column data types from integers to strings for renaming
initial_pa_education_2012.columns = initial_pa_education_2012.columns.astype(str)
print(initial_pa_education_2012.columns)


Index(['County', '4', '6', '18', '19', '21', '22', '24', '25', '27', '28'], dtype='object')


In [32]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_education_2012.replace('N', np.nan, inplace=True)


In [33]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_education_2012 = initial_pa_education_2012.rename(columns={'4': '% High School Graduate (18-24)', '6': '% Bachelors Degree or Higher (18-24)', '18': '% High School Graduate or Higher (25-34)',
                                                                         '19': '% Bachelors Degree or Higher (25-34)', '21': '% High School Graduate or Higher (35-44)', '22': '% Bachelors Degree or Higher (35-44)',
                                                                         '24': '% High School Graduate or Higher (45-64)', '25': '% Bachelors Degree or Higher (45-64)',
                                                                         '27': '% High School Graduate or Higher (65 & Older)', '28': '% Bachelors Degree or Higher (65 & Older)'})
initial_pa_education_2012 = initial_pa_education_2012.drop(0)
initial_pa_education_2012 = initial_pa_education_2012.reset_index(drop=True)
initial_pa_education_2012['County'] = initial_pa_education_2012['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_education_2012['County'] = initial_pa_education_2012['County'].apply(lambda x: x.upper())
initial_pa_education_2012.insert(0, 'Year', 2012)
initial_pa_education_2012['% High School Graduate (18-24)'] = initial_pa_education_2012['% High School Graduate (18-24)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2012['% Bachelors Degree or Higher (18-24)'] = initial_pa_education_2012['% Bachelors Degree or Higher (18-24)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2012['% High School Graduate or Higher (25-34)'] = initial_pa_education_2012['% High School Graduate or Higher (25-34)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2012['% Bachelors Degree or Higher (25-34)'] = initial_pa_education_2012['% Bachelors Degree or Higher (25-34)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2012['% High School Graduate or Higher (35-44)'] = initial_pa_education_2012['% High School Graduate or Higher (35-44)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2012['% Bachelors Degree or Higher (35-44)'] = initial_pa_education_2012['% Bachelors Degree or Higher (35-44)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2012['% High School Graduate or Higher (45-64)'] = initial_pa_education_2012['% High School Graduate or Higher (45-64)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2012['% Bachelors Degree or Higher (45-64)'] = initial_pa_education_2012['% Bachelors Degree or Higher (45-64)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2012['% High School Graduate or Higher (65 & Older)'] = initial_pa_education_2012['% High School Graduate or Higher (65 & Older)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2012['% Bachelors Degree or Higher (65 & Older)'] = initial_pa_education_2012['% Bachelors Degree or Higher (65 & Older)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2012


Year          County  % High School Graduate (18-24)  \
0   2012           ADAMS                           0.361   
1   2012       ALLEGHENY                           0.257   
2   2012       ARMSTRONG                           0.479   
3   2012          BEAVER                           0.291   
4   2012           BERKS                           0.367   
5   2012           BLAIR                           0.472   
6   2012           BUCKS                           0.342   
7   2012          BUTLER                           0.297   
8   2012         CAMBRIA                           0.318   
9   2012          CARBON                           0.323   
10  2012          CENTRE                           0.225   
11  2012         CHESTER                           0.285   
12  2012      CLEARFIELD                           0.390   
13  2012        COLUMBIA                           0.276   
14  2012        CRAWFORD                           0.331   
15  2012      CUMBERLAND                           0.209   
16  2012         DAUPHIN                           0.357   
17  2012        DELAWARE                           0.335   
18  2012            ERIE                           0.334   
19  2012         FAYETTE                           0.462   
20  2012        FRANKLIN                           0.528   
21  2012         INDIANA                           0.262   
22  2012      LACKAWANNA                           0.225   
23  2012       LANCASTER                           0.318   
24  2012        LAWRENCE                           0.338   
25  2012         LEBANON                           0.253   
26  2012          LEHIGH                           0.317   
27  2012         LUZERNE                           0.319   
28  2012        LYCOMING                           0.335   
29  2012          MERCER                           0.369   
30  2012          MONROE                           0.345   
31  2012      MONTGOMERY                           0.336   
32  2012     NORTHAMPTON                           0.369   
33  2012  NORTHUMBERLAND                           0.312   
34  2012    PHILADELPHIA                           0.306   
35  2012      SCHUYLKILL                           0.450   
36  2012        SOMERSET                           0.503   
37  2012      WASHINGTON                           0.323   
38  2012    WESTMORELAND                           0.302   
39  2012            YORK                           0.415   

    % Bachelors Degree or Higher (18-24)  \
0                                  0.049   
1                                  0.195   
2                                  0.104   
3                                  0.126   
4                                  0.058   
5                                  0.070   
6                                  0.149   
7                                  0.099   
8                                  0.065   
9                                  0.098   
10                                 0.104   
11                                 0.145   
12                                 0.080   
13                                 0.067   
14                                 0.065   
15                                 0.089   
16                                 0.175   
17                                 0.109   
18                                 0.110   
19                                 0.082   
20                                 0.092   
21                                 0.071   
22                                 0.137   
23                                 0.083   
24                                 0.065   
25                                 0.074   
26                                 0.078   
27                                 0.101   
28                                 0.101   
29                                 0.090   
30                                 0.052   
31                                 0.161   
32                                 0.111   
33                                 0.068   
34 

**2016**
-

In [34]:
# Reading in 2016 U.S. Census Bureau education dataset
initial_pa_education_2016 = pd.read_excel("Resources/PA_Education_2016.xlsx")
initial_pa_education_2016


Unnamed: 0 Adams County, Pennsylvania  \
0                                           NaN                    Percent   
1                                         Label                   Estimate   
2                 AGE BY EDUCATIONAL ATTAINMENT                        NaN   
3                     Population 18 to 24 years                        (X)   
4                Less than high school graduate                      12.4%   
..                                          ...                        ...   
65               Less than high school graduate                        (X)   
66  High school graduate (includes equivalency)                        (X)   
67           Some college or associate's degree                        (X)   
68                            Bachelor's degree                        (X)   
69              Graduate or professional degree                        (X)   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
0                         Percent                        Percent   
1                        Estimate                       Estimate   
2                             NaN                            NaN   
3                             (X)                            (X)   
4                            9.1%                          18.2%   
..                            ...                            ...   
65                            (X)                            (X)   
66                            (X)                            (X)   
67                            (X)                            (X)   
68                            (X)                            (X)   
69                            (X)                            (X)   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
0                      Percent                    Percent   
1                     Estimate                   Estimate   
2                          NaN                        NaN   
3                          (X)                        (X)   
4                        13.2%                      14.0%   
..                         ...                        ...   
65                         (X)                        (X)   
66                         (X)                        (X)   
67                         (X)                        (X)   
68                         (X)                        (X)   
69                         (X)                        (X)   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
0                     Percent                    Percent   
1                    Estimate                   Estimate   
2                         NaN                        NaN   
3                         (X)                        (X)   
4                       11.4%                      11.1%   
..                        ...                        ...   
65                        (X)                        (X)   
66                        (X)                        (X)   
67                        (X)                        (X)   
68                        (X)                        (X)   
69                        (X)                        (X)   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
0                      Percent                      Percent  ...   
1                     Estimate                     Estimate  ...   
2                          NaN                          NaN  ...   
3                          (X)                          (X)  ...   
4                         7.7%                        13.8%  ...   
..                         ...                          ...  ...   
65                         (X)                          (X)  ...   
66                         (X)                          (X)  ...   
67                         (X)                          (X)  ...   
68                         (X)                          (X)  ...   
69                         (X)                          (X)  ...   

   Monroe Co

In [35]:
# Retrieving only rows that contain the desired county summary demographic statistics
# % High School Graduate & % Bachelor's degree or higher for 18 to 24 years old and % High School Graduate or Higher and % Bachelor's degree or higher for the remaining age groups:
# 25 to 34, 35 to 44, 45 to 64 and 65 & older
initial_pa_education_2016 = initial_pa_education_2016.iloc[[5, 7, 19, 20, 22, 23, 25, 26, 28, 29], :]
initial_pa_education_2016


Unnamed: 0 Adams County, Pennsylvania  \
5   High school graduate (includes equivalency)                      40.5%   
7                   Bachelor's degree or higher                       9.8%   
19               High school graduate or higher                      89.5%   
20                  Bachelor's degree or higher                      22.8%   
22               High school graduate or higher                      90.4%   
23                  Bachelor's degree or higher                      31.7%   
25               High school graduate or higher                      88.9%   
26                  Bachelor's degree or higher                      18.7%   
28               High school graduate or higher                      79.8%   
29                  Bachelor's degree or higher                      20.1%   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
5                           28.3%                          38.0%   
7                           20.4%                          14.5%   
19                          96.9%                          88.7%   
20                          56.0%                          18.9%   
22                          96.8%                          94.9%   
23                          53.9%                          24.2%   
25                          95.2%                          90.6%   
26                          37.7%                          15.9%   
28                          89.5%                          82.2%   
29                          27.3%                          10.9%   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
5                        29.3%                      40.6%   
7                        13.4%                       9.3%   
19                       92.6%                      88.5%   
20                       38.3%                      27.2%   
22                       92.1%                      86.2%   
23                       36.0%                      30.1%   
25                       95.8%                      88.9%   
26                       21.8%                      26.5%   
28                       87.7%                      80.7%   
29                       18.0%                      17.4%   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
5                       38.2%                      33.1%   
7                       10.3%                      18.5%   
19                      90.9%                      95.6%   
20                      23.3%                      46.2%   
22                      94.4%                      95.4%   
23                      25.9%                      45.3%   
25                      93.5%                      94.8%   
26                      19.3%                      41.3%   
28                      88.0%                      89.0%   
29                       9.8%                      30.9%   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
5                        30.8%                        25.8%  ...   
7                        13.7%                         8.9%  ...   
19                       97.0%                        95.9%  ...   
20                       45.9%                        29.3%  ...   
22                       97.6%                        96.6%  ...   
23                       52.4%                        30.2%  ...   
25                       95.4%                        93.1%  ...   
26                       35.5%                        20.2%  ...   
28                       91.3%                        86.1%  ...   
29                       21.4%                        17.3%  ...   

   Monroe County, Pennsylvania Montgomery County, Pennsylvania  \
5                        36.7%                           29.4%   
7                         8.4%                           18.9%   
19                       96.1%                           95.7%   
20                       33.5%                           54.6%   
22               

In [36]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_education_2016 = initial_pa_education_2016.T
initial_pa_education_2016.head()


5   \
Unnamed: 0                      High school graduate (includes equivalency)   
Adams County, Pennsylvania                                            40.5%   
Allegheny County, Pennsylvania                                        28.3%   
Armstrong County, Pennsylvania                                        38.0%   
Beaver County, Pennsylvania                                           29.3%   

                                                         7   \
Unnamed: 0                      Bachelor's degree or higher   
Adams County, Pennsylvania                             9.8%   
Allegheny County, Pennsylvania                        20.4%   
Armstrong County, Pennsylvania                        14.5%   
Beaver County, Pennsylvania                           13.4%   

                                                            19  \
Unnamed: 0                      High school graduate or higher   
Adams County, Pennsylvania                               89.5%   
Allegheny County, Pennsylvania                           96.9%   
Armstrong County, Pennsylvania                           88.7%   
Beaver County, Pennsylvania                              92.6%   

                                                         20  \
Unnamed: 0                      Bachelor's degree or higher   
Adams County, Pennsylvania                            22.8%   
Allegheny County, Pennsylvania                        56.0%   
Armstrong County, Pennsylvania                        18.9%   
Beaver County, Pennsylvania                           38.3%   

                                                            22  \
Unnamed: 0                      High school graduate or higher   
Adams County, Pennsylvania                               90.4%   
Allegheny County, Pennsylvania                           96.8%   
Armstrong County, Pennsylvania                           94.9%   
Beaver County, Pennsylvania                              92.1%   

                                                         23  \
Unnamed: 0                      Bachelor's degree or higher   
Adams County, Pennsylvania                            31.7%   
Allegheny County, Pennsylvania                        53.9%   
Armstrong County, Pennsylvania                        24.2%   
Beaver County, Pennsylvania                           36.0%   

                                                            25  \
Unnamed: 0                      High school graduate or higher   
Adams County, Pennsylvania                               88.9%   
Allegheny County, Pennsylvania                           95.2%   
Armstrong County, Pennsylvania                           90.6%   
Beaver County, Pennsylvania                              95.8%   

                                                         26  \
Unnamed: 0                      Bachelor's degree or higher   
Adams County, Pennsylvania                            18.7%   
Allegheny County, Pennsylvania                        37.7%   
Armstrong County, Pennsylvania                        15.9%   
Beaver County, Pennsylvania                           21.8%   

                                                            28  \
Unnamed: 0                      High school graduate or higher   
Adams County, Pennsylvania                               79.8%   
Allegheny County, Pennsylvania                           89.5%   
Armstrong County, Pennsylvania                           82.2%   
Beaver County, Pennsylvania                              87.7%   

                                                         29  
Unnamed: 0                      Bachelor's degree or higher  
Adams County, Pennsylvania                            20.1%  
Allegheny County, Pennsylvania                        27.3%  
Armstrong County, Pennsylvania                        10.9%  
Beaver County, Pennsylvania                           18.0%

In [37]:
# Resetting index and renaming to create a 'County' column
initial_pa_education_2016 = initial_pa_education_2016.reset_index()
initial_pa_education_2016.rename(columns={'index': 'County'}, inplace=True)
initial_pa_education_2016.head()


County  \
0                      Unnamed: 0   
1      Adams County, Pennsylvania   
2  Allegheny County, Pennsylvania   
3  Armstrong County, Pennsylvania   
4     Beaver County, Pennsylvania   

                                             5                            7  \
0  High school graduate (includes equivalency)  Bachelor's degree or higher   
1                                        40.5%                         9.8%   
2                                        28.3%                        20.4%   
3                                        38.0%                        14.5%   
4                                        29.3%                        13.4%   

                               19                           20  \
0  High school graduate or higher  Bachelor's degree or higher   
1                           89.5%                        22.8%   
2                           96.9%                        56.0%   
3                           88.7%                        18.9%   
4                           92.6%                        38.3%   

                               22                           23  \
0  High school graduate or higher  Bachelor's degree or higher   
1                           90.4%                        31.7%   
2                           96.8%                        53.9%   
3                           94.9%                        24.2%   
4                           92.1%                        36.0%   

                               25                           26  \
0  High school graduate or higher  Bachelor's degree or higher   
1                           88.9%                        18.7%   
2                           95.2%                        37.7%   
3                           90.6%                        15.9%   
4                           95.8%                        21.8%   

                               28                           29  
0  High school graduate or higher  Bachelor's degree or higher  
1                           79.8%                        20.1%  
2                           89.5%                        27.3%  
3                           82.2%                        10.9%  
4                           87.7%                        18.0%

In [38]:
# Confirming column data types prior to renaming
print(initial_pa_education_2016.columns)


Index(['County', 5, 7, 19, 20, 22, 23, 25, 26, 28, 29], dtype='object')


In [39]:
# Converting column data types from integers to strings for renaming
initial_pa_education_2016.columns = initial_pa_education_2016.columns.astype(str)
print(initial_pa_education_2016.columns)


Index(['County', '5', '7', '19', '20', '22', '23', '25', '26', '28', '29'], dtype='object')


In [40]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_education_2016.replace('N', np.nan, inplace=True)


In [41]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_education_2016 = initial_pa_education_2016.rename(columns={'5': '% High School Graduate (18-24)', '7': '% Bachelors Degree or Higher (18-24)', '19': '% High School Graduate or Higher (25-34)',
                                                                         '20': '% Bachelors Degree or Higher (25-34)', '22': '% High School Graduate or Higher (35-44)', '23': '% Bachelors Degree or Higher (35-44)',
                                                                         '25': '% High School Graduate or Higher (45-64)', '26': '% Bachelors Degree or Higher (45-64)',
                                                                         '28': '% High School Graduate or Higher (65 & Older)', '29': '% Bachelors Degree or Higher (65 & Older)'})
initial_pa_education_2016 = initial_pa_education_2016.drop(0)
initial_pa_education_2016 = initial_pa_education_2016.reset_index(drop=True)
initial_pa_education_2016['County'] = initial_pa_education_2016['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_education_2016['County'] = initial_pa_education_2016['County'].apply(lambda x: x.upper())
initial_pa_education_2016.insert(0, 'Year', 2016)
initial_pa_education_2016['% High School Graduate (18-24)'] = initial_pa_education_2016['% High School Graduate (18-24)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2016['% Bachelors Degree or Higher (18-24)'] = initial_pa_education_2016['% Bachelors Degree or Higher (18-24)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2016['% High School Graduate or Higher (25-34)'] = initial_pa_education_2016['% High School Graduate or Higher (25-34)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2016['% Bachelors Degree or Higher (25-34)'] = initial_pa_education_2016['% Bachelors Degree or Higher (25-34)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2016['% High School Graduate or Higher (35-44)'] = initial_pa_education_2016['% High School Graduate or Higher (35-44)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2016['% Bachelors Degree or Higher (35-44)'] = initial_pa_education_2016['% Bachelors Degree or Higher (35-44)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2016['% High School Graduate or Higher (45-64)'] = initial_pa_education_2016['% High School Graduate or Higher (45-64)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2016['% Bachelors Degree or Higher (45-64)'] = initial_pa_education_2016['% Bachelors Degree or Higher (45-64)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2016['% High School Graduate or Higher (65 & Older)'] = initial_pa_education_2016['% High School Graduate or Higher (65 & Older)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2016['% Bachelors Degree or Higher (65 & Older)'] = initial_pa_education_2016['% Bachelors Degree or Higher (65 & Older)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2016


Year          County  % High School Graduate (18-24)  \
0   2016           ADAMS                           0.405   
1   2016       ALLEGHENY                           0.283   
2   2016       ARMSTRONG                           0.380   
3   2016          BEAVER                           0.293   
4   2016           BERKS                           0.406   
5   2016           BLAIR                           0.382   
6   2016           BUCKS                           0.331   
7   2016          BUTLER                           0.308   
8   2016         CAMBRIA                           0.258   
9   2016          CARBON                           0.607   
10  2016          CENTRE                           0.262   
11  2016         CHESTER                           0.329   
12  2016      CLEARFIELD                           0.621   
13  2016        COLUMBIA                           0.267   
14  2016        CRAWFORD                           0.324   
15  2016      CUMBERLAND                           0.295   
16  2016         DAUPHIN                           0.394   
17  2016        DELAWARE                           0.283   
18  2016            ERIE                           0.314   
19  2016         FAYETTE                           0.480   
20  2016        FRANKLIN                           0.461   
21  2016         INDIANA                           0.249   
22  2016      LACKAWANNA                           0.326   
23  2016       LANCASTER                           0.358   
24  2016        LAWRENCE                           0.368   
25  2016         LEBANON                           0.461   
26  2016          LEHIGH                           0.308   
27  2016         LUZERNE                           0.334   
28  2016        LYCOMING                           0.395   
29  2016          MERCER                           0.381   
30  2016          MONROE                           0.367   
31  2016      MONTGOMERY                           0.294   
32  2016     NORTHAMPTON                           0.329   
33  2016  NORTHUMBERLAND                           0.370   
34  2016    PHILADELPHIA                           0.309   
35  2016      SCHUYLKILL                           0.468   
36  2016        SOMERSET                           0.466   
37  2016      WASHINGTON                           0.334   
38  2016    WESTMORELAND                           0.296   
39  2016            YORK                           0.439   

    % Bachelors Degree or Higher (18-24)  \
0                                  0.098   
1                                  0.204   
2                                  0.145   
3                                  0.134   
4                                  0.093   
5                                  0.103   
6                                  0.185   
7                                  0.137   
8                                  0.089   
9                                  0.096   
10                                 0.093   
11                                 0.156   
12                                 0.095   
13                                 0.101   
14                                 0.060   
15                                 0.100   
16                                 0.137   
17                                 0.127   
18                                 0.121   
19                                 0.082   
20                                 0.091   
21                                 0.121   
22                                 0.117   
23                                 0.119   
24                                 0.052   
25                                 0.027   
26                                 0.095   
27                                 0.090   
28                                 0.064   
29                                 0.059   
30                                 0.084   
31                                 0.189   
32                                 0.096   
33                                 0.086   
34 

**2019**
-
Please note: 2020 United States Census Bureau was unavailable and as such the closest year prior to the election (2019) was utilized

In [42]:
# Reading in 2019 U.S. Census Bureau education dataset
initial_pa_education_2019 = pd.read_excel("Resources/PA_Education_2019.xlsx")
initial_pa_education_2019.head(35)


Unnamed: 0  \
0                                                 NaN   
1                                               Label   
2                       AGE BY EDUCATIONAL ATTAINMENT   
3                           Population 18 to 24 years   
4                      Less than high school graduate   
5         High school graduate (includes equivalency)   
6                  Some college or associate's degree   
7                         Bachelor's degree or higher   
8                        Population 25 years and over   
9                                 Less than 9th grade   
10                      9th to 12th grade, no diploma   
11        High school graduate (includes equivalency)   
12                            Some college, no degree   
13                                 Associate's degree   
14                                  Bachelor's degree   
15                    Graduate or professional degree   
16                     High school graduate or higher   
17                        Bachelor's degree or higher   
18                          Population 25 to 34 years   
19                     High school graduate or higher   
20                        Bachelor's degree or higher   
21                          Population 35 to 44 years   
22                     High school graduate or higher   
23                        Bachelor's degree or higher   
24                          Population 45 to 64 years   
25                     High school graduate or higher   
26                        Bachelor's degree or higher   
27                       Population 65 years and over   
28                     High school graduate or higher   
29                        Bachelor's degree or higher   
30  RACE AND HISPANIC OR LATINO ORIGIN BY EDUCATIO...   
31                                        White alone   
32                     High school graduate or higher   
33                        Bachelor's degree or higher   
34                White alone, not Hispanic or Latino   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
0                     Percent                        Percent   
1                    Estimate                       Estimate   
2                         NaN                            NaN   
3                         (X)                            (X)   
4                        6.5%                           8.9%   
5                       48.7%                          29.8%   
6                       37.1%                          41.0%   
7                        7.7%                          20.3%   
8                         (X)                            (X)   
9                        3.6%                           1.5%   
10                       7.3%                           3.2%   
11                      42.6%                          26.2%   
12                      17.1%                          16.1%   
13                       7.9%                          10.0%   
14                      12.0%                          24.8%   
15                       9.6%                          18.1%   
16                      89.1%                          95.2%   
17                      21.6%                          42.9%   
18                        (X)                            (X)   
19                      90.8%                          95.7%   
20                      24.0%                          56.8%   
21                        (X)                            (X)   
22                      89.1%                          96.4%   
23                      27.2%                          53.8%   
24                        (X)                            (X)   
25                      89.4%                          96.2%   
26                      18.5%                          38.8%   
27                        (X)                            (X)   
28                      87.8%                          92.9%   
29                      21.6%                          30.5%   
30    

In [43]:
# Retrieving only rows that contain the desired county summary demographic statistics
# % High School Graduate & % Bachelor's degree or higher for 18 to 24 years old and % High School Graduate or Higher and % Bachelor's degree or higher for the remaining age groups:
# 25 to 34, 35 to 44, 45 to 64 and 65 & older
initial_pa_education_2019 = initial_pa_education_2019.iloc[[5, 7, 19, 20, 22, 23, 25, 26, 28, 29], :]
initial_pa_education_2019


Unnamed: 0 Adams County, Pennsylvania  \
5   High school graduate (includes equivalency)                      48.7%   
7                   Bachelor's degree or higher                       7.7%   
19               High school graduate or higher                      90.8%   
20                  Bachelor's degree or higher                      24.0%   
22               High school graduate or higher                      89.1%   
23                  Bachelor's degree or higher                      27.2%   
25               High school graduate or higher                      89.4%   
26                  Bachelor's degree or higher                      18.5%   
28               High school graduate or higher                      87.8%   
29                  Bachelor's degree or higher                      21.6%   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
5                           29.8%                          55.6%   
7                           20.3%                          11.0%   
19                          95.7%                          91.9%   
20                          56.8%                          19.7%   
22                          96.4%                          94.7%   
23                          53.8%                          26.7%   
25                          96.2%                          93.9%   
26                          38.8%                          13.3%   
28                          92.9%                          89.2%   
29                          30.5%                          11.3%   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
5                        36.9%                      37.7%   
7                         8.7%                      10.0%   
19                       95.5%                      91.1%   
20                       33.0%                      25.7%   
22                       95.4%                      87.3%   
23                       38.8%                      28.5%   
25                       92.2%                      87.0%   
26                       24.0%                      26.0%   
28                       89.8%                      84.7%   
29                       21.2%                      22.1%   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
5                       44.2%                      30.5%   
7                       11.9%                      22.7%   
19                      91.7%                      95.5%   
20                      26.0%                      50.0%   
22                      92.4%                      94.8%   
23                      37.3%                      47.2%   
25                      94.3%                      95.5%   
26                      20.4%                      41.4%   
28                      87.7%                      90.3%   
29                      17.5%                      35.7%   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
5                        37.7%                        37.6%  ...   
7                        14.7%                         6.2%  ...   
19                       97.3%                        95.3%  ...   
20                       42.1%                        26.0%  ...   
22                       97.9%                        98.1%  ...   
23                       53.4%                        30.0%  ...   
25                       95.8%                        95.0%  ...   
26                       36.8%                        19.9%  ...   
28                       92.3%                        90.0%  ...   
29                       26.2%                        14.9%  ...   

   Monroe County, Pennsylvania Montgomery County, Pennsylvania  \
5                        37.5%                           28.9%   
7                        10.9%                           19.3%   
19                       91.7%                           97.9%   
20                       28.5%                           56.5%   
22               

In [44]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_education_2019 = initial_pa_education_2019.T
initial_pa_education_2019.head()


5   \
Unnamed: 0                      High school graduate (includes equivalency)   
Adams County, Pennsylvania                                            48.7%   
Allegheny County, Pennsylvania                                        29.8%   
Armstrong County, Pennsylvania                                        55.6%   
Beaver County, Pennsylvania                                           36.9%   

                                                         7   \
Unnamed: 0                      Bachelor's degree or higher   
Adams County, Pennsylvania                             7.7%   
Allegheny County, Pennsylvania                        20.3%   
Armstrong County, Pennsylvania                        11.0%   
Beaver County, Pennsylvania                            8.7%   

                                                            19  \
Unnamed: 0                      High school graduate or higher   
Adams County, Pennsylvania                               90.8%   
Allegheny County, Pennsylvania                           95.7%   
Armstrong County, Pennsylvania                           91.9%   
Beaver County, Pennsylvania                              95.5%   

                                                         20  \
Unnamed: 0                      Bachelor's degree or higher   
Adams County, Pennsylvania                            24.0%   
Allegheny County, Pennsylvania                        56.8%   
Armstrong County, Pennsylvania                        19.7%   
Beaver County, Pennsylvania                           33.0%   

                                                            22  \
Unnamed: 0                      High school graduate or higher   
Adams County, Pennsylvania                               89.1%   
Allegheny County, Pennsylvania                           96.4%   
Armstrong County, Pennsylvania                           94.7%   
Beaver County, Pennsylvania                              95.4%   

                                                         23  \
Unnamed: 0                      Bachelor's degree or higher   
Adams County, Pennsylvania                            27.2%   
Allegheny County, Pennsylvania                        53.8%   
Armstrong County, Pennsylvania                        26.7%   
Beaver County, Pennsylvania                           38.8%   

                                                            25  \
Unnamed: 0                      High school graduate or higher   
Adams County, Pennsylvania                               89.4%   
Allegheny County, Pennsylvania                           96.2%   
Armstrong County, Pennsylvania                           93.9%   
Beaver County, Pennsylvania                              92.2%   

                                                         26  \
Unnamed: 0                      Bachelor's degree or higher   
Adams County, Pennsylvania                            18.5%   
Allegheny County, Pennsylvania                        38.8%   
Armstrong County, Pennsylvania                        13.3%   
Beaver County, Pennsylvania                           24.0%   

                                                            28  \
Unnamed: 0                      High school graduate or higher   
Adams County, Pennsylvania                               87.8%   
Allegheny County, Pennsylvania                           92.9%   
Armstrong County, Pennsylvania                           89.2%   
Beaver County, Pennsylvania                              89.8%   

                                                         29  
Unnamed: 0                      Bachelor's degree or higher  
Adams County, Pennsylvania                            21.6%  
Allegheny County, Pennsylvania                        30.5%  
Armstrong County, Pennsylvania                        11.3%  
Beaver County, Pennsylvania                           21.2%

In [45]:
# Resetting index and renaming to create a 'County' column
initial_pa_education_2019 = initial_pa_education_2019.reset_index()
initial_pa_education_2019.rename(columns={'index': 'County'}, inplace=True)
initial_pa_education_2019.head()


County  \
0                      Unnamed: 0   
1      Adams County, Pennsylvania   
2  Allegheny County, Pennsylvania   
3  Armstrong County, Pennsylvania   
4     Beaver County, Pennsylvania   

                                             5                            7  \
0  High school graduate (includes equivalency)  Bachelor's degree or higher   
1                                        48.7%                         7.7%   
2                                        29.8%                        20.3%   
3                                        55.6%                        11.0%   
4                                        36.9%                         8.7%   

                               19                           20  \
0  High school graduate or higher  Bachelor's degree or higher   
1                           90.8%                        24.0%   
2                           95.7%                        56.8%   
3                           91.9%                        19.7%   
4                           95.5%                        33.0%   

                               22                           23  \
0  High school graduate or higher  Bachelor's degree or higher   
1                           89.1%                        27.2%   
2                           96.4%                        53.8%   
3                           94.7%                        26.7%   
4                           95.4%                        38.8%   

                               25                           26  \
0  High school graduate or higher  Bachelor's degree or higher   
1                           89.4%                        18.5%   
2                           96.2%                        38.8%   
3                           93.9%                        13.3%   
4                           92.2%                        24.0%   

                               28                           29  
0  High school graduate or higher  Bachelor's degree or higher  
1                           87.8%                        21.6%  
2                           92.9%                        30.5%  
3                           89.2%                        11.3%  
4                           89.8%                        21.2%

In [46]:
# Confirming column data types prior to renaming
print(initial_pa_education_2019.columns)


Index(['County', 5, 7, 19, 20, 22, 23, 25, 26, 28, 29], dtype='object')


In [47]:
# Converting column data types from integers to strings for renaming
initial_pa_education_2019.columns = initial_pa_education_2019.columns.astype(str)
print(initial_pa_education_2019.columns)


Index(['County', '5', '7', '19', '20', '22', '23', '25', '26', '28', '29'], dtype='object')


In [48]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_education_2019.replace('N', np.nan, inplace=True)


In [49]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_education_2019 = initial_pa_education_2019.rename(columns={'5': '% High School Graduate (18-24)', '7': '% Bachelors Degree or Higher (18-24)', '19': '% High School Graduate or Higher (25-34)',
                                                                         '20': '% Bachelors Degree or Higher (25-34)', '22': '% High School Graduate or Higher (35-44)', '23': '% Bachelors Degree or Higher (35-44)',
                                                                         '25': '% High School Graduate or Higher (45-64)', '26': '% Bachelors Degree or Higher (45-64)',
                                                                         '28': '% High School Graduate or Higher (65 & Older)', '29': '% Bachelors Degree or Higher (65 & Older)'})
initial_pa_education_2019 = initial_pa_education_2019.drop(0)
initial_pa_education_2019 = initial_pa_education_2019.reset_index(drop=True)
initial_pa_education_2019['County'] = initial_pa_education_2019['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_education_2019['County'] = initial_pa_education_2019['County'].apply(lambda x: x.upper())
initial_pa_education_2019.insert(0, 'Year', 2020)
initial_pa_education_2019['% High School Graduate (18-24)'] = initial_pa_education_2019['% High School Graduate (18-24)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2019['% Bachelors Degree or Higher (18-24)'] = initial_pa_education_2019['% Bachelors Degree or Higher (18-24)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2019['% High School Graduate or Higher (25-34)'] = initial_pa_education_2019['% High School Graduate or Higher (25-34)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2019['% Bachelors Degree or Higher (25-34)'] = initial_pa_education_2019['% Bachelors Degree or Higher (25-34)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2019['% High School Graduate or Higher (35-44)'] = initial_pa_education_2019['% High School Graduate or Higher (35-44)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2019['% Bachelors Degree or Higher (35-44)'] = initial_pa_education_2019['% Bachelors Degree or Higher (35-44)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2019['% High School Graduate or Higher (45-64)'] = initial_pa_education_2019['% High School Graduate or Higher (45-64)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2019['% Bachelors Degree or Higher (45-64)'] = initial_pa_education_2019['% Bachelors Degree or Higher (45-64)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2019['% High School Graduate or Higher (65 & Older)'] = initial_pa_education_2019['% High School Graduate or Higher (65 & Older)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2019['% Bachelors Degree or Higher (65 & Older)'] = initial_pa_education_2019['% Bachelors Degree or Higher (65 & Older)'].str.rstrip('%').astype(float) / 100
initial_pa_education_2019


Year          County  % High School Graduate (18-24)  \
0   2020           ADAMS                           0.487   
1   2020       ALLEGHENY                           0.298   
2   2020       ARMSTRONG                           0.556   
3   2020          BEAVER                           0.369   
4   2020           BERKS                           0.377   
5   2020           BLAIR                           0.442   
6   2020           BUCKS                           0.305   
7   2020          BUTLER                           0.377   
8   2020         CAMBRIA                           0.376   
9   2020          CARBON                           0.446   
10  2020          CENTRE                           0.286   
11  2020         CHESTER                           0.272   
12  2020      CLEARFIELD                           0.546   
13  2020        COLUMBIA                           0.297   
14  2020        CRAWFORD                           0.338   
15  2020      CUMBERLAND                           0.258   
16  2020         DAUPHIN                           0.450   
17  2020        DELAWARE                           0.347   
18  2020            ERIE                           0.369   
19  2020         FAYETTE                           0.574   
20  2020        FRANKLIN                           0.436   
21  2020         INDIANA                           0.236   
22  2020      LACKAWANNA                           0.258   
23  2020       LANCASTER                           0.355   
24  2020        LAWRENCE                           0.424   
25  2020         LEBANON                           0.557   
26  2020          LEHIGH                           0.332   
27  2020         LUZERNE                           0.326   
28  2020        LYCOMING                           0.438   
29  2020          MERCER                           0.481   
30  2020          MONROE                           0.375   
31  2020      MONTGOMERY                           0.289   
32  2020     NORTHAMPTON                           0.302   
33  2020  NORTHUMBERLAND                           0.495   
34  2020    PHILADELPHIA                           0.332   
35  2020      SCHUYLKILL                           0.427   
36  2020        SOMERSET                           0.520   
37  2020      WASHINGTON                           0.378   
38  2020    WESTMORELAND                           0.326   
39  2020            YORK                           0.384   

    % Bachelors Degree or Higher (18-24)  \
0                                  0.077   
1                                  0.203   
2                                  0.110   
3                                  0.087   
4                                  0.100   
5                                  0.119   
6                                  0.227   
7                                  0.147   
8                                  0.062   
9                                  0.093   
10                                 0.104   
11                                 0.215   
12                                 0.045   
13                                 0.058   
14                                 0.070   
15                                 0.104   
16                                 0.111   
17                                 0.144   
18                                 0.118   
19                                 0.136   
20                                 0.043   
21                                 0.050   
22                                 0.165   
23                                 0.107   
24                                 0.066   
25                                 0.095   
26                                 0.099   
27                                 0.069   
28                                 0.062   
29                                 0.083   
30                                 0.109   
31                                 0.193   
32                                 0.115   
33                                 0.048   
34 

**Income (Households) Data Extraction, Transformation & Loading (2012, 2016 & 2019)**
-
-----------

**2012**
-

In [50]:
# Reading in 2012 U.S. Census Bureau income (household) dataset
initial_pa_households_2012 = pd.read_excel("Resources/PA_Income_Households_2012.xlsx")
initial_pa_households_2012.head(19)


Unnamed: 0 Adams County, Pennsylvania  \
0                                      NaN                 Households   
1                                    Label                   Estimate   
2                                    Total                     38,102   
3                        Less than $10,000                       3.5%   
4                       $10,000 to $14,999                       5.5%   
5                       $15,000 to $24,999                      10.4%   
6                       $25,000 to $34,999                      10.3%   
7                       $35,000 to $49,999                      11.5%   
8                       $50,000 to $74,999                      21.1%   
9                       $75,000 to $99,999                      16.9%   
10                    $100,000 to $149,999                      14.1%   
11                    $150,000 to $199,999                       4.6%   
12                        $200,000 or more                       2.0%   
13                 Median income (dollars)                     60,136   
14                   Mean income (dollars)                     69,324   
15                         PERCENT IMPUTED                        NaN   
16  Household income in the past 12 months                      25.8%   
17     Family income in the past 12 months                        (X)   
18  Nonfamily income in the past 12 months                        (X)   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
0                      Households                     Households   
1                        Estimate                       Estimate   
2                         527,219                         29,099   
3                            7.9%                           8.7%   
4                            5.2%                           5.7%   
5                           11.5%                          13.1%   
6                           10.7%                          14.1%   
7                           13.7%                          17.2%   
8                           18.0%                          18.0%   
9                           12.2%                          11.4%   
10                          12.1%                           8.7%   
11                           4.5%                           1.1%   
12                           4.2%                           1.9%   
13                         50,884                         41,841   
14                         72,077                         52,635   
15                            NaN                            NaN   
16                          25.8%                          30.3%   
17                            (X)                            (X)   
18                            (X)                            (X)   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
0                   Households                 Households   
1                     Estimate                   Estimate   
2                       70,767                    151,291   
3                         6.1%                       6.4%   
4                         6.1%                       5.6%   
5                        13.8%                      11.0%   
6                        12.8%                      10.5%   
7                        13.2%                      14.8%   
8                        19.6%                      19.5%   
9                        13.2%                      13.2%   
10                       11.9%                      11.4%   
11                        2.0%                       4.1%   
12                        1.5%                       3.6%   
13                      47,083                     52,022   
14                      58,980                     68,265   
15                         NaN                        NaN   
16                       28.9%                      31.0%   
17                         (X)                        (X)   
18                         (X)                     

In [51]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Four groupings = Households, Families, Married-couple families & non family households
# % of groups above that fall into the income categories: Less Than $10,000, $10,000-$14,999, $15,000-$24,999, $25,000-$34,999,
# $35,000-$49,999, $50,000-$74,999, $75,000-$99,999, $100,000-$149,999, $150,000-$199,999, $200,000 or More
# Total count for each grouping
# Median income for each grouping
# Mean income for each grouping
initial_pa_households_2012 = initial_pa_households_2012.iloc[[2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], :]
initial_pa_households_2012


Unnamed: 0 Adams County, Pennsylvania  \
2                     Total                     38,102   
3         Less than $10,000                       3.5%   
4        $10,000 to $14,999                       5.5%   
5        $15,000 to $24,999                      10.4%   
6        $25,000 to $34,999                      10.3%   
7        $35,000 to $49,999                      11.5%   
8        $50,000 to $74,999                      21.1%   
9        $75,000 to $99,999                      16.9%   
10     $100,000 to $149,999                      14.1%   
11     $150,000 to $199,999                       4.6%   
12         $200,000 or more                       2.0%   
13  Median income (dollars)                     60,136   
14    Mean income (dollars)                     69,324   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
2                         527,219                         29,099   
3                            7.9%                           8.7%   
4                            5.2%                           5.7%   
5                           11.5%                          13.1%   
6                           10.7%                          14.1%   
7                           13.7%                          17.2%   
8                           18.0%                          18.0%   
9                           12.2%                          11.4%   
10                          12.1%                           8.7%   
11                           4.5%                           1.1%   
12                           4.2%                           1.9%   
13                         50,884                         41,841   
14                         72,077                         52,635   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
2                       70,767                    151,291   
3                         6.1%                       6.4%   
4                         6.1%                       5.6%   
5                        13.8%                      11.0%   
6                        12.8%                      10.5%   
7                        13.2%                      14.8%   
8                        19.6%                      19.5%   
9                        13.2%                      13.2%   
10                       11.9%                      11.4%   
11                        2.0%                       4.1%   
12                        1.5%                       3.6%   
13                      47,083                     52,022   
14                      58,980                     68,265   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
2                      50,098                    231,626   
3                        8.1%                       3.7%   
4                        7.1%                       3.0%   
5                       13.6%                       7.2%   
6                       12.6%                       6.9%   
7                       16.1%                      11.4%   
8                       21.3%                      17.5%   
9                        9.1%                      14.4%   
10                       8.1%                      19.2%   
11                       1.8%                       8.4%   
12                       2.2%                       8.3%   
13                     41,258                     75,471   
14                     53,745                     95,823   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
2                       73,318                       58,228  ...   
3                         5.4%                         8.4%  ...   
4                         5.4%                        10.0%  ...   
5                         9.9%                        13.1%  ...   
6                         8.7%                        12.1%  ...   
7                        13.5%                        16.4%  ...   
8                        18.8%                        18.1%  ...   
9          

In [52]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_households_2012 = initial_pa_households_2012.T
initial_pa_households_2012.head()


2                  3   \
Unnamed: 0                        Total  Less than $10,000   
Adams County, Pennsylvania       38,102               3.5%   
Allegheny County, Pennsylvania  527,219               7.9%   
Armstrong County, Pennsylvania   29,099               8.7%   
Beaver County, Pennsylvania      70,767               6.1%   

                                                4                   5   \
Unnamed: 0                      $10,000 to $14,999  $15,000 to $24,999   
Adams County, Pennsylvania                    5.5%               10.4%   
Allegheny County, Pennsylvania                5.2%               11.5%   
Armstrong County, Pennsylvania                5.7%               13.1%   
Beaver County, Pennsylvania                   6.1%               13.8%   

                                                6                   7   \
Unnamed: 0                      $25,000 to $34,999  $35,000 to $49,999   
Adams County, Pennsylvania                   10.3%               11.5%   
Allegheny County, Pennsylvania               10.7%               13.7%   
Armstrong County, Pennsylvania               14.1%               17.2%   
Beaver County, Pennsylvania                  12.8%               13.2%   

                                                8                   9   \
Unnamed: 0                      $50,000 to $74,999  $75,000 to $99,999   
Adams County, Pennsylvania                   21.1%               16.9%   
Allegheny County, Pennsylvania               18.0%               12.2%   
Armstrong County, Pennsylvania               18.0%               11.4%   
Beaver County, Pennsylvania                  19.6%               13.2%   

                                                  10                    11  \
Unnamed: 0                      $100,000 to $149,999  $150,000 to $199,999   
Adams County, Pennsylvania                     14.1%                  4.6%   
Allegheny County, Pennsylvania                 12.1%                  4.5%   
Armstrong County, Pennsylvania                  8.7%                  1.1%   
Beaver County, Pennsylvania                    11.9%                  2.0%   

                                              12                       13  \
Unnamed: 0                      $200,000 or more  Median income (dollars)   
Adams County, Pennsylvania                  2.0%                   60,136   
Allegheny County, Pennsylvania              4.2%                   50,884   
Armstrong County, Pennsylvania              1.9%                   41,841   
Beaver County, Pennsylvania                 1.5%                   47,083   

                                                   14  
Unnamed: 0                      Mean income (dollars)  
Adams County, Pennsylvania                     69,324  
Allegheny County, Pennsylvania                 72,077  
Armstrong County, Pennsylvania                 52,635  
Beaver County, Pennsylvania                    58,980

In [53]:
# Resetting index and renaming to create a 'County' column
initial_pa_households_2012 = initial_pa_households_2012.reset_index()
initial_pa_households_2012.rename(columns={'index': 'County'}, inplace=True)
initial_pa_households_2012.head()


County        2                  3  \
0                      Unnamed: 0    Total  Less than $10,000   
1      Adams County, Pennsylvania   38,102               3.5%   
2  Allegheny County, Pennsylvania  527,219               7.9%   
3  Armstrong County, Pennsylvania   29,099               8.7%   
4     Beaver County, Pennsylvania   70,767               6.1%   

                    4                   5                   6  \
0  $10,000 to $14,999  $15,000 to $24,999  $25,000 to $34,999   
1                5.5%               10.4%               10.3%   
2                5.2%               11.5%               10.7%   
3                5.7%               13.1%               14.1%   
4                6.1%               13.8%               12.8%   

                    7                   8                   9  \
0  $35,000 to $49,999  $50,000 to $74,999  $75,000 to $99,999   
1               11.5%               21.1%               16.9%   
2               13.7%               18.0%               12.2%   
3               17.2%               18.0%               11.4%   
4               13.2%               19.6%               13.2%   

                     10                    11                12  \
0  $100,000 to $149,999  $150,000 to $199,999  $200,000 or more   
1                 14.1%                  4.6%              2.0%   
2                 12.1%                  4.5%              4.2%   
3                  8.7%                  1.1%              1.9%   
4                 11.9%                  2.0%              1.5%   

                        13                     14  
0  Median income (dollars)  Mean income (dollars)  
1                   60,136                 69,324  
2                   50,884                 72,077  
3                   41,841                 52,635  
4                   47,083                 58,980

In [54]:
# Confirming column data types prior to renaming
print(initial_pa_households_2012.columns)


Index(['County', 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], dtype='object')


In [55]:
# Converting column data types from integers to strings for renaming
initial_pa_households_2012.columns = initial_pa_households_2012.columns.astype(str)
print(initial_pa_households_2012.columns)


Index(['County', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12',
       '13', '14'],
      dtype='object')


In [56]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_households_2012.replace('N', np.nan, inplace=True)


In [57]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_households_2012 = initial_pa_households_2012.rename(columns={'2': '# of Households', '3': '% Households <$10,000', '4': '% Households $10,000-$14,999',
                                                                         '5': '% Households $15,000-$24,999', '6': '% Households $25,000-$34,999', '7': '% Households $35,000-$49,999',
                                                                         '8': '% Households $50,000-$74,999', '9': '% Households $75,000-$99,999',
                                                                         '10': '% Households $100,000-$149,999', '11': '% Households $150,000-$199,999',
                                                                        '12': '% Households $200,000 or More', '13': 'Median Household Income ($)',
                                                                       '14': 'Mean Household Income ($)'})
initial_pa_households_2012 = initial_pa_households_2012.drop(0)
initial_pa_households_2012 = initial_pa_households_2012.reset_index(drop=True)
initial_pa_households_2012['County'] = initial_pa_households_2012['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_households_2012['County'] = initial_pa_households_2012['County'].apply(lambda x: x.upper())
initial_pa_households_2012.insert(0, 'Year', 2012)
initial_pa_households_2012['% Households <$10,000'] = initial_pa_households_2012['% Households <$10,000'].str.rstrip('%').astype(float) / 100
initial_pa_households_2012['% Households $10,000-$14,999'] = initial_pa_households_2012['% Households $10,000-$14,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2012['% Households $15,000-$24,999'] = initial_pa_households_2012['% Households $15,000-$24,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2012['% Households $25,000-$34,999'] = initial_pa_households_2012['% Households $25,000-$34,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2012['% Households $35,000-$49,999'] = initial_pa_households_2012['% Households $35,000-$49,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2012['% Households $50,000-$74,999'] = initial_pa_households_2012['% Households $50,000-$74,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2012['% Households $75,000-$99,999'] = initial_pa_households_2012['% Households $75,000-$99,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2012['% Households $100,000-$149,999'] = initial_pa_households_2012['% Households $100,000-$149,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2012['% Households $150,000-$199,999'] = initial_pa_households_2012['% Households $150,000-$199,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2012['% Households $200,000 or More'] = initial_pa_households_2012['% Households $200,000 or More'].str.rstrip('%').astype(float) / 100
initial_pa_households_2012['# of Households'] = initial_pa_households_2012['# of Households'].str.replace(',', '').astype(float)
initial_pa_households_2012['Median Household Income ($)'] = initial_pa_households_2012['Median Household Income ($)'].str.replace(',', '').astype(float)
initial_pa_households_2012['Mean Household Income ($)'] = initial_pa_households_2012['Mean Household Income ($)'].str.replace(',', '').astype(float)
initial_pa_households_2012


Year          County  # of Households  % Households <$10,000  \
0   2012           ADAMS          38102.0                  0.035   
1   2012       ALLEGHENY         527219.0                  0.079   
2   2012       ARMSTRONG          29099.0                  0.087   
3   2012          BEAVER          70767.0                  0.061   
4   2012           BERKS         151291.0                  0.064   
5   2012           BLAIR          50098.0                  0.081   
6   2012           BUCKS         231626.0                  0.037   
7   2012          BUTLER          73318.0                  0.054   
8   2012         CAMBRIA          58228.0                  0.084   
9   2012          CARBON          26476.0                  0.055   
10  2012          CENTRE          56980.0                  0.107   
11  2012         CHESTER         184574.0                  0.040   
12  2012      CLEARFIELD          32186.0                  0.073   
13  2012        COLUMBIA          26460.0                  0.065   
14  2012        CRAWFORD          34792.0                  0.080   
15  2012      CUMBERLAND          94453.0                  0.051   
16  2012         DAUPHIN         107336.0                  0.063   
17  2012        DELAWARE         204112.0                  0.063   
18  2012            ERIE         109973.0                  0.083   
19  2012         FAYETTE          53599.0                  0.094   
20  2012        FRANKLIN          58515.0                  0.053   
21  2012         INDIANA          34934.0                  0.081   
22  2012      LACKAWANNA          85491.0                  0.065   
23  2012       LANCASTER         194198.0                  0.049   
24  2012        LAWRENCE          37154.0                  0.082   
25  2012         LEBANON          52424.0                  0.056   
26  2012          LEHIGH         133861.0                  0.060   
27  2012         LUZERNE         129158.0                  0.091   
28  2012        LYCOMING          45595.0                  0.067   
29  2012          MERCER          45647.0                  0.075   
30  2012          MONROE          57561.0                  0.048   
31  2012      MONTGOMERY         308795.0                  0.036   
32  2012     NORTHAMPTON         112574.0                  0.049   
33  2012  NORTHUMBERLAND          39070.0                  0.077   
34  2012    PHILADELPHIA         579874.0                  0.148   
35  2012      SCHUYLKILL          59338.0                  0.069   
36  2012        SOMERSET          30048.0                  0.064   
37  2012      WASHINGTON          84509.0                  0.061   
38  2012    WESTMORELAND         152420.0                  0.060   
39  2012            YORK         168508.0                  0.055   

    % Households $10,000-$14,999  % Households $15,000-$24,999  \
0                          0.055                         0.104   
1                          0.052                         0.115   
2                          0.057                         0.131   
3                          0.061                         0.138   
4                          0.056                         0.110   
5                          0.071                         0.136   
6                          0.030                         0.072   
7                          0.054                         0.099   
8                          0.100                         0.131   
9                          0.073                         0.107   
10                         0.047                         0.116   
11                         0.028                         0.065   
12                         0.073                         0.136   
13                         0.061                         0.140   
14                         0.062                         0.150   
15                         0.038                         0.106   
16                         0.045                         0.114   
17                         

**2016**
-

In [58]:
# Reading in 2016 U.S. Census Bureau income (household) dataset
initial_pa_households_2016 = pd.read_excel("Resources/PA_Income_Households_2016.xlsx")
initial_pa_households_2016.head(19)


Unnamed: 0 Adams County, Pennsylvania  \
0                                      NaN                 Households   
1                                    Label                   Estimate   
2                                    Total                     38,125   
3                        Less than $10,000                       3.5%   
4                       $10,000 to $14,999                       4.7%   
5                       $15,000 to $24,999                       7.5%   
6                       $25,000 to $34,999                      12.8%   
7                       $35,000 to $49,999                      15.3%   
8                       $50,000 to $74,999                      16.7%   
9                       $75,000 to $99,999                      16.3%   
10                    $100,000 to $149,999                      15.5%   
11                    $150,000 to $199,999                       4.6%   
12                        $200,000 or more                       3.2%   
13                 Median income (dollars)                     59,300   
14                   Mean income (dollars)                     72,296   
15                       PERCENT ALLOCATED                        NaN   
16  Household income in the past 12 months                      30.2%   
17     Family income in the past 12 months                        (X)   
18  Nonfamily income in the past 12 months                        (X)   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
0                      Households                     Households   
1                        Estimate                       Estimate   
2                         528,892                         26,105   
3                            7.2%                           6.1%   
4                            5.1%                           7.1%   
5                           10.3%                          12.6%   
6                            9.5%                          12.0%   
7                           12.8%                          14.0%   
8                           17.1%                          21.3%   
9                           12.4%                           9.6%   
10                          14.3%                          12.1%   
11                           5.5%                           2.4%   
12                           5.8%                           2.7%   
13                         56,140                         47,398   
14                         78,027                         60,137   
15                            NaN                            NaN   
16                          31.8%                          35.7%   
17                            (X)                            (X)   
18                            (X)                            (X)   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
0                   Households                 Households   
1                     Estimate                   Estimate   
2                       68,811                    150,402   
3                         5.2%                       5.9%   
4                         4.5%                       4.2%   
5                         9.6%                       9.3%   
6                        10.9%                       8.2%   
7                        14.9%                      14.3%   
8                        18.9%                      18.5%   
9                        13.9%                      14.5%   
10                       14.0%                      14.7%   
11                        4.8%                       6.0%   
12                        3.3%                       4.3%   
13                      55,221                     59,286   
14                      69,655                     76,779   
15                         NaN                        NaN   
16                       34.4%                      37.1%   
17                         (X)                        (X)   
18                         (X)                     

In [59]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Four groupings = Households, Families, Married-couple families & non family households
# % of groups above that fall into the income categories: Less Than $10,000, $10,000-$14,999, $15,000-$24,999, $25,000-$34,999,
# $35,000-$49,999, $50,000-$74,999, $75,000-$99,999, $100,000-$149,999, $150,000-$199,999, $200,000 or More
# Total count for each grouping
# Median income for each grouping
# Mean income for each grouping
initial_pa_households_2016 = initial_pa_households_2016.iloc[[2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], :]
initial_pa_households_2016


Unnamed: 0 Adams County, Pennsylvania  \
2                     Total                     38,125   
3         Less than $10,000                       3.5%   
4        $10,000 to $14,999                       4.7%   
5        $15,000 to $24,999                       7.5%   
6        $25,000 to $34,999                      12.8%   
7        $35,000 to $49,999                      15.3%   
8        $50,000 to $74,999                      16.7%   
9        $75,000 to $99,999                      16.3%   
10     $100,000 to $149,999                      15.5%   
11     $150,000 to $199,999                       4.6%   
12         $200,000 or more                       3.2%   
13  Median income (dollars)                     59,300   
14    Mean income (dollars)                     72,296   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
2                         528,892                         26,105   
3                            7.2%                           6.1%   
4                            5.1%                           7.1%   
5                           10.3%                          12.6%   
6                            9.5%                          12.0%   
7                           12.8%                          14.0%   
8                           17.1%                          21.3%   
9                           12.4%                           9.6%   
10                          14.3%                          12.1%   
11                           5.5%                           2.4%   
12                           5.8%                           2.7%   
13                         56,140                         47,398   
14                         78,027                         60,137   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
2                       68,811                    150,402   
3                         5.2%                       5.9%   
4                         4.5%                       4.2%   
5                         9.6%                       9.3%   
6                        10.9%                       8.2%   
7                        14.9%                      14.3%   
8                        18.9%                      18.5%   
9                        13.9%                      14.5%   
10                       14.0%                      14.7%   
11                        4.8%                       6.0%   
12                        3.3%                       4.3%   
13                      55,221                     59,286   
14                      69,655                     76,779   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
2                      51,154                    234,126   
3                        6.5%                       4.0%   
4                        6.3%                       2.3%   
5                       12.3%                       6.6%   
6                       14.0%                       6.3%   
7                       16.5%                      10.3%   
8                       19.7%                      17.4%   
9                       11.7%                      14.1%   
10                       8.8%                      19.2%   
11                       2.5%                       8.7%   
12                       1.6%                      11.1%   
13                     43,443                     79,936   
14                     58,867                    106,713   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
2                       75,472                       56,443  ...   
3                         4.0%                         7.0%  ...   
4                         2.8%                         7.1%  ...   
5                         8.7%                        12.7%  ...   
6                         8.0%                        11.7%  ...   
7                        13.5%                        16.1%  ...   
8                        18.4%                        18.2%  ...   
9          

In [60]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_households_2016 = initial_pa_households_2016.T
initial_pa_households_2016.head()


2                  3   \
Unnamed: 0                        Total  Less than $10,000   
Adams County, Pennsylvania       38,125               3.5%   
Allegheny County, Pennsylvania  528,892               7.2%   
Armstrong County, Pennsylvania   26,105               6.1%   
Beaver County, Pennsylvania      68,811               5.2%   

                                                4                   5   \
Unnamed: 0                      $10,000 to $14,999  $15,000 to $24,999   
Adams County, Pennsylvania                    4.7%                7.5%   
Allegheny County, Pennsylvania                5.1%               10.3%   
Armstrong County, Pennsylvania                7.1%               12.6%   
Beaver County, Pennsylvania                   4.5%                9.6%   

                                                6                   7   \
Unnamed: 0                      $25,000 to $34,999  $35,000 to $49,999   
Adams County, Pennsylvania                   12.8%               15.3%   
Allegheny County, Pennsylvania                9.5%               12.8%   
Armstrong County, Pennsylvania               12.0%               14.0%   
Beaver County, Pennsylvania                  10.9%               14.9%   

                                                8                   9   \
Unnamed: 0                      $50,000 to $74,999  $75,000 to $99,999   
Adams County, Pennsylvania                   16.7%               16.3%   
Allegheny County, Pennsylvania               17.1%               12.4%   
Armstrong County, Pennsylvania               21.3%                9.6%   
Beaver County, Pennsylvania                  18.9%               13.9%   

                                                  10                    11  \
Unnamed: 0                      $100,000 to $149,999  $150,000 to $199,999   
Adams County, Pennsylvania                     15.5%                  4.6%   
Allegheny County, Pennsylvania                 14.3%                  5.5%   
Armstrong County, Pennsylvania                 12.1%                  2.4%   
Beaver County, Pennsylvania                    14.0%                  4.8%   

                                              12                       13  \
Unnamed: 0                      $200,000 or more  Median income (dollars)   
Adams County, Pennsylvania                  3.2%                   59,300   
Allegheny County, Pennsylvania              5.8%                   56,140   
Armstrong County, Pennsylvania              2.7%                   47,398   
Beaver County, Pennsylvania                 3.3%                   55,221   

                                                   14  
Unnamed: 0                      Mean income (dollars)  
Adams County, Pennsylvania                     72,296  
Allegheny County, Pennsylvania                 78,027  
Armstrong County, Pennsylvania                 60,137  
Beaver County, Pennsylvania                    69,655

In [61]:
# Resetting index and renaming to create a 'County' column
initial_pa_households_2016 = initial_pa_households_2016.reset_index()
initial_pa_households_2016.rename(columns={'index': 'County'}, inplace=True)
initial_pa_households_2016.head()


County        2                  3  \
0                      Unnamed: 0    Total  Less than $10,000   
1      Adams County, Pennsylvania   38,125               3.5%   
2  Allegheny County, Pennsylvania  528,892               7.2%   
3  Armstrong County, Pennsylvania   26,105               6.1%   
4     Beaver County, Pennsylvania   68,811               5.2%   

                    4                   5                   6  \
0  $10,000 to $14,999  $15,000 to $24,999  $25,000 to $34,999   
1                4.7%                7.5%               12.8%   
2                5.1%               10.3%                9.5%   
3                7.1%               12.6%               12.0%   
4                4.5%                9.6%               10.9%   

                    7                   8                   9  \
0  $35,000 to $49,999  $50,000 to $74,999  $75,000 to $99,999   
1               15.3%               16.7%               16.3%   
2               12.8%               17.1%               12.4%   
3               14.0%               21.3%                9.6%   
4               14.9%               18.9%               13.9%   

                     10                    11                12  \
0  $100,000 to $149,999  $150,000 to $199,999  $200,000 or more   
1                 15.5%                  4.6%              3.2%   
2                 14.3%                  5.5%              5.8%   
3                 12.1%                  2.4%              2.7%   
4                 14.0%                  4.8%              3.3%   

                        13                     14  
0  Median income (dollars)  Mean income (dollars)  
1                   59,300                 72,296  
2                   56,140                 78,027  
3                   47,398                 60,137  
4                   55,221                 69,655

In [62]:
# Confirming column data types prior to renaming
print(initial_pa_households_2016.columns)


Index(['County', 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], dtype='object')


In [63]:
# Converting column data types from integers to strings for renaming
initial_pa_households_2016.columns = initial_pa_households_2016.columns.astype(str)
print(initial_pa_households_2016.columns)


Index(['County', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12',
       '13', '14'],
      dtype='object')


In [64]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_households_2016.replace('N', np.nan, inplace=True)


In [65]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_households_2016 = initial_pa_households_2016.rename(columns={'2': '# of Households', '3': '% Households <$10,000', '4': '% Households $10,000-$14,999',
                                                                         '5': '% Households $15,000-$24,999', '6': '% Households $25,000-$34,999', '7': '% Households $35,000-$49,999',
                                                                         '8': '% Households $50,000-$74,999', '9': '% Households $75,000-$99,999',
                                                                         '10': '% Households $100,000-$149,999', '11': '% Households $150,000-$199,999',
                                                                        '12': '% Households $200,000 or More', '13': 'Median Household Income ($)',
                                                                       '14': 'Mean Household Income ($)'})
initial_pa_households_2016 = initial_pa_households_2016.drop(0)
initial_pa_households_2016 = initial_pa_households_2016.reset_index(drop=True)
initial_pa_households_2016['County'] = initial_pa_households_2016['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_households_2016['County'] = initial_pa_households_2016['County'].apply(lambda x: x.upper())
initial_pa_households_2016.insert(0, 'Year', 2016)
initial_pa_households_2016['% Households <$10,000'] = initial_pa_households_2016['% Households <$10,000'].str.rstrip('%').astype(float) / 100
initial_pa_households_2016['% Households $10,000-$14,999'] = initial_pa_households_2016['% Households $10,000-$14,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2016['% Households $15,000-$24,999'] = initial_pa_households_2016['% Households $15,000-$24,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2016['% Households $25,000-$34,999'] = initial_pa_households_2016['% Households $25,000-$34,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2016['% Households $35,000-$49,999'] = initial_pa_households_2016['% Households $35,000-$49,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2016['% Households $50,000-$74,999'] = initial_pa_households_2016['% Households $50,000-$74,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2016['% Households $75,000-$99,999'] = initial_pa_households_2016['% Households $75,000-$99,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2016['% Households $100,000-$149,999'] = initial_pa_households_2016['% Households $100,000-$149,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2016['% Households $150,000-$199,999'] = initial_pa_households_2016['% Households $150,000-$199,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2016['% Households $200,000 or More'] = initial_pa_households_2016['% Households $200,000 or More'].str.rstrip('%').astype(float) / 100
initial_pa_households_2016['# of Households'] = initial_pa_households_2016['# of Households'].str.replace(',', '').astype(float)
initial_pa_households_2016['Median Household Income ($)'] = initial_pa_households_2016['Median Household Income ($)'].str.replace(',', '').astype(float)
initial_pa_households_2016['Mean Household Income ($)'] = initial_pa_households_2016['Mean Household Income ($)'].str.replace(',', '').astype(float)
initial_pa_households_2016


Year          County  # of Households  % Households <$10,000  \
0   2016           ADAMS          38125.0                  0.035   
1   2016       ALLEGHENY         528892.0                  0.072   
2   2016       ARMSTRONG          26105.0                  0.061   
3   2016          BEAVER          68811.0                  0.052   
4   2016           BERKS         150402.0                  0.059   
5   2016           BLAIR          51154.0                  0.065   
6   2016           BUCKS         234126.0                  0.040   
7   2016          BUTLER          75472.0                  0.040   
8   2016         CAMBRIA          56443.0                  0.070   
9   2016          CARBON          25986.0                  0.042   
10  2016          CENTRE          57410.0                  0.092   
11  2016         CHESTER         187188.0                  0.036   
12  2016      CLEARFIELD          29061.0                  0.052   
13  2016        COLUMBIA          26531.0                  0.070   
14  2016        CRAWFORD          33955.0                  0.062   
15  2016      CUMBERLAND          96906.0                  0.027   
16  2016         DAUPHIN         111260.0                  0.053   
17  2016        DELAWARE         205188.0                  0.058   
18  2016            ERIE         109705.0                  0.070   
19  2016         FAYETTE          53662.0                  0.071   
20  2016        FRANKLIN          60492.0                  0.035   
21  2016         INDIANA          34786.0                  0.089   
22  2016      LACKAWANNA          86203.0                  0.075   
23  2016       LANCASTER         196807.0                  0.037   
24  2016        LAWRENCE          35861.0                  0.080   
25  2016         LEBANON          51143.0                  0.036   
26  2016          LEHIGH         139199.0                  0.048   
27  2016         LUZERNE         124118.0                  0.074   
28  2016        LYCOMING          45525.0                  0.059   
29  2016          MERCER          45630.0                  0.057   
30  2016          MONROE          57284.0                  0.049   
31  2016      MONTGOMERY         312447.0                  0.030   
32  2016     NORTHAMPTON         111760.0                  0.029   
33  2016  NORTHUMBERLAND          38098.0                  0.063   
34  2016    PHILADELPHIA         580205.0                  0.145   
35  2016      SCHUYLKILL          58149.0                  0.070   
36  2016        SOMERSET          29189.0                  0.078   
37  2016      WASHINGTON          83117.0                  0.047   
38  2016    WESTMORELAND         148238.0                  0.054   
39  2016            YORK         169885.0                  0.043   

    % Households $10,000-$14,999  % Households $15,000-$24,999  \
0                          0.047                         0.075   
1                          0.051                         0.103   
2                          0.071                         0.126   
3                          0.045                         0.096   
4                          0.042                         0.093   
5                          0.063                         0.123   
6                          0.023                         0.066   
7                          0.028                         0.087   
8                          0.071                         0.127   
9                          0.066                         0.101   
10                         0.038                         0.091   
11                         0.025                         0.062   
12                         0.090                         0.119   
13                         0.063                         0.109   
14                         0.047                         0.133   
15                         0.033                         0.094   
16                         0.041                         0.082   
17                         

**2019**
-
Please note: 2020 United States Census Bureau was unavailable and as such the closest year prior to the election (2019) was utilized

In [66]:
# Reading in 2019 U.S. Census Bureau income (household) dataset
initial_pa_households_2019 = pd.read_excel("Resources/PA_Income_Households_2019.xlsx")
initial_pa_households_2019.head(19)


Unnamed: 0 Adams County, Pennsylvania  \
0                                      NaN                 Households   
1                                    Label                   Estimate   
2                                    Total                     38,703   
3                        Less than $10,000                       2.6%   
4                       $10,000 to $14,999                       3.2%   
5                       $15,000 to $24,999                       9.3%   
6                       $25,000 to $34,999                       8.1%   
7                       $35,000 to $49,999                      13.2%   
8                       $50,000 to $74,999                      18.0%   
9                       $75,000 to $99,999                      17.4%   
10                    $100,000 to $149,999                      16.2%   
11                    $150,000 to $199,999                       6.7%   
12                        $200,000 or more                       5.2%   
13                 Median income (dollars)                     67,715   
14                   Mean income (dollars)                     84,262   
15                       PERCENT ALLOCATED                        NaN   
16  Household income in the past 12 months                      28.4%   
17     Family income in the past 12 months                        (X)   
18  Nonfamily income in the past 12 months                        (X)   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
0                      Households                     Households   
1                        Estimate                       Estimate   
2                         553,858                         29,095   
3                            6.4%                           3.1%   
4                            3.6%                           5.7%   
5                            8.4%                          12.2%   
6                            8.6%                           8.2%   
7                           11.9%                          15.3%   
8                           17.5%                          22.6%   
9                           12.7%                          13.6%   
10                          16.1%                          12.6%   
11                           7.0%                           4.2%   
12                           7.9%                           2.5%   
13                         64,871                         57,636   
14                         91,448                         68,661   
15                            NaN                            NaN   
16                          33.7%                          38.1%   
17                            (X)                            (X)   
18                            (X)                            (X)   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
0                   Households                 Households   
1                     Estimate                   Estimate   
2                       70,745                    154,696   
3                         5.2%                       5.0%   
4                         4.8%                       3.1%   
5                         9.9%                       7.8%   
6                         8.7%                       7.6%   
7                        14.3%                      13.7%   
8                        17.5%                      18.1%   
9                        13.7%                      13.6%   
10                       15.2%                      19.3%   
11                        6.8%                       6.6%   
12                        3.8%                       5.2%   
13                      60,672                     67,708   
14                      75,836                     84,720   
15                         NaN                        NaN   
16                       35.3%                      44.7%   
17                         (X)                        (X)   
18                         (X)                     

In [67]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Four groupings = Households, Families, Married-couple families & non family households
# % of groups above that fall into the income categories: Less Than $10,000, $10,000-$14,999, $15,000-$24,999, $25,000-$34,999,
# $35,000-$49,999, $50,000-$74,999, $75,000-$99,999, $100,000-$149,999, $150,000-$199,999, $200,000 or More
# Total count for each grouping
# Median income for each grouping
# Mean income for each grouping
initial_pa_households_2019 = initial_pa_households_2019.iloc[[2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], :]
initial_pa_households_2019


Unnamed: 0 Adams County, Pennsylvania  \
2                     Total                     38,703   
3         Less than $10,000                       2.6%   
4        $10,000 to $14,999                       3.2%   
5        $15,000 to $24,999                       9.3%   
6        $25,000 to $34,999                       8.1%   
7        $35,000 to $49,999                      13.2%   
8        $50,000 to $74,999                      18.0%   
9        $75,000 to $99,999                      17.4%   
10     $100,000 to $149,999                      16.2%   
11     $150,000 to $199,999                       6.7%   
12         $200,000 or more                       5.2%   
13  Median income (dollars)                     67,715   
14    Mean income (dollars)                     84,262   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
2                         553,858                         29,095   
3                            6.4%                           3.1%   
4                            3.6%                           5.7%   
5                            8.4%                          12.2%   
6                            8.6%                           8.2%   
7                           11.9%                          15.3%   
8                           17.5%                          22.6%   
9                           12.7%                          13.6%   
10                          16.1%                          12.6%   
11                           7.0%                           4.2%   
12                           7.9%                           2.5%   
13                         64,871                         57,636   
14                         91,448                         68,661   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
2                       70,745                    154,696   
3                         5.2%                       5.0%   
4                         4.8%                       3.1%   
5                         9.9%                       7.8%   
6                         8.7%                       7.6%   
7                        14.3%                      13.7%   
8                        17.5%                      18.1%   
9                        13.7%                      13.6%   
10                       15.2%                      19.3%   
11                        6.8%                       6.6%   
12                        3.8%                       5.2%   
13                      60,672                     67,708   
14                      75,836                     84,720   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
2                      52,497                    240,491   
3                        6.5%                       3.0%   
4                        4.8%                       1.9%   
5                       10.0%                       7.0%   
6                       11.7%                       5.4%   
7                       15.9%                       8.7%   
8                       17.5%                      14.1%   
9                       12.6%                      12.9%   
10                      13.2%                      20.3%   
11                       5.1%                      12.0%   
12                       2.8%                      14.8%   
13                     51,004                     93,767   
14                     69,143                    120,851   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
2                       77,920                       56,490  ...   
3                         6.2%                         8.0%  ...   
4                         3.3%                         7.1%  ...   
5                         6.9%                        10.8%  ...   
6                         7.6%                        10.8%  ...   
7                        11.0%                        14.0%  ...   
8                        16.4%                        18.2%  ...   
9          

In [68]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_households_2019 = initial_pa_households_2019.T
initial_pa_households_2019.head()


2                  3   \
Unnamed: 0                        Total  Less than $10,000   
Adams County, Pennsylvania       38,703               2.6%   
Allegheny County, Pennsylvania  553,858               6.4%   
Armstrong County, Pennsylvania   29,095               3.1%   
Beaver County, Pennsylvania      70,745               5.2%   

                                                4                   5   \
Unnamed: 0                      $10,000 to $14,999  $15,000 to $24,999   
Adams County, Pennsylvania                    3.2%                9.3%   
Allegheny County, Pennsylvania                3.6%                8.4%   
Armstrong County, Pennsylvania                5.7%               12.2%   
Beaver County, Pennsylvania                   4.8%                9.9%   

                                                6                   7   \
Unnamed: 0                      $25,000 to $34,999  $35,000 to $49,999   
Adams County, Pennsylvania                    8.1%               13.2%   
Allegheny County, Pennsylvania                8.6%               11.9%   
Armstrong County, Pennsylvania                8.2%               15.3%   
Beaver County, Pennsylvania                   8.7%               14.3%   

                                                8                   9   \
Unnamed: 0                      $50,000 to $74,999  $75,000 to $99,999   
Adams County, Pennsylvania                   18.0%               17.4%   
Allegheny County, Pennsylvania               17.5%               12.7%   
Armstrong County, Pennsylvania               22.6%               13.6%   
Beaver County, Pennsylvania                  17.5%               13.7%   

                                                  10                    11  \
Unnamed: 0                      $100,000 to $149,999  $150,000 to $199,999   
Adams County, Pennsylvania                     16.2%                  6.7%   
Allegheny County, Pennsylvania                 16.1%                  7.0%   
Armstrong County, Pennsylvania                 12.6%                  4.2%   
Beaver County, Pennsylvania                    15.2%                  6.8%   

                                              12                       13  \
Unnamed: 0                      $200,000 or more  Median income (dollars)   
Adams County, Pennsylvania                  5.2%                   67,715   
Allegheny County, Pennsylvania              7.9%                   64,871   
Armstrong County, Pennsylvania              2.5%                   57,636   
Beaver County, Pennsylvania                 3.8%                   60,672   

                                                   14  
Unnamed: 0                      Mean income (dollars)  
Adams County, Pennsylvania                     84,262  
Allegheny County, Pennsylvania                 91,448  
Armstrong County, Pennsylvania                 68,661  
Beaver County, Pennsylvania                    75,836

In [69]:
# Resetting index and renaming to create a 'County' column
initial_pa_households_2019 = initial_pa_households_2019.reset_index()
initial_pa_households_2019.rename(columns={'index': 'County'}, inplace=True)
initial_pa_households_2019.head()


County        2                  3  \
0                      Unnamed: 0    Total  Less than $10,000   
1      Adams County, Pennsylvania   38,703               2.6%   
2  Allegheny County, Pennsylvania  553,858               6.4%   
3  Armstrong County, Pennsylvania   29,095               3.1%   
4     Beaver County, Pennsylvania   70,745               5.2%   

                    4                   5                   6  \
0  $10,000 to $14,999  $15,000 to $24,999  $25,000 to $34,999   
1                3.2%                9.3%                8.1%   
2                3.6%                8.4%                8.6%   
3                5.7%               12.2%                8.2%   
4                4.8%                9.9%                8.7%   

                    7                   8                   9  \
0  $35,000 to $49,999  $50,000 to $74,999  $75,000 to $99,999   
1               13.2%               18.0%               17.4%   
2               11.9%               17.5%               12.7%   
3               15.3%               22.6%               13.6%   
4               14.3%               17.5%               13.7%   

                     10                    11                12  \
0  $100,000 to $149,999  $150,000 to $199,999  $200,000 or more   
1                 16.2%                  6.7%              5.2%   
2                 16.1%                  7.0%              7.9%   
3                 12.6%                  4.2%              2.5%   
4                 15.2%                  6.8%              3.8%   

                        13                     14  
0  Median income (dollars)  Mean income (dollars)  
1                   67,715                 84,262  
2                   64,871                 91,448  
3                   57,636                 68,661  
4                   60,672                 75,836

In [70]:
# Confirming column data types prior to renaming
print(initial_pa_households_2019.columns)


Index(['County', 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], dtype='object')


In [71]:
# Converting column data types from integers to strings for renaming
initial_pa_households_2019.columns = initial_pa_households_2019.columns.astype(str)
print(initial_pa_households_2019.columns)


Index(['County', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12',
       '13', '14'],
      dtype='object')


In [72]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_households_2019.replace('N', np.nan, inplace=True)


In [73]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_households_2019 = initial_pa_households_2019.rename(columns={'2': '# of Households', '3': '% Households <$10,000', '4': '% Households $10,000-$14,999',
                                                                         '5': '% Households $15,000-$24,999', '6': '% Households $25,000-$34,999', '7': '% Households $35,000-$49,999',
                                                                         '8': '% Households $50,000-$74,999', '9': '% Households $75,000-$99,999',
                                                                         '10': '% Households $100,000-$149,999', '11': '% Households $150,000-$199,999',
                                                                        '12': '% Households $200,000 or More', '13': 'Median Household Income ($)',
                                                                       '14': 'Mean Household Income ($)'})
initial_pa_households_2019 = initial_pa_households_2019.drop(0)
initial_pa_households_2019 = initial_pa_households_2019.reset_index(drop=True)
initial_pa_households_2019['County'] = initial_pa_households_2019['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_households_2019['County'] = initial_pa_households_2019['County'].apply(lambda x: x.upper())
initial_pa_households_2019.insert(0, 'Year', 2020)
initial_pa_households_2019['% Households <$10,000'] = initial_pa_households_2019['% Households <$10,000'].str.rstrip('%').astype(float) / 100
initial_pa_households_2019['% Households $10,000-$14,999'] = initial_pa_households_2019['% Households $10,000-$14,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2019['% Households $15,000-$24,999'] = initial_pa_households_2019['% Households $15,000-$24,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2019['% Households $25,000-$34,999'] = initial_pa_households_2019['% Households $25,000-$34,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2019['% Households $35,000-$49,999'] = initial_pa_households_2019['% Households $35,000-$49,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2019['% Households $50,000-$74,999'] = initial_pa_households_2019['% Households $50,000-$74,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2019['% Households $75,000-$99,999'] = initial_pa_households_2019['% Households $75,000-$99,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2019['% Households $100,000-$149,999'] = initial_pa_households_2019['% Households $100,000-$149,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2019['% Households $150,000-$199,999'] = initial_pa_households_2019['% Households $150,000-$199,999'].str.rstrip('%').astype(float) / 100
initial_pa_households_2019['% Households $200,000 or More'] = initial_pa_households_2019['% Households $200,000 or More'].str.rstrip('%').astype(float) / 100
initial_pa_households_2019['# of Households'] = initial_pa_households_2019['# of Households'].str.replace(',', '').astype(float)
initial_pa_households_2019['Median Household Income ($)'] = initial_pa_households_2019['Median Household Income ($)'].str.replace(',', '').astype(float)
initial_pa_households_2019['Mean Household Income ($)'] = initial_pa_households_2019['Mean Household Income ($)'].str.replace(',', '').astype(float)
initial_pa_households_2019


Year          County  # of Households  % Households <$10,000  \
0   2020           ADAMS          38703.0                  0.026   
1   2020       ALLEGHENY         553858.0                  0.064   
2   2020       ARMSTRONG          29095.0                  0.031   
3   2020          BEAVER          70745.0                  0.052   
4   2020           BERKS         154696.0                  0.050   
5   2020           BLAIR          52497.0                  0.065   
6   2020           BUCKS         240491.0                  0.030   
7   2020          BUTLER          77920.0                  0.062   
8   2020         CAMBRIA          56490.0                  0.080   
9   2020          CARBON          27107.0                  0.036   
10  2020          CENTRE          58963.0                  0.068   
11  2020         CHESTER         193234.0                  0.032   
12  2020      CLEARFIELD          31990.0                  0.055   
13  2020        COLUMBIA          26219.0                  0.083   
14  2020        CRAWFORD          35387.0                  0.050   
15  2020      CUMBERLAND         101823.0                  0.032   
16  2020         DAUPHIN         113905.0                  0.066   
17  2020        DELAWARE         209502.0                  0.052   
18  2020            ERIE         110128.0                  0.081   
19  2020         FAYETTE          54955.0                  0.076   
20  2020        FRANKLIN          60260.0                  0.029   
21  2020         INDIANA          30704.0                  0.061   
22  2020      LACKAWANNA          88154.0                  0.056   
23  2020       LANCASTER         204701.0                  0.047   
24  2020        LAWRENCE          37282.0                  0.073   
25  2020         LEBANON          53861.0                  0.040   
26  2020          LEHIGH         137847.0                  0.046   
27  2020         LUZERNE         130890.0                  0.070   
28  2020        LYCOMING          44842.0                  0.056   
29  2020          MERCER          46427.0                  0.053   
30  2020          MONROE          56274.0                  0.056   
31  2020      MONTGOMERY         321373.0                  0.030   
32  2020     NORTHAMPTON         114950.0                  0.041   
33  2020  NORTHUMBERLAND          38592.0                  0.056   
34  2020    PHILADELPHIA         619505.0                  0.122   
35  2020      SCHUYLKILL          58242.0                  0.050   
36  2020        SOMERSET          29456.0                  0.059   
37  2020      WASHINGTON          86716.0                  0.051   
38  2020    WESTMORELAND         155147.0                  0.072   
39  2020            YORK         175441.0                  0.043   

    % Households $10,000-$14,999  % Households $15,000-$24,999  \
0                          0.032                         0.093   
1                          0.036                         0.084   
2                          0.057                         0.122   
3                          0.048                         0.099   
4                          0.031                         0.078   
5                          0.048                         0.100   
6                          0.019                         0.070   
7                          0.033                         0.069   
8                          0.071                         0.108   
9                          0.034                         0.080   
10                         0.037                         0.101   
11                         0.020                         0.045   
12                         0.062                         0.111   
13                         0.056                         0.071   
14                         0.057                         0.113   
15                         0.028                         0.062   
16                         0.028                         0.094   
17                         

**Income (Families) Data Extraction, Transformation & Loading (2012, 2016 & 2019)**
-
-----------

In [74]:
# Reading in 2012 U.S. Census Bureau income (families) dataset
initial_pa_families_2012 = pd.read_excel("Resources/PA_Income_Families_2012.xlsx")
initial_pa_families_2012.head(19)


Unnamed: 0 Adams County, Pennsylvania  \
0                                      NaN                   Families   
1                                    Label                   Estimate   
2                                    Total                     27,025   
3                        Less than $10,000                       1.2%   
4                       $10,000 to $14,999                       2.8%   
5                       $15,000 to $24,999                       8.1%   
6                       $25,000 to $34,999                       7.7%   
7                       $35,000 to $49,999                      10.1%   
8                       $50,000 to $74,999                      22.1%   
9                       $75,000 to $99,999                      21.0%   
10                    $100,000 to $149,999                      18.2%   
11                    $150,000 to $199,999                       6.0%   
12                        $200,000 or more                       2.8%   
13                 Median income (dollars)                     71,371   
14                   Mean income (dollars)                     80,738   
15                         PERCENT IMPUTED                        NaN   
16  Household income in the past 12 months                        (X)   
17     Family income in the past 12 months                      24.3%   
18  Nonfamily income in the past 12 months                        (X)   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
0                        Families                       Families   
1                        Estimate                       Estimate   
2                         304,375                         19,535   
3                            4.8%                           5.1%   
4                            2.6%                           3.0%   
5                            7.1%                           7.7%   
6                            7.9%                          12.7%   
7                           12.4%                          20.7%   
8                           18.9%                          21.9%   
9                           15.9%                          12.9%   
10                          17.7%                          11.7%   
11                           6.5%                           1.5%   
12                           6.2%                           2.8%   
13                         69,212                         50,469   
14                         91,391                         61,919   
15                            NaN                            NaN   
16                            (X)                            (X)   
17                          27.1%                          30.4%   
18                            (X)                            (X)   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
0                     Families                   Families   
1                     Estimate                   Estimate   
2                       45,560                    103,312   
3                         4.2%                       5.1%   
4                         1.8%                       2.8%   
5                         9.4%                       7.5%   
6                         9.1%                       8.8%   
7                        13.2%                      13.6%   
8                        23.8%                      20.8%   
9                        16.1%                      16.2%   
10                       17.2%                      15.2%   
11                        3.0%                       5.2%   
12                        2.2%                       4.7%   
13                      63,001                     64,264   
14                      71,953                     80,280   
15                         NaN                        NaN   
16                         (X)                        (X)   
17                       29.1%                      31.9%   
18                         (X)                     

In [75]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Four groupings = Households, Families, Married-couple families & non family households
# % of groups above that fall into the income categories: Less Than $10,000, $10,000-$14,999, $15,000-$24,999, $25,000-$34,999,
# $35,000-$49,999, $50,000-$74,999, $75,000-$99,999, $100,000-$149,999, $150,000-$199,999, $200,000 or More
# Total count for each grouping
# Median income for each grouping
# Mean income for each grouping
initial_pa_families_2012 = initial_pa_families_2012.iloc[[2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], :]
initial_pa_families_2012


Unnamed: 0 Adams County, Pennsylvania  \
2                     Total                     27,025   
3         Less than $10,000                       1.2%   
4        $10,000 to $14,999                       2.8%   
5        $15,000 to $24,999                       8.1%   
6        $25,000 to $34,999                       7.7%   
7        $35,000 to $49,999                      10.1%   
8        $50,000 to $74,999                      22.1%   
9        $75,000 to $99,999                      21.0%   
10     $100,000 to $149,999                      18.2%   
11     $150,000 to $199,999                       6.0%   
12         $200,000 or more                       2.8%   
13  Median income (dollars)                     71,371   
14    Mean income (dollars)                     80,738   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
2                         304,375                         19,535   
3                            4.8%                           5.1%   
4                            2.6%                           3.0%   
5                            7.1%                           7.7%   
6                            7.9%                          12.7%   
7                           12.4%                          20.7%   
8                           18.9%                          21.9%   
9                           15.9%                          12.9%   
10                          17.7%                          11.7%   
11                           6.5%                           1.5%   
12                           6.2%                           2.8%   
13                         69,212                         50,469   
14                         91,391                         61,919   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
2                       45,560                    103,312   
3                         4.2%                       5.1%   
4                         1.8%                       2.8%   
5                         9.4%                       7.5%   
6                         9.1%                       8.8%   
7                        13.2%                      13.6%   
8                        23.8%                      20.8%   
9                        16.1%                      16.2%   
10                       17.2%                      15.2%   
11                        3.0%                       5.2%   
12                        2.2%                       4.7%   
13                      63,001                     64,264   
14                      71,953                     80,280   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
2                      32,068                    166,398   
3                        3.3%                       1.3%   
4                        3.4%                       1.6%   
5                        9.5%                       3.9%   
6                       11.7%                       5.5%   
7                       19.6%                      10.2%   
8                       24.5%                      16.9%   
9                       11.0%                      16.3%   
10                      11.4%                      23.1%   
11                       2.5%                      10.9%   
12                       3.1%                      10.4%   
13                     52,079                     90,345   
14                     64,426                    110,787   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
2                       50,201                       37,266  ...   
3                         2.7%                         4.9%  ...   
4                         1.8%                         3.9%  ...   
5                         6.5%                         9.1%  ...   
6                         7.1%                        12.3%  ...   
7                        11.8%                        18.0%  ...   
8                        20.2%                        21.8%  ...   
9          

In [76]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_families_2012 = initial_pa_families_2012.T
initial_pa_families_2012.head()


2                  3   \
Unnamed: 0                        Total  Less than $10,000   
Adams County, Pennsylvania       27,025               1.2%   
Allegheny County, Pennsylvania  304,375               4.8%   
Armstrong County, Pennsylvania   19,535               5.1%   
Beaver County, Pennsylvania      45,560               4.2%   

                                                4                   5   \
Unnamed: 0                      $10,000 to $14,999  $15,000 to $24,999   
Adams County, Pennsylvania                    2.8%                8.1%   
Allegheny County, Pennsylvania                2.6%                7.1%   
Armstrong County, Pennsylvania                3.0%                7.7%   
Beaver County, Pennsylvania                   1.8%                9.4%   

                                                6                   7   \
Unnamed: 0                      $25,000 to $34,999  $35,000 to $49,999   
Adams County, Pennsylvania                    7.7%               10.1%   
Allegheny County, Pennsylvania                7.9%               12.4%   
Armstrong County, Pennsylvania               12.7%               20.7%   
Beaver County, Pennsylvania                   9.1%               13.2%   

                                                8                   9   \
Unnamed: 0                      $50,000 to $74,999  $75,000 to $99,999   
Adams County, Pennsylvania                   22.1%               21.0%   
Allegheny County, Pennsylvania               18.9%               15.9%   
Armstrong County, Pennsylvania               21.9%               12.9%   
Beaver County, Pennsylvania                  23.8%               16.1%   

                                                  10                    11  \
Unnamed: 0                      $100,000 to $149,999  $150,000 to $199,999   
Adams County, Pennsylvania                     18.2%                  6.0%   
Allegheny County, Pennsylvania                 17.7%                  6.5%   
Armstrong County, Pennsylvania                 11.7%                  1.5%   
Beaver County, Pennsylvania                    17.2%                  3.0%   

                                              12                       13  \
Unnamed: 0                      $200,000 or more  Median income (dollars)   
Adams County, Pennsylvania                  2.8%                   71,371   
Allegheny County, Pennsylvania              6.2%                   69,212   
Armstrong County, Pennsylvania              2.8%                   50,469   
Beaver County, Pennsylvania                 2.2%                   63,001   

                                                   14  
Unnamed: 0                      Mean income (dollars)  
Adams County, Pennsylvania                     80,738  
Allegheny County, Pennsylvania                 91,391  
Armstrong County, Pennsylvania                 61,919  
Beaver County, Pennsylvania                    71,953

In [77]:
# Resetting index and renaming to create a 'County' column
initial_pa_families_2012 = initial_pa_families_2012.reset_index()
initial_pa_families_2012.rename(columns={'index': 'County'}, inplace=True)
initial_pa_families_2012.head()


County        2                  3  \
0                      Unnamed: 0    Total  Less than $10,000   
1      Adams County, Pennsylvania   27,025               1.2%   
2  Allegheny County, Pennsylvania  304,375               4.8%   
3  Armstrong County, Pennsylvania   19,535               5.1%   
4     Beaver County, Pennsylvania   45,560               4.2%   

                    4                   5                   6  \
0  $10,000 to $14,999  $15,000 to $24,999  $25,000 to $34,999   
1                2.8%                8.1%                7.7%   
2                2.6%                7.1%                7.9%   
3                3.0%                7.7%               12.7%   
4                1.8%                9.4%                9.1%   

                    7                   8                   9  \
0  $35,000 to $49,999  $50,000 to $74,999  $75,000 to $99,999   
1               10.1%               22.1%               21.0%   
2               12.4%               18.9%               15.9%   
3               20.7%               21.9%               12.9%   
4               13.2%               23.8%               16.1%   

                     10                    11                12  \
0  $100,000 to $149,999  $150,000 to $199,999  $200,000 or more   
1                 18.2%                  6.0%              2.8%   
2                 17.7%                  6.5%              6.2%   
3                 11.7%                  1.5%              2.8%   
4                 17.2%                  3.0%              2.2%   

                        13                     14  
0  Median income (dollars)  Mean income (dollars)  
1                   71,371                 80,738  
2                   69,212                 91,391  
3                   50,469                 61,919  
4                   63,001                 71,953

In [78]:
# Confirming column data types prior to renaming
print(initial_pa_families_2012.columns)


Index(['County', 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], dtype='object')


In [79]:
# Converting column data types from integers to strings for renaming
initial_pa_families_2012.columns = initial_pa_families_2012.columns.astype(str)
print(initial_pa_families_2012.columns)


Index(['County', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12',
       '13', '14'],
      dtype='object')


In [80]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_families_2012.replace('N', np.nan, inplace=True)


In [81]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_families_2012 = initial_pa_families_2012.rename(columns={'2': '# of Families', '3': '% Families <$10,000', '4': '% Families $10,000-$14,999',
                                                                         '5': '% Families $15,000-$24,999', '6': '% Families $25,000-$34,999', '7': '% Families $35,000-$49,999',
                                                                         '8': '% Families $50,000-$74,999', '9': '% Families $75,000-$99,999',
                                                                         '10': '% Families $100,000-$149,999', '11': '% Families $150,000-$199,999',
                                                                        '12': '% Families $200,000 or More', '13': 'Median Families Income ($)',
                                                                       '14': 'Mean Families Income ($)'})
initial_pa_families_2012 = initial_pa_families_2012.drop(0)
initial_pa_families_2012 = initial_pa_families_2012.reset_index(drop=True)
initial_pa_families_2012['County'] = initial_pa_families_2012['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_families_2012['County'] = initial_pa_families_2012['County'].apply(lambda x: x.upper())
initial_pa_families_2012.insert(0, 'Year', 2012)
initial_pa_families_2012['% Families <$10,000'] = initial_pa_families_2012['% Families <$10,000'].str.rstrip('%').astype(float) / 100
initial_pa_families_2012['% Families $10,000-$14,999'] = initial_pa_families_2012['% Families $10,000-$14,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2012['% Families $15,000-$24,999'] = initial_pa_families_2012['% Families $15,000-$24,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2012['% Families $25,000-$34,999'] = initial_pa_families_2012['% Families $25,000-$34,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2012['% Families $35,000-$49,999'] = initial_pa_families_2012['% Families $35,000-$49,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2012['% Families $50,000-$74,999'] = initial_pa_families_2012['% Families $50,000-$74,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2012['% Families $75,000-$99,999'] = initial_pa_families_2012['% Families $75,000-$99,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2012['% Families $100,000-$149,999'] = initial_pa_families_2012['% Families $100,000-$149,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2012['% Families $150,000-$199,999'] = initial_pa_families_2012['% Families $150,000-$199,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2012['% Families $200,000 or More'] = initial_pa_families_2012['% Families $200,000 or More'].str.rstrip('%').astype(float) / 100
initial_pa_families_2012['# of Families'] = initial_pa_families_2012['# of Families'].str.replace(',', '').astype(float)
initial_pa_families_2012['Median Families Income ($)'] = initial_pa_families_2012['Median Families Income ($)'].str.replace(',', '').astype(float)
initial_pa_families_2012['Mean Families Income ($)'] = initial_pa_families_2012['Mean Families Income ($)'].str.replace(',', '').astype(float)
initial_pa_families_2012


Year          County  # of Families  % Families <$10,000  \
0   2012           ADAMS        27025.0                0.012   
1   2012       ALLEGHENY       304375.0                0.048   
2   2012       ARMSTRONG        19535.0                0.051   
3   2012          BEAVER        45560.0                0.042   
4   2012           BERKS       103312.0                0.051   
5   2012           BLAIR        32068.0                0.033   
6   2012           BUCKS       166398.0                0.013   
7   2012          BUTLER        50201.0                0.027   
8   2012         CAMBRIA        37266.0                0.049   
9   2012          CARBON        17537.0                0.008   
10  2012          CENTRE        33643.0                0.040   
11  2012         CHESTER       129045.0                0.024   
12  2012      CLEARFIELD        21145.0                0.059   
13  2012        COLUMBIA        17023.0                0.017   
14  2012        CRAWFORD        23483.0                0.049   
15  2012      CUMBERLAND        62252.0                0.028   
16  2012         DAUPHIN        69116.0                0.044   
17  2012        DELAWARE       135890.0                0.035   
18  2012            ERIE        71175.0                0.048   
19  2012         FAYETTE        33553.0                0.055   
20  2012        FRANKLIN        41469.0                0.038   
21  2012         INDIANA        22825.0                0.038   
22  2012      LACKAWANNA        52268.0                0.039   
23  2012       LANCASTER       138426.0                0.029   
24  2012        LAWRENCE        24583.0                0.069   
25  2012         LEBANON        34949.0                0.043   
26  2012          LEHIGH        88845.0                0.045   
27  2012         LUZERNE        80171.0                0.056   
28  2012        LYCOMING        29827.0                0.044   
29  2012          MERCER        31525.0                0.047   
30  2012          MONROE        40865.0                0.044   
31  2012      MONTGOMERY       210306.0                0.015   
32  2012     NORTHAMPTON        76899.0                0.037   
33  2012  NORTHUMBERLAND        24864.0                0.044   
34  2012    PHILADELPHIA       307880.0                0.097   
35  2012      SCHUYLKILL        38613.0                0.052   
36  2012        SOMERSET        21076.0                0.020   
37  2012      WASHINGTON        54650.0                0.043   
38  2012    WESTMORELAND       101414.0                0.032   
39  2012            YORK       118190.0                0.030   

    % Families $10,000-$14,999  % Families $15,000-$24,999  \
0                        0.028                       0.081   
1                        0.026                       0.071   
2                        0.030                       0.077   
3                        0.018                       0.094   
4                        0.028                       0.075   
5                        0.034                       0.095   
6                        0.016                       0.039   
7                        0.018                       0.065   
8                        0.039                       0.091   
9                        0.041                       0.081   
10                       0.019                       0.061   
11                       0.016                       0.039   
12                       0.027                       0.084   
13                       0.026                       0.084   
14                       0.031                       0.109   
15                       0.030                       0.073   
16                       0.028                       0.075   
17                       0.022                       0.066   
18                       0.029                       0.095   
19                       0.040                       0.108   
20                       0.026                       0.063   
21             

**2016**
-

In [82]:
# Reading in 2016 U.S. Census Bureau income (families) dataset
initial_pa_families_2016 = pd.read_excel("Resources/PA_Income_Families_2016.xlsx")
initial_pa_families_2016.head(19)


Unnamed: 0 Adams County, Pennsylvania  \
0                                      NaN                   Families   
1                                    Label                   Estimate   
2                                    Total                     26,243   
3                        Less than $10,000                       3.8%   
4                       $10,000 to $14,999                       1.0%   
5                       $15,000 to $24,999                       4.0%   
6                       $25,000 to $34,999                       9.2%   
7                       $35,000 to $49,999                      15.2%   
8                       $50,000 to $74,999                      17.2%   
9                       $75,000 to $99,999                      20.5%   
10                    $100,000 to $149,999                      18.8%   
11                    $150,000 to $199,999                       6.0%   
12                        $200,000 or more                       4.4%   
13                 Median income (dollars)                     74,680   
14                   Mean income (dollars)                     83,756   
15                       PERCENT ALLOCATED                        NaN   
16  Household income in the past 12 months                        (X)   
17     Family income in the past 12 months                      30.6%   
18  Nonfamily income in the past 12 months                        (X)   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
0                        Families                       Families   
1                        Estimate                       Estimate   
2                         295,807                         17,519   
3                            3.9%                           4.2%   
4                            2.6%                           4.2%   
5                            5.3%                           6.8%   
6                            7.0%                           7.6%   
7                           10.8%                          15.0%   
8                           17.7%                          26.1%   
9                           15.8%                          13.8%   
10                          19.6%                          15.9%   
11                           8.5%                           2.9%   
12                           8.8%                           3.5%   
13                         79,075                         61,167   
14                         99,613                         71,921   
15                            NaN                            NaN   
16                            (X)                            (X)   
17                          32.3%                          38.0%   
18                            (X)                            (X)   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
0                     Families                   Families   
1                     Estimate                   Estimate   
2                       44,810                    102,478   
3                         2.8%                       4.3%   
4                         1.1%                       2.4%   
5                         5.3%                       6.1%   
6                         9.2%                       7.0%   
7                        14.8%                      12.4%   
8                        20.9%                      20.4%   
9                        16.8%                      15.8%   
10                       17.6%                      18.0%   
11                        6.8%                       7.9%   
12                        4.6%                       5.7%   
13                      68,243                     71,795   
14                      83,078                     89,282   
15                         NaN                        NaN   
16                         (X)                        (X)   
17                       33.6%                      37.4%   
18                         (X)                     

In [83]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Four groupings = Households, Families, Married-couple families & non family households
# % of groups above that fall into the income categories: Less Than $10,000, $10,000-$14,999, $15,000-$24,999, $25,000-$34,999,
# $35,000-$49,999, $50,000-$74,999, $75,000-$99,999, $100,000-$149,999, $150,000-$199,999, $200,000 or More
# Total count for each grouping
# Median income for each grouping
# Mean income for each grouping
initial_pa_families_2016 = initial_pa_families_2016.iloc[[2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], :]
initial_pa_families_2016


Unnamed: 0 Adams County, Pennsylvania  \
2                     Total                     26,243   
3         Less than $10,000                       3.8%   
4        $10,000 to $14,999                       1.0%   
5        $15,000 to $24,999                       4.0%   
6        $25,000 to $34,999                       9.2%   
7        $35,000 to $49,999                      15.2%   
8        $50,000 to $74,999                      17.2%   
9        $75,000 to $99,999                      20.5%   
10     $100,000 to $149,999                      18.8%   
11     $150,000 to $199,999                       6.0%   
12         $200,000 or more                       4.4%   
13  Median income (dollars)                     74,680   
14    Mean income (dollars)                     83,756   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
2                         295,807                         17,519   
3                            3.9%                           4.2%   
4                            2.6%                           4.2%   
5                            5.3%                           6.8%   
6                            7.0%                           7.6%   
7                           10.8%                          15.0%   
8                           17.7%                          26.1%   
9                           15.8%                          13.8%   
10                          19.6%                          15.9%   
11                           8.5%                           2.9%   
12                           8.8%                           3.5%   
13                         79,075                         61,167   
14                         99,613                         71,921   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
2                       44,810                    102,478   
3                         2.8%                       4.3%   
4                         1.1%                       2.4%   
5                         5.3%                       6.1%   
6                         9.2%                       7.0%   
7                        14.8%                      12.4%   
8                        20.9%                      20.4%   
9                        16.8%                      15.8%   
10                       17.6%                      18.0%   
11                        6.8%                       7.9%   
12                        4.6%                       5.7%   
13                      68,243                     71,795   
14                      83,078                     89,282   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
2                      32,897                    165,984   
3                        2.8%                       1.8%   
4                        2.8%                       1.1%   
5                        8.2%                       3.4%   
6                       11.5%                       4.8%   
7                       16.5%                       8.2%   
8                       24.5%                      17.0%   
9                       15.6%                      14.8%   
10                      12.4%                      23.6%   
11                       3.4%                      11.1%   
12                       2.2%                      14.1%   
13                     59,272                     97,670   
14                     71,014                    124,255   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
2                       50,214                       35,951  ...   
3                         1.7%                         3.8%  ...   
4                         0.7%                         3.4%  ...   
5                         3.6%                         7.8%  ...   
6                         7.5%                        10.5%  ...   
7                        11.7%                        14.1%  ...   
8                        18.3%                        22.6%  ...   
9          

In [84]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_families_2016 = initial_pa_families_2016.T
initial_pa_families_2016.head()


2                  3   \
Unnamed: 0                        Total  Less than $10,000   
Adams County, Pennsylvania       26,243               3.8%   
Allegheny County, Pennsylvania  295,807               3.9%   
Armstrong County, Pennsylvania   17,519               4.2%   
Beaver County, Pennsylvania      44,810               2.8%   

                                                4                   5   \
Unnamed: 0                      $10,000 to $14,999  $15,000 to $24,999   
Adams County, Pennsylvania                    1.0%                4.0%   
Allegheny County, Pennsylvania                2.6%                5.3%   
Armstrong County, Pennsylvania                4.2%                6.8%   
Beaver County, Pennsylvania                   1.1%                5.3%   

                                                6                   7   \
Unnamed: 0                      $25,000 to $34,999  $35,000 to $49,999   
Adams County, Pennsylvania                    9.2%               15.2%   
Allegheny County, Pennsylvania                7.0%               10.8%   
Armstrong County, Pennsylvania                7.6%               15.0%   
Beaver County, Pennsylvania                   9.2%               14.8%   

                                                8                   9   \
Unnamed: 0                      $50,000 to $74,999  $75,000 to $99,999   
Adams County, Pennsylvania                   17.2%               20.5%   
Allegheny County, Pennsylvania               17.7%               15.8%   
Armstrong County, Pennsylvania               26.1%               13.8%   
Beaver County, Pennsylvania                  20.9%               16.8%   

                                                  10                    11  \
Unnamed: 0                      $100,000 to $149,999  $150,000 to $199,999   
Adams County, Pennsylvania                     18.8%                  6.0%   
Allegheny County, Pennsylvania                 19.6%                  8.5%   
Armstrong County, Pennsylvania                 15.9%                  2.9%   
Beaver County, Pennsylvania                    17.6%                  6.8%   

                                              12                       13  \
Unnamed: 0                      $200,000 or more  Median income (dollars)   
Adams County, Pennsylvania                  4.4%                   74,680   
Allegheny County, Pennsylvania              8.8%                   79,075   
Armstrong County, Pennsylvania              3.5%                   61,167   
Beaver County, Pennsylvania                 4.6%                   68,243   

                                                   14  
Unnamed: 0                      Mean income (dollars)  
Adams County, Pennsylvania                     83,756  
Allegheny County, Pennsylvania                 99,613  
Armstrong County, Pennsylvania                 71,921  
Beaver County, Pennsylvania                    83,078

In [85]:
# Resetting index and renaming to create a 'County' column
initial_pa_families_2016 = initial_pa_families_2016.reset_index()
initial_pa_families_2016.rename(columns={'index': 'County'}, inplace=True)
initial_pa_families_2016.head()


County        2                  3  \
0                      Unnamed: 0    Total  Less than $10,000   
1      Adams County, Pennsylvania   26,243               3.8%   
2  Allegheny County, Pennsylvania  295,807               3.9%   
3  Armstrong County, Pennsylvania   17,519               4.2%   
4     Beaver County, Pennsylvania   44,810               2.8%   

                    4                   5                   6  \
0  $10,000 to $14,999  $15,000 to $24,999  $25,000 to $34,999   
1                1.0%                4.0%                9.2%   
2                2.6%                5.3%                7.0%   
3                4.2%                6.8%                7.6%   
4                1.1%                5.3%                9.2%   

                    7                   8                   9  \
0  $35,000 to $49,999  $50,000 to $74,999  $75,000 to $99,999   
1               15.2%               17.2%               20.5%   
2               10.8%               17.7%               15.8%   
3               15.0%               26.1%               13.8%   
4               14.8%               20.9%               16.8%   

                     10                    11                12  \
0  $100,000 to $149,999  $150,000 to $199,999  $200,000 or more   
1                 18.8%                  6.0%              4.4%   
2                 19.6%                  8.5%              8.8%   
3                 15.9%                  2.9%              3.5%   
4                 17.6%                  6.8%              4.6%   

                        13                     14  
0  Median income (dollars)  Mean income (dollars)  
1                   74,680                 83,756  
2                   79,075                 99,613  
3                   61,167                 71,921  
4                   68,243                 83,078

In [86]:
# Confirming column data types prior to renaming
print(initial_pa_families_2016.columns)


Index(['County', 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], dtype='object')


In [87]:
# Converting column data types from integers to strings for renaming
initial_pa_families_2016.columns = initial_pa_families_2016.columns.astype(str)
print(initial_pa_families_2016.columns)


Index(['County', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12',
       '13', '14'],
      dtype='object')


In [88]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_families_2016.replace('N', np.nan, inplace=True)


In [89]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_families_2016 = initial_pa_families_2016.rename(columns={'2': '# of Families', '3': '% Families <$10,000', '4': '% Families $10,000-$14,999',
                                                                         '5': '% Families $15,000-$24,999', '6': '% Families $25,000-$34,999', '7': '% Families $35,000-$49,999',
                                                                         '8': '% Families $50,000-$74,999', '9': '% Families $75,000-$99,999',
                                                                         '10': '% Families $100,000-$149,999', '11': '% Families $150,000-$199,999',
                                                                        '12': '% Families $200,000 or More', '13': 'Median Families Income ($)',
                                                                       '14': 'Mean Families Income ($)'})
initial_pa_families_2016 = initial_pa_families_2016.drop(0)
initial_pa_families_2016 = initial_pa_families_2016.reset_index(drop=True)
initial_pa_families_2016['County'] = initial_pa_families_2016['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_families_2016['County'] = initial_pa_families_2016['County'].apply(lambda x: x.upper())
initial_pa_families_2016.insert(0, 'Year', 2016)
initial_pa_families_2016['% Families <$10,000'] = initial_pa_families_2016['% Families <$10,000'].str.rstrip('%').astype(float) / 100
initial_pa_families_2016['% Families $10,000-$14,999'] = initial_pa_families_2016['% Families $10,000-$14,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2016['% Families $15,000-$24,999'] = initial_pa_families_2016['% Families $15,000-$24,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2016['% Families $25,000-$34,999'] = initial_pa_families_2016['% Families $25,000-$34,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2016['% Families $35,000-$49,999'] = initial_pa_families_2016['% Families $35,000-$49,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2016['% Families $50,000-$74,999'] = initial_pa_families_2016['% Families $50,000-$74,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2016['% Families $75,000-$99,999'] = initial_pa_families_2016['% Families $75,000-$99,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2016['% Families $100,000-$149,999'] = initial_pa_families_2016['% Families $100,000-$149,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2016['% Families $150,000-$199,999'] = initial_pa_families_2016['% Families $150,000-$199,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2016['% Families $200,000 or More'] = initial_pa_families_2016['% Families $200,000 or More'].str.rstrip('%').astype(float) / 100
initial_pa_families_2016['# of Families'] = initial_pa_families_2016['# of Families'].str.replace(',', '').astype(float)
initial_pa_families_2016['Median Families Income ($)'] = initial_pa_families_2016['Median Families Income ($)'].str.replace(',', '').astype(float)
initial_pa_families_2016['Mean Families Income ($)'] = initial_pa_families_2016['Mean Families Income ($)'].str.replace(',', '').astype(float)
initial_pa_families_2016


Year          County  # of Families  % Families <$10,000  \
0   2016           ADAMS        26243.0                0.038   
1   2016       ALLEGHENY       295807.0                0.039   
2   2016       ARMSTRONG        17519.0                0.042   
3   2016          BEAVER        44810.0                0.028   
4   2016           BERKS       102478.0                0.043   
5   2016           BLAIR        32897.0                0.028   
6   2016           BUCKS       165984.0                0.018   
7   2016          BUTLER        50214.0                0.017   
8   2016         CAMBRIA        35951.0                0.038   
9   2016          CARBON        16260.0                0.025   
10  2016          CENTRE        32850.0                0.027   
11  2016         CHESTER       131367.0                0.014   
12  2016      CLEARFIELD        19113.0                0.033   
13  2016        COLUMBIA        17031.0                0.027   
14  2016        CRAWFORD        20970.0                0.035   
15  2016      CUMBERLAND        61117.0                0.018   
16  2016         DAUPHIN        69998.0                0.032   
17  2016        DELAWARE       135761.0                0.031   
18  2016            ERIE        67945.0                0.039   
19  2016         FAYETTE        33312.0                0.060   
20  2016        FRANKLIN        41130.0                0.014   
21  2016         INDIANA        21239.0                0.045   
22  2016      LACKAWANNA        50976.0                0.042   
23  2016       LANCASTER       136226.0                0.021   
24  2016        LAWRENCE        23510.0                0.051   
25  2016         LEBANON        35259.0                0.025   
26  2016          LEHIGH        93392.0                0.032   
27  2016         LUZERNE        76894.0                0.052   
28  2016        LYCOMING        29498.0                0.050   
29  2016          MERCER        30630.0                0.049   
30  2016          MONROE        37671.0                0.024   
31  2016      MONTGOMERY       214764.0                0.015   
32  2016     NORTHAMPTON        78821.0                0.021   
33  2016  NORTHUMBERLAND        24845.0                0.043   
34  2016    PHILADELPHIA       309558.0                0.081   
35  2016      SCHUYLKILL        38214.0                0.042   
36  2016        SOMERSET        19345.0                0.048   
37  2016      WASHINGTON        54369.0                0.027   
38  2016    WESTMORELAND        99302.0                0.032   
39  2016            YORK       117745.0                0.031   

    % Families $10,000-$14,999  % Families $15,000-$24,999  \
0                        0.010                       0.040   
1                        0.026                       0.053   
2                        0.042                       0.068   
3                        0.011                       0.053   
4                        0.024                       0.061   
5                        0.028                       0.082   
6                        0.011                       0.034   
7                        0.007                       0.036   
8                        0.034                       0.078   
9                        0.031                       0.052   
10                       0.012                       0.044   
11                       0.013                       0.034   
12                       0.034                       0.085   
13                       0.022                       0.086   
14                       0.020                       0.087   
15                       0.019                       0.052   
16                       0.013                       0.056   
17                       0.022                       0.056   
18                       0.023                       0.072   
19                       0.045                       0.087   
20                       0.018                       0.030   
21             

**2019**
-
Please note: 2020 United States Census Bureau was unavailable and as such the closest year prior to the election (2019) was utilized

In [90]:
# Reading in 2019 U.S. Census Bureau income (families) dataset
initial_pa_families_2019 = pd.read_excel("Resources/PA_Income_Families_2019.xlsx")
initial_pa_families_2019.head(19)


Unnamed: 0 Adams County, Pennsylvania  \
0                                      NaN                   Families   
1                                    Label                   Estimate   
2                                    Total                     26,375   
3                        Less than $10,000                       1.3%   
4                       $10,000 to $14,999                       2.3%   
5                       $15,000 to $24,999                       3.4%   
6                       $25,000 to $34,999                       7.2%   
7                       $35,000 to $49,999                      11.9%   
8                       $50,000 to $74,999                      18.4%   
9                       $75,000 to $99,999                      19.3%   
10                    $100,000 to $149,999                      20.3%   
11                    $150,000 to $199,999                       8.6%   
12                        $200,000 or more                       7.1%   
13                 Median income (dollars)                     81,210   
14                   Mean income (dollars)                     99,218   
15                       PERCENT ALLOCATED                        NaN   
16  Household income in the past 12 months                        (X)   
17     Family income in the past 12 months                      29.4%   
18  Nonfamily income in the past 12 months                        (X)   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
0                        Families                       Families   
1                        Estimate                       Estimate   
2                         301,596                         18,184   
3                            3.5%                           2.6%   
4                            1.3%                           2.4%   
5                            4.0%                           5.8%   
6                            5.5%                           7.1%   
7                            8.2%                          14.6%   
8                           17.8%                          23.1%   
9                           14.5%                          17.8%   
10                          22.6%                          17.2%   
11                          10.2%                           6.2%   
12                          12.3%                           3.3%   
13                         90,891                         68,733   
14                        119,863                         82,941   
15                            NaN                            NaN   
16                            (X)                            (X)   
17                          34.7%                          35.8%   
18                            (X)                            (X)   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
0                     Families                   Families   
1                     Estimate                   Estimate   
2                       43,107                    105,402   
3                         3.0%                       3.5%   
4                         1.7%                       1.2%   
5                         5.9%                       4.9%   
6                         6.5%                       5.2%   
7                        11.5%                      11.9%   
8                        17.1%                      19.1%   
9                        18.0%                      15.3%   
10                       20.7%                      24.1%   
11                        9.6%                       8.3%   
12                        5.8%                       6.7%   
13                      79,450                     81,575   
14                      94,002                     97,936   
15                         NaN                        NaN   
16                         (X)                        (X)   
17                       35.4%                      45.8%   
18                         (X)                     

In [91]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Four groupings = Households, Families, Married-couple families & non family households
# % of groups above that fall into the income categories: Less Than $10,000, $10,000-$14,999, $15,000-$24,999, $25,000-$34,999,
# $35,000-$49,999, $50,000-$74,999, $75,000-$99,999, $100,000-$149,999, $150,000-$199,999, $200,000 or More
# Total count for each grouping
# Median income for each grouping
# Mean income for each grouping
initial_pa_families_2019 = initial_pa_families_2019.iloc[[2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], :]
initial_pa_families_2019


Unnamed: 0 Adams County, Pennsylvania  \
2                     Total                     26,375   
3         Less than $10,000                       1.3%   
4        $10,000 to $14,999                       2.3%   
5        $15,000 to $24,999                       3.4%   
6        $25,000 to $34,999                       7.2%   
7        $35,000 to $49,999                      11.9%   
8        $50,000 to $74,999                      18.4%   
9        $75,000 to $99,999                      19.3%   
10     $100,000 to $149,999                      20.3%   
11     $150,000 to $199,999                       8.6%   
12         $200,000 or more                       7.1%   
13  Median income (dollars)                     81,210   
14    Mean income (dollars)                     99,218   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
2                         301,596                         18,184   
3                            3.5%                           2.6%   
4                            1.3%                           2.4%   
5                            4.0%                           5.8%   
6                            5.5%                           7.1%   
7                            8.2%                          14.6%   
8                           17.8%                          23.1%   
9                           14.5%                          17.8%   
10                          22.6%                          17.2%   
11                          10.2%                           6.2%   
12                          12.3%                           3.3%   
13                         90,891                         68,733   
14                        119,863                         82,941   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
2                       43,107                    105,402   
3                         3.0%                       3.5%   
4                         1.7%                       1.2%   
5                         5.9%                       4.9%   
6                         6.5%                       5.2%   
7                        11.5%                      11.9%   
8                        17.1%                      19.1%   
9                        18.0%                      15.3%   
10                       20.7%                      24.1%   
11                        9.6%                       8.3%   
12                        5.8%                       6.7%   
13                      79,450                     81,575   
14                      94,002                     97,936   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
2                      34,637                    167,024   
3                        3.8%                       1.7%   
4                        3.4%                       0.6%   
5                        7.0%                       3.1%   
6                        9.2%                       3.7%   
7                       14.9%                       6.9%   
8                       18.5%                      12.0%   
9                       15.1%                      13.8%   
10                      17.6%                      24.3%   
11                       6.8%                      16.0%   
12                       3.6%                      18.0%   
13                     65,157                    112,006   
14                     80,697                    139,798   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
2                       50,071                       35,187  ...   
3                         2.9%                         4.3%  ...   
4                         1.1%                         2.6%  ...   
5                         2.7%                         5.7%  ...   
6                         4.5%                         9.0%  ...   
7                         8.4%                        13.3%  ...   
8                        17.1%                        21.5%  ...   
9          

In [92]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_families_2019 = initial_pa_families_2019.T
initial_pa_families_2019.head()


2                  3   \
Unnamed: 0                        Total  Less than $10,000   
Adams County, Pennsylvania       26,375               1.3%   
Allegheny County, Pennsylvania  301,596               3.5%   
Armstrong County, Pennsylvania   18,184               2.6%   
Beaver County, Pennsylvania      43,107               3.0%   

                                                4                   5   \
Unnamed: 0                      $10,000 to $14,999  $15,000 to $24,999   
Adams County, Pennsylvania                    2.3%                3.4%   
Allegheny County, Pennsylvania                1.3%                4.0%   
Armstrong County, Pennsylvania                2.4%                5.8%   
Beaver County, Pennsylvania                   1.7%                5.9%   

                                                6                   7   \
Unnamed: 0                      $25,000 to $34,999  $35,000 to $49,999   
Adams County, Pennsylvania                    7.2%               11.9%   
Allegheny County, Pennsylvania                5.5%                8.2%   
Armstrong County, Pennsylvania                7.1%               14.6%   
Beaver County, Pennsylvania                   6.5%               11.5%   

                                                8                   9   \
Unnamed: 0                      $50,000 to $74,999  $75,000 to $99,999   
Adams County, Pennsylvania                   18.4%               19.3%   
Allegheny County, Pennsylvania               17.8%               14.5%   
Armstrong County, Pennsylvania               23.1%               17.8%   
Beaver County, Pennsylvania                  17.1%               18.0%   

                                                  10                    11  \
Unnamed: 0                      $100,000 to $149,999  $150,000 to $199,999   
Adams County, Pennsylvania                     20.3%                  8.6%   
Allegheny County, Pennsylvania                 22.6%                 10.2%   
Armstrong County, Pennsylvania                 17.2%                  6.2%   
Beaver County, Pennsylvania                    20.7%                  9.6%   

                                              12                       13  \
Unnamed: 0                      $200,000 or more  Median income (dollars)   
Adams County, Pennsylvania                  7.1%                   81,210   
Allegheny County, Pennsylvania             12.3%                   90,891   
Armstrong County, Pennsylvania              3.3%                   68,733   
Beaver County, Pennsylvania                 5.8%                   79,450   

                                                   14  
Unnamed: 0                      Mean income (dollars)  
Adams County, Pennsylvania                     99,218  
Allegheny County, Pennsylvania                119,863  
Armstrong County, Pennsylvania                 82,941  
Beaver County, Pennsylvania                    94,002

In [93]:
# Resetting index and renaming to create a 'County' column
initial_pa_families_2019 = initial_pa_families_2019.reset_index()
initial_pa_families_2019.rename(columns={'index': 'County'}, inplace=True)
initial_pa_families_2019.head()


County        2                  3  \
0                      Unnamed: 0    Total  Less than $10,000   
1      Adams County, Pennsylvania   26,375               1.3%   
2  Allegheny County, Pennsylvania  301,596               3.5%   
3  Armstrong County, Pennsylvania   18,184               2.6%   
4     Beaver County, Pennsylvania   43,107               3.0%   

                    4                   5                   6  \
0  $10,000 to $14,999  $15,000 to $24,999  $25,000 to $34,999   
1                2.3%                3.4%                7.2%   
2                1.3%                4.0%                5.5%   
3                2.4%                5.8%                7.1%   
4                1.7%                5.9%                6.5%   

                    7                   8                   9  \
0  $35,000 to $49,999  $50,000 to $74,999  $75,000 to $99,999   
1               11.9%               18.4%               19.3%   
2                8.2%               17.8%               14.5%   
3               14.6%               23.1%               17.8%   
4               11.5%               17.1%               18.0%   

                     10                    11                12  \
0  $100,000 to $149,999  $150,000 to $199,999  $200,000 or more   
1                 20.3%                  8.6%              7.1%   
2                 22.6%                 10.2%             12.3%   
3                 17.2%                  6.2%              3.3%   
4                 20.7%                  9.6%              5.8%   

                        13                     14  
0  Median income (dollars)  Mean income (dollars)  
1                   81,210                 99,218  
2                   90,891                119,863  
3                   68,733                 82,941  
4                   79,450                 94,002

In [94]:
# Confirming column data types prior to renaming
print(initial_pa_families_2019.columns)


Index(['County', 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], dtype='object')


In [95]:
# Converting column data types from integers to strings for renaming
initial_pa_families_2019.columns = initial_pa_families_2019.columns.astype(str)
print(initial_pa_families_2019.columns)


Index(['County', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12',
       '13', '14'],
      dtype='object')


In [96]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_families_2019.replace('N', np.nan, inplace=True)


In [97]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_families_2019 = initial_pa_families_2019.rename(columns={'2': '# of Families', '3': '% Families <$10,000', '4': '% Families $10,000-$14,999',
                                                                         '5': '% Families $15,000-$24,999', '6': '% Families $25,000-$34,999', '7': '% Families $35,000-$49,999',
                                                                         '8': '% Families $50,000-$74,999', '9': '% Families $75,000-$99,999',
                                                                         '10': '% Families $100,000-$149,999', '11': '% Families $150,000-$199,999',
                                                                        '12': '% Families $200,000 or More', '13': 'Median Families Income ($)',
                                                                       '14': 'Mean Families Income ($)'})
initial_pa_families_2019 = initial_pa_families_2019.drop(0)
initial_pa_families_2019 = initial_pa_families_2019.reset_index(drop=True)
initial_pa_families_2019['County'] = initial_pa_families_2019['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_families_2019['County'] = initial_pa_families_2019['County'].apply(lambda x: x.upper())
initial_pa_families_2019.insert(0, 'Year', 2020)
initial_pa_families_2019['% Families <$10,000'] = initial_pa_families_2019['% Families <$10,000'].str.rstrip('%').astype(float) / 100
initial_pa_families_2019['% Families $10,000-$14,999'] = initial_pa_families_2019['% Families $10,000-$14,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2019['% Families $15,000-$24,999'] = initial_pa_families_2019['% Families $15,000-$24,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2019['% Families $25,000-$34,999'] = initial_pa_families_2019['% Families $25,000-$34,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2019['% Families $35,000-$49,999'] = initial_pa_families_2019['% Families $35,000-$49,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2019['% Families $50,000-$74,999'] = initial_pa_families_2019['% Families $50,000-$74,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2019['% Families $75,000-$99,999'] = initial_pa_families_2019['% Families $75,000-$99,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2019['% Families $100,000-$149,999'] = initial_pa_families_2019['% Families $100,000-$149,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2019['% Families $150,000-$199,999'] = initial_pa_families_2019['% Families $150,000-$199,999'].str.rstrip('%').astype(float) / 100
initial_pa_families_2019['% Families $200,000 or More'] = initial_pa_families_2019['% Families $200,000 or More'].str.rstrip('%').astype(float) / 100
initial_pa_families_2019['# of Families'] = initial_pa_families_2019['# of Families'].str.replace(',', '').astype(float)
initial_pa_families_2019['Median Families Income ($)'] = initial_pa_families_2019['Median Families Income ($)'].str.replace(',', '').astype(float)
initial_pa_families_2019['Mean Families Income ($)'] = initial_pa_families_2019['Mean Families Income ($)'].str.replace(',', '').astype(float)
initial_pa_families_2019


Year          County  # of Families  % Families <$10,000  \
0   2020           ADAMS        26375.0                0.013   
1   2020       ALLEGHENY       301596.0                0.035   
2   2020       ARMSTRONG        18184.0                0.026   
3   2020          BEAVER        43107.0                0.030   
4   2020           BERKS       105402.0                0.035   
5   2020           BLAIR        34637.0                0.038   
6   2020           BUCKS       167024.0                0.017   
7   2020          BUTLER        50071.0                0.029   
8   2020         CAMBRIA        35187.0                0.043   
9   2020          CARBON        17562.0                0.020   
10  2020          CENTRE        33225.0                0.020   
11  2020         CHESTER       136514.0                0.018   
12  2020      CLEARFIELD        20083.0                0.026   
13  2020        COLUMBIA        16631.0                0.036   
14  2020        CRAWFORD        23814.0                0.027   
15  2020      CUMBERLAND        64780.0                0.024   
16  2020         DAUPHIN        67366.0                0.044   
17  2020        DELAWARE       138319.0                0.030   
18  2020            ERIE        65759.0                0.046   
19  2020         FAYETTE        32290.0                0.046   
20  2020        FRANKLIN        40079.0                0.025   
21  2020         INDIANA        19008.0                0.040   
22  2020      LACKAWANNA        55846.0                0.039   
23  2020       LANCASTER       142461.0                0.033   
24  2020        LAWRENCE        24265.0                0.047   
25  2020         LEBANON        36317.0                0.042   
26  2020          LEHIGH        95079.0                0.033   
27  2020         LUZERNE        80336.0                0.046   
28  2020        LYCOMING        28763.0                0.059   
29  2020          MERCER        29296.0                0.042   
30  2020          MONROE        40663.0                0.032   
31  2020      MONTGOMERY       217598.0                0.017   
32  2020     NORTHAMPTON        76846.0                0.023   
33  2020  NORTHUMBERLAND        24939.0                0.066   
34  2020    PHILADELPHIA       338852.0                0.077   
35  2020      SCHUYLKILL        37730.0                0.042   
36  2020        SOMERSET        19642.0                0.030   
37  2020      WASHINGTON        55227.0                0.026   
38  2020    WESTMORELAND        94737.0                0.030   
39  2020            YORK       118266.0                0.015   

    % Families $10,000-$14,999  % Families $15,000-$24,999  \
0                        0.023                       0.034   
1                        0.013                       0.040   
2                        0.024                       0.058   
3                        0.017                       0.059   
4                        0.012                       0.049   
5                        0.034                       0.070   
6                        0.006                       0.031   
7                        0.011                       0.027   
8                        0.026                       0.057   
9                        0.008                       0.039   
10                       0.017                       0.030   
11                       0.006                       0.020   
12                       0.024                       0.088   
13                       0.037                       0.072   
14                       0.027                       0.074   
15                       0.012                       0.025   
16                       0.011                       0.050   
17                       0.016                       0.038   
18                       0.038                       0.073   
19                       0.032                       0.092   
20                       0.007                       0.035   
21             

**Income (Married Couple Families) Data Extraction, Transformation & Loading (2012, 2016 & 2019)**
-
-----------

**2012**
-

In [98]:
# Reading in 2012 U.S. Census Bureau income (Married Couple Families) dataset
initial_pa_mc_families_2012 = pd.read_excel("Resources/PA_Income_Married_Couple_Families_2012.xlsx")
initial_pa_mc_families_2012.head(19)


Unnamed: 0 Adams County, Pennsylvania  \
0                                      NaN    Married-couple families   
1                                    Label                   Estimate   
2                                    Total                     21,723   
3                        Less than $10,000                       0.7%   
4                       $10,000 to $14,999                       1.8%   
5                       $15,000 to $24,999                       5.3%   
6                       $25,000 to $34,999                       5.9%   
7                       $35,000 to $49,999                       9.8%   
8                       $50,000 to $74,999                      21.6%   
9                       $75,000 to $99,999                      23.0%   
10                    $100,000 to $149,999                      21.4%   
11                    $150,000 to $199,999                       7.0%   
12                        $200,000 or more                       3.5%   
13                 Median income (dollars)                     79,010   
14                   Mean income (dollars)                          N   
15                         PERCENT IMPUTED                        NaN   
16  Household income in the past 12 months                        (X)   
17     Family income in the past 12 months                        (X)   
18  Nonfamily income in the past 12 months                        (X)   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
0         Married-couple families        Married-couple families   
1                        Estimate                       Estimate   
2                         223,942                         15,553   
3                            1.1%                           2.0%   
4                            0.9%                           2.3%   
5                            4.4%                           5.5%   
6                            6.3%                          11.3%   
7                           10.1%                          20.0%   
8                           20.0%                          24.2%   
9                           18.7%                          15.0%   
10                          22.3%                          14.3%   
11                           8.4%                           1.9%   
12                           8.0%                           3.5%   
13                         83,482                         56,338   
14                        107,991                              N   
15                            NaN                            NaN   
16                            (X)                            (X)   
17                            (X)                            (X)   
18                            (X)                            (X)   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
0      Married-couple families    Married-couple families   
1                     Estimate                   Estimate   
2                       35,185                     76,132   
3                         1.6%                       1.6%   
4                         0.9%                       1.1%   
5                         6.5%                       4.5%   
6                         7.3%                       7.0%   
7                        13.2%                      12.5%   
8                        23.7%                      22.3%   
9                        19.5%                      19.3%   
10                       21.3%                      19.1%   
11                        3.6%                       6.6%   
12                        2.5%                       6.1%   
13                      72,440                     76,113   
14                           N                     93,235   
15                         NaN                        NaN   
16                         (X)                        (X)   
17                         (X)                        (X)   
18                         (X)                     

In [99]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Four groupings = Households, Families, Married-couple families & non family households
# % of groups above that fall into the income categories: Less Than $10,000, $10,000-$14,999, $15,000-$24,999, $25,000-$34,999,
# $35,000-$49,999, $50,000-$74,999, $75,000-$99,999, $100,000-$149,999, $150,000-$199,999, $200,000 or More
# Total count for each grouping
# Median income for each grouping
# Mean income for each grouping
initial_pa_mc_families_2012 = initial_pa_mc_families_2012.iloc[[2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], :]
initial_pa_mc_families_2012


Unnamed: 0 Adams County, Pennsylvania  \
2                     Total                     21,723   
3         Less than $10,000                       0.7%   
4        $10,000 to $14,999                       1.8%   
5        $15,000 to $24,999                       5.3%   
6        $25,000 to $34,999                       5.9%   
7        $35,000 to $49,999                       9.8%   
8        $50,000 to $74,999                      21.6%   
9        $75,000 to $99,999                      23.0%   
10     $100,000 to $149,999                      21.4%   
11     $150,000 to $199,999                       7.0%   
12         $200,000 or more                       3.5%   
13  Median income (dollars)                     79,010   
14    Mean income (dollars)                          N   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
2                         223,942                         15,553   
3                            1.1%                           2.0%   
4                            0.9%                           2.3%   
5                            4.4%                           5.5%   
6                            6.3%                          11.3%   
7                           10.1%                          20.0%   
8                           20.0%                          24.2%   
9                           18.7%                          15.0%   
10                          22.3%                          14.3%   
11                           8.4%                           1.9%   
12                           8.0%                           3.5%   
13                         83,482                         56,338   
14                        107,991                              N   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
2                       35,185                     76,132   
3                         1.6%                       1.6%   
4                         0.9%                       1.1%   
5                         6.5%                       4.5%   
6                         7.3%                       7.0%   
7                        13.2%                      12.5%   
8                        23.7%                      22.3%   
9                        19.5%                      19.3%   
10                       21.3%                      19.1%   
11                        3.6%                       6.6%   
12                        2.5%                       6.1%   
13                      72,440                     76,113   
14                           N                     93,235   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
2                      24,351                    136,406   
3                        1.3%                       0.6%   
4                        1.6%                       0.9%   
5                        6.4%                       2.7%   
6                       10.8%                       4.3%   
7                       17.8%                       7.6%   
8                       27.5%                      16.5%   
9                       13.4%                      17.3%   
10                      14.3%                      24.8%   
11                       3.2%                      12.8%   
12                       3.8%                      12.5%   
13                     59,183                    100,086   
14                          N                    121,754   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
2                       41,674                       27,432  ...   
3                         0.7%                         1.8%  ...   
4                         0.7%                         1.6%  ...   
5                         3.7%                         7.0%  ...   
6                         5.3%                         9.9%  ...   
7                        11.4%                        18.2%  ...   
8                        21.3%                        24.7%  ...   
9          

In [100]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_mc_families_2012 = initial_pa_mc_families_2012.T
initial_pa_mc_families_2012.head()


2                  3   \
Unnamed: 0                        Total  Less than $10,000   
Adams County, Pennsylvania       21,723               0.7%   
Allegheny County, Pennsylvania  223,942               1.1%   
Armstrong County, Pennsylvania   15,553               2.0%   
Beaver County, Pennsylvania      35,185               1.6%   

                                                4                   5   \
Unnamed: 0                      $10,000 to $14,999  $15,000 to $24,999   
Adams County, Pennsylvania                    1.8%                5.3%   
Allegheny County, Pennsylvania                0.9%                4.4%   
Armstrong County, Pennsylvania                2.3%                5.5%   
Beaver County, Pennsylvania                   0.9%                6.5%   

                                                6                   7   \
Unnamed: 0                      $25,000 to $34,999  $35,000 to $49,999   
Adams County, Pennsylvania                    5.9%                9.8%   
Allegheny County, Pennsylvania                6.3%               10.1%   
Armstrong County, Pennsylvania               11.3%               20.0%   
Beaver County, Pennsylvania                   7.3%               13.2%   

                                                8                   9   \
Unnamed: 0                      $50,000 to $74,999  $75,000 to $99,999   
Adams County, Pennsylvania                   21.6%               23.0%   
Allegheny County, Pennsylvania               20.0%               18.7%   
Armstrong County, Pennsylvania               24.2%               15.0%   
Beaver County, Pennsylvania                  23.7%               19.5%   

                                                  10                    11  \
Unnamed: 0                      $100,000 to $149,999  $150,000 to $199,999   
Adams County, Pennsylvania                     21.4%                  7.0%   
Allegheny County, Pennsylvania                 22.3%                  8.4%   
Armstrong County, Pennsylvania                 14.3%                  1.9%   
Beaver County, Pennsylvania                    21.3%                  3.6%   

                                              12                       13  \
Unnamed: 0                      $200,000 or more  Median income (dollars)   
Adams County, Pennsylvania                  3.5%                   79,010   
Allegheny County, Pennsylvania              8.0%                   83,482   
Armstrong County, Pennsylvania              3.5%                   56,338   
Beaver County, Pennsylvania                 2.5%                   72,440   

                                                   14  
Unnamed: 0                      Mean income (dollars)  
Adams County, Pennsylvania                          N  
Allegheny County, Pennsylvania                107,991  
Armstrong County, Pennsylvania                      N  
Beaver County, Pennsylvania                         N

In [101]:
# Resetting index and renaming to create a 'County' column
initial_pa_mc_families_2012 = initial_pa_mc_families_2012.reset_index()
initial_pa_mc_families_2012.rename(columns={'index': 'County'}, inplace=True)
initial_pa_mc_families_2012.head()


County        2                  3  \
0                      Unnamed: 0    Total  Less than $10,000   
1      Adams County, Pennsylvania   21,723               0.7%   
2  Allegheny County, Pennsylvania  223,942               1.1%   
3  Armstrong County, Pennsylvania   15,553               2.0%   
4     Beaver County, Pennsylvania   35,185               1.6%   

                    4                   5                   6  \
0  $10,000 to $14,999  $15,000 to $24,999  $25,000 to $34,999   
1                1.8%                5.3%                5.9%   
2                0.9%                4.4%                6.3%   
3                2.3%                5.5%               11.3%   
4                0.9%                6.5%                7.3%   

                    7                   8                   9  \
0  $35,000 to $49,999  $50,000 to $74,999  $75,000 to $99,999   
1                9.8%               21.6%               23.0%   
2               10.1%               20.0%               18.7%   
3               20.0%               24.2%               15.0%   
4               13.2%               23.7%               19.5%   

                     10                    11                12  \
0  $100,000 to $149,999  $150,000 to $199,999  $200,000 or more   
1                 21.4%                  7.0%              3.5%   
2                 22.3%                  8.4%              8.0%   
3                 14.3%                  1.9%              3.5%   
4                 21.3%                  3.6%              2.5%   

                        13                     14  
0  Median income (dollars)  Mean income (dollars)  
1                   79,010                      N  
2                   83,482                107,991  
3                   56,338                      N  
4                   72,440                      N

In [102]:
# Confirming column data types prior to renaming
print(initial_pa_mc_families_2012.columns)


Index(['County', 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], dtype='object')


In [103]:
# Converting column data types from integers to strings for renaming
initial_pa_mc_families_2012.columns = initial_pa_mc_families_2012.columns.astype(str)
print(initial_pa_mc_families_2012.columns)


Index(['County', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12',
       '13', '14'],
      dtype='object')


In [104]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_mc_families_2012.replace('N', np.nan, inplace=True)


In [105]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_mc_families_2012 = initial_pa_mc_families_2012.rename(columns={'2': '# of Married Couple Families', '3': '% Married Couple Families <$10,000', '4': '% Married Couple Families $10,000-$14,999',
                                                                         '5': '% Married Couple Families $15,000-$24,999', '6': '% Married Couple Families $25,000-$34,999', '7': '% Married Couple Families $35,000-$49,999',
                                                                         '8': '% Married Couple Families $50,000-$74,999', '9': '% Married Couple Families $75,000-$99,999',
                                                                         '10': '% Married Couple Families $100,000-$149,999', '11': '% Married Couple Families $150,000-$199,999',
                                                                        '12': '% Married Couple Families $200,000 or More', '13': 'Median Married Couple Families Income ($)',
                                                                       '14': 'Mean Married Couple Families Income ($)'})
initial_pa_mc_families_2012 = initial_pa_mc_families_2012.drop(0)
initial_pa_mc_families_2012 = initial_pa_mc_families_2012.reset_index(drop=True)
initial_pa_mc_families_2012['County'] = initial_pa_mc_families_2012['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_mc_families_2012['County'] = initial_pa_mc_families_2012['County'].apply(lambda x: x.upper())
initial_pa_mc_families_2012.insert(0, 'Year', 2012)
initial_pa_mc_families_2012['% Married Couple Families <$10,000'] = initial_pa_mc_families_2012['% Married Couple Families <$10,000'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2012['% Married Couple Families $10,000-$14,999'] = initial_pa_mc_families_2012['% Married Couple Families $10,000-$14,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2012['% Married Couple Families $15,000-$24,999'] = initial_pa_mc_families_2012['% Married Couple Families $15,000-$24,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2012['% Married Couple Families $25,000-$34,999'] = initial_pa_mc_families_2012['% Married Couple Families $25,000-$34,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2012['% Married Couple Families $35,000-$49,999'] = initial_pa_mc_families_2012['% Married Couple Families $35,000-$49,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2012['% Married Couple Families $50,000-$74,999'] = initial_pa_mc_families_2012['% Married Couple Families $50,000-$74,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2012['% Married Couple Families $75,000-$99,999'] = initial_pa_mc_families_2012['% Married Couple Families $75,000-$99,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2012['% Married Couple Families $100,000-$149,999'] = initial_pa_mc_families_2012['% Married Couple Families $100,000-$149,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2012['% Married Couple Families $150,000-$199,999'] = initial_pa_mc_families_2012['% Married Couple Families $150,000-$199,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2012['% Married Couple Families $200,000 or More'] = initial_pa_mc_families_2012['% Married Couple Families $200,000 or More'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2012['# of Married Couple Families'] = initial_pa_mc_families_2012['# of Married Couple Families'].str.replace(',', '').astype(float)
initial_pa_mc_families_2012['Median Married Couple Families Income ($)'] = initial_pa_mc_families_2012['Median Married Couple Families Income ($)'].str.replace(',', '').astype(float)
initial_pa_mc_families_2012['Mean Married Couple Families Income ($)'] = initial_pa_mc_families_2012['Mean Married Couple Families Income ($)'].str.replace(',', '').astype(float)
initial_pa_mc_families_2012


Year          County  # of Married Couple Families  \
0   2012           ADAMS                       21723.0   
1   2012       ALLEGHENY                      223942.0   
2   2012       ARMSTRONG                       15553.0   
3   2012          BEAVER                       35185.0   
4   2012           BERKS                       76132.0   
5   2012           BLAIR                       24351.0   
6   2012           BUCKS                      136406.0   
7   2012          BUTLER                       41674.0   
8   2012         CAMBRIA                       27432.0   
9   2012          CARBON                           NaN   
10  2012          CENTRE                       27172.0   
11  2012         CHESTER                      107984.0   
12  2012      CLEARFIELD                       17071.0   
13  2012        COLUMBIA                           NaN   
14  2012        CRAWFORD                       18292.0   
15  2012      CUMBERLAND                       49541.0   
16  2012         DAUPHIN                       48236.0   
17  2012        DELAWARE                       96242.0   
18  2012            ERIE                       51803.0   
19  2012         FAYETTE                       25099.0   
20  2012        FRANKLIN                       33832.0   
21  2012         INDIANA                       18191.0   
22  2012      LACKAWANNA                       38025.0   
23  2012       LANCASTER                      112299.0   
24  2012        LAWRENCE                       18975.0   
25  2012         LEBANON                       27007.0   
26  2012          LEHIGH                       65359.0   
27  2012         LUZERNE                       56949.0   
28  2012        LYCOMING                       22331.0   
29  2012          MERCER                       23739.0   
30  2012          MONROE                       29060.0   
31  2012      MONTGOMERY                      171313.0   
32  2012     NORTHAMPTON                       56774.0   
33  2012  NORTHUMBERLAND                           NaN   
34  2012    PHILADELPHIA                      154319.0   
35  2012      SCHUYLKILL                       28076.0   
36  2012        SOMERSET                       17874.0   
37  2012      WASHINGTON                       44139.0   
38  2012    WESTMORELAND                       78714.0   
39  2012            YORK                       91558.0   

    % Married Couple Families <$10,000  \
0                                0.007   
1                                0.011   
2                                0.020   
3                                0.016   
4                                0.016   
5                                0.013   
6                                0.006   
7                                0.007   
8                                0.018   
9                                  NaN   
10                               0.007   
11                               0.009   
12                               0.015   
13                                 NaN   
14                               0.016   
15                               0.010   
16                               0.014   
17                               0.013   
18                               0.008   
19                               0.015   
20                               0.008   
21                               0.014   
22                               0.017   
23                               0.014   
24                               0.013   
25                               0.011   
26                               0.013   
27                               0.015   
28                               0.006   
29                               0.019   
30                               0.009   
31                               0.008   
32                               0.006   
33                                 NaN   
34                               0.029   
35                               0.017   
36                               0.009   
37                           

**2016**
-

In [106]:
# Reading in 2016 U.S. Census Bureau income (Married Couple Families) dataset
initial_pa_mc_families_2016 = pd.read_excel("Resources/PA_Income_Married_Couple_Families_2016.xlsx")
initial_pa_mc_families_2016.head(19)


Unnamed: 0 Adams County, Pennsylvania  \
0                                      NaN    Married-couple families   
1                                    Label                   Estimate   
2                                    Total                          N   
3                        Less than $10,000                          N   
4                       $10,000 to $14,999                          N   
5                       $15,000 to $24,999                          N   
6                       $25,000 to $34,999                          N   
7                       $35,000 to $49,999                          N   
8                       $50,000 to $74,999                          N   
9                       $75,000 to $99,999                          N   
10                    $100,000 to $149,999                          N   
11                    $150,000 to $199,999                          N   
12                        $200,000 or more                          N   
13                 Median income (dollars)                     81,817   
14                   Mean income (dollars)                          N   
15                       PERCENT ALLOCATED                        NaN   
16  Household income in the past 12 months                        (X)   
17     Family income in the past 12 months                        (X)   
18  Nonfamily income in the past 12 months                        (X)   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
0         Married-couple families        Married-couple families   
1                        Estimate                       Estimate   
2                         219,048                         13,582   
3                            1.2%                           1.3%   
4                            0.9%                           2.6%   
5                            2.9%                           4.8%   
6                            4.6%                           7.5%   
7                            9.2%                          14.0%   
8                           17.0%                          26.8%   
9                           17.5%                          15.5%   
10                          24.3%                          19.3%   
11                          10.8%                           3.6%   
12                          11.6%                           4.6%   
13                         94,674                         68,241   
14                        117,354                              N   
15                            NaN                            NaN   
16                            (X)                            (X)   
17                            (X)                            (X)   
18                            (X)                            (X)   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
0      Married-couple families    Married-couple families   
1                     Estimate                   Estimate   
2                       34,077                     74,186   
3                         1.1%                       1.1%   
4                         0.8%                       0.9%   
5                         2.3%                       3.4%   
6                         6.7%                       4.9%   
7                        12.0%                      10.8%   
8                        21.5%                      19.8%   
9                        19.9%                      19.0%   
10                       21.5%                      22.3%   
11                        8.5%                      10.5%   
12                        5.8%                       7.3%   
13                      80,740                     88,174   
14                      94,471                    104,518   
15                         NaN                        NaN   
16                         (X)                        (X)   
17                         (X)                        (X)   
18                         (X)                     

In [107]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Four groupings = Households, Families, Married-couple families & non family households
# % of groups above that fall into the income categories: Less Than $10,000, $10,000-$14,999, $15,000-$24,999, $25,000-$34,999,
# $35,000-$49,999, $50,000-$74,999, $75,000-$99,999, $100,000-$149,999, $150,000-$199,999, $200,000 or More
# Total count for each grouping
# Median income for each grouping
# Mean income for each grouping
initial_pa_mc_families_2016 = initial_pa_mc_families_2016.iloc[[2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], :]
initial_pa_mc_families_2016


Unnamed: 0 Adams County, Pennsylvania  \
2                     Total                          N   
3         Less than $10,000                          N   
4        $10,000 to $14,999                          N   
5        $15,000 to $24,999                          N   
6        $25,000 to $34,999                          N   
7        $35,000 to $49,999                          N   
8        $50,000 to $74,999                          N   
9        $75,000 to $99,999                          N   
10     $100,000 to $149,999                          N   
11     $150,000 to $199,999                          N   
12         $200,000 or more                          N   
13  Median income (dollars)                     81,817   
14    Mean income (dollars)                          N   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
2                         219,048                         13,582   
3                            1.2%                           1.3%   
4                            0.9%                           2.6%   
5                            2.9%                           4.8%   
6                            4.6%                           7.5%   
7                            9.2%                          14.0%   
8                           17.0%                          26.8%   
9                           17.5%                          15.5%   
10                          24.3%                          19.3%   
11                          10.8%                           3.6%   
12                          11.6%                           4.6%   
13                         94,674                         68,241   
14                        117,354                              N   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
2                       34,077                     74,186   
3                         1.1%                       1.1%   
4                         0.8%                       0.9%   
5                         2.3%                       3.4%   
6                         6.7%                       4.9%   
7                        12.0%                      10.8%   
8                        21.5%                      19.8%   
9                        19.9%                      19.0%   
10                       21.5%                      22.3%   
11                        8.5%                      10.5%   
12                        5.8%                       7.3%   
13                      80,740                     88,174   
14                      94,471                    104,518   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
2                      24,110                    133,809   
3                        0.9%                       1.2%   
4                        1.1%                       0.4%   
5                        5.5%                       1.9%   
6                       11.2%                       4.1%   
7                       15.5%                       7.1%   
8                       25.0%                      15.6%   
9                       18.0%                      14.6%   
10                      16.3%                      25.3%   
11                       4.1%                      13.1%   
12                       2.3%                      16.9%   
13                     65,874                    108,258   
14                          N                          N   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
2                       42,219                       27,102  ...   
3                         0.6%                         0.7%  ...   
4                         0.5%                         1.1%  ...   
5                         2.7%                         4.8%  ...   
6                         6.2%                         9.7%  ...   
7                        10.4%                        12.9%  ...   
8                        17.8%                        23.2%  ...   
9          

In [108]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_mc_families_2016 = initial_pa_mc_families_2016.T
initial_pa_mc_families_2016.head()


2                  3   \
Unnamed: 0                        Total  Less than $10,000   
Adams County, Pennsylvania            N                  N   
Allegheny County, Pennsylvania  219,048               1.2%   
Armstrong County, Pennsylvania   13,582               1.3%   
Beaver County, Pennsylvania      34,077               1.1%   

                                                4                   5   \
Unnamed: 0                      $10,000 to $14,999  $15,000 to $24,999   
Adams County, Pennsylvania                       N                   N   
Allegheny County, Pennsylvania                0.9%                2.9%   
Armstrong County, Pennsylvania                2.6%                4.8%   
Beaver County, Pennsylvania                   0.8%                2.3%   

                                                6                   7   \
Unnamed: 0                      $25,000 to $34,999  $35,000 to $49,999   
Adams County, Pennsylvania                       N                   N   
Allegheny County, Pennsylvania                4.6%                9.2%   
Armstrong County, Pennsylvania                7.5%               14.0%   
Beaver County, Pennsylvania                   6.7%               12.0%   

                                                8                   9   \
Unnamed: 0                      $50,000 to $74,999  $75,000 to $99,999   
Adams County, Pennsylvania                       N                   N   
Allegheny County, Pennsylvania               17.0%               17.5%   
Armstrong County, Pennsylvania               26.8%               15.5%   
Beaver County, Pennsylvania                  21.5%               19.9%   

                                                  10                    11  \
Unnamed: 0                      $100,000 to $149,999  $150,000 to $199,999   
Adams County, Pennsylvania                         N                     N   
Allegheny County, Pennsylvania                 24.3%                 10.8%   
Armstrong County, Pennsylvania                 19.3%                  3.6%   
Beaver County, Pennsylvania                    21.5%                  8.5%   

                                              12                       13  \
Unnamed: 0                      $200,000 or more  Median income (dollars)   
Adams County, Pennsylvania                     N                   81,817   
Allegheny County, Pennsylvania             11.6%                   94,674   
Armstrong County, Pennsylvania              4.6%                   68,241   
Beaver County, Pennsylvania                 5.8%                   80,740   

                                                   14  
Unnamed: 0                      Mean income (dollars)  
Adams County, Pennsylvania                          N  
Allegheny County, Pennsylvania                117,354  
Armstrong County, Pennsylvania                      N  
Beaver County, Pennsylvania                    94,471

In [109]:
# Resetting index and renaming to create a 'County' column
initial_pa_mc_families_2016 = initial_pa_mc_families_2016.reset_index()
initial_pa_mc_families_2016.rename(columns={'index': 'County'}, inplace=True)
initial_pa_mc_families_2016.head()


County        2                  3  \
0                      Unnamed: 0    Total  Less than $10,000   
1      Adams County, Pennsylvania        N                  N   
2  Allegheny County, Pennsylvania  219,048               1.2%   
3  Armstrong County, Pennsylvania   13,582               1.3%   
4     Beaver County, Pennsylvania   34,077               1.1%   

                    4                   5                   6  \
0  $10,000 to $14,999  $15,000 to $24,999  $25,000 to $34,999   
1                   N                   N                   N   
2                0.9%                2.9%                4.6%   
3                2.6%                4.8%                7.5%   
4                0.8%                2.3%                6.7%   

                    7                   8                   9  \
0  $35,000 to $49,999  $50,000 to $74,999  $75,000 to $99,999   
1                   N                   N                   N   
2                9.2%               17.0%               17.5%   
3               14.0%               26.8%               15.5%   
4               12.0%               21.5%               19.9%   

                     10                    11                12  \
0  $100,000 to $149,999  $150,000 to $199,999  $200,000 or more   
1                     N                     N                 N   
2                 24.3%                 10.8%             11.6%   
3                 19.3%                  3.6%              4.6%   
4                 21.5%                  8.5%              5.8%   

                        13                     14  
0  Median income (dollars)  Mean income (dollars)  
1                   81,817                      N  
2                   94,674                117,354  
3                   68,241                      N  
4                   80,740                 94,471

In [110]:
# Confirming column data types prior to renaming
print(initial_pa_mc_families_2016.columns)


Index(['County', 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], dtype='object')


In [111]:
# Converting column data types from integers to strings for renaming
initial_pa_mc_families_2016.columns = initial_pa_mc_families_2016.columns.astype(str)
print(initial_pa_mc_families_2016.columns)


Index(['County', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12',
       '13', '14'],
      dtype='object')


In [112]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_mc_families_2016.replace('N', np.nan, inplace=True)


In [113]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_mc_families_2016 = initial_pa_mc_families_2016.rename(columns={'2': '# of Married Couple Families', '3': '% Married Couple Families <$10,000', '4': '% Married Couple Families $10,000-$14,999',
                                                                         '5': '% Married Couple Families $15,000-$24,999', '6': '% Married Couple Families $25,000-$34,999', '7': '% Married Couple Families $35,000-$49,999',
                                                                         '8': '% Married Couple Families $50,000-$74,999', '9': '% Married Couple Families $75,000-$99,999',
                                                                         '10': '% Married Couple Families $100,000-$149,999', '11': '% Married Couple Families $150,000-$199,999',
                                                                        '12': '% Married Couple Families $200,000 or More', '13': 'Median Married Couple Families Income ($)',
                                                                       '14': 'Mean Married Couple Families Income ($)'})
initial_pa_mc_families_2016 = initial_pa_mc_families_2016.drop(0)
initial_pa_mc_families_2016 = initial_pa_mc_families_2016.reset_index(drop=True)
initial_pa_mc_families_2016['County'] = initial_pa_mc_families_2016['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_mc_families_2016['County'] = initial_pa_mc_families_2016['County'].apply(lambda x: x.upper())
initial_pa_mc_families_2016.insert(0, 'Year', 2016)
initial_pa_mc_families_2016['% Married Couple Families <$10,000'] = initial_pa_mc_families_2016['% Married Couple Families <$10,000'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2016['% Married Couple Families $10,000-$14,999'] = initial_pa_mc_families_2016['% Married Couple Families $10,000-$14,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2016['% Married Couple Families $15,000-$24,999'] = initial_pa_mc_families_2016['% Married Couple Families $15,000-$24,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2016['% Married Couple Families $25,000-$34,999'] = initial_pa_mc_families_2016['% Married Couple Families $25,000-$34,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2016['% Married Couple Families $35,000-$49,999'] = initial_pa_mc_families_2016['% Married Couple Families $35,000-$49,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2016['% Married Couple Families $50,000-$74,999'] = initial_pa_mc_families_2016['% Married Couple Families $50,000-$74,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2016['% Married Couple Families $75,000-$99,999'] = initial_pa_mc_families_2016['% Married Couple Families $75,000-$99,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2016['% Married Couple Families $100,000-$149,999'] = initial_pa_mc_families_2016['% Married Couple Families $100,000-$149,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2016['% Married Couple Families $150,000-$199,999'] = initial_pa_mc_families_2016['% Married Couple Families $150,000-$199,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2016['% Married Couple Families $200,000 or More'] = initial_pa_mc_families_2016['% Married Couple Families $200,000 or More'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2016['# of Married Couple Families'] = initial_pa_mc_families_2016['# of Married Couple Families'].str.replace(',', '').astype(float)
initial_pa_mc_families_2016['Median Married Couple Families Income ($)'] = initial_pa_mc_families_2016['Median Married Couple Families Income ($)'].str.replace(',', '').astype(float)
initial_pa_mc_families_2016['Mean Married Couple Families Income ($)'] = initial_pa_mc_families_2016['Mean Married Couple Families Income ($)'].str.replace(',', '').astype(float)
initial_pa_mc_families_2016


Year          County  # of Married Couple Families  \
0   2016           ADAMS                           NaN   
1   2016       ALLEGHENY                      219048.0   
2   2016       ARMSTRONG                       13582.0   
3   2016          BEAVER                       34077.0   
4   2016           BERKS                       74186.0   
5   2016           BLAIR                       24110.0   
6   2016           BUCKS                      133809.0   
7   2016          BUTLER                       42219.0   
8   2016         CAMBRIA                       27102.0   
9   2016          CARBON                           NaN   
10  2016          CENTRE                           NaN   
11  2016         CHESTER                      103671.0   
12  2016      CLEARFIELD                           NaN   
13  2016        COLUMBIA                           NaN   
14  2016        CRAWFORD                       16458.0   
15  2016      CUMBERLAND                       47934.0   
16  2016         DAUPHIN                       51180.0   
17  2016        DELAWARE                       96160.0   
18  2016            ERIE                       48295.0   
19  2016         FAYETTE                       24282.0   
20  2016        FRANKLIN                       33775.0   
21  2016         INDIANA                       16929.0   
22  2016      LACKAWANNA                       37814.0   
23  2016       LANCASTER                      109776.0   
24  2016        LAWRENCE                           NaN   
25  2016         LEBANON                       26572.0   
26  2016          LEHIGH                       65369.0   
27  2016         LUZERNE                       54730.0   
28  2016        LYCOMING                       22472.0   
29  2016          MERCER                       23305.0   
30  2016          MONROE                           NaN   
31  2016      MONTGOMERY                      174229.0   
32  2016     NORTHAMPTON                       61272.0   
33  2016  NORTHUMBERLAND                       17817.0   
34  2016    PHILADELPHIA                      160379.0   
35  2016      SCHUYLKILL                       28091.0   
36  2016        SOMERSET                       15784.0   
37  2016      WASHINGTON                       42957.0   
38  2016    WESTMORELAND                       79115.0   
39  2016            YORK                       90540.0   

    % Married Couple Families <$10,000  \
0                                  NaN   
1                                0.012   
2                                0.013   
3                                0.011   
4                                0.011   
5                                0.009   
6                                0.012   
7                                0.006   
8                                0.007   
9                                  NaN   
10                                 NaN   
11                               0.004   
12                                 NaN   
13                                 NaN   
14                               0.005   
15                               0.007   
16                               0.007   
17                               0.012   
18                               0.009   
19                               0.018   
20                               0.007   
21                               0.009   
22                               0.011   
23                               0.011   
24                                 NaN   
25                               0.008   
26                               0.010   
27                               0.017   
28                               0.017   
29                               0.020   
30                                 NaN   
31                               0.009   
32                               0.007   
33                               0.012   
34                               0.037   
35                               0.017   
36                               0.018   
37                           

**2019**
-
Please note: 2020 United States Census Bureau was unavailable and as such the closest year prior to the election (2019) was utilized


In [114]:
# Reading in 2019 U.S. Census Bureau income (Married Couple Families) dataset
initial_pa_mc_families_2019 = pd.read_excel("Resources/PA_Income_Married_Couple_Families_2019.xlsx")
initial_pa_mc_families_2019.head(19)


Unnamed: 0 Adams County, Pennsylvania  \
0                                      NaN    Married-couple families   
1                                    Label                   Estimate   
2                                    Total                     21,827   
3                        Less than $10,000                       0.6%   
4                       $10,000 to $14,999                       0.5%   
5                       $15,000 to $24,999                       3.2%   
6                       $25,000 to $34,999                       5.2%   
7                       $35,000 to $49,999                      10.2%   
8                       $50,000 to $74,999                      18.1%   
9                       $75,000 to $99,999                      21.7%   
10                    $100,000 to $149,999                      22.1%   
11                    $150,000 to $199,999                      10.1%   
12                        $200,000 or more                       8.2%   
13                 Median income (dollars)                     88,173   
14                   Mean income (dollars)                          N   
15                       PERCENT ALLOCATED                        NaN   
16  Household income in the past 12 months                        (X)   
17     Family income in the past 12 months                        (X)   
18  Nonfamily income in the past 12 months                        (X)   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
0         Married-couple families        Married-couple families   
1                        Estimate                       Estimate   
2                         225,213                              N   
3                            1.1%                              N   
4                            0.5%                              N   
5                            2.3%                              N   
6                            3.3%                              N   
7                            6.4%                              N   
8                           15.7%                              N   
9                           15.8%                              N   
10                          26.4%                              N   
11                          12.8%                              N   
12                          15.7%                              N   
13                        107,939                         74,786   
14                        139,626                              N   
15                            NaN                            NaN   
16                            (X)                            (X)   
17                            (X)                            (X)   
18                            (X)                            (X)   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
0      Married-couple families    Married-couple families   
1                     Estimate                   Estimate   
2                       31,950                     75,762   
3                         0.9%                       1.4%   
4                         0.8%                       0.3%   
5                         3.7%                       2.3%   
6                         4.6%                       3.3%   
7                         7.4%                       9.8%   
8                        17.1%                      18.0%   
9                        19.3%                      15.8%   
10                       26.5%                      29.7%   
11                       12.1%                      10.7%   
12                        7.6%                       8.8%   
13                      95,142                     98,170   
14                           N                    113,907   
15                         NaN                        NaN   
16                         (X)                        (X)   
17                         (X)                        (X)   
18                         (X)                     

In [115]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Four groupings = Households, Families, Married-couple families & non family households
# % of groups above that fall into the income categories: Less Than $10,000, $10,000-$14,999, $15,000-$24,999, $25,000-$34,999,
# $35,000-$49,999, $50,000-$74,999, $75,000-$99,999, $100,000-$149,999, $150,000-$199,999, $200,000 or More
# Total count for each grouping
# Median income for each grouping
# Mean income for each grouping
initial_pa_mc_families_2019 = initial_pa_mc_families_2019.iloc[[2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], :]
initial_pa_mc_families_2019


Unnamed: 0 Adams County, Pennsylvania  \
2                     Total                     21,827   
3         Less than $10,000                       0.6%   
4        $10,000 to $14,999                       0.5%   
5        $15,000 to $24,999                       3.2%   
6        $25,000 to $34,999                       5.2%   
7        $35,000 to $49,999                      10.2%   
8        $50,000 to $74,999                      18.1%   
9        $75,000 to $99,999                      21.7%   
10     $100,000 to $149,999                      22.1%   
11     $150,000 to $199,999                      10.1%   
12         $200,000 or more                       8.2%   
13  Median income (dollars)                     88,173   
14    Mean income (dollars)                          N   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
2                         225,213                              N   
3                            1.1%                              N   
4                            0.5%                              N   
5                            2.3%                              N   
6                            3.3%                              N   
7                            6.4%                              N   
8                           15.7%                              N   
9                           15.8%                              N   
10                          26.4%                              N   
11                          12.8%                              N   
12                          15.7%                              N   
13                        107,939                         74,786   
14                        139,626                              N   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
2                       31,950                     75,762   
3                         0.9%                       1.4%   
4                         0.8%                       0.3%   
5                         3.7%                       2.3%   
6                         4.6%                       3.3%   
7                         7.4%                       9.8%   
8                        17.1%                      18.0%   
9                        19.3%                      15.8%   
10                       26.5%                      29.7%   
11                       12.1%                      10.7%   
12                        7.6%                       8.8%   
13                      95,142                     98,170   
14                           N                    113,907   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
2                      24,065                    135,073   
3                        0.5%                       0.7%   
4                        1.0%                       0.4%   
5                        2.7%                       1.6%   
6                        6.6%                       2.6%   
7                       14.0%                       5.2%   
8                       19.3%                      11.0%   
9                       18.2%                      13.6%   
10                      24.3%                      25.6%   
11                       9.2%                      18.0%   
12                       4.3%                      21.3%   
13                     81,980                    125,966   
14                          N                          N   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
2                       42,584                       26,658  ...   
3                         1.0%                         1.1%  ...   
4                         0.3%                         0.4%  ...   
5                         1.9%                         2.7%  ...   
6                         3.7%                         6.9%  ...   
7                         7.3%                        12.6%  ...   
8                        16.9%                        23.4%  ...   
9          

In [116]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_mc_families_2019 = initial_pa_mc_families_2019.T
initial_pa_mc_families_2019.head()


2                  3   \
Unnamed: 0                        Total  Less than $10,000   
Adams County, Pennsylvania       21,827               0.6%   
Allegheny County, Pennsylvania  225,213               1.1%   
Armstrong County, Pennsylvania        N                  N   
Beaver County, Pennsylvania      31,950               0.9%   

                                                4                   5   \
Unnamed: 0                      $10,000 to $14,999  $15,000 to $24,999   
Adams County, Pennsylvania                    0.5%                3.2%   
Allegheny County, Pennsylvania                0.5%                2.3%   
Armstrong County, Pennsylvania                   N                   N   
Beaver County, Pennsylvania                   0.8%                3.7%   

                                                6                   7   \
Unnamed: 0                      $25,000 to $34,999  $35,000 to $49,999   
Adams County, Pennsylvania                    5.2%               10.2%   
Allegheny County, Pennsylvania                3.3%                6.4%   
Armstrong County, Pennsylvania                   N                   N   
Beaver County, Pennsylvania                   4.6%                7.4%   

                                                8                   9   \
Unnamed: 0                      $50,000 to $74,999  $75,000 to $99,999   
Adams County, Pennsylvania                   18.1%               21.7%   
Allegheny County, Pennsylvania               15.7%               15.8%   
Armstrong County, Pennsylvania                   N                   N   
Beaver County, Pennsylvania                  17.1%               19.3%   

                                                  10                    11  \
Unnamed: 0                      $100,000 to $149,999  $150,000 to $199,999   
Adams County, Pennsylvania                     22.1%                 10.1%   
Allegheny County, Pennsylvania                 26.4%                 12.8%   
Armstrong County, Pennsylvania                     N                     N   
Beaver County, Pennsylvania                    26.5%                 12.1%   

                                              12                       13  \
Unnamed: 0                      $200,000 or more  Median income (dollars)   
Adams County, Pennsylvania                  8.2%                   88,173   
Allegheny County, Pennsylvania             15.7%                  107,939   
Armstrong County, Pennsylvania                 N                   74,786   
Beaver County, Pennsylvania                 7.6%                   95,142   

                                                   14  
Unnamed: 0                      Mean income (dollars)  
Adams County, Pennsylvania                          N  
Allegheny County, Pennsylvania                139,626  
Armstrong County, Pennsylvania                      N  
Beaver County, Pennsylvania                         N

In [117]:
# Resetting index and renaming to create a 'County' column
initial_pa_mc_families_2019 = initial_pa_mc_families_2019.reset_index()
initial_pa_mc_families_2019.rename(columns={'index': 'County'}, inplace=True)
initial_pa_mc_families_2019.head()


County        2                  3  \
0                      Unnamed: 0    Total  Less than $10,000   
1      Adams County, Pennsylvania   21,827               0.6%   
2  Allegheny County, Pennsylvania  225,213               1.1%   
3  Armstrong County, Pennsylvania        N                  N   
4     Beaver County, Pennsylvania   31,950               0.9%   

                    4                   5                   6  \
0  $10,000 to $14,999  $15,000 to $24,999  $25,000 to $34,999   
1                0.5%                3.2%                5.2%   
2                0.5%                2.3%                3.3%   
3                   N                   N                   N   
4                0.8%                3.7%                4.6%   

                    7                   8                   9  \
0  $35,000 to $49,999  $50,000 to $74,999  $75,000 to $99,999   
1               10.2%               18.1%               21.7%   
2                6.4%               15.7%               15.8%   
3                   N                   N                   N   
4                7.4%               17.1%               19.3%   

                     10                    11                12  \
0  $100,000 to $149,999  $150,000 to $199,999  $200,000 or more   
1                 22.1%                 10.1%              8.2%   
2                 26.4%                 12.8%             15.7%   
3                     N                     N                 N   
4                 26.5%                 12.1%              7.6%   

                        13                     14  
0  Median income (dollars)  Mean income (dollars)  
1                   88,173                      N  
2                  107,939                139,626  
3                   74,786                      N  
4                   95,142                      N

In [118]:
# Confirming column data types prior to renaming
print(initial_pa_mc_families_2019.columns)


Index(['County', 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], dtype='object')


In [119]:
# Converting column data types from integers to strings for renaming
initial_pa_mc_families_2019.columns = initial_pa_mc_families_2019.columns.astype(str)
print(initial_pa_mc_families_2019.columns)


Index(['County', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12',
       '13', '14'],
      dtype='object')


In [120]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_mc_families_2019.replace('N', np.nan, inplace=True)


In [121]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_mc_families_2019 = initial_pa_mc_families_2019.rename(columns={'2': '# of Married Couple Families', '3': '% Married Couple Families <$10,000', '4': '% Married Couple Families $10,000-$14,999',
                                                                         '5': '% Married Couple Families $15,000-$24,999', '6': '% Married Couple Families $25,000-$34,999', '7': '% Married Couple Families $35,000-$49,999',
                                                                         '8': '% Married Couple Families $50,000-$74,999', '9': '% Married Couple Families $75,000-$99,999',
                                                                         '10': '% Married Couple Families $100,000-$149,999', '11': '% Married Couple Families $150,000-$199,999',
                                                                        '12': '% Married Couple Families $200,000 or More', '13': 'Median Married Couple Families Income ($)',
                                                                       '14': 'Mean Married Couple Families Income ($)'})
initial_pa_mc_families_2019 = initial_pa_mc_families_2019.drop(0)
initial_pa_mc_families_2019 = initial_pa_mc_families_2019.reset_index(drop=True)
initial_pa_mc_families_2019['County'] = initial_pa_mc_families_2019['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_mc_families_2019['County'] = initial_pa_mc_families_2019['County'].apply(lambda x: x.upper())
initial_pa_mc_families_2019.insert(0, 'Year', 2020)
initial_pa_mc_families_2019['% Married Couple Families <$10,000'] = initial_pa_mc_families_2019['% Married Couple Families <$10,000'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2019['% Married Couple Families $10,000-$14,999'] = initial_pa_mc_families_2019['% Married Couple Families $10,000-$14,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2019['% Married Couple Families $15,000-$24,999'] = initial_pa_mc_families_2019['% Married Couple Families $15,000-$24,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2019['% Married Couple Families $25,000-$34,999'] = initial_pa_mc_families_2019['% Married Couple Families $25,000-$34,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2019['% Married Couple Families $35,000-$49,999'] = initial_pa_mc_families_2019['% Married Couple Families $35,000-$49,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2019['% Married Couple Families $50,000-$74,999'] = initial_pa_mc_families_2019['% Married Couple Families $50,000-$74,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2019['% Married Couple Families $75,000-$99,999'] = initial_pa_mc_families_2019['% Married Couple Families $75,000-$99,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2019['% Married Couple Families $100,000-$149,999'] = initial_pa_mc_families_2019['% Married Couple Families $100,000-$149,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2019['% Married Couple Families $150,000-$199,999'] = initial_pa_mc_families_2019['% Married Couple Families $150,000-$199,999'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2019['% Married Couple Families $200,000 or More'] = initial_pa_mc_families_2019['% Married Couple Families $200,000 or More'].str.rstrip('%').astype(float) / 100
initial_pa_mc_families_2019['# of Married Couple Families'] = initial_pa_mc_families_2019['# of Married Couple Families'].str.replace(',', '').astype(float)
initial_pa_mc_families_2019['Median Married Couple Families Income ($)'] = initial_pa_mc_families_2019['Median Married Couple Families Income ($)'].str.replace(',', '').astype(float)
initial_pa_mc_families_2019['Mean Married Couple Families Income ($)'] = initial_pa_mc_families_2019['Mean Married Couple Families Income ($)'].str.replace(',', '').astype(float)
initial_pa_mc_families_2019


Year          County  # of Married Couple Families  \
0   2020           ADAMS                       21827.0   
1   2020       ALLEGHENY                      225213.0   
2   2020       ARMSTRONG                           NaN   
3   2020          BEAVER                       31950.0   
4   2020           BERKS                       75762.0   
5   2020           BLAIR                       24065.0   
6   2020           BUCKS                      135073.0   
7   2020          BUTLER                       42584.0   
8   2020         CAMBRIA                       26658.0   
9   2020          CARBON                           NaN   
10  2020          CENTRE                           NaN   
11  2020         CHESTER                      112500.0   
12  2020      CLEARFIELD                           NaN   
13  2020        COLUMBIA                           NaN   
14  2020        CRAWFORD                       18110.0   
15  2020      CUMBERLAND                       51939.0   
16  2020         DAUPHIN                       49061.0   
17  2020        DELAWARE                      100601.0   
18  2020            ERIE                       45251.0   
19  2020         FAYETTE                       23092.0   
20  2020        FRANKLIN                           NaN   
21  2020         INDIANA                           NaN   
22  2020      LACKAWANNA                       39700.0   
23  2020       LANCASTER                      110503.0   
24  2020        LAWRENCE                       17680.0   
25  2020         LEBANON                       27202.0   
26  2020          LEHIGH                       66703.0   
27  2020         LUZERNE                       55359.0   
28  2020        LYCOMING                       21024.0   
29  2020          MERCER                       21793.0   
30  2020          MONROE                           NaN   
31  2020      MONTGOMERY                      173673.0   
32  2020     NORTHAMPTON                       57892.0   
33  2020  NORTHUMBERLAND                           NaN   
34  2020    PHILADELPHIA                      174209.0   
35  2020      SCHUYLKILL                       26926.0   
36  2020        SOMERSET                       15244.0   
37  2020      WASHINGTON                       42556.0   
38  2020    WESTMORELAND                       74209.0   
39  2020            YORK                       90877.0   

    % Married Couple Families <$10,000  \
0                                0.006   
1                                0.011   
2                                  NaN   
3                                0.009   
4                                0.014   
5                                0.005   
6                                0.007   
7                                0.010   
8                                0.011   
9                                  NaN   
10                                 NaN   
11                               0.006   
12                                 NaN   
13                                 NaN   
14                               0.013   
15                               0.013   
16                               0.005   
17                               0.011   
18                               0.018   
19                               0.009   
20                                 NaN   
21                                 NaN   
22                               0.011   
23                               0.012   
24                               0.016   
25                               0.014   
26                               0.014   
27                               0.017   
28                               0.006   
29                               0.014   
30                                 NaN   
31                               0.006   
32                               0.012   
33                                 NaN   
34                               0.026   
35                               0.007   
36                               0.005   
37                           

**Income (Nonfamily Households) Data Extraction, Transformation & Loading (2012, 2016 & 2019)**
-
-----------

**2012**
-

In [122]:
# Reading in 2012 U.S. Census Bureau income (Nonfamily Households) dataset
initial_pa_nonfamily_2012 = pd.read_excel("Resources/PA_Income_Nonfamily_Households_2012.xlsx")
initial_pa_nonfamily_2012.head(19)


Unnamed: 0 Adams County, Pennsylvania  \
0                                      NaN       Nonfamily households   
1                                    Label                   Estimate   
2                                    Total                     11,077   
3                        Less than $10,000                       9.2%   
4                       $10,000 to $14,999                      13.2%   
5                       $15,000 to $24,999                      16.3%   
6                       $25,000 to $34,999                      18.3%   
7                       $35,000 to $49,999                      15.4%   
8                       $50,000 to $74,999                      16.4%   
9                       $75,000 to $99,999                       6.3%   
10                    $100,000 to $149,999                       4.5%   
11                    $150,000 to $199,999                       0.2%   
12                        $200,000 or more                       0.2%   
13                 Median income (dollars)                     31,678   
14                   Mean income (dollars)                     39,002   
15                         PERCENT IMPUTED                        NaN   
16  Household income in the past 12 months                        (X)   
17     Family income in the past 12 months                        (X)   
18  Nonfamily income in the past 12 months                      24.3%   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
0            Nonfamily households           Nonfamily households   
1                        Estimate                       Estimate   
2                         222,844                          9,564   
3                           13.2%                          17.2%   
4                            9.0%                          11.4%   
5                           17.8%                          24.7%   
6                           14.5%                          17.8%   
7                           15.3%                          10.2%   
8                           16.5%                           9.8%   
9                            6.4%                           7.1%   
10                           4.3%                           1.6%   
11                           1.7%                           0.0%   
12                           1.3%                           0.2%   
13                         31,395                         23,832   
14                         44,363                         31,013   
15                            NaN                            NaN   
16                            (X)                            (X)   
17                            (X)                            (X)   
18                          23.3%                          28.5%   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
0         Nonfamily households       Nonfamily households   
1                     Estimate                   Estimate   
2                       25,207                     47,979   
3                        10.1%                      11.8%   
4                        14.1%                      11.1%   
5                        22.8%                      18.8%   
6                        19.1%                      15.1%   
7                        12.9%                      18.0%   
8                        12.5%                      15.3%   
9                         6.1%                       5.9%   
10                        2.2%                       2.2%   
11                        0.2%                       0.9%   
12                        0.1%                       0.9%   
13                      26,133                     30,445   
14                      33,987                     38,835   
15                         NaN                        NaN   
16                         (X)                        (X)   
17                         (X)                        (X)   
18                       27.6%                     

In [123]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Four groupings = Households, Families, Married-couple families & non family households
# % of groups above that fall into the income categories: Less Than $10,000, $10,000-$14,999, $15,000-$24,999, $25,000-$34,999,
# $35,000-$49,999, $50,000-$74,999, $75,000-$99,999, $100,000-$149,999, $150,000-$199,999, $200,000 or More
# Total count for each grouping
# Median income for each grouping
# Mean income for each grouping
initial_pa_nonfamily_2012 = initial_pa_nonfamily_2012.iloc[[2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], :]
initial_pa_nonfamily_2012


Unnamed: 0 Adams County, Pennsylvania  \
2                     Total                     11,077   
3         Less than $10,000                       9.2%   
4        $10,000 to $14,999                      13.2%   
5        $15,000 to $24,999                      16.3%   
6        $25,000 to $34,999                      18.3%   
7        $35,000 to $49,999                      15.4%   
8        $50,000 to $74,999                      16.4%   
9        $75,000 to $99,999                       6.3%   
10     $100,000 to $149,999                       4.5%   
11     $150,000 to $199,999                       0.2%   
12         $200,000 or more                       0.2%   
13  Median income (dollars)                     31,678   
14    Mean income (dollars)                     39,002   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
2                         222,844                          9,564   
3                           13.2%                          17.2%   
4                            9.0%                          11.4%   
5                           17.8%                          24.7%   
6                           14.5%                          17.8%   
7                           15.3%                          10.2%   
8                           16.5%                           9.8%   
9                            6.4%                           7.1%   
10                           4.3%                           1.6%   
11                           1.7%                           0.0%   
12                           1.3%                           0.2%   
13                         31,395                         23,832   
14                         44,363                         31,013   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
2                       25,207                     47,979   
3                        10.1%                      11.8%   
4                        14.1%                      11.1%   
5                        22.8%                      18.8%   
6                        19.1%                      15.1%   
7                        12.9%                      18.0%   
8                        12.5%                      15.3%   
9                         6.1%                       5.9%   
10                        2.2%                       2.2%   
11                        0.2%                       0.9%   
12                        0.1%                       0.9%   
13                      26,133                     30,445   
14                      33,987                     38,835   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
2                      18,030                     65,228   
3                       17.4%                      10.9%   
4                       14.5%                       7.3%   
5                       24.0%                      15.6%   
6                       14.7%                      10.9%   
7                        9.7%                      15.0%   
8                       13.5%                      18.4%   
9                        3.8%                       8.9%   
10                       1.2%                       8.5%   
11                       0.6%                       1.8%   
12                       0.6%                       2.7%   
13                     21,889                     40,759   
14                     31,403                     54,310   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
2                       23,117                       20,962  ...   
3                        12.4%                        15.4%  ...   
4                        13.1%                        21.5%  ...   
5                        18.0%                        20.6%  ...   
6                        11.9%                        13.1%  ...   
7                        16.9%                        12.6%  ...   
8                        15.0%                        10.5%  ...   
9          

In [124]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_nonfamily_2012 = initial_pa_nonfamily_2012.T
initial_pa_nonfamily_2012.head()


2                  3   \
Unnamed: 0                        Total  Less than $10,000   
Adams County, Pennsylvania       11,077               9.2%   
Allegheny County, Pennsylvania  222,844              13.2%   
Armstrong County, Pennsylvania    9,564              17.2%   
Beaver County, Pennsylvania      25,207              10.1%   

                                                4                   5   \
Unnamed: 0                      $10,000 to $14,999  $15,000 to $24,999   
Adams County, Pennsylvania                   13.2%               16.3%   
Allegheny County, Pennsylvania                9.0%               17.8%   
Armstrong County, Pennsylvania               11.4%               24.7%   
Beaver County, Pennsylvania                  14.1%               22.8%   

                                                6                   7   \
Unnamed: 0                      $25,000 to $34,999  $35,000 to $49,999   
Adams County, Pennsylvania                   18.3%               15.4%   
Allegheny County, Pennsylvania               14.5%               15.3%   
Armstrong County, Pennsylvania               17.8%               10.2%   
Beaver County, Pennsylvania                  19.1%               12.9%   

                                                8                   9   \
Unnamed: 0                      $50,000 to $74,999  $75,000 to $99,999   
Adams County, Pennsylvania                   16.4%                6.3%   
Allegheny County, Pennsylvania               16.5%                6.4%   
Armstrong County, Pennsylvania                9.8%                7.1%   
Beaver County, Pennsylvania                  12.5%                6.1%   

                                                  10                    11  \
Unnamed: 0                      $100,000 to $149,999  $150,000 to $199,999   
Adams County, Pennsylvania                      4.5%                  0.2%   
Allegheny County, Pennsylvania                  4.3%                  1.7%   
Armstrong County, Pennsylvania                  1.6%                  0.0%   
Beaver County, Pennsylvania                     2.2%                  0.2%   

                                              12                       13  \
Unnamed: 0                      $200,000 or more  Median income (dollars)   
Adams County, Pennsylvania                  0.2%                   31,678   
Allegheny County, Pennsylvania              1.3%                   31,395   
Armstrong County, Pennsylvania              0.2%                   23,832   
Beaver County, Pennsylvania                 0.1%                   26,133   

                                                   14  
Unnamed: 0                      Mean income (dollars)  
Adams County, Pennsylvania                     39,002  
Allegheny County, Pennsylvania                 44,363  
Armstrong County, Pennsylvania                 31,013  
Beaver County, Pennsylvania                    33,987

In [125]:
# Resetting index and renaming to create a 'County' column
initial_pa_nonfamily_2012 = initial_pa_nonfamily_2012.reset_index()
initial_pa_nonfamily_2012.rename(columns={'index': 'County'}, inplace=True)
initial_pa_nonfamily_2012.head()


County        2                  3  \
0                      Unnamed: 0    Total  Less than $10,000   
1      Adams County, Pennsylvania   11,077               9.2%   
2  Allegheny County, Pennsylvania  222,844              13.2%   
3  Armstrong County, Pennsylvania    9,564              17.2%   
4     Beaver County, Pennsylvania   25,207              10.1%   

                    4                   5                   6  \
0  $10,000 to $14,999  $15,000 to $24,999  $25,000 to $34,999   
1               13.2%               16.3%               18.3%   
2                9.0%               17.8%               14.5%   
3               11.4%               24.7%               17.8%   
4               14.1%               22.8%               19.1%   

                    7                   8                   9  \
0  $35,000 to $49,999  $50,000 to $74,999  $75,000 to $99,999   
1               15.4%               16.4%                6.3%   
2               15.3%               16.5%                6.4%   
3               10.2%                9.8%                7.1%   
4               12.9%               12.5%                6.1%   

                     10                    11                12  \
0  $100,000 to $149,999  $150,000 to $199,999  $200,000 or more   
1                  4.5%                  0.2%              0.2%   
2                  4.3%                  1.7%              1.3%   
3                  1.6%                  0.0%              0.2%   
4                  2.2%                  0.2%              0.1%   

                        13                     14  
0  Median income (dollars)  Mean income (dollars)  
1                   31,678                 39,002  
2                   31,395                 44,363  
3                   23,832                 31,013  
4                   26,133                 33,987

In [126]:
# Confirming column data types prior to renaming
print(initial_pa_nonfamily_2012.columns)


Index(['County', 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], dtype='object')


In [127]:
# Converting column data types from integers to strings for renaming
initial_pa_nonfamily_2012.columns = initial_pa_nonfamily_2012.columns.astype(str)
print(initial_pa_nonfamily_2012.columns)


Index(['County', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12',
       '13', '14'],
      dtype='object')


In [128]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_nonfamily_2012.replace('N', np.nan, inplace=True)


In [129]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_nonfamily_2012 = initial_pa_nonfamily_2012.rename(columns={'2': '# of Nonfamily Households', '3': '% Nonfamily Households <$10,000', '4': '% Nonfamily Households $10,000-$14,999',
                                                                         '5': '% Nonfamily Households $15,000-$24,999', '6': '% Nonfamily Households $25,000-$34,999', '7': '% Nonfamily Households $35,000-$49,999',
                                                                         '8': '% Nonfamily Households $50,000-$74,999', '9': '% Nonfamily Households $75,000-$99,999',
                                                                         '10': '% Nonfamily Households $100,000-$149,999', '11': '% Nonfamily Households $150,000-$199,999',
                                                                        '12': '% Nonfamily Households $200,000 or More', '13': 'Median Nonfamily Households Income ($)',
                                                                       '14': 'Mean Nonfamily Households Income ($)'})
initial_pa_nonfamily_2012 = initial_pa_nonfamily_2012.drop(0)
initial_pa_nonfamily_2012 = initial_pa_nonfamily_2012.reset_index(drop=True)
initial_pa_nonfamily_2012['County'] = initial_pa_nonfamily_2012['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_nonfamily_2012['County'] = initial_pa_nonfamily_2012['County'].apply(lambda x: x.upper())
initial_pa_nonfamily_2012.insert(0, 'Year', 2012)
initial_pa_nonfamily_2012['% Nonfamily Households <$10,000'] = initial_pa_nonfamily_2012['% Nonfamily Households <$10,000'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2012['% Nonfamily Households $10,000-$14,999'] = initial_pa_nonfamily_2012['% Nonfamily Households $10,000-$14,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2012['% Nonfamily Households $15,000-$24,999'] = initial_pa_nonfamily_2012['% Nonfamily Households $15,000-$24,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2012['% Nonfamily Households $25,000-$34,999'] = initial_pa_nonfamily_2012['% Nonfamily Households $25,000-$34,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2012['% Nonfamily Households $35,000-$49,999'] = initial_pa_nonfamily_2012['% Nonfamily Households $35,000-$49,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2012['% Nonfamily Households $50,000-$74,999'] = initial_pa_nonfamily_2012['% Nonfamily Households $50,000-$74,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2012['% Nonfamily Households $75,000-$99,999'] = initial_pa_nonfamily_2012['% Nonfamily Households $75,000-$99,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2012['% Nonfamily Households $100,000-$149,999'] = initial_pa_nonfamily_2012['% Nonfamily Households $100,000-$149,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2012['% Nonfamily Households $150,000-$199,999'] = initial_pa_nonfamily_2012['% Nonfamily Households $150,000-$199,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2012['% Nonfamily Households $200,000 or More'] = initial_pa_nonfamily_2012['% Nonfamily Households $200,000 or More'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2012['# of Nonfamily Households'] = initial_pa_nonfamily_2012['# of Nonfamily Households'].str.replace(',', '').astype(float)
initial_pa_nonfamily_2012['Median Nonfamily Households Income ($)'] = initial_pa_nonfamily_2012['Median Nonfamily Households Income ($)'].str.replace(',', '').astype(float)
initial_pa_nonfamily_2012['Mean Nonfamily Households Income ($)'] = initial_pa_nonfamily_2012['Mean Nonfamily Households Income ($)'].str.replace(',', '').astype(float)
initial_pa_nonfamily_2012


Year          County  # of Nonfamily Households  \
0   2012           ADAMS                    11077.0   
1   2012       ALLEGHENY                   222844.0   
2   2012       ARMSTRONG                     9564.0   
3   2012          BEAVER                    25207.0   
4   2012           BERKS                    47979.0   
5   2012           BLAIR                    18030.0   
6   2012           BUCKS                    65228.0   
7   2012          BUTLER                    23117.0   
8   2012         CAMBRIA                    20962.0   
9   2012          CARBON                     8939.0   
10  2012          CENTRE                    23337.0   
11  2012         CHESTER                    55529.0   
12  2012      CLEARFIELD                    11041.0   
13  2012        COLUMBIA                     9437.0   
14  2012        CRAWFORD                    11309.0   
15  2012      CUMBERLAND                    32201.0   
16  2012         DAUPHIN                    38220.0   
17  2012        DELAWARE                    68222.0   
18  2012            ERIE                    38798.0   
19  2012         FAYETTE                    20046.0   
20  2012        FRANKLIN                    17046.0   
21  2012         INDIANA                    12109.0   
22  2012      LACKAWANNA                    33223.0   
23  2012       LANCASTER                    55772.0   
24  2012        LAWRENCE                    12571.0   
25  2012         LEBANON                    17475.0   
26  2012          LEHIGH                    45016.0   
27  2012         LUZERNE                    48987.0   
28  2012        LYCOMING                    15768.0   
29  2012          MERCER                    14122.0   
30  2012          MONROE                    16696.0   
31  2012      MONTGOMERY                    98489.0   
32  2012     NORTHAMPTON                    35675.0   
33  2012  NORTHUMBERLAND                    14206.0   
34  2012    PHILADELPHIA                   271994.0   
35  2012      SCHUYLKILL                    20725.0   
36  2012        SOMERSET                     8972.0   
37  2012      WASHINGTON                    29859.0   
38  2012    WESTMORELAND                    51006.0   
39  2012            YORK                    50318.0   

    % Nonfamily Households <$10,000  % Nonfamily Households $10,000-$14,999  \
0                             0.092                                   0.132   
1                             0.132                                   0.090   
2                             0.172                                   0.114   
3                             0.101                                   0.141   
4                             0.118                                   0.111   
5                             0.174                                   0.145   
6                             0.109                                   0.073   
7                             0.124                                   0.131   
8                             0.154                                   0.215   
9                             0.156                                   0.143   
10                            0.222                                   0.080   
11                            0.086                                   0.060   
12                            0.137                                   0.163   
13                            0.152                                   0.130   
14                            0.172                                   0.125   
15                            0.104                                   0.070   
16                            0.107                                   0.076   
17                            0.130                                   0.095   
18                            0.158                                   0.121   
19                            0.176                                   0.179   
20                            0.092                                   0.087   
21        

**2016**
-

In [130]:
# Reading in 2016 U.S. Census Bureau income (Nonfamily Households) dataset
initial_pa_nonfamily_2016 = pd.read_excel("Resources/PA_Income_Nonfamily_Households_2016.xlsx")
initial_pa_nonfamily_2016.head(19)


Unnamed: 0 Adams County, Pennsylvania  \
0                                      NaN       Nonfamily households   
1                                    Label                   Estimate   
2                                    Total                     11,882   
3                        Less than $10,000                       6.4%   
4                       $10,000 to $14,999                      12.8%   
5                       $15,000 to $24,999                      15.6%   
6                       $25,000 to $34,999                      21.6%   
7                       $35,000 to $49,999                      16.1%   
8                       $50,000 to $74,999                      13.4%   
9                       $75,000 to $99,999                       5.5%   
10                    $100,000 to $149,999                       6.8%   
11                    $150,000 to $199,999                       1.5%   
12                        $200,000 or more                       0.4%   
13                 Median income (dollars)                     31,033   
14                   Mean income (dollars)                     42,653   
15                       PERCENT ALLOCATED                        NaN   
16  Household income in the past 12 months                        (X)   
17     Family income in the past 12 months                        (X)   
18  Nonfamily income in the past 12 months                      26.7%   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
0            Nonfamily households           Nonfamily households   
1                        Estimate                       Estimate   
2                         233,085                          8,586   
3                           12.0%                          10.3%   
4                            8.6%                          13.6%   
5                           17.0%                          26.0%   
6                           13.2%                          20.0%   
7                           15.2%                          12.0%   
8                           16.0%                          10.9%   
9                            7.9%                           1.8%   
10                           6.8%                           3.3%   
11                           1.4%                           1.1%   
12                           1.8%                           1.1%   
13                         33,974                         25,070   
14                         48,416                         34,235   
15                            NaN                            NaN   
16                            (X)                            (X)   
17                            (X)                            (X)   
18                          30.4%                          30.0%   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
0         Nonfamily households       Nonfamily households   
1                     Estimate                   Estimate   
2                       24,001                     47,924   
3                         9.9%                      10.7%   
4                        11.1%                       8.7%   
5                        19.1%                      15.8%   
6                        13.7%                      11.9%   
7                        15.0%                      19.1%   
8                        15.9%                      15.7%   
9                         7.8%                      10.2%   
10                        6.1%                       5.5%   
11                        0.6%                       1.3%   
12                        0.8%                       1.2%   
13                      32,343                     36,853   
14                      42,638                     45,662   
15                         NaN                        NaN   
16                         (X)                        (X)   
17                         (X)                        (X)   
18                       33.7%                     

In [131]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Four groupings = Households, Families, Married-couple families & non family households
# % of groups above that fall into the income categories: Less Than $10,000, $10,000-$14,999, $15,000-$24,999, $25,000-$34,999,
# $35,000-$49,999, $50,000-$74,999, $75,000-$99,999, $100,000-$149,999, $150,000-$199,999, $200,000 or More
# Total count for each grouping
# Median income for each grouping
# Mean income for each grouping
initial_pa_nonfamily_2016 = initial_pa_nonfamily_2016.iloc[[2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], :]
initial_pa_nonfamily_2016


Unnamed: 0 Adams County, Pennsylvania  \
2                     Total                     11,882   
3         Less than $10,000                       6.4%   
4        $10,000 to $14,999                      12.8%   
5        $15,000 to $24,999                      15.6%   
6        $25,000 to $34,999                      21.6%   
7        $35,000 to $49,999                      16.1%   
8        $50,000 to $74,999                      13.4%   
9        $75,000 to $99,999                       5.5%   
10     $100,000 to $149,999                       6.8%   
11     $150,000 to $199,999                       1.5%   
12         $200,000 or more                       0.4%   
13  Median income (dollars)                     31,033   
14    Mean income (dollars)                     42,653   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
2                         233,085                          8,586   
3                           12.0%                          10.3%   
4                            8.6%                          13.6%   
5                           17.0%                          26.0%   
6                           13.2%                          20.0%   
7                           15.2%                          12.0%   
8                           16.0%                          10.9%   
9                            7.9%                           1.8%   
10                           6.8%                           3.3%   
11                           1.4%                           1.1%   
12                           1.8%                           1.1%   
13                         33,974                         25,070   
14                         48,416                         34,235   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
2                       24,001                     47,924   
3                         9.9%                      10.7%   
4                        11.1%                       8.7%   
5                        19.1%                      15.8%   
6                        13.7%                      11.9%   
7                        15.0%                      19.1%   
8                        15.9%                      15.7%   
9                         7.8%                      10.2%   
10                        6.1%                       5.5%   
11                        0.6%                       1.3%   
12                        0.8%                       1.2%   
13                      32,343                     36,853   
14                      42,638                     45,662   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
2                      18,257                     68,142   
3                       14.0%                       9.8%   
4                       13.5%                       5.6%   
5                       20.2%                      15.6%   
6                       18.5%                       9.9%   
7                       15.1%                      15.8%   
8                       12.5%                      18.7%   
9                        3.8%                      11.2%   
10                       1.6%                       7.8%   
11                       0.3%                       2.6%   
12                       0.5%                       3.0%   
13                     25,956                     43,036   
14                     34,858                     60,793   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
2                       25,258                       20,492  ...   
3                         9.6%                        13.6%  ...   
4                         7.0%                        13.5%  ...   
5                        17.8%                        22.9%  ...   
6                         9.9%                        14.4%  ...   
7                        16.7%                        18.1%  ...   
8                        20.3%                        11.1%  ...   
9          

In [132]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_nonfamily_2016 = initial_pa_nonfamily_2016.T
initial_pa_nonfamily_2016.head()


2                  3   \
Unnamed: 0                        Total  Less than $10,000   
Adams County, Pennsylvania       11,882               6.4%   
Allegheny County, Pennsylvania  233,085              12.0%   
Armstrong County, Pennsylvania    8,586              10.3%   
Beaver County, Pennsylvania      24,001               9.9%   

                                                4                   5   \
Unnamed: 0                      $10,000 to $14,999  $15,000 to $24,999   
Adams County, Pennsylvania                   12.8%               15.6%   
Allegheny County, Pennsylvania                8.6%               17.0%   
Armstrong County, Pennsylvania               13.6%               26.0%   
Beaver County, Pennsylvania                  11.1%               19.1%   

                                                6                   7   \
Unnamed: 0                      $25,000 to $34,999  $35,000 to $49,999   
Adams County, Pennsylvania                   21.6%               16.1%   
Allegheny County, Pennsylvania               13.2%               15.2%   
Armstrong County, Pennsylvania               20.0%               12.0%   
Beaver County, Pennsylvania                  13.7%               15.0%   

                                                8                   9   \
Unnamed: 0                      $50,000 to $74,999  $75,000 to $99,999   
Adams County, Pennsylvania                   13.4%                5.5%   
Allegheny County, Pennsylvania               16.0%                7.9%   
Armstrong County, Pennsylvania               10.9%                1.8%   
Beaver County, Pennsylvania                  15.9%                7.8%   

                                                  10                    11  \
Unnamed: 0                      $100,000 to $149,999  $150,000 to $199,999   
Adams County, Pennsylvania                      6.8%                  1.5%   
Allegheny County, Pennsylvania                  6.8%                  1.4%   
Armstrong County, Pennsylvania                  3.3%                  1.1%   
Beaver County, Pennsylvania                     6.1%                  0.6%   

                                              12                       13  \
Unnamed: 0                      $200,000 or more  Median income (dollars)   
Adams County, Pennsylvania                  0.4%                   31,033   
Allegheny County, Pennsylvania              1.8%                   33,974   
Armstrong County, Pennsylvania              1.1%                   25,070   
Beaver County, Pennsylvania                 0.8%                   32,343   

                                                   14  
Unnamed: 0                      Mean income (dollars)  
Adams County, Pennsylvania                     42,653  
Allegheny County, Pennsylvania                 48,416  
Armstrong County, Pennsylvania                 34,235  
Beaver County, Pennsylvania                    42,638

In [133]:
# Resetting index and renaming to create a 'County' column
initial_pa_nonfamily_2016 = initial_pa_nonfamily_2016.reset_index()
initial_pa_nonfamily_2016.rename(columns={'index': 'County'}, inplace=True)
initial_pa_nonfamily_2016.head()


County        2                  3  \
0                      Unnamed: 0    Total  Less than $10,000   
1      Adams County, Pennsylvania   11,882               6.4%   
2  Allegheny County, Pennsylvania  233,085              12.0%   
3  Armstrong County, Pennsylvania    8,586              10.3%   
4     Beaver County, Pennsylvania   24,001               9.9%   

                    4                   5                   6  \
0  $10,000 to $14,999  $15,000 to $24,999  $25,000 to $34,999   
1               12.8%               15.6%               21.6%   
2                8.6%               17.0%               13.2%   
3               13.6%               26.0%               20.0%   
4               11.1%               19.1%               13.7%   

                    7                   8                   9  \
0  $35,000 to $49,999  $50,000 to $74,999  $75,000 to $99,999   
1               16.1%               13.4%                5.5%   
2               15.2%               16.0%                7.9%   
3               12.0%               10.9%                1.8%   
4               15.0%               15.9%                7.8%   

                     10                    11                12  \
0  $100,000 to $149,999  $150,000 to $199,999  $200,000 or more   
1                  6.8%                  1.5%              0.4%   
2                  6.8%                  1.4%              1.8%   
3                  3.3%                  1.1%              1.1%   
4                  6.1%                  0.6%              0.8%   

                        13                     14  
0  Median income (dollars)  Mean income (dollars)  
1                   31,033                 42,653  
2                   33,974                 48,416  
3                   25,070                 34,235  
4                   32,343                 42,638

In [134]:
# Confirming column data types prior to renaming
print(initial_pa_nonfamily_2016.columns)


Index(['County', 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], dtype='object')


In [135]:
# Converting column data types from integers to strings for renaming
initial_pa_nonfamily_2016.columns = initial_pa_nonfamily_2016.columns.astype(str)
print(initial_pa_nonfamily_2016.columns)


Index(['County', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12',
       '13', '14'],
      dtype='object')


In [136]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_nonfamily_2016.replace('N', np.nan, inplace=True)


In [137]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_nonfamily_2016 = initial_pa_nonfamily_2016.rename(columns={'2': '# of Nonfamily Households', '3': '% Nonfamily Households <$10,000', '4': '% Nonfamily Households $10,000-$14,999',
                                                                         '5': '% Nonfamily Households $15,000-$24,999', '6': '% Nonfamily Households $25,000-$34,999', '7': '% Nonfamily Households $35,000-$49,999',
                                                                         '8': '% Nonfamily Households $50,000-$74,999', '9': '% Nonfamily Households $75,000-$99,999',
                                                                         '10': '% Nonfamily Households $100,000-$149,999', '11': '% Nonfamily Households $150,000-$199,999',
                                                                        '12': '% Nonfamily Households $200,000 or More', '13': 'Median Nonfamily Households Income ($)',
                                                                       '14': 'Mean Nonfamily Households Income ($)'})
initial_pa_nonfamily_2016 = initial_pa_nonfamily_2016.drop(0)
initial_pa_nonfamily_2016 = initial_pa_nonfamily_2016.reset_index(drop=True)
initial_pa_nonfamily_2016['County'] = initial_pa_nonfamily_2016['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_nonfamily_2016['County'] = initial_pa_nonfamily_2016['County'].apply(lambda x: x.upper())
initial_pa_nonfamily_2016.insert(0, 'Year', 2016)
initial_pa_nonfamily_2016['% Nonfamily Households <$10,000'] = initial_pa_nonfamily_2016['% Nonfamily Households <$10,000'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2016['% Nonfamily Households $10,000-$14,999'] = initial_pa_nonfamily_2016['% Nonfamily Households $10,000-$14,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2016['% Nonfamily Households $15,000-$24,999'] = initial_pa_nonfamily_2016['% Nonfamily Households $15,000-$24,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2016['% Nonfamily Households $25,000-$34,999'] = initial_pa_nonfamily_2016['% Nonfamily Households $25,000-$34,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2016['% Nonfamily Households $35,000-$49,999'] = initial_pa_nonfamily_2016['% Nonfamily Households $35,000-$49,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2016['% Nonfamily Households $50,000-$74,999'] = initial_pa_nonfamily_2016['% Nonfamily Households $50,000-$74,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2016['% Nonfamily Households $75,000-$99,999'] = initial_pa_nonfamily_2016['% Nonfamily Households $75,000-$99,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2016['% Nonfamily Households $100,000-$149,999'] = initial_pa_nonfamily_2016['% Nonfamily Households $100,000-$149,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2016['% Nonfamily Households $150,000-$199,999'] = initial_pa_nonfamily_2016['% Nonfamily Households $150,000-$199,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2016['% Nonfamily Households $200,000 or More'] = initial_pa_nonfamily_2016['% Nonfamily Households $200,000 or More'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2016['# of Nonfamily Households'] = initial_pa_nonfamily_2016['# of Nonfamily Households'].str.replace(',', '').astype(float)
initial_pa_nonfamily_2016['Median Nonfamily Households Income ($)'] = initial_pa_nonfamily_2016['Median Nonfamily Households Income ($)'].str.replace(',', '').astype(float)
initial_pa_nonfamily_2016['Mean Nonfamily Households Income ($)'] = initial_pa_nonfamily_2016['Mean Nonfamily Households Income ($)'].str.replace(',', '').astype(float)
initial_pa_nonfamily_2016


Year          County  # of Nonfamily Households  \
0   2016           ADAMS                    11882.0   
1   2016       ALLEGHENY                   233085.0   
2   2016       ARMSTRONG                     8586.0   
3   2016          BEAVER                    24001.0   
4   2016           BERKS                    47924.0   
5   2016           BLAIR                    18257.0   
6   2016           BUCKS                    68142.0   
7   2016          BUTLER                    25258.0   
8   2016         CAMBRIA                    20492.0   
9   2016          CARBON                     9726.0   
10  2016          CENTRE                    24560.0   
11  2016         CHESTER                    55821.0   
12  2016      CLEARFIELD                     9948.0   
13  2016        COLUMBIA                     9500.0   
14  2016        CRAWFORD                    12985.0   
15  2016      CUMBERLAND                    35789.0   
16  2016         DAUPHIN                    41262.0   
17  2016        DELAWARE                    69427.0   
18  2016            ERIE                    41760.0   
19  2016         FAYETTE                    20350.0   
20  2016        FRANKLIN                    19362.0   
21  2016         INDIANA                    13547.0   
22  2016      LACKAWANNA                    35227.0   
23  2016       LANCASTER                    60581.0   
24  2016        LAWRENCE                    12351.0   
25  2016         LEBANON                    15884.0   
26  2016          LEHIGH                    45807.0   
27  2016         LUZERNE                    47224.0   
28  2016        LYCOMING                    16027.0   
29  2016          MERCER                    15000.0   
30  2016          MONROE                    19613.0   
31  2016      MONTGOMERY                    97683.0   
32  2016     NORTHAMPTON                    32939.0   
33  2016  NORTHUMBERLAND                    13253.0   
34  2016    PHILADELPHIA                   270647.0   
35  2016      SCHUYLKILL                    19935.0   
36  2016        SOMERSET                     9844.0   
37  2016      WASHINGTON                    28748.0   
38  2016    WESTMORELAND                    48936.0   
39  2016            YORK                    52140.0   

    % Nonfamily Households <$10,000  % Nonfamily Households $10,000-$14,999  \
0                             0.064                                   0.128   
1                             0.120                                   0.086   
2                             0.103                                   0.136   
3                             0.099                                   0.111   
4                             0.107                                   0.087   
5                             0.140                                   0.135   
6                             0.098                                   0.056   
7                             0.096                                   0.070   
8                             0.136                                   0.135   
9                             0.076                                   0.134   
10                            0.181                                   0.073   
11                            0.088                                   0.064   
12                            0.107                                   0.216   
13                            0.160                                   0.149   
14                            0.119                                   0.097   
15                            0.047                                   0.057   
16                            0.091                                   0.088   
17                            0.118                                   0.058   
18                            0.131                                   0.103   
19                            0.117                                   0.163   
20                            0.091                                   0.085   
21        

**2019**
-
Please note: 2020 United States Census Bureau was unavailable and as such the closest year prior to the election (2019) was utilized


In [138]:
# Reading in 2019 U.S. Census Bureau income (Nonfamily Households) dataset
initial_pa_nonfamily_2019 = pd.read_excel("Resources/PA_Income_Nonfamily_Households_2019.xlsx")
initial_pa_nonfamily_2019.head(19)


Unnamed: 0 Adams County, Pennsylvania  \
0                                      NaN       Nonfamily households   
1                                    Label                   Estimate   
2                                    Total                     12,328   
3                        Less than $10,000                       5.6%   
4                       $10,000 to $14,999                       5.5%   
5                       $15,000 to $24,999                      22.5%   
6                       $25,000 to $34,999                      11.1%   
7                       $35,000 to $49,999                      16.4%   
8                       $50,000 to $74,999                      17.3%   
9                       $75,000 to $99,999                      12.5%   
10                    $100,000 to $149,999                       7.6%   
11                    $150,000 to $199,999                       0.6%   
12                        $200,000 or more                       0.9%   
13                 Median income (dollars)                     38,218   
14                   Mean income (dollars)                     48,790   
15                       PERCENT ALLOCATED                        NaN   
16  Household income in the past 12 months                        (X)   
17     Family income in the past 12 months                        (X)   
18  Nonfamily income in the past 12 months                      24.7%   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
0            Nonfamily households           Nonfamily households   
1                        Estimate                       Estimate   
2                         252,262                         10,911   
3                           10.7%                           4.4%   
4                            6.5%                          12.2%   
5                           14.0%                          25.2%   
6                           12.5%                           9.1%   
7                           16.1%                          18.3%   
8                           17.6%                          18.3%   
9                           10.0%                           6.5%   
10                           7.4%                           4.4%   
11                           2.9%                           0.8%   
12                           2.3%                           0.8%   
13                         40,156                         32,290   
14                         55,208                         41,674   
15                            NaN                            NaN   
16                            (X)                            (X)   
17                            (X)                            (X)   
18                          31.8%                          41.4%   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
0         Nonfamily households       Nonfamily households   
1                     Estimate                   Estimate   
2                       27,638                     49,294   
3                         9.7%                       9.8%   
4                         9.5%                       7.3%   
5                        17.7%                      15.2%   
6                        12.3%                      13.0%   
7                        18.3%                      18.5%   
8                        18.1%                      17.2%   
9                         7.1%                       9.6%   
10                        4.7%                       5.8%   
11                        2.0%                       2.2%   
12                        0.6%                       1.3%   
13                      35,330                     38,557   
14                      44,751                     49,681   
15                         NaN                        NaN   
16                         (X)                        (X)   
17                         (X)                        (X)   
18                       33.8%                     

In [139]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Four groupings = Households, Families, Married-couple families & non family households
# % of groups above that fall into the income categories: Less Than $10,000, $10,000-$14,999, $15,000-$24,999, $25,000-$34,999,
# $35,000-$49,999, $50,000-$74,999, $75,000-$99,999, $100,000-$149,999, $150,000-$199,999, $200,000 or More
# Total count for each grouping
# Median income for each grouping
# Mean income for each grouping
initial_pa_nonfamily_2019 = initial_pa_nonfamily_2019.iloc[[2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], :]
initial_pa_nonfamily_2019


Unnamed: 0 Adams County, Pennsylvania  \
2                     Total                     12,328   
3         Less than $10,000                       5.6%   
4        $10,000 to $14,999                       5.5%   
5        $15,000 to $24,999                      22.5%   
6        $25,000 to $34,999                      11.1%   
7        $35,000 to $49,999                      16.4%   
8        $50,000 to $74,999                      17.3%   
9        $75,000 to $99,999                      12.5%   
10     $100,000 to $149,999                       7.6%   
11     $150,000 to $199,999                       0.6%   
12         $200,000 or more                       0.9%   
13  Median income (dollars)                     38,218   
14    Mean income (dollars)                     48,790   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
2                         252,262                         10,911   
3                           10.7%                           4.4%   
4                            6.5%                          12.2%   
5                           14.0%                          25.2%   
6                           12.5%                           9.1%   
7                           16.1%                          18.3%   
8                           17.6%                          18.3%   
9                           10.0%                           6.5%   
10                           7.4%                           4.4%   
11                           2.9%                           0.8%   
12                           2.3%                           0.8%   
13                         40,156                         32,290   
14                         55,208                         41,674   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
2                       27,638                     49,294   
3                         9.7%                       9.8%   
4                         9.5%                       7.3%   
5                        17.7%                      15.2%   
6                        12.3%                      13.0%   
7                        18.3%                      18.5%   
8                        18.1%                      17.2%   
9                         7.1%                       9.6%   
10                        4.7%                       5.8%   
11                        2.0%                       2.2%   
12                        0.6%                       1.3%   
13                      35,330                     38,557   
14                      44,751                     49,681   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
2                      17,860                     73,467   
3                       13.5%                       6.5%   
4                        8.9%                       4.9%   
5                       18.2%                      16.2%   
6                       18.9%                       9.3%   
7                       14.2%                      13.5%   
8                       14.1%                      19.8%   
9                        6.1%                       9.9%   
10                       3.4%                      11.7%   
11                       1.6%                       2.6%   
12                       1.1%                       5.7%   
13                     29,644                     49,565   
14                     42,377                     72,632   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
2                       27,849                       21,303  ...   
3                        12.2%                        14.9%  ...   
4                         7.3%                        14.8%  ...   
5                        14.6%                        20.9%  ...   
6                        13.7%                        14.1%  ...   
7                        16.2%                        13.9%  ...   
8                        16.2%                        12.0%  ...   
9          

In [140]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_nonfamily_2019 = initial_pa_nonfamily_2019.T
initial_pa_nonfamily_2019.head()


2                  3   \
Unnamed: 0                        Total  Less than $10,000   
Adams County, Pennsylvania       12,328               5.6%   
Allegheny County, Pennsylvania  252,262              10.7%   
Armstrong County, Pennsylvania   10,911               4.4%   
Beaver County, Pennsylvania      27,638               9.7%   

                                                4                   5   \
Unnamed: 0                      $10,000 to $14,999  $15,000 to $24,999   
Adams County, Pennsylvania                    5.5%               22.5%   
Allegheny County, Pennsylvania                6.5%               14.0%   
Armstrong County, Pennsylvania               12.2%               25.2%   
Beaver County, Pennsylvania                   9.5%               17.7%   

                                                6                   7   \
Unnamed: 0                      $25,000 to $34,999  $35,000 to $49,999   
Adams County, Pennsylvania                   11.1%               16.4%   
Allegheny County, Pennsylvania               12.5%               16.1%   
Armstrong County, Pennsylvania                9.1%               18.3%   
Beaver County, Pennsylvania                  12.3%               18.3%   

                                                8                   9   \
Unnamed: 0                      $50,000 to $74,999  $75,000 to $99,999   
Adams County, Pennsylvania                   17.3%               12.5%   
Allegheny County, Pennsylvania               17.6%               10.0%   
Armstrong County, Pennsylvania               18.3%                6.5%   
Beaver County, Pennsylvania                  18.1%                7.1%   

                                                  10                    11  \
Unnamed: 0                      $100,000 to $149,999  $150,000 to $199,999   
Adams County, Pennsylvania                      7.6%                  0.6%   
Allegheny County, Pennsylvania                  7.4%                  2.9%   
Armstrong County, Pennsylvania                  4.4%                  0.8%   
Beaver County, Pennsylvania                     4.7%                  2.0%   

                                              12                       13  \
Unnamed: 0                      $200,000 or more  Median income (dollars)   
Adams County, Pennsylvania                  0.9%                   38,218   
Allegheny County, Pennsylvania              2.3%                   40,156   
Armstrong County, Pennsylvania              0.8%                   32,290   
Beaver County, Pennsylvania                 0.6%                   35,330   

                                                   14  
Unnamed: 0                      Mean income (dollars)  
Adams County, Pennsylvania                     48,790  
Allegheny County, Pennsylvania                 55,208  
Armstrong County, Pennsylvania                 41,674  
Beaver County, Pennsylvania                    44,751

In [141]:
# Resetting index and renaming to create a 'County' column
initial_pa_nonfamily_2019 = initial_pa_nonfamily_2019.reset_index()
initial_pa_nonfamily_2019.rename(columns={'index': 'County'}, inplace=True)
initial_pa_nonfamily_2019.head()


County        2                  3  \
0                      Unnamed: 0    Total  Less than $10,000   
1      Adams County, Pennsylvania   12,328               5.6%   
2  Allegheny County, Pennsylvania  252,262              10.7%   
3  Armstrong County, Pennsylvania   10,911               4.4%   
4     Beaver County, Pennsylvania   27,638               9.7%   

                    4                   5                   6  \
0  $10,000 to $14,999  $15,000 to $24,999  $25,000 to $34,999   
1                5.5%               22.5%               11.1%   
2                6.5%               14.0%               12.5%   
3               12.2%               25.2%                9.1%   
4                9.5%               17.7%               12.3%   

                    7                   8                   9  \
0  $35,000 to $49,999  $50,000 to $74,999  $75,000 to $99,999   
1               16.4%               17.3%               12.5%   
2               16.1%               17.6%               10.0%   
3               18.3%               18.3%                6.5%   
4               18.3%               18.1%                7.1%   

                     10                    11                12  \
0  $100,000 to $149,999  $150,000 to $199,999  $200,000 or more   
1                  7.6%                  0.6%              0.9%   
2                  7.4%                  2.9%              2.3%   
3                  4.4%                  0.8%              0.8%   
4                  4.7%                  2.0%              0.6%   

                        13                     14  
0  Median income (dollars)  Mean income (dollars)  
1                   38,218                 48,790  
2                   40,156                 55,208  
3                   32,290                 41,674  
4                   35,330                 44,751

In [142]:
# Confirming column data types prior to renaming
print(initial_pa_nonfamily_2019.columns)


Index(['County', 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14], dtype='object')


In [143]:
# Converting column data types from integers to strings for renaming
initial_pa_nonfamily_2019.columns = initial_pa_nonfamily_2019.columns.astype(str)
print(initial_pa_nonfamily_2019.columns)


Index(['County', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12',
       '13', '14'],
      dtype='object')


In [144]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_nonfamily_2019.replace('N', np.nan, inplace=True)


In [145]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_nonfamily_2019 = initial_pa_nonfamily_2019.rename(columns={'2': '# of Nonfamily Households', '3': '% Nonfamily Households <$10,000', '4': '% Nonfamily Households $10,000-$14,999',
                                                                         '5': '% Nonfamily Households $15,000-$24,999', '6': '% Nonfamily Households $25,000-$34,999', '7': '% Nonfamily Households $35,000-$49,999',
                                                                         '8': '% Nonfamily Households $50,000-$74,999', '9': '% Nonfamily Households $75,000-$99,999',
                                                                         '10': '% Nonfamily Households $100,000-$149,999', '11': '% Nonfamily Households $150,000-$199,999',
                                                                        '12': '% Nonfamily Households $200,000 or More', '13': 'Median Nonfamily Households Income ($)',
                                                                       '14': 'Mean Nonfamily Households Income ($)'})
initial_pa_nonfamily_2019 = initial_pa_nonfamily_2019.drop(0)
initial_pa_nonfamily_2019 = initial_pa_nonfamily_2019.reset_index(drop=True)
initial_pa_nonfamily_2019['County'] = initial_pa_nonfamily_2019['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_nonfamily_2019['County'] = initial_pa_nonfamily_2019['County'].apply(lambda x: x.upper())
initial_pa_nonfamily_2019.insert(0, 'Year', 2020)
initial_pa_nonfamily_2019['% Nonfamily Households <$10,000'] = initial_pa_nonfamily_2019['% Nonfamily Households <$10,000'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2019['% Nonfamily Households $10,000-$14,999'] = initial_pa_nonfamily_2019['% Nonfamily Households $10,000-$14,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2019['% Nonfamily Households $15,000-$24,999'] = initial_pa_nonfamily_2019['% Nonfamily Households $15,000-$24,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2019['% Nonfamily Households $25,000-$34,999'] = initial_pa_nonfamily_2019['% Nonfamily Households $25,000-$34,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2019['% Nonfamily Households $35,000-$49,999'] = initial_pa_nonfamily_2019['% Nonfamily Households $35,000-$49,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2019['% Nonfamily Households $50,000-$74,999'] = initial_pa_nonfamily_2019['% Nonfamily Households $50,000-$74,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2019['% Nonfamily Households $75,000-$99,999'] = initial_pa_nonfamily_2019['% Nonfamily Households $75,000-$99,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2019['% Nonfamily Households $100,000-$149,999'] = initial_pa_nonfamily_2019['% Nonfamily Households $100,000-$149,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2019['% Nonfamily Households $150,000-$199,999'] = initial_pa_nonfamily_2019['% Nonfamily Households $150,000-$199,999'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2019['% Nonfamily Households $200,000 or More'] = initial_pa_nonfamily_2019['% Nonfamily Households $200,000 or More'].str.rstrip('%').astype(float) / 100
initial_pa_nonfamily_2019['# of Nonfamily Households'] = initial_pa_nonfamily_2019['# of Nonfamily Households'].str.replace(',', '').astype(float)
initial_pa_nonfamily_2019['Median Nonfamily Households Income ($)'] = initial_pa_nonfamily_2019['Median Nonfamily Households Income ($)'].str.replace(',', '').astype(float)
initial_pa_nonfamily_2019['Mean Nonfamily Households Income ($)'] = initial_pa_nonfamily_2019['Mean Nonfamily Households Income ($)'].str.replace(',', '').astype(float)
initial_pa_nonfamily_2019


Year          County  # of Nonfamily Households  \
0   2020           ADAMS                    12328.0   
1   2020       ALLEGHENY                   252262.0   
2   2020       ARMSTRONG                    10911.0   
3   2020          BEAVER                    27638.0   
4   2020           BERKS                    49294.0   
5   2020           BLAIR                    17860.0   
6   2020           BUCKS                    73467.0   
7   2020          BUTLER                    27849.0   
8   2020         CAMBRIA                    21303.0   
9   2020          CARBON                     9545.0   
10  2020          CENTRE                    25738.0   
11  2020         CHESTER                    56720.0   
12  2020      CLEARFIELD                    11907.0   
13  2020        COLUMBIA                     9588.0   
14  2020        CRAWFORD                    11573.0   
15  2020      CUMBERLAND                    37043.0   
16  2020         DAUPHIN                    46539.0   
17  2020        DELAWARE                    71183.0   
18  2020            ERIE                    44369.0   
19  2020         FAYETTE                    22665.0   
20  2020        FRANKLIN                    20181.0   
21  2020         INDIANA                    11696.0   
22  2020      LACKAWANNA                    32308.0   
23  2020       LANCASTER                    62240.0   
24  2020        LAWRENCE                    13017.0   
25  2020         LEBANON                    17544.0   
26  2020          LEHIGH                    42768.0   
27  2020         LUZERNE                    50554.0   
28  2020        LYCOMING                    16079.0   
29  2020          MERCER                    17131.0   
30  2020          MONROE                    15611.0   
31  2020      MONTGOMERY                   103775.0   
32  2020     NORTHAMPTON                    38104.0   
33  2020  NORTHUMBERLAND                    13653.0   
34  2020    PHILADELPHIA                   280653.0   
35  2020      SCHUYLKILL                    20512.0   
36  2020        SOMERSET                     9814.0   
37  2020      WASHINGTON                    31489.0   
38  2020    WESTMORELAND                    60410.0   
39  2020            YORK                    57175.0   

    % Nonfamily Households <$10,000  % Nonfamily Households $10,000-$14,999  \
0                             0.056                                   0.055   
1                             0.107                                   0.065   
2                             0.044                                   0.122   
3                             0.097                                   0.095   
4                             0.098                                   0.073   
5                             0.135                                   0.089   
6                             0.065                                   0.049   
7                             0.122                                   0.073   
8                             0.149                                   0.148   
9                             0.067                                   0.085   
10                            0.131                                   0.070   
11                            0.075                                   0.053   
12                            0.105                                   0.132   
13                            0.182                                   0.093   
14                            0.112                                   0.118   
15                            0.051                                   0.057   
16                            0.114                                   0.051   
17                            0.103                                   0.052   
18                            0.139                                   0.071   
19                            0.127                                   0.143   
20                            0.044                                   0.068   
21        

**Auxillary (Total)  Data Extraction, Transformation & Loading (2012, 2016 & 2019)**
-
-----------

**2012**
-

In [146]:
# Reading in 2012 U.S. Census Bureau auxillary (Total) dataset
initial_pa_total_aux_2012 = pd.read_excel("Resources/PA_Total_Auxillary_2012.xlsx")
initial_pa_total_aux_2012.head(60)


Unnamed: 0  \
0                                                 NaN   
1                                               Label   
2               Civilian population 18 years and over   
3                                   PERIOD OF SERVICE   
4                 Gulf War (9/2001 or later) veterans   
5                Gulf War (8/1990 to 8/2001) veterans   
6                                Vietnam era veterans   
7                                 Korean War veterans   
8                               World War II veterans   
9                                                 SEX   
10                                               Male   
11                                             Female   
12                                                AGE   
13                                     18 to 34 years   
14                                     35 to 54 years   
15                                     55 to 64 years   
16                                     65 to 74 years   
17                                  75 years and over   
18                 RACE AND HISPANIC OR LATINO ORIGIN   
19                                           One race   
20                                              White   
21                          Black or African American   
22                  American Indian and Alaska Native   
23                                              Asian   
24         Native Hawaiian and Other Pacific Islander   
25                                    Some other race   
26                                  Two or more races   
27                   Hispanic or Latino (of any race)   
28                White alone, not Hispanic or Latino   
29  MEDIAN INCOME IN THE PAST 12 MONTHS (IN 2012 I...   
30  Civilian population 18 years and over with income   
31                                               Male   
32                                             Female   
33                             EDUCATIONAL ATTAINMENT   
34              Civilian population 25 years and over   
35                     Less than high school graduate   
36        High school graduate (includes equivalency)   
37                 Some college or associate's degree   
38                        Bachelor's degree or higher   
39                                  EMPLOYMENT STATUS   
40                 Civilian population 18 to 64 years   
41                     Labor force participation rate   
42                Civilian labor force 18 to 64 years   
43                                  Unemployment rate   
44               POVERTY STATUS IN THE PAST 12 MONTHS   
45  Civilian population 18 years and over for whom...   
46                Below poverty in the past 12 months   
47                                  DISABILITY STATUS   
48  Civilian population 18 years and over for whom...   
49                                With any disability   
50                                    PERCENT IMPUTED   
51  Veteran status for the population 18 years and...   
52  Period of service for the civilian veteran pop...   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
0                       Total                          Total   
1                    Estimate                       Estimate   
2                      79,767                        991,547   
3                         NaN                            NaN   
4                         (X)                            (X)   
5                         (X)                            (X)   
6                         (X)                            (X)   
7                         (X)                            (X)   
8                         (X)                            (X)   
9                         NaN                            NaN   
10                      48.7%                          47.3%   
11                      51.3%                          52.7%   
12                        NaN                            NaN   
13                      25.9%                          29.4%   
14  

In [147]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Three groupings = Total Population, Veteran Population, Nonveteran Population
# % of population groups above that fall into these age categories: 18 to 34, 35 to 54, 55 to 64, 65 to 74 and 75 & Over
# Labor force participation rate
# Unemployment rate
# % of Population group with income below poverty level in the past 12 months
# % of Population group with any disability
initial_pa_total_aux_2012 = initial_pa_total_aux_2012.iloc[[13, 14, 15, 16, 17, 41, 43, 46, 49], :]
initial_pa_total_aux_2012


Unnamed: 0 Adams County, Pennsylvania  \
13                       18 to 34 years                      25.9%   
14                       35 to 54 years                      34.5%   
15                       55 to 64 years                      18.0%   
16                       65 to 74 years                      11.8%   
17                    75 years and over                       9.9%   
41       Labor force participation rate                      80.6%   
43                    Unemployment rate                       5.4%   
46  Below poverty in the past 12 months                       8.0%   
49                  With any disability                      16.3%   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
13                          29.4%                          21.9%   
14                          32.2%                          34.6%   
15                          17.4%                          19.4%   
16                          10.3%                          12.4%   
17                          10.7%                          11.7%   
41                          78.1%                          74.2%   
43                           7.3%                           8.4%   
46                          11.3%                          11.7%   
49                          15.3%                          20.8%   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
13                       23.9%                      28.0%   
14                       33.5%                      35.7%   
15                       18.4%                      16.5%   
16                       12.3%                      10.1%   
17                       11.8%                       9.6%   
41                       78.5%                      79.6%   
43                        8.1%                       9.6%   
46                        9.5%                      12.0%   
49                       17.7%                      16.0%   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
13                      25.7%                      23.9%   
14                      32.9%                      37.7%   
15                      18.1%                      18.3%   
16                      11.8%                      10.8%   
17                      11.4%                       9.2%   
41                      74.5%                      81.7%   
43                       7.5%                       7.8%   
46                      11.5%                       5.1%   
49                      18.9%                      11.9%   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
13                       25.6%                        24.8%  ...   
14                       36.1%                        32.2%  ...   
15                       17.9%                        18.8%  ...   
16                       10.8%                        11.9%  ...   
17                        9.6%                        12.2%  ...   
41                       77.9%                        70.3%  ...   
43                        6.3%                         9.7%  ...   
46                        9.1%                        12.5%  ...   
49                       14.7%                        20.9%  ...   

   Monroe County, Pennsylvania Montgomery County, Pennsylvania  \
13                       27.2%                           26.0%   
14                       37.0%                           36.7%   
15                       18.3%                           17.0%   
16                       10.4%                           10.3%   
17                        7.1%                           10.0%   
41                       76.9%                           81.9%   
43                       13.4%                            6.8%   
46                       12.8%                            6.2%   
49                       15.7%                           11.5%   

   Northampton County, Pennsylvania Northumberland County, Pennsylvania  \
13                

In [148]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_total_aux_2012 = initial_pa_total_aux_2012.T
initial_pa_total_aux_2012.head()


13              14  \
Unnamed: 0                      18 to 34 years  35 to 54 years   
Adams County, Pennsylvania               25.9%           34.5%   
Allegheny County, Pennsylvania           29.4%           32.2%   
Armstrong County, Pennsylvania           21.9%           34.6%   
Beaver County, Pennsylvania              23.9%           33.5%   

                                            15              16  \
Unnamed: 0                      55 to 64 years  65 to 74 years   
Adams County, Pennsylvania               18.0%           11.8%   
Allegheny County, Pennsylvania           17.4%           10.3%   
Armstrong County, Pennsylvania           19.4%           12.4%   
Beaver County, Pennsylvania              18.4%           12.3%   

                                               17  \
Unnamed: 0                      75 years and over   
Adams County, Pennsylvania                   9.9%   
Allegheny County, Pennsylvania              10.7%   
Armstrong County, Pennsylvania              11.7%   
Beaver County, Pennsylvania                 11.8%   

                                                            41  \
Unnamed: 0                      Labor force participation rate   
Adams County, Pennsylvania                               80.6%   
Allegheny County, Pennsylvania                           78.1%   
Armstrong County, Pennsylvania                           74.2%   
Beaver County, Pennsylvania                              78.5%   

                                               43  \
Unnamed: 0                      Unemployment rate   
Adams County, Pennsylvania                   5.4%   
Allegheny County, Pennsylvania               7.3%   
Armstrong County, Pennsylvania               8.4%   
Beaver County, Pennsylvania                  8.1%   

                                                                 46  \
Unnamed: 0                      Below poverty in the past 12 months   
Adams County, Pennsylvania                                     8.0%   
Allegheny County, Pennsylvania                                11.3%   
Armstrong County, Pennsylvania                                11.7%   
Beaver County, Pennsylvania                                    9.5%   

                                                 49  
Unnamed: 0                      With any disability  
Adams County, Pennsylvania                    16.3%  
Allegheny County, Pennsylvania                15.3%  
Armstrong County, Pennsylvania                20.8%  
Beaver County, Pennsylvania                   17.7%

In [149]:
# Resetting index and renaming to create a 'County' column
initial_pa_total_aux_2012 = initial_pa_total_aux_2012.reset_index()
initial_pa_total_aux_2012.rename(columns={'index': 'County'}, inplace=True)
initial_pa_total_aux_2012.head()


County              13              14  \
0                      Unnamed: 0  18 to 34 years  35 to 54 years   
1      Adams County, Pennsylvania           25.9%           34.5%   
2  Allegheny County, Pennsylvania           29.4%           32.2%   
3  Armstrong County, Pennsylvania           21.9%           34.6%   
4     Beaver County, Pennsylvania           23.9%           33.5%   

               15              16                 17  \
0  55 to 64 years  65 to 74 years  75 years and over   
1           18.0%           11.8%               9.9%   
2           17.4%           10.3%              10.7%   
3           19.4%           12.4%              11.7%   
4           18.4%           12.3%              11.8%   

                               41                 43  \
0  Labor force participation rate  Unemployment rate   
1                           80.6%               5.4%   
2                           78.1%               7.3%   
3                           74.2%               8.4%   
4                           78.5%               8.1%   

                                    46                   49  
0  Below poverty in the past 12 months  With any disability  
1                                 8.0%                16.3%  
2                                11.3%                15.3%  
3                                11.7%                20.8%  
4                                 9.5%                17.7%

In [150]:
# Confirming column data types prior to renaming
print(initial_pa_total_aux_2012.columns)


Index(['County', 13, 14, 15, 16, 17, 41, 43, 46, 49], dtype='object')


In [151]:
# Converting column data types from integers to strings for renaming
initial_pa_total_aux_2012.columns = initial_pa_total_aux_2012.columns.astype(str)
print(initial_pa_total_aux_2012.columns)


Index(['County', '13', '14', '15', '16', '17', '41', '43', '46', '49'], dtype='object')


In [152]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_total_aux_2012.replace('N', np.nan, inplace=True)


In [153]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_total_aux_2012 = initial_pa_total_aux_2012.rename(columns={'13': '% Total Population 18-34 Years Old', '14': '% Total Population 35-54 Years Old', '15': '% Total Population 55-64 Years Old',
                                                                         '16': '% Total Population 65-74 Years Old', '17': '% Total Population 75 Years Old & Over', '41': 'Total Labor Force Participation Rate (%)',
                                                                         '43': 'Total Unemployment Rate (%)', '46': '% Total Population With Income Below Poverty Level (Past 12 Months)',
                                                                         '49': '% Total Population With Any Disability'})
initial_pa_total_aux_2012 = initial_pa_total_aux_2012.drop(0)
initial_pa_total_aux_2012 = initial_pa_total_aux_2012.reset_index(drop=True)
initial_pa_total_aux_2012['County'] = initial_pa_total_aux_2012['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_total_aux_2012['County'] = initial_pa_total_aux_2012['County'].apply(lambda x: x.upper())
initial_pa_total_aux_2012.insert(0, 'Year', 2012)
initial_pa_total_aux_2012['% Total Population 18-34 Years Old'] = initial_pa_total_aux_2012['% Total Population 18-34 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2012['% Total Population 35-54 Years Old'] = initial_pa_total_aux_2012['% Total Population 35-54 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2012['% Total Population 55-64 Years Old'] = initial_pa_total_aux_2012['% Total Population 55-64 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2012['% Total Population 65-74 Years Old'] = initial_pa_total_aux_2012['% Total Population 65-74 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2012['% Total Population 75 Years Old & Over'] = initial_pa_total_aux_2012['% Total Population 75 Years Old & Over'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2012['Total Labor Force Participation Rate (%)'] = initial_pa_total_aux_2012['Total Labor Force Participation Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2012['Total Unemployment Rate (%)'] = initial_pa_total_aux_2012['Total Unemployment Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2012['% Total Population With Income Below Poverty Level (Past 12 Months)'] = initial_pa_total_aux_2012['% Total Population With Income Below Poverty Level (Past 12 Months)'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2012['% Total Population With Any Disability'] = initial_pa_total_aux_2012['% Total Population With Any Disability'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2012


Year          County  % Total Population 18-34 Years Old  \
0   2012           ADAMS                               0.259   
1   2012       ALLEGHENY                               0.294   
2   2012       ARMSTRONG                               0.219   
3   2012          BEAVER                               0.239   
4   2012           BERKS                               0.280   
5   2012           BLAIR                               0.257   
6   2012           BUCKS                               0.239   
7   2012          BUTLER                               0.256   
8   2012         CAMBRIA                               0.248   
9   2012          CARBON                               0.213   
10  2012          CENTRE                               0.485   
11  2012         CHESTER                               0.264   
12  2012      CLEARFIELD                               0.245   
13  2012        COLUMBIA                               0.319   
14  2012        CRAWFORD                               0.262   
15  2012      CUMBERLAND                               0.288   
16  2012         DAUPHIN                               0.285   
17  2012        DELAWARE                               0.296   
18  2012            ERIE                               0.304   
19  2012         FAYETTE                               0.239   
20  2012        FRANKLIN                               0.261   
21  2012         INDIANA                               0.339   
22  2012      LACKAWANNA                               0.276   
23  2012       LANCASTER                               0.290   
24  2012        LAWRENCE                               0.235   
25  2012         LEBANON                               0.261   
26  2012          LEHIGH                               0.279   
27  2012         LUZERNE                               0.260   
28  2012        LYCOMING                               0.286   
29  2012          MERCER                               0.247   
30  2012          MONROE                               0.272   
31  2012      MONTGOMERY                               0.260   
32  2012     NORTHAMPTON                               0.269   
33  2012  NORTHUMBERLAND                               0.246   
34  2012    PHILADELPHIA                               0.382   
35  2012      SCHUYLKILL                               0.235   
36  2012        SOMERSET                               0.230   
37  2012      WASHINGTON                               0.236   
38  2012    WESTMORELAND                               0.222   
39  2012            YORK                               0.261   

    % Total Population 35-54 Years Old  % Total Population 55-64 Years Old  \
0                                0.345                               0.180   
1                                0.322                               0.174   
2                                0.346                               0.194   
3                                0.335                               0.184   
4                                0.357                               0.165   
5                                0.329                               0.181   
6                                0.377                               0.183   
7                                0.361                               0.179   
8                                0.322                               0.188   
9                                0.364                               0.187   
10                               0.251                               0.122   
11                               0.383                               0.173   
12                               0.353                               0.175   
13                               0.308                               0.166   
14                               0.330                               0.185   
15                               0.338                               0.168   
16                               0.349               

**2016**
-

In [154]:
# Reading in 2016 U.S. Census Bureau auxillary (Total) dataset
initial_pa_total_aux_2016 = pd.read_excel("Resources/PA_Total_Auxillary_2016.xlsx")
initial_pa_total_aux_2016.head(60)


Unnamed: 0  \
0                                                 NaN   
1                                               Label   
2               Civilian population 18 years and over   
3                                   PERIOD OF SERVICE   
4                 Gulf War (9/2001 or later) veterans   
5                Gulf War (8/1990 to 8/2001) veterans   
6                                Vietnam era veterans   
7                                 Korean War veterans   
8                               World War II veterans   
9                                                 SEX   
10                                               Male   
11                                             Female   
12                                                AGE   
13                                     18 to 34 years   
14                                     35 to 54 years   
15                                     55 to 64 years   
16                                     65 to 74 years   
17                                  75 years and over   
18                 RACE AND HISPANIC OR LATINO ORIGIN   
19                                        White alone   
20                    Black or African American alone   
21            American Indian and Alaska Native alone   
22                                        Asian alone   
23   Native Hawaiian and Other Pacific Islander alone   
24                              Some other race alone   
25                                  Two or more races   
26                   Hispanic or Latino (of any race)   
27                White alone, not Hispanic or Latino   
28  MEDIAN INCOME IN THE PAST 12 MONTHS (IN 2016 I...   
29  Civilian population 18 years and over with income   
30                                               Male   
31                                             Female   
32                             EDUCATIONAL ATTAINMENT   
33              Civilian population 25 years and over   
34                     Less than high school graduate   
35        High school graduate (includes equivalency)   
36                 Some college or associate's degree   
37                        Bachelor's degree or higher   
38                                  EMPLOYMENT STATUS   
39                 Civilian population 18 to 64 years   
40                     Labor force participation rate   
41                Civilian labor force 18 to 64 years   
42                                  Unemployment rate   
43               POVERTY STATUS IN THE PAST 12 MONTHS   
44  Civilian population 18 years and over for whom...   
45   Income in the past 12 months below poverty level   
46  Income in the past 12 months at or above pover...   
47                                  DISABILITY STATUS   
48  Civilian population 18 years and over for whom...   
49                                With any disability   
50                               Without a disability   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
0                     Percent                        Percent   
1                    Estimate                       Estimate   
2                         (X)                            (X)   
3                         NaN                            NaN   
4                         (X)                            (X)   
5                         (X)                            (X)   
6                         (X)                            (X)   
7                         (X)                            (X)   
8                         (X)                            (X)   
9                         NaN                            NaN   
10                      49.0%                          47.7%   
11                      51.0%                          52.3%   
12                        NaN                            NaN   
13                      25.2%                          29.9%   
14                      31.7%                          29.8%   
15                      18.4%                         

In [155]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Three groupings = Total Population, Veteran Population, Nonveteran Population
# % of population groups above that fall into these age categories: 18 to 34, 35 to 54, 55 to 64, 65 to 74 and 75 & Over
# Labor force participation rate
# Unemployment rate
# % of Population group with income below poverty level in the past 12 months
# % of Population group with any disability
initial_pa_total_aux_2016 = initial_pa_total_aux_2016.iloc[[13, 14, 15, 16, 17, 40, 42, 45, 49], :]
initial_pa_total_aux_2016


Unnamed: 0  \
13                                    18 to 34 years   
14                                    35 to 54 years   
15                                    55 to 64 years   
16                                    65 to 74 years   
17                                 75 years and over   
40                    Labor force participation rate   
42                                 Unemployment rate   
45  Income in the past 12 months below poverty level   
49                               With any disability   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
13                      25.2%                          29.9%   
14                      31.7%                          29.8%   
15                      18.4%                          18.1%   
16                      14.3%                          12.0%   
17                      10.6%                          10.2%   
40                      78.5%                          80.0%   
42                       5.6%                           5.3%   
45                       7.7%                          10.9%   
49                      17.7%                          16.2%   

   Armstrong County, Pennsylvania Beaver County, Pennsylvania  \
13                          21.8%                       24.2%   
14                          31.8%                       30.7%   
15                          20.0%                       19.7%   
16                          14.8%                       13.7%   
17                          11.6%                       11.7%   
40                          71.1%                       77.9%   
42                           5.7%                        4.3%   
45                          12.6%                        7.1%   
49                          22.9%                       17.4%   

   Berks County, Pennsylvania Blair County, Pennsylvania  \
13                      28.5%                      24.8%   
14                      32.8%                      30.9%   
15                      17.4%                      18.7%   
16                      11.9%                      13.9%   
17                       9.4%                      11.6%   
40                      78.6%                      73.8%   
42                       5.8%                       4.6%   
45                      11.3%                      11.0%   
49                      16.2%                      21.0%   

   Bucks County, Pennsylvania Butler County, Pennsylvania  \
13                      24.0%                       24.8%   
14                      34.0%                       33.4%   
15                      19.7%                       19.2%   
16                      12.7%                       12.7%   
17                       9.6%                        9.9%   
40                      80.3%                       77.4%   
42                       3.8%                        3.6%   
45                       6.2%                        6.3%   
49                      13.8%                       14.9%   

   Cambria County, Pennsylvania  ... Monroe County, Pennsylvania  \
13                        24.5%  ...                       27.8%   
14                        29.5%  ...                       32.5%   
15                        19.3%  ...                       19.4%   
16                        14.6%  ...                       13.1%   
17                        12.1%  ...                        7.1%   
40                        70.7%  ...                       72.7%   
42                         7.7%  ...                        7.3%   
45                        13.6%  ...                        9.8%   
49                        20.6%  ...                       18.2%   

   Montgomery County, Pennsylvania Northampton County, Pennsylvania  \
13                           26.1%                            27.3%   
14                           34.0%                            32.0%   
15                           17.9%                            18.1%   
16          

In [156]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_total_aux_2016 = initial_pa_total_aux_2016.T
initial_pa_total_aux_2016.head()


13              14  \
Unnamed: 0                      18 to 34 years  35 to 54 years   
Adams County, Pennsylvania               25.2%           31.7%   
Allegheny County, Pennsylvania           29.9%           29.8%   
Armstrong County, Pennsylvania           21.8%           31.8%   
Beaver County, Pennsylvania              24.2%           30.7%   

                                            15              16  \
Unnamed: 0                      55 to 64 years  65 to 74 years   
Adams County, Pennsylvania               18.4%           14.3%   
Allegheny County, Pennsylvania           18.1%           12.0%   
Armstrong County, Pennsylvania           20.0%           14.8%   
Beaver County, Pennsylvania              19.7%           13.7%   

                                               17  \
Unnamed: 0                      75 years and over   
Adams County, Pennsylvania                  10.6%   
Allegheny County, Pennsylvania              10.2%   
Armstrong County, Pennsylvania              11.6%   
Beaver County, Pennsylvania                 11.7%   

                                                            40  \
Unnamed: 0                      Labor force participation rate   
Adams County, Pennsylvania                               78.5%   
Allegheny County, Pennsylvania                           80.0%   
Armstrong County, Pennsylvania                           71.1%   
Beaver County, Pennsylvania                              77.9%   

                                               42  \
Unnamed: 0                      Unemployment rate   
Adams County, Pennsylvania                   5.6%   
Allegheny County, Pennsylvania               5.3%   
Armstrong County, Pennsylvania               5.7%   
Beaver County, Pennsylvania                  4.3%   

                                                                              45  \
Unnamed: 0                      Income in the past 12 months below poverty level   
Adams County, Pennsylvania                                                  7.7%   
Allegheny County, Pennsylvania                                             10.9%   
Armstrong County, Pennsylvania                                             12.6%   
Beaver County, Pennsylvania                                                 7.1%   

                                                 49  
Unnamed: 0                      With any disability  
Adams County, Pennsylvania                    17.7%  
Allegheny County, Pennsylvania                16.2%  
Armstrong County, Pennsylvania                22.9%  
Beaver County, Pennsylvania                   17.4%

In [157]:
# Resetting index and renaming to create a 'County' column
initial_pa_total_aux_2016 = initial_pa_total_aux_2016.reset_index()
initial_pa_total_aux_2016.rename(columns={'index': 'County'}, inplace=True)
initial_pa_total_aux_2016.head()


County              13              14  \
0                      Unnamed: 0  18 to 34 years  35 to 54 years   
1      Adams County, Pennsylvania           25.2%           31.7%   
2  Allegheny County, Pennsylvania           29.9%           29.8%   
3  Armstrong County, Pennsylvania           21.8%           31.8%   
4     Beaver County, Pennsylvania           24.2%           30.7%   

               15              16                 17  \
0  55 to 64 years  65 to 74 years  75 years and over   
1           18.4%           14.3%              10.6%   
2           18.1%           12.0%              10.2%   
3           20.0%           14.8%              11.6%   
4           19.7%           13.7%              11.7%   

                               40                 42  \
0  Labor force participation rate  Unemployment rate   
1                           78.5%               5.6%   
2                           80.0%               5.3%   
3                           71.1%               5.7%   
4                           77.9%               4.3%   

                                                 45                   49  
0  Income in the past 12 months below poverty level  With any disability  
1                                              7.7%                17.7%  
2                                             10.9%                16.2%  
3                                             12.6%                22.9%  
4                                              7.1%                17.4%

In [158]:
# Confirming column data types prior to renaming
print(initial_pa_total_aux_2016.columns)


Index(['County', 13, 14, 15, 16, 17, 40, 42, 45, 49], dtype='object')


In [159]:
# Converting column data types from integers to strings for renaming
initial_pa_total_aux_2016.columns = initial_pa_total_aux_2016.columns.astype(str)
print(initial_pa_total_aux_2016.columns)


Index(['County', '13', '14', '15', '16', '17', '40', '42', '45', '49'], dtype='object')


In [160]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_total_aux_2016.replace('N', np.nan, inplace=True)


In [161]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_total_aux_2016 = initial_pa_total_aux_2016.rename(columns={'13': '% Total Population 18-34 Years Old', '14': '% Total Population 35-54 Years Old', '15': '% Total Population 55-64 Years Old',
                                                                         '16': '% Total Population 65-74 Years Old', '17': '% Total Population 75 Years Old & Over', '40': 'Total Labor Force Participation Rate (%)',
                                                                         '42': 'Total Unemployment Rate (%)', '45': '% Total Population With Income Below Poverty Level (Past 12 Months)',
                                                                         '49': '% Total Population With Any Disability'})
initial_pa_total_aux_2016 = initial_pa_total_aux_2016.drop(0)
initial_pa_total_aux_2016 = initial_pa_total_aux_2016.reset_index(drop=True)
initial_pa_total_aux_2016['County'] = initial_pa_total_aux_2016['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_total_aux_2016['County'] = initial_pa_total_aux_2016['County'].apply(lambda x: x.upper())
initial_pa_total_aux_2016.insert(0, 'Year', 2016)
initial_pa_total_aux_2016['% Total Population 18-34 Years Old'] = initial_pa_total_aux_2016['% Total Population 18-34 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2016['% Total Population 35-54 Years Old'] = initial_pa_total_aux_2016['% Total Population 35-54 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2016['% Total Population 55-64 Years Old'] = initial_pa_total_aux_2016['% Total Population 55-64 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2016['% Total Population 65-74 Years Old'] = initial_pa_total_aux_2016['% Total Population 65-74 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2016['% Total Population 75 Years Old & Over'] = initial_pa_total_aux_2016['% Total Population 75 Years Old & Over'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2016['Total Labor Force Participation Rate (%)'] = initial_pa_total_aux_2016['Total Labor Force Participation Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2016['Total Unemployment Rate (%)'] = initial_pa_total_aux_2016['Total Unemployment Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2016['% Total Population With Income Below Poverty Level (Past 12 Months)'] = initial_pa_total_aux_2016['% Total Population With Income Below Poverty Level (Past 12 Months)'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2016['% Total Population With Any Disability'] = initial_pa_total_aux_2016['% Total Population With Any Disability'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2016


Year          County  % Total Population 18-34 Years Old  \
0   2016           ADAMS                               0.252   
1   2016       ALLEGHENY                               0.299   
2   2016       ARMSTRONG                               0.218   
3   2016          BEAVER                               0.242   
4   2016           BERKS                               0.285   
5   2016           BLAIR                               0.248   
6   2016           BUCKS                               0.240   
7   2016          BUTLER                               0.248   
8   2016         CAMBRIA                               0.245   
9   2016          CARBON                               0.216   
10  2016          CENTRE                               0.452   
11  2016         CHESTER                               0.266   
12  2016      CLEARFIELD                               0.240   
13  2016        COLUMBIA                               0.322   
14  2016        CRAWFORD                               0.262   
15  2016      CUMBERLAND                               0.285   
16  2016         DAUPHIN                               0.283   
17  2016        DELAWARE                               0.296   
18  2016            ERIE                               0.294   
19  2016         FAYETTE                               0.233   
20  2016        FRANKLIN                               0.244   
21  2016         INDIANA                               0.333   
22  2016      LACKAWANNA                               0.273   
23  2016       LANCASTER                               0.290   
24  2016        LAWRENCE                               0.237   
25  2016         LEBANON                               0.266   
26  2016          LEHIGH                               0.285   
27  2016         LUZERNE                               0.264   
28  2016        LYCOMING                               0.287   
29  2016          MERCER                               0.249   
30  2016          MONROE                               0.278   
31  2016      MONTGOMERY                               0.261   
32  2016     NORTHAMPTON                               0.273   
33  2016  NORTHUMBERLAND                               0.231   
34  2016    PHILADELPHIA                               0.376   
35  2016      SCHUYLKILL                               0.237   
36  2016        SOMERSET                               0.232   
37  2016      WASHINGTON                               0.246   
38  2016    WESTMORELAND                               0.223   
39  2016            YORK                               0.264   

    % Total Population 35-54 Years Old  % Total Population 55-64 Years Old  \
0                                0.317                               0.184   
1                                0.298                               0.181   
2                                0.318                               0.200   
3                                0.307                               0.197   
4                                0.328                               0.174   
5                                0.309                               0.187   
6                                0.340                               0.197   
7                                0.334                               0.192   
8                                0.295                               0.193   
9                                0.335                               0.200   
10                               0.257                               0.137   
11                               0.351                               0.182   
12                               0.335                               0.184   
13                               0.284                               0.173   
14                               0.304                               0.190   
15                               0.323                               0.171   
16                               0.327               

**2019**
-
Please note: 2020 United States Census Bureau was unavailable and as such the closest year prior to the election (2019) was utilized


In [162]:
# Reading in 2019 U.S. Census Bureau auxillary (Total) dataset
initial_pa_total_aux_2019 = pd.read_excel("Resources/PA_Total_Auxillary_2019.xlsx")
initial_pa_total_aux_2019.head(60)


Unnamed: 0  \
0                                                 NaN   
1                                               Label   
2               Civilian population 18 years and over   
3                                   PERIOD OF SERVICE   
4                 Gulf War (9/2001 or later) veterans   
5                Gulf War (8/1990 to 8/2001) veterans   
6                                Vietnam era veterans   
7                                 Korean War veterans   
8                               World War II veterans   
9                                                 SEX   
10                                               Male   
11                                             Female   
12                                                AGE   
13                                     18 to 34 years   
14                                     35 to 54 years   
15                                     55 to 64 years   
16                                     65 to 74 years   
17                                  75 years and over   
18                 RACE AND HISPANIC OR LATINO ORIGIN   
19                                        White alone   
20                    Black or African American alone   
21            American Indian and Alaska Native alone   
22                                        Asian alone   
23   Native Hawaiian and Other Pacific Islander alone   
24                              Some other race alone   
25                                  Two or more races   
26                   Hispanic or Latino (of any race)   
27                White alone, not Hispanic or Latino   
28  MEDIAN INCOME IN THE PAST 12 MONTHS (IN 2019 I...   
29  Civilian population 18 years and over with income   
30                                               Male   
31                                             Female   
32                             EDUCATIONAL ATTAINMENT   
33              Civilian population 25 years and over   
34                     Less than high school graduate   
35        High school graduate (includes equivalency)   
36                 Some college or associate's degree   
37                        Bachelor's degree or higher   
38                                  EMPLOYMENT STATUS   
39                 Civilian population 18 to 64 years   
40                     Labor force participation rate   
41                Civilian labor force 18 to 64 years   
42                                  Unemployment rate   
43               POVERTY STATUS IN THE PAST 12 MONTHS   
44  Civilian population 18 years and over for whom...   
45   Income in the past 12 months below poverty level   
46  Income in the past 12 months at or above pover...   
47                                  DISABILITY STATUS   
48  Civilian population 18 years and over for whom...   
49                                With any disability   
50                               Without a disability   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
0                     Percent                        Percent   
1                    Estimate                       Estimate   
2                         (X)                            (X)   
3                         NaN                            NaN   
4                         (X)                            (X)   
5                         (X)                            (X)   
6                         (X)                            (X)   
7                         (X)                            (X)   
8                         (X)                            (X)   
9                         NaN                            NaN   
10                      48.7%                          47.7%   
11                      51.3%                          52.3%   
12                        NaN                            NaN   
13                      25.6%                          29.6%   
14                      29.6%                          29.1%   
15                      18.6%                         

In [163]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Three groupings = Total Population, Veteran Population, Nonveteran Population
# % of population groups above that fall into these age categories: 18 to 34, 35 to 54, 55 to 64, 65 to 74 and 75 & Over
# Labor force participation rate
# Unemployment rate
# % of Population group with income below poverty level in the past 12 months
# % of Population group with any disability
initial_pa_total_aux_2019 = initial_pa_total_aux_2019.iloc[[13, 14, 15, 16, 17, 40, 42, 45, 49], :]
initial_pa_total_aux_2019


Unnamed: 0  \
13                                    18 to 34 years   
14                                    35 to 54 years   
15                                    55 to 64 years   
16                                    65 to 74 years   
17                                 75 years and over   
40                    Labor force participation rate   
42                                 Unemployment rate   
45  Income in the past 12 months below poverty level   
49                               With any disability   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
13                      25.6%                          29.6%   
14                      29.6%                          29.1%   
15                      18.6%                          17.4%   
16                      15.3%                          13.4%   
17                      10.9%                          10.4%   
40                      78.9%                          80.5%   
42                       1.8%                           4.1%   
45                       6.7%                          10.1%   
49                      15.8%                          16.0%   

   Armstrong County, Pennsylvania Beaver County, Pennsylvania  \
13                          21.9%                       24.0%   
14                          29.9%                       29.2%   
15                          20.2%                       19.5%   
16                          15.9%                       15.3%   
17                          12.1%                       12.1%   
40                          78.8%                       79.1%   
42                           2.9%                        4.6%   
45                           8.9%                        9.9%   
49                          18.6%                       19.3%   

   Berks County, Pennsylvania Blair County, Pennsylvania  \
13                      28.2%                      25.3%   
14                      31.3%                      29.6%   
15                      17.7%                      18.4%   
16                      13.0%                      14.7%   
17                       9.7%                      12.1%   
40                      80.6%                      78.2%   
42                       4.8%                       3.9%   
45                       8.2%                      13.3%   
49                      16.0%                      18.9%   

   Bucks County, Pennsylvania Butler County, Pennsylvania  \
13                      23.3%                       24.9%   
14                      32.4%                       31.8%   
15                      20.1%                       19.3%   
16                      13.8%                       13.8%   
17                      10.4%                       10.2%   
40                      82.9%                       76.5%   
42                       3.7%                        3.5%   
45                       5.1%                        7.7%   
49                      12.0%                       15.2%   

   Cambria County, Pennsylvania  ... Monroe County, Pennsylvania  \
13                        23.4%  ...                       27.3%   
14                        28.7%  ...                       30.4%   
15                        18.9%  ...                       20.4%   
16                        16.3%  ...                       13.4%   
17                        12.7%  ...                        8.4%   
40                        72.0%  ...                       74.8%   
42                         4.1%  ...                        3.2%   
45                        12.6%  ...                       11.2%   
49                        21.7%  ...                       15.5%   

   Montgomery County, Pennsylvania Northampton County, Pennsylvania  \
13                           26.0%                            27.6%   
14                           32.8%                            30.4%   
15                           18.0%                            17.7%   
16          

In [164]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_total_aux_2019 = initial_pa_total_aux_2019.T
initial_pa_total_aux_2019.head()


13              14  \
Unnamed: 0                      18 to 34 years  35 to 54 years   
Adams County, Pennsylvania               25.6%           29.6%   
Allegheny County, Pennsylvania           29.6%           29.1%   
Armstrong County, Pennsylvania           21.9%           29.9%   
Beaver County, Pennsylvania              24.0%           29.2%   

                                            15              16  \
Unnamed: 0                      55 to 64 years  65 to 74 years   
Adams County, Pennsylvania               18.6%           15.3%   
Allegheny County, Pennsylvania           17.4%           13.4%   
Armstrong County, Pennsylvania           20.2%           15.9%   
Beaver County, Pennsylvania              19.5%           15.3%   

                                               17  \
Unnamed: 0                      75 years and over   
Adams County, Pennsylvania                  10.9%   
Allegheny County, Pennsylvania              10.4%   
Armstrong County, Pennsylvania              12.1%   
Beaver County, Pennsylvania                 12.1%   

                                                            40  \
Unnamed: 0                      Labor force participation rate   
Adams County, Pennsylvania                               78.9%   
Allegheny County, Pennsylvania                           80.5%   
Armstrong County, Pennsylvania                           78.8%   
Beaver County, Pennsylvania                              79.1%   

                                               42  \
Unnamed: 0                      Unemployment rate   
Adams County, Pennsylvania                   1.8%   
Allegheny County, Pennsylvania               4.1%   
Armstrong County, Pennsylvania               2.9%   
Beaver County, Pennsylvania                  4.6%   

                                                                              45  \
Unnamed: 0                      Income in the past 12 months below poverty level   
Adams County, Pennsylvania                                                  6.7%   
Allegheny County, Pennsylvania                                             10.1%   
Armstrong County, Pennsylvania                                              8.9%   
Beaver County, Pennsylvania                                                 9.9%   

                                                 49  
Unnamed: 0                      With any disability  
Adams County, Pennsylvania                    15.8%  
Allegheny County, Pennsylvania                16.0%  
Armstrong County, Pennsylvania                18.6%  
Beaver County, Pennsylvania                   19.3%

In [165]:
# Resetting index and renaming to create a 'County' column
initial_pa_total_aux_2019 = initial_pa_total_aux_2019.reset_index()
initial_pa_total_aux_2019.rename(columns={'index': 'County'}, inplace=True)
initial_pa_total_aux_2019.head()


County              13              14  \
0                      Unnamed: 0  18 to 34 years  35 to 54 years   
1      Adams County, Pennsylvania           25.6%           29.6%   
2  Allegheny County, Pennsylvania           29.6%           29.1%   
3  Armstrong County, Pennsylvania           21.9%           29.9%   
4     Beaver County, Pennsylvania           24.0%           29.2%   

               15              16                 17  \
0  55 to 64 years  65 to 74 years  75 years and over   
1           18.6%           15.3%              10.9%   
2           17.4%           13.4%              10.4%   
3           20.2%           15.9%              12.1%   
4           19.5%           15.3%              12.1%   

                               40                 42  \
0  Labor force participation rate  Unemployment rate   
1                           78.9%               1.8%   
2                           80.5%               4.1%   
3                           78.8%               2.9%   
4                           79.1%               4.6%   

                                                 45                   49  
0  Income in the past 12 months below poverty level  With any disability  
1                                              6.7%                15.8%  
2                                             10.1%                16.0%  
3                                              8.9%                18.6%  
4                                              9.9%                19.3%

In [166]:
# Confirming column data types prior to renaming
print(initial_pa_total_aux_2019.columns)


Index(['County', 13, 14, 15, 16, 17, 40, 42, 45, 49], dtype='object')


In [167]:
# Converting column data types from integers to strings for renaming
initial_pa_total_aux_2019.columns = initial_pa_total_aux_2019.columns.astype(str)
print(initial_pa_total_aux_2019.columns)


Index(['County', '13', '14', '15', '16', '17', '40', '42', '45', '49'], dtype='object')


In [168]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_total_aux_2019.replace('N', np.nan, inplace=True)


In [169]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_total_aux_2019 = initial_pa_total_aux_2019.rename(columns={'13': '% Total Population 18-34 Years Old', '14': '% Total Population 35-54 Years Old', '15': '% Total Population 55-64 Years Old',
                                                                         '16': '% Total Population 65-74 Years Old', '17': '% Total Population 75 Years Old & Over', '40': 'Total Labor Force Participation Rate (%)',
                                                                         '42': 'Total Unemployment Rate (%)', '45': '% Total Population With Income Below Poverty Level (Past 12 Months)',
                                                                         '49': '% Total Population With Any Disability'})
initial_pa_total_aux_2019 = initial_pa_total_aux_2019.drop(0)
initial_pa_total_aux_2019 = initial_pa_total_aux_2019.reset_index(drop=True)
initial_pa_total_aux_2019['County'] = initial_pa_total_aux_2019['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_total_aux_2019['County'] = initial_pa_total_aux_2019['County'].apply(lambda x: x.upper())
initial_pa_total_aux_2019.insert(0, 'Year', 2020)
initial_pa_total_aux_2019['% Total Population 18-34 Years Old'] = initial_pa_total_aux_2019['% Total Population 18-34 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2019['% Total Population 35-54 Years Old'] = initial_pa_total_aux_2019['% Total Population 35-54 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2019['% Total Population 55-64 Years Old'] = initial_pa_total_aux_2019['% Total Population 55-64 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2019['% Total Population 65-74 Years Old'] = initial_pa_total_aux_2019['% Total Population 65-74 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2019['% Total Population 75 Years Old & Over'] = initial_pa_total_aux_2019['% Total Population 75 Years Old & Over'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2019['Total Labor Force Participation Rate (%)'] = initial_pa_total_aux_2019['Total Labor Force Participation Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2019['Total Unemployment Rate (%)'] = initial_pa_total_aux_2019['Total Unemployment Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2019['% Total Population With Income Below Poverty Level (Past 12 Months)'] = initial_pa_total_aux_2019['% Total Population With Income Below Poverty Level (Past 12 Months)'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2019['% Total Population With Any Disability'] = initial_pa_total_aux_2019['% Total Population With Any Disability'].str.rstrip('%').astype(float) / 100
initial_pa_total_aux_2019


Year          County  % Total Population 18-34 Years Old  \
0   2020           ADAMS                               0.256   
1   2020       ALLEGHENY                               0.296   
2   2020       ARMSTRONG                               0.219   
3   2020          BEAVER                               0.240   
4   2020           BERKS                               0.282   
5   2020           BLAIR                               0.253   
6   2020           BUCKS                               0.233   
7   2020          BUTLER                               0.249   
8   2020         CAMBRIA                               0.234   
9   2020          CARBON                               0.216   
10  2020          CENTRE                               0.435   
11  2020         CHESTER                               0.266   
12  2020      CLEARFIELD                               0.233   
13  2020        COLUMBIA                               0.307   
14  2020        CRAWFORD                               0.252   
15  2020      CUMBERLAND                               0.281   
16  2020         DAUPHIN                               0.279   
17  2020        DELAWARE                               0.291   
18  2020            ERIE                               0.285   
19  2020         FAYETTE                               0.240   
20  2020        FRANKLIN                               0.241   
21  2020         INDIANA                               0.330   
22  2020      LACKAWANNA                               0.263   
23  2020       LANCASTER                               0.288   
24  2020        LAWRENCE                               0.241   
25  2020         LEBANON                               0.266   
26  2020          LEHIGH                               0.285   
27  2020         LUZERNE                               0.264   
28  2020        LYCOMING                               0.269   
29  2020          MERCER                               0.247   
30  2020          MONROE                               0.273   
31  2020      MONTGOMERY                               0.260   
32  2020     NORTHAMPTON                               0.276   
33  2020  NORTHUMBERLAND                               0.253   
34  2020    PHILADELPHIA                               0.369   
35  2020      SCHUYLKILL                               0.233   
36  2020        SOMERSET                               0.220   
37  2020      WASHINGTON                               0.244   
38  2020    WESTMORELAND                               0.221   
39  2020            YORK                               0.262   

    % Total Population 35-54 Years Old  % Total Population 55-64 Years Old  \
0                                0.296                               0.186   
1                                0.291                               0.174   
2                                0.299                               0.202   
3                                0.292                               0.195   
4                                0.313                               0.177   
5                                0.296                               0.184   
6                                0.324                               0.201   
7                                0.318                               0.193   
8                                0.287                               0.189   
9                                0.325                               0.194   
10                               0.252                               0.139   
11                               0.334                               0.185   
12                               0.323                               0.184   
13                               0.281                               0.169   
14                               0.293                               0.186   
15                               0.313                               0.167   
16                               0.319               

**Auxillary (Veterans)  Data Extraction, Transformation & Loading (2012, 2016 & 2019)**
-
-----------

**2012**
-

In [170]:
# Reading in 2012 U.S. Census Bureau auxillary (Veterans) dataset
initial_pa_veterans_aux_2012 = pd.read_excel("Resources/PA_Veterans_Auxillary_2012.xlsx")
initial_pa_veterans_aux_2012.head(60)


Unnamed: 0  \
0                                                 NaN   
1                                               Label   
2               Civilian population 18 years and over   
3                                   PERIOD OF SERVICE   
4                 Gulf War (9/2001 or later) veterans   
5                Gulf War (8/1990 to 8/2001) veterans   
6                                Vietnam era veterans   
7                                 Korean War veterans   
8                               World War II veterans   
9                                                 SEX   
10                                               Male   
11                                             Female   
12                                                AGE   
13                                     18 to 34 years   
14                                     35 to 54 years   
15                                     55 to 64 years   
16                                     65 to 74 years   
17                                  75 years and over   
18                 RACE AND HISPANIC OR LATINO ORIGIN   
19                                           One race   
20                                              White   
21                          Black or African American   
22                  American Indian and Alaska Native   
23                                              Asian   
24         Native Hawaiian and Other Pacific Islander   
25                                    Some other race   
26                                  Two or more races   
27                   Hispanic or Latino (of any race)   
28                White alone, not Hispanic or Latino   
29  MEDIAN INCOME IN THE PAST 12 MONTHS (IN 2012 I...   
30  Civilian population 18 years and over with income   
31                                               Male   
32                                             Female   
33                             EDUCATIONAL ATTAINMENT   
34              Civilian population 25 years and over   
35                     Less than high school graduate   
36        High school graduate (includes equivalency)   
37                 Some college or associate's degree   
38                        Bachelor's degree or higher   
39                                  EMPLOYMENT STATUS   
40                 Civilian population 18 to 64 years   
41                     Labor force participation rate   
42                Civilian labor force 18 to 64 years   
43                                  Unemployment rate   
44               POVERTY STATUS IN THE PAST 12 MONTHS   
45  Civilian population 18 years and over for whom...   
46                Below poverty in the past 12 months   
47                                  DISABILITY STATUS   
48  Civilian population 18 years and over for whom...   
49                                With any disability   
50                                    PERCENT IMPUTED   
51  Veteran status for the population 18 years and...   
52  Period of service for the civilian veteran pop...   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
0                    Veterans                       Veterans   
1                    Estimate                       Estimate   
2                       8,297                         90,743   
3                         NaN                            NaN   
4                       13.6%                           8.5%   
5                       19.2%                          10.9%   
6                       33.1%                          33.1%   
7                       14.1%                          13.9%   
8                        5.4%                          12.3%   
9                         NaN                            NaN   
10                      93.6%                          94.6%   
11                       6.4%                           5.4%   
12                        NaN                            NaN   
13                       8.4%                           6.2%   
14  

In [171]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Three groupings = Total Population, Veteran Population, Nonveteran Population
# % of population groups above that fall into these age categories: 18 to 34, 35 to 54, 55 to 64, 65 to 74 and 75 & Over
# Labor force participation rate
# Unemployment rate
# % of Population group with income below poverty level in the past 12 months
# % of Population group with any disability
initial_pa_veterans_aux_2012 = initial_pa_veterans_aux_2012.iloc[[13, 14, 15, 16, 17, 41, 43, 46, 49], :]
initial_pa_veterans_aux_2012


Unnamed: 0 Adams County, Pennsylvania  \
13                       18 to 34 years                       8.4%   
14                       35 to 54 years                      23.8%   
15                       55 to 64 years                      18.7%   
16                       65 to 74 years                      23.8%   
17                    75 years and over                      25.3%   
41       Labor force participation rate                      88.1%   
43                    Unemployment rate                       4.1%   
46  Below poverty in the past 12 months                       3.4%   
49                  With any disability                      26.7%   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
13                           6.2%                           5.3%   
14                          18.8%                          14.4%   
15                          20.8%                          27.5%   
16                          22.6%                          24.5%   
17                          31.6%                          28.3%   
41                          74.0%                          63.7%   
43                           5.2%                           7.7%   
46                           6.5%                           7.6%   
49                          27.4%                          32.9%   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
13                        5.3%                       5.5%   
14                       21.8%                      23.9%   
15                       20.2%                      21.7%   
16                       23.2%                      21.3%   
17                       29.4%                      27.6%   
41                       77.9%                      80.5%   
43                        6.3%                      11.3%   
46                        6.2%                       5.3%   
49                       29.4%                      32.3%   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
13                       7.3%                       3.9%   
14                      24.9%                      16.5%   
15                      21.5%                      22.5%   
16                      20.3%                      27.9%   
17                      26.0%                      29.2%   
41                      72.4%                      78.5%   
43                       9.0%                       9.1%   
46                       6.6%                       5.0%   
49                      26.0%                      20.9%   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
13                        4.9%                         6.2%  ...   
14                       18.6%                        21.1%  ...   
15                       24.0%                        23.9%  ...   
16                       23.7%                        22.2%  ...   
17                       28.8%                        26.5%  ...   
41                       70.4%                        64.6%  ...   
43                        8.4%                        12.5%  ...   
46                        6.5%                         8.5%  ...   
49                       29.1%                        31.7%  ...   

   Monroe County, Pennsylvania Montgomery County, Pennsylvania  \
13                        3.4%                            5.4%   
14                       26.3%                           16.6%   
15                       26.5%                           20.3%   
16                       22.5%                           26.2%   
17                       21.3%                           31.6%   
41                       81.8%                           81.4%   
43                        8.9%                            7.7%   
46                        6.4%                            3.0%   
49                       24.7%                           22.0%   

   Northampton County, Pennsylvania Northumberland County, Pennsylvania  \
13                

In [172]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_veterans_aux_2012 = initial_pa_veterans_aux_2012.T
initial_pa_veterans_aux_2012.head()


13              14  \
Unnamed: 0                      18 to 34 years  35 to 54 years   
Adams County, Pennsylvania                8.4%           23.8%   
Allegheny County, Pennsylvania            6.2%           18.8%   
Armstrong County, Pennsylvania            5.3%           14.4%   
Beaver County, Pennsylvania               5.3%           21.8%   

                                            15              16  \
Unnamed: 0                      55 to 64 years  65 to 74 years   
Adams County, Pennsylvania               18.7%           23.8%   
Allegheny County, Pennsylvania           20.8%           22.6%   
Armstrong County, Pennsylvania           27.5%           24.5%   
Beaver County, Pennsylvania              20.2%           23.2%   

                                               17  \
Unnamed: 0                      75 years and over   
Adams County, Pennsylvania                  25.3%   
Allegheny County, Pennsylvania              31.6%   
Armstrong County, Pennsylvania              28.3%   
Beaver County, Pennsylvania                 29.4%   

                                                            41  \
Unnamed: 0                      Labor force participation rate   
Adams County, Pennsylvania                               88.1%   
Allegheny County, Pennsylvania                           74.0%   
Armstrong County, Pennsylvania                           63.7%   
Beaver County, Pennsylvania                              77.9%   

                                               43  \
Unnamed: 0                      Unemployment rate   
Adams County, Pennsylvania                   4.1%   
Allegheny County, Pennsylvania               5.2%   
Armstrong County, Pennsylvania               7.7%   
Beaver County, Pennsylvania                  6.3%   

                                                                 46  \
Unnamed: 0                      Below poverty in the past 12 months   
Adams County, Pennsylvania                                     3.4%   
Allegheny County, Pennsylvania                                 6.5%   
Armstrong County, Pennsylvania                                 7.6%   
Beaver County, Pennsylvania                                    6.2%   

                                                 49  
Unnamed: 0                      With any disability  
Adams County, Pennsylvania                    26.7%  
Allegheny County, Pennsylvania                27.4%  
Armstrong County, Pennsylvania                32.9%  
Beaver County, Pennsylvania                   29.4%

In [173]:
# Resetting index and renaming to create a 'County' column
initial_pa_veterans_aux_2012 = initial_pa_veterans_aux_2012.reset_index()
initial_pa_veterans_aux_2012.rename(columns={'index': 'County'}, inplace=True)
initial_pa_veterans_aux_2012.head()


County              13              14  \
0                      Unnamed: 0  18 to 34 years  35 to 54 years   
1      Adams County, Pennsylvania            8.4%           23.8%   
2  Allegheny County, Pennsylvania            6.2%           18.8%   
3  Armstrong County, Pennsylvania            5.3%           14.4%   
4     Beaver County, Pennsylvania            5.3%           21.8%   

               15              16                 17  \
0  55 to 64 years  65 to 74 years  75 years and over   
1           18.7%           23.8%              25.3%   
2           20.8%           22.6%              31.6%   
3           27.5%           24.5%              28.3%   
4           20.2%           23.2%              29.4%   

                               41                 43  \
0  Labor force participation rate  Unemployment rate   
1                           88.1%               4.1%   
2                           74.0%               5.2%   
3                           63.7%               7.7%   
4                           77.9%               6.3%   

                                    46                   49  
0  Below poverty in the past 12 months  With any disability  
1                                 3.4%                26.7%  
2                                 6.5%                27.4%  
3                                 7.6%                32.9%  
4                                 6.2%                29.4%

In [174]:
# Confirming column data types prior to renaming
print(initial_pa_veterans_aux_2012.columns)


Index(['County', 13, 14, 15, 16, 17, 41, 43, 46, 49], dtype='object')


In [175]:
# Converting column data types from integers to strings for renaming
initial_pa_veterans_aux_2012.columns = initial_pa_veterans_aux_2012.columns.astype(str)
print(initial_pa_veterans_aux_2012.columns)


Index(['County', '13', '14', '15', '16', '17', '41', '43', '46', '49'], dtype='object')


In [176]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_veterans_aux_2012.replace('N', np.nan, inplace=True)


In [177]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_veterans_aux_2012 = initial_pa_veterans_aux_2012.rename(columns={'13': '% Veteran Population 18-34 Years Old', '14': '% Veteran Population 35-54 Years Old', '15': '% Veteran Population 55-64 Years Old',
                                                                         '16': '% Veteran Population 65-74 Years Old', '17': '% Veteran Population 75 Years Old & Over', '41': 'Veteran Labor Force Participation Rate (%)',
                                                                         '43': 'Veteran Unemployment Rate (%)', '46': '% Veteran Population With Income Below Poverty Level (Past 12 Months)',
                                                                         '49': '% Veteran Population With Any Disability'})
initial_pa_veterans_aux_2012 = initial_pa_veterans_aux_2012.drop(0)
initial_pa_veterans_aux_2012 = initial_pa_veterans_aux_2012.reset_index(drop=True)
initial_pa_veterans_aux_2012['County'] = initial_pa_veterans_aux_2012['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_veterans_aux_2012['County'] = initial_pa_veterans_aux_2012['County'].apply(lambda x: x.upper())
initial_pa_veterans_aux_2012.insert(0, 'Year', 2012)
initial_pa_veterans_aux_2012['% Veteran Population 18-34 Years Old'] = initial_pa_veterans_aux_2012['% Veteran Population 18-34 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2012['% Veteran Population 35-54 Years Old'] = initial_pa_veterans_aux_2012['% Veteran Population 35-54 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2012['% Veteran Population 55-64 Years Old'] = initial_pa_veterans_aux_2012['% Veteran Population 55-64 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2012['% Veteran Population 65-74 Years Old'] = initial_pa_veterans_aux_2012['% Veteran Population 65-74 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2012['% Veteran Population 75 Years Old & Over'] = initial_pa_veterans_aux_2012['% Veteran Population 75 Years Old & Over'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2012['Veteran Labor Force Participation Rate (%)'] = initial_pa_veterans_aux_2012['Veteran Labor Force Participation Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2012['Veteran Unemployment Rate (%)'] = initial_pa_veterans_aux_2012['Veteran Unemployment Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2012['% Veteran Population With Income Below Poverty Level (Past 12 Months)'] = initial_pa_veterans_aux_2012['% Veteran Population With Income Below Poverty Level (Past 12 Months)'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2012['% Veteran Population With Any Disability'] = initial_pa_veterans_aux_2012['% Veteran Population With Any Disability'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2012


Year          County  % Veteran Population 18-34 Years Old  \
0   2012           ADAMS                                 0.084   
1   2012       ALLEGHENY                                 0.062   
2   2012       ARMSTRONG                                 0.053   
3   2012          BEAVER                                 0.053   
4   2012           BERKS                                 0.055   
5   2012           BLAIR                                 0.073   
6   2012           BUCKS                                 0.039   
7   2012          BUTLER                                 0.049   
8   2012         CAMBRIA                                 0.062   
9   2012          CARBON                                 0.059   
10  2012          CENTRE                                 0.099   
11  2012         CHESTER                                 0.042   
12  2012      CLEARFIELD                                 0.111   
13  2012        COLUMBIA                                 0.088   
14  2012        CRAWFORD                                 0.069   
15  2012      CUMBERLAND                                 0.060   
16  2012         DAUPHIN                                 0.097   
17  2012        DELAWARE                                 0.066   
18  2012            ERIE                                 0.064   
19  2012         FAYETTE                                 0.053   
20  2012        FRANKLIN                                 0.053   
21  2012         INDIANA                                 0.063   
22  2012      LACKAWANNA                                 0.046   
23  2012       LANCASTER                                 0.047   
24  2012        LAWRENCE                                 0.039   
25  2012         LEBANON                                 0.098   
26  2012          LEHIGH                                 0.073   
27  2012         LUZERNE                                 0.051   
28  2012        LYCOMING                                 0.075   
29  2012          MERCER                                 0.043   
30  2012          MONROE                                 0.034   
31  2012      MONTGOMERY                                 0.054   
32  2012     NORTHAMPTON                                 0.039   
33  2012  NORTHUMBERLAND                                 0.077   
34  2012    PHILADELPHIA                                 0.076   
35  2012      SCHUYLKILL                                 0.103   
36  2012        SOMERSET                                 0.053   
37  2012      WASHINGTON                                 0.036   
38  2012    WESTMORELAND                                 0.053   
39  2012            YORK                                 0.078   

    % Veteran Population 35-54 Years Old  \
0                                  0.238   
1                                  0.188   
2                                  0.144   
3                                  0.218   
4                                  0.239   
5                                  0.249   
6                                  0.165   
7                                  0.186   
8                                  0.211   
9                                  0.277   
10                                 0.250   
11                                 0.194   
12                                 0.226   
13                                 0.230   
14                                 0.190   
15                                 0.261   
16                                 0.264   
17                                 0.185   
18                                 0.227   
19                                 0.228   
20                                 0.230   
21                                 0.229   
22                                 0.194   
23                                 0.222   
24                                 0.259   
25                                 0.246   
26                                 0.199   
27                                 0.219   
28                   

**2016**
-

In [178]:
# Reading in 2016 U.S. Census Bureau auxillary (Veterans) dataset
initial_pa_veterans_aux_2016 = pd.read_excel("Resources/PA_Veterans_Auxillary_2016.xlsx")
initial_pa_veterans_aux_2016.head(60)


Unnamed: 0  \
0                                                 NaN   
1                                               Label   
2               Civilian population 18 years and over   
3                                   PERIOD OF SERVICE   
4                 Gulf War (9/2001 or later) veterans   
5                Gulf War (8/1990 to 8/2001) veterans   
6                                Vietnam era veterans   
7                                 Korean War veterans   
8                               World War II veterans   
9                                                 SEX   
10                                               Male   
11                                             Female   
12                                                AGE   
13                                     18 to 34 years   
14                                     35 to 54 years   
15                                     55 to 64 years   
16                                     65 to 74 years   
17                                  75 years and over   
18                 RACE AND HISPANIC OR LATINO ORIGIN   
19                                        White alone   
20                    Black or African American alone   
21            American Indian and Alaska Native alone   
22                                        Asian alone   
23   Native Hawaiian and Other Pacific Islander alone   
24                              Some other race alone   
25                                  Two or more races   
26                   Hispanic or Latino (of any race)   
27                White alone, not Hispanic or Latino   
28  MEDIAN INCOME IN THE PAST 12 MONTHS (IN 2016 I...   
29  Civilian population 18 years and over with income   
30                                               Male   
31                                             Female   
32                             EDUCATIONAL ATTAINMENT   
33              Civilian population 25 years and over   
34                     Less than high school graduate   
35        High school graduate (includes equivalency)   
36                 Some college or associate's degree   
37                        Bachelor's degree or higher   
38                                  EMPLOYMENT STATUS   
39                 Civilian population 18 to 64 years   
40                     Labor force participation rate   
41                Civilian labor force 18 to 64 years   
42                                  Unemployment rate   
43               POVERTY STATUS IN THE PAST 12 MONTHS   
44  Civilian population 18 years and over for whom...   
45   Income in the past 12 months below poverty level   
46  Income in the past 12 months at or above pover...   
47                                  DISABILITY STATUS   
48  Civilian population 18 years and over for whom...   
49                                With any disability   
50                               Without a disability   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
0                     Percent                        Percent   
1                    Estimate                       Estimate   
2                       10.7%                           7.8%   
3                         NaN                            NaN   
4                       12.9%                          13.7%   
5                       19.5%                          14.2%   
6                       39.2%                          34.1%   
7                        5.8%                          12.0%   
8                        3.9%                           6.8%   
9                         NaN                            NaN   
10                      90.0%                          93.6%   
11                      10.0%                           6.4%   
12                        NaN                            NaN   
13                       6.3%                           8.9%   
14                      21.5%                          18.5%   
15                      25.4%                         

In [179]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Three groupings = Total Population, Veteran Population, Nonveteran Population
# % of population groups above that fall into these age categories: 18 to 34, 35 to 54, 55 to 64, 65 to 74 and 75 & Over
# Labor force participation rate
# Unemployment rate
# % of Population group with income below poverty level in the past 12 months
# % of Population group with any disability
initial_pa_veterans_aux_2016 = initial_pa_veterans_aux_2016.iloc[[13, 14, 15, 16, 17, 40, 42, 45, 49], :]
initial_pa_veterans_aux_2016


Unnamed: 0  \
13                                    18 to 34 years   
14                                    35 to 54 years   
15                                    55 to 64 years   
16                                    65 to 74 years   
17                                 75 years and over   
40                    Labor force participation rate   
42                                 Unemployment rate   
45  Income in the past 12 months below poverty level   
49                               With any disability   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
13                       6.3%                           8.9%   
14                      21.5%                          18.5%   
15                      25.4%                          14.1%   
16                      28.2%                          28.3%   
17                      18.6%                          30.3%   
40                      71.0%                          78.5%   
42                      11.3%                           8.8%   
45                       3.9%                           7.0%   
49                      30.2%                          29.6%   

   Armstrong County, Pennsylvania Beaver County, Pennsylvania  \
13                           4.8%                        6.5%   
14                          22.4%                       16.8%   
15                          16.0%                       14.4%   
16                          30.7%                       28.7%   
17                          26.2%                       33.5%   
40                          67.3%                       80.8%   
42                           3.5%                        2.8%   
45                          14.4%                        5.2%   
49                          33.4%                       29.9%   

   Berks County, Pennsylvania Blair County, Pennsylvania  \
13                       6.2%                       5.8%   
14                      16.5%                      18.5%   
15                      13.6%                      19.9%   
16                      34.8%                      29.5%   
17                      29.0%                      26.3%   
40                      83.5%                      63.7%   
42                       0.6%                       3.9%   
45                       5.0%                       5.3%   
49                      27.7%                      33.3%   

   Bucks County, Pennsylvania Butler County, Pennsylvania  \
13                       7.0%                        4.9%   
14                      19.2%                       25.2%   
15                      13.0%                       15.8%   
16                      30.4%                       26.4%   
17                      30.5%                       27.7%   
40                      81.9%                       87.5%   
42                       7.8%                        4.0%   
45                       4.9%                        3.7%   
49                      24.3%                       26.2%   

   Cambria County, Pennsylvania  ... Monroe County, Pennsylvania  \
13                         8.0%  ...                        7.8%   
14                        20.0%  ...                       17.1%   
15                        19.0%  ...                       21.2%   
16                        26.7%  ...                       32.3%   
17                        26.3%  ...                       21.7%   
40                        61.1%  ...                       66.7%   
42                         7.3%  ...                        0.0%   
45                         6.5%  ...                        6.2%   
49                        31.3%  ...                       35.9%   

   Montgomery County, Pennsylvania Northampton County, Pennsylvania  \
13                            7.4%                             7.8%   
14                           20.1%                            18.3%   
15                           13.7%                            13.6%   
16          

In [180]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_veterans_aux_2016 = initial_pa_veterans_aux_2016.T
initial_pa_veterans_aux_2016.head()


13              14  \
Unnamed: 0                      18 to 34 years  35 to 54 years   
Adams County, Pennsylvania                6.3%           21.5%   
Allegheny County, Pennsylvania            8.9%           18.5%   
Armstrong County, Pennsylvania            4.8%           22.4%   
Beaver County, Pennsylvania               6.5%           16.8%   

                                            15              16  \
Unnamed: 0                      55 to 64 years  65 to 74 years   
Adams County, Pennsylvania               25.4%           28.2%   
Allegheny County, Pennsylvania           14.1%           28.3%   
Armstrong County, Pennsylvania           16.0%           30.7%   
Beaver County, Pennsylvania              14.4%           28.7%   

                                               17  \
Unnamed: 0                      75 years and over   
Adams County, Pennsylvania                  18.6%   
Allegheny County, Pennsylvania              30.3%   
Armstrong County, Pennsylvania              26.2%   
Beaver County, Pennsylvania                 33.5%   

                                                            40  \
Unnamed: 0                      Labor force participation rate   
Adams County, Pennsylvania                               71.0%   
Allegheny County, Pennsylvania                           78.5%   
Armstrong County, Pennsylvania                           67.3%   
Beaver County, Pennsylvania                              80.8%   

                                               42  \
Unnamed: 0                      Unemployment rate   
Adams County, Pennsylvania                  11.3%   
Allegheny County, Pennsylvania               8.8%   
Armstrong County, Pennsylvania               3.5%   
Beaver County, Pennsylvania                  2.8%   

                                                                              45  \
Unnamed: 0                      Income in the past 12 months below poverty level   
Adams County, Pennsylvania                                                  3.9%   
Allegheny County, Pennsylvania                                              7.0%   
Armstrong County, Pennsylvania                                             14.4%   
Beaver County, Pennsylvania                                                 5.2%   

                                                 49  
Unnamed: 0                      With any disability  
Adams County, Pennsylvania                    30.2%  
Allegheny County, Pennsylvania                29.6%  
Armstrong County, Pennsylvania                33.4%  
Beaver County, Pennsylvania                   29.9%

In [181]:
# Resetting index and renaming to create a 'County' column
initial_pa_veterans_aux_2016 = initial_pa_veterans_aux_2016.reset_index()
initial_pa_veterans_aux_2016.rename(columns={'index': 'County'}, inplace=True)
initial_pa_veterans_aux_2016.head()


County              13              14  \
0                      Unnamed: 0  18 to 34 years  35 to 54 years   
1      Adams County, Pennsylvania            6.3%           21.5%   
2  Allegheny County, Pennsylvania            8.9%           18.5%   
3  Armstrong County, Pennsylvania            4.8%           22.4%   
4     Beaver County, Pennsylvania            6.5%           16.8%   

               15              16                 17  \
0  55 to 64 years  65 to 74 years  75 years and over   
1           25.4%           28.2%              18.6%   
2           14.1%           28.3%              30.3%   
3           16.0%           30.7%              26.2%   
4           14.4%           28.7%              33.5%   

                               40                 42  \
0  Labor force participation rate  Unemployment rate   
1                           71.0%              11.3%   
2                           78.5%               8.8%   
3                           67.3%               3.5%   
4                           80.8%               2.8%   

                                                 45                   49  
0  Income in the past 12 months below poverty level  With any disability  
1                                              3.9%                30.2%  
2                                              7.0%                29.6%  
3                                             14.4%                33.4%  
4                                              5.2%                29.9%

In [182]:
# Confirming column data types prior to renaming
print(initial_pa_veterans_aux_2016.columns)


Index(['County', 13, 14, 15, 16, 17, 40, 42, 45, 49], dtype='object')


In [183]:
# Converting column data types from integers to strings for renaming
initial_pa_veterans_aux_2016.columns = initial_pa_veterans_aux_2016.columns.astype(str)
print(initial_pa_veterans_aux_2016.columns)


Index(['County', '13', '14', '15', '16', '17', '40', '42', '45', '49'], dtype='object')


In [184]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_veterans_aux_2016.replace('N', np.nan, inplace=True)


In [185]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_veterans_aux_2016 = initial_pa_veterans_aux_2016.rename(columns={'13': '% Veteran Population 18-34 Years Old', '14': '% Veteran Population 35-54 Years Old', '15': '% Veteran Population 55-64 Years Old',
                                                                         '16': '% Veteran Population 65-74 Years Old', '17': '% Veteran Population 75 Years Old & Over', '40': 'Veteran Labor Force Participation Rate (%)',
                                                                         '42': 'Veteran Unemployment Rate (%)', '45': '% Veteran Population With Income Below Poverty Level (Past 12 Months)',
                                                                         '49': '% Veteran Population With Any Disability'})
initial_pa_veterans_aux_2016 = initial_pa_veterans_aux_2016.drop(0)
initial_pa_veterans_aux_2016 = initial_pa_veterans_aux_2016.reset_index(drop=True)
initial_pa_veterans_aux_2016['County'] = initial_pa_veterans_aux_2016['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_veterans_aux_2016['County'] = initial_pa_veterans_aux_2016['County'].apply(lambda x: x.upper())
initial_pa_veterans_aux_2016.insert(0, 'Year', 2016)
initial_pa_veterans_aux_2016['% Veteran Population 18-34 Years Old'] = initial_pa_veterans_aux_2016['% Veteran Population 18-34 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2016['% Veteran Population 35-54 Years Old'] = initial_pa_veterans_aux_2016['% Veteran Population 35-54 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2016['% Veteran Population 55-64 Years Old'] = initial_pa_veterans_aux_2016['% Veteran Population 55-64 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2016['% Veteran Population 65-74 Years Old'] = initial_pa_veterans_aux_2016['% Veteran Population 65-74 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2016['% Veteran Population 75 Years Old & Over'] = initial_pa_veterans_aux_2016['% Veteran Population 75 Years Old & Over'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2016['Veteran Labor Force Participation Rate (%)'] = initial_pa_veterans_aux_2016['Veteran Labor Force Participation Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2016['Veteran Unemployment Rate (%)'] = initial_pa_veterans_aux_2016['Veteran Unemployment Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2016['% Veteran Population With Income Below Poverty Level (Past 12 Months)'] = initial_pa_veterans_aux_2016['% Veteran Population With Income Below Poverty Level (Past 12 Months)'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2016['% Veteran Population With Any Disability'] = initial_pa_veterans_aux_2016['% Veteran Population With Any Disability'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2016


Year          County  % Veteran Population 18-34 Years Old  \
0   2016           ADAMS                                 0.063   
1   2016       ALLEGHENY                                 0.089   
2   2016       ARMSTRONG                                 0.048   
3   2016          BEAVER                                 0.065   
4   2016           BERKS                                 0.062   
5   2016           BLAIR                                 0.058   
6   2016           BUCKS                                 0.070   
7   2016          BUTLER                                 0.049   
8   2016         CAMBRIA                                 0.080   
9   2016          CARBON                                 0.072   
10  2016          CENTRE                                 0.098   
11  2016         CHESTER                                 0.073   
12  2016      CLEARFIELD                                 0.120   
13  2016        COLUMBIA                                 0.036   
14  2016        CRAWFORD                                 0.082   
15  2016      CUMBERLAND                                 0.048   
16  2016         DAUPHIN                                 0.062   
17  2016        DELAWARE                                 0.060   
18  2016            ERIE                                 0.048   
19  2016         FAYETTE                                 0.033   
20  2016        FRANKLIN                                 0.044   
21  2016         INDIANA                                 0.093   
22  2016      LACKAWANNA                                 0.025   
23  2016       LANCASTER                                 0.076   
24  2016        LAWRENCE                                 0.053   
25  2016         LEBANON                                 0.053   
26  2016          LEHIGH                                 0.091   
27  2016         LUZERNE                                 0.064   
28  2016        LYCOMING                                 0.091   
29  2016          MERCER                                 0.048   
30  2016          MONROE                                 0.078   
31  2016      MONTGOMERY                                 0.074   
32  2016     NORTHAMPTON                                 0.078   
33  2016  NORTHUMBERLAND                                 0.083   
34  2016    PHILADELPHIA                                 0.059   
35  2016      SCHUYLKILL                                 0.081   
36  2016        SOMERSET                                 0.014   
37  2016      WASHINGTON                                 0.074   
38  2016    WESTMORELAND                                 0.069   
39  2016            YORK                                 0.084   

    % Veteran Population 35-54 Years Old  \
0                                  0.215   
1                                  0.185   
2                                  0.224   
3                                  0.168   
4                                  0.165   
5                                  0.185   
6                                  0.192   
7                                  0.252   
8                                  0.200   
9                                  0.260   
10                                 0.205   
11                                 0.190   
12                                 0.276   
13                                 0.254   
14                                 0.215   
15                                 0.252   
16                                 0.220   
17                                 0.174   
18                                 0.206   
19                                 0.265   
20                                 0.230   
21                                 0.206   
22                                 0.158   
23                                 0.176   
24                                 0.190   
25                                 0.171   
26                                 0.189   
27                                 0.201   
28                   

**2019**
-
Please note: 2020 United States Census Bureau was unavailable and as such the closest year prior to the election (2019) was utilized


In [186]:
# Reading in 2019 U.S. Census Bureau auxillary (Veterans) dataset
initial_pa_veterans_aux_2019 = pd.read_excel("Resources/PA_Veterans_Auxillary_2019.xlsx")
initial_pa_veterans_aux_2019.head(60)


Unnamed: 0  \
0                                                 NaN   
1                                               Label   
2               Civilian population 18 years and over   
3                                   PERIOD OF SERVICE   
4                 Gulf War (9/2001 or later) veterans   
5                Gulf War (8/1990 to 8/2001) veterans   
6                                Vietnam era veterans   
7                                 Korean War veterans   
8                               World War II veterans   
9                                                 SEX   
10                                               Male   
11                                             Female   
12                                                AGE   
13                                     18 to 34 years   
14                                     35 to 54 years   
15                                     55 to 64 years   
16                                     65 to 74 years   
17                                  75 years and over   
18                 RACE AND HISPANIC OR LATINO ORIGIN   
19                                        White alone   
20                    Black or African American alone   
21            American Indian and Alaska Native alone   
22                                        Asian alone   
23   Native Hawaiian and Other Pacific Islander alone   
24                              Some other race alone   
25                                  Two or more races   
26                   Hispanic or Latino (of any race)   
27                White alone, not Hispanic or Latino   
28  MEDIAN INCOME IN THE PAST 12 MONTHS (IN 2019 I...   
29  Civilian population 18 years and over with income   
30                                               Male   
31                                             Female   
32                             EDUCATIONAL ATTAINMENT   
33              Civilian population 25 years and over   
34                     Less than high school graduate   
35        High school graduate (includes equivalency)   
36                 Some college or associate's degree   
37                        Bachelor's degree or higher   
38                                  EMPLOYMENT STATUS   
39                 Civilian population 18 to 64 years   
40                     Labor force participation rate   
41                Civilian labor force 18 to 64 years   
42                                  Unemployment rate   
43               POVERTY STATUS IN THE PAST 12 MONTHS   
44  Civilian population 18 years and over for whom...   
45   Income in the past 12 months below poverty level   
46  Income in the past 12 months at or above pover...   
47                                  DISABILITY STATUS   
48  Civilian population 18 years and over for whom...   
49                                With any disability   
50                               Without a disability   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
0            Percent Veterans               Percent Veterans   
1                    Estimate                       Estimate   
2                        8.3%                           6.8%   
3                         NaN                            NaN   
4                           N                          12.5%   
5                           N                          15.9%   
6                           N                          34.4%   
7                           N                          11.1%   
8                           N                           3.9%   
9                         NaN                            NaN   
10                      94.0%                          93.2%   
11                       6.0%                           6.8%   
12                        NaN                            NaN   
13                       7.7%                           5.0%   
14                      15.3%                          19.8%   
15                      24.3%                         

In [187]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Three groupings = Total Population, Veteran Population, Nonveteran Population
# % of population groups above that fall into these age categories: 18 to 34, 35 to 54, 55 to 64, 65 to 74 and 75 & Over
# Labor force participation rate
# Unemployment rate
# % of Population group with income below poverty level in the past 12 months
# % of Population group with any disability
initial_pa_veterans_aux_2019 = initial_pa_veterans_aux_2019.iloc[[13, 14, 15, 16, 17, 40, 42, 45, 49], :]
initial_pa_veterans_aux_2019


Unnamed: 0  \
13                                    18 to 34 years   
14                                    35 to 54 years   
15                                    55 to 64 years   
16                                    65 to 74 years   
17                                 75 years and over   
40                    Labor force participation rate   
42                                 Unemployment rate   
45  Income in the past 12 months below poverty level   
49                               With any disability   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
13                       7.7%                           5.0%   
14                      15.3%                          19.8%   
15                      24.3%                          16.8%   
16                      26.3%                          25.8%   
17                      26.4%                          32.7%   
40                      78.3%                          78.6%   
42                       2.1%                           6.6%   
45                       4.5%                           7.1%   
49                      16.7%                          32.0%   

   Armstrong County, Pennsylvania Beaver County, Pennsylvania  \
13                          15.4%                        6.5%   
14                          24.7%                       15.8%   
15                          11.1%                       22.9%   
16                          27.5%                       24.1%   
17                          21.4%                       30.8%   
40                          82.9%                       70.3%   
42                           0.6%                       15.0%   
45                           4.9%                        9.9%   
49                          26.6%                       25.5%   

   Berks County, Pennsylvania Blair County, Pennsylvania  \
13                       5.8%                       3.8%   
14                      15.8%                      17.1%   
15                      19.1%                      22.9%   
16                      33.0%                      26.0%   
17                      26.3%                      30.2%   
40                      72.0%                      71.9%   
42                       4.0%                       0.6%   
45                       4.8%                       9.6%   
49                      27.8%                      34.0%   

   Bucks County, Pennsylvania Butler County, Pennsylvania  \
13                       4.1%                        3.2%   
14                      19.8%                       22.3%   
15                      12.7%                       18.3%   
16                      28.6%                       27.3%   
17                      34.8%                       29.0%   
40                      84.4%                       75.0%   
42                       2.2%                        1.5%   
45                       2.8%                        7.9%   
49                      22.6%                       23.5%   

   Cambria County, Pennsylvania  ... Monroe County, Pennsylvania  \
13                         2.4%  ...                        6.1%   
14                        20.2%  ...                       24.3%   
15                        16.8%  ...                       25.1%   
16                        30.7%  ...                       23.4%   
17                        29.8%  ...                       21.1%   
40                        68.2%  ...                       79.5%   
42                         6.5%  ...                        4.5%   
45                        10.1%  ...                        9.1%   
49                        32.2%  ...                       18.7%   

   Montgomery County, Pennsylvania Northampton County, Pennsylvania  \
13                            7.0%                             4.8%   
14                           16.9%                            15.3%   
15                           13.1%                            26.0%   
16          

In [188]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_veterans_aux_2019 = initial_pa_veterans_aux_2019.T
initial_pa_veterans_aux_2019.head()


13              14  \
Unnamed: 0                      18 to 34 years  35 to 54 years   
Adams County, Pennsylvania                7.7%           15.3%   
Allegheny County, Pennsylvania            5.0%           19.8%   
Armstrong County, Pennsylvania           15.4%           24.7%   
Beaver County, Pennsylvania               6.5%           15.8%   

                                            15              16  \
Unnamed: 0                      55 to 64 years  65 to 74 years   
Adams County, Pennsylvania               24.3%           26.3%   
Allegheny County, Pennsylvania           16.8%           25.8%   
Armstrong County, Pennsylvania           11.1%           27.5%   
Beaver County, Pennsylvania              22.9%           24.1%   

                                               17  \
Unnamed: 0                      75 years and over   
Adams County, Pennsylvania                  26.4%   
Allegheny County, Pennsylvania              32.7%   
Armstrong County, Pennsylvania              21.4%   
Beaver County, Pennsylvania                 30.8%   

                                                            40  \
Unnamed: 0                      Labor force participation rate   
Adams County, Pennsylvania                               78.3%   
Allegheny County, Pennsylvania                           78.6%   
Armstrong County, Pennsylvania                           82.9%   
Beaver County, Pennsylvania                              70.3%   

                                               42  \
Unnamed: 0                      Unemployment rate   
Adams County, Pennsylvania                   2.1%   
Allegheny County, Pennsylvania               6.6%   
Armstrong County, Pennsylvania               0.6%   
Beaver County, Pennsylvania                 15.0%   

                                                                              45  \
Unnamed: 0                      Income in the past 12 months below poverty level   
Adams County, Pennsylvania                                                  4.5%   
Allegheny County, Pennsylvania                                              7.1%   
Armstrong County, Pennsylvania                                              4.9%   
Beaver County, Pennsylvania                                                 9.9%   

                                                 49  
Unnamed: 0                      With any disability  
Adams County, Pennsylvania                    16.7%  
Allegheny County, Pennsylvania                32.0%  
Armstrong County, Pennsylvania                26.6%  
Beaver County, Pennsylvania                   25.5%

In [189]:
# Resetting index and renaming to create a 'County' column
initial_pa_veterans_aux_2019 = initial_pa_veterans_aux_2019.reset_index()
initial_pa_veterans_aux_2019.rename(columns={'index': 'County'}, inplace=True)
initial_pa_veterans_aux_2019.head()


County              13              14  \
0                      Unnamed: 0  18 to 34 years  35 to 54 years   
1      Adams County, Pennsylvania            7.7%           15.3%   
2  Allegheny County, Pennsylvania            5.0%           19.8%   
3  Armstrong County, Pennsylvania           15.4%           24.7%   
4     Beaver County, Pennsylvania            6.5%           15.8%   

               15              16                 17  \
0  55 to 64 years  65 to 74 years  75 years and over   
1           24.3%           26.3%              26.4%   
2           16.8%           25.8%              32.7%   
3           11.1%           27.5%              21.4%   
4           22.9%           24.1%              30.8%   

                               40                 42  \
0  Labor force participation rate  Unemployment rate   
1                           78.3%               2.1%   
2                           78.6%               6.6%   
3                           82.9%               0.6%   
4                           70.3%              15.0%   

                                                 45                   49  
0  Income in the past 12 months below poverty level  With any disability  
1                                              4.5%                16.7%  
2                                              7.1%                32.0%  
3                                              4.9%                26.6%  
4                                              9.9%                25.5%

In [190]:
# Confirming column data types prior to renaming
print(initial_pa_veterans_aux_2019.columns)


Index(['County', 13, 14, 15, 16, 17, 40, 42, 45, 49], dtype='object')


In [191]:
# Converting column data types from integers to strings for renaming
initial_pa_veterans_aux_2019.columns = initial_pa_veterans_aux_2019.columns.astype(str)
print(initial_pa_veterans_aux_2019.columns)


Index(['County', '13', '14', '15', '16', '17', '40', '42', '45', '49'], dtype='object')


In [192]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_veterans_aux_2019.replace('N', np.nan, inplace=True)


In [193]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_veterans_aux_2019 = initial_pa_veterans_aux_2019.rename(columns={'13': '% Veteran Population 18-34 Years Old', '14': '% Veteran Population 35-54 Years Old', '15': '% Veteran Population 55-64 Years Old',
                                                                         '16': '% Veteran Population 65-74 Years Old', '17': '% Veteran Population 75 Years Old & Over', '40': 'Veteran Labor Force Participation Rate (%)',
                                                                         '42': 'Veteran Unemployment Rate (%)', '45': '% Veteran Population With Income Below Poverty Level (Past 12 Months)',
                                                                         '49': '% Veteran Population With Any Disability'})
initial_pa_veterans_aux_2019 = initial_pa_veterans_aux_2019.drop(0)
initial_pa_veterans_aux_2019 = initial_pa_veterans_aux_2019.reset_index(drop=True)
initial_pa_veterans_aux_2019['County'] = initial_pa_veterans_aux_2019['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_veterans_aux_2019['County'] = initial_pa_veterans_aux_2019['County'].apply(lambda x: x.upper())
initial_pa_veterans_aux_2019.insert(0, 'Year', 2020)
initial_pa_veterans_aux_2019['% Veteran Population 18-34 Years Old'] = initial_pa_veterans_aux_2019['% Veteran Population 18-34 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2019['% Veteran Population 35-54 Years Old'] = initial_pa_veterans_aux_2019['% Veteran Population 35-54 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2019['% Veteran Population 55-64 Years Old'] = initial_pa_veterans_aux_2019['% Veteran Population 55-64 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2019['% Veteran Population 65-74 Years Old'] = initial_pa_veterans_aux_2019['% Veteran Population 65-74 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2019['% Veteran Population 75 Years Old & Over'] = initial_pa_veterans_aux_2019['% Veteran Population 75 Years Old & Over'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2019['Veteran Labor Force Participation Rate (%)'] = initial_pa_veterans_aux_2019['Veteran Labor Force Participation Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2019['Veteran Unemployment Rate (%)'] = initial_pa_veterans_aux_2019['Veteran Unemployment Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2019['% Veteran Population With Income Below Poverty Level (Past 12 Months)'] = initial_pa_veterans_aux_2019['% Veteran Population With Income Below Poverty Level (Past 12 Months)'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2019['% Veteran Population With Any Disability'] = initial_pa_veterans_aux_2019['% Veteran Population With Any Disability'].str.rstrip('%').astype(float) / 100
initial_pa_veterans_aux_2019


Year          County  % Veteran Population 18-34 Years Old  \
0   2020           ADAMS                                 0.077   
1   2020       ALLEGHENY                                 0.050   
2   2020       ARMSTRONG                                 0.154   
3   2020          BEAVER                                 0.065   
4   2020           BERKS                                 0.058   
5   2020           BLAIR                                 0.038   
6   2020           BUCKS                                 0.041   
7   2020          BUTLER                                 0.032   
8   2020         CAMBRIA                                 0.024   
9   2020          CARBON                                 0.000   
10  2020          CENTRE                                 0.073   
11  2020         CHESTER                                 0.078   
12  2020      CLEARFIELD                                 0.066   
13  2020        COLUMBIA                                 0.138   
14  2020        CRAWFORD                                 0.060   
15  2020      CUMBERLAND                                 0.087   
16  2020         DAUPHIN                                 0.070   
17  2020        DELAWARE                                 0.069   
18  2020            ERIE                                 0.074   
19  2020         FAYETTE                                 0.104   
20  2020        FRANKLIN                                 0.103   
21  2020         INDIANA                                 0.111   
22  2020      LACKAWANNA                                 0.065   
23  2020       LANCASTER                                 0.074   
24  2020        LAWRENCE                                 0.081   
25  2020         LEBANON                                 0.058   
26  2020          LEHIGH                                 0.064   
27  2020         LUZERNE                                 0.041   
28  2020        LYCOMING                                 0.068   
29  2020          MERCER                                 0.098   
30  2020          MONROE                                 0.061   
31  2020      MONTGOMERY                                 0.070   
32  2020     NORTHAMPTON                                 0.048   
33  2020  NORTHUMBERLAND                                 0.034   
34  2020    PHILADELPHIA                                 0.083   
35  2020      SCHUYLKILL                                 0.020   
36  2020        SOMERSET                                 0.029   
37  2020      WASHINGTON                                 0.079   
38  2020    WESTMORELAND                                 0.077   
39  2020            YORK                                 0.086   

    % Veteran Population 35-54 Years Old  \
0                                  0.153   
1                                  0.198   
2                                  0.247   
3                                  0.158   
4                                  0.158   
5                                  0.171   
6                                  0.198   
7                                  0.223   
8                                  0.202   
9                                  0.083   
10                                 0.215   
11                                 0.195   
12                                 0.249   
13                                 0.125   
14                                 0.124   
15                                 0.219   
16                                 0.193   
17                                 0.175   
18                                 0.227   
19                                 0.263   
20                                 0.217   
21                                 0.239   
22                                 0.158   
23                                 0.170   
24                                 0.261   
25                                 0.250   
26                                 0.182   
27                                 0.256   
28                   

**Auxillary (Nonveterans)  Data Extraction, Transformation & Loading (2012, 2016 & 2019)**
-
-----------

**2012**
-

In [194]:
# Reading in 2012 U.S. Census Bureau auxillary (Nonveterans) dataset
initial_pa_nonveterans_aux_2012 = pd.read_excel("Resources/PA_Nonveterans_Auxillary_2012.xlsx")
initial_pa_nonveterans_aux_2012.head(60)


Unnamed: 0  \
0                                                 NaN   
1                                               Label   
2               Civilian population 18 years and over   
3                                   PERIOD OF SERVICE   
4                 Gulf War (9/2001 or later) veterans   
5                Gulf War (8/1990 to 8/2001) veterans   
6                                Vietnam era veterans   
7                                 Korean War veterans   
8                               World War II veterans   
9                                                 SEX   
10                                               Male   
11                                             Female   
12                                                AGE   
13                                     18 to 34 years   
14                                     35 to 54 years   
15                                     55 to 64 years   
16                                     65 to 74 years   
17                                  75 years and over   
18                 RACE AND HISPANIC OR LATINO ORIGIN   
19                                           One race   
20                                              White   
21                          Black or African American   
22                  American Indian and Alaska Native   
23                                              Asian   
24         Native Hawaiian and Other Pacific Islander   
25                                    Some other race   
26                                  Two or more races   
27                   Hispanic or Latino (of any race)   
28                White alone, not Hispanic or Latino   
29  MEDIAN INCOME IN THE PAST 12 MONTHS (IN 2012 I...   
30  Civilian population 18 years and over with income   
31                                               Male   
32                                             Female   
33                             EDUCATIONAL ATTAINMENT   
34              Civilian population 25 years and over   
35                     Less than high school graduate   
36        High school graduate (includes equivalency)   
37                 Some college or associate's degree   
38                        Bachelor's degree or higher   
39                                  EMPLOYMENT STATUS   
40                 Civilian population 18 to 64 years   
41                     Labor force participation rate   
42                Civilian labor force 18 to 64 years   
43                                  Unemployment rate   
44               POVERTY STATUS IN THE PAST 12 MONTHS   
45  Civilian population 18 years and over for whom...   
46                Below poverty in the past 12 months   
47                                  DISABILITY STATUS   
48  Civilian population 18 years and over for whom...   
49                                With any disability   
50                                    PERCENT IMPUTED   
51  Veteran status for the population 18 years and...   
52  Period of service for the civilian veteran pop...   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
0                 Nonveterans                    Nonveterans   
1                    Estimate                       Estimate   
2                      71,470                        900,804   
3                         NaN                            NaN   
4                         (X)                            (X)   
5                         (X)                            (X)   
6                         (X)                            (X)   
7                         (X)                            (X)   
8                         (X)                            (X)   
9                         NaN                            NaN   
10                      43.4%                          42.5%   
11                      56.6%                          57.5%   
12                        NaN                            NaN   
13                      27.9%                          31.8%   
14  

In [195]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Three groupings = Total Population, Veteran Population, Nonveteran Population
# % of population groups above that fall into these age categories: 18 to 34, 35 to 54, 55 to 64, 65 to 74 and 75 & Over
# Labor force participation rate
# Unemployment rate
# % of Population group with income below poverty level in the past 12 months
# % of Population group with any disability
initial_pa_nonveterans_aux_2012 = initial_pa_nonveterans_aux_2012.iloc[[13, 14, 15, 16, 17, 41, 43, 46, 49], :]
initial_pa_nonveterans_aux_2012


Unnamed: 0 Adams County, Pennsylvania  \
13                       18 to 34 years                      27.9%   
14                       35 to 54 years                      35.7%   
15                       55 to 64 years                      17.9%   
16                       65 to 74 years                      10.4%   
17                    75 years and over                       8.1%   
41       Labor force participation rate                      80.1%   
43                    Unemployment rate                       5.5%   
46  Below poverty in the past 12 months                       8.6%   
49                  With any disability                      15.1%   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
13                          31.8%                          24.1%   
14                          33.5%                          37.3%   
15                          17.0%                          18.3%   
16                           9.1%                          10.8%   
17                           8.6%                           9.5%   
41                          78.3%                          75.0%   
43                           7.4%                           8.5%   
46                          11.8%                          12.2%   
49                          14.1%                          19.2%   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
13                       26.3%                      30.4%   
14                       35.0%                      37.0%   
15                       18.2%                      16.0%   
16                       10.9%                       8.9%   
17                        9.6%                       7.7%   
41                       78.6%                      79.6%   
43                        8.3%                       9.5%   
46                       10.0%                      12.7%   
49                       16.2%                      14.2%   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
13                      28.4%                      25.8%   
14                      34.1%                      39.7%   
15                      17.6%                      18.0%   
16                      10.6%                       9.2%   
17                       9.3%                       7.4%   
41                      74.7%                      81.9%   
43                       7.4%                       7.7%   
46                      12.1%                       5.1%   
49                      17.9%                      11.1%   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
13                       27.8%                        27.4%  ...   
14                       38.0%                        33.7%  ...   
15                       17.2%                        18.2%  ...   
16                        9.4%                        10.5%  ...   
17                        7.5%                        10.3%  ...   
41                       78.4%                        70.8%  ...   
43                        6.1%                         9.5%  ...   
46                        9.4%                        13.0%  ...   
49                       13.1%                        19.4%  ...   

   Monroe County, Pennsylvania Montgomery County, Pennsylvania  \
13                       29.7%                           27.7%   
14                       38.2%                           38.4%   
15                       17.4%                           16.7%   
16                        9.1%                            9.0%   
17                        5.7%                            8.2%   
41                       76.6%                           81.9%   
43                       13.7%                            6.8%   
46                       13.5%                            6.5%   
49                       14.8%                           10.6%   

   Northampton County, Pennsylvania Northumberland County, Pennsylvania  \
13                

In [196]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_nonveterans_aux_2012 = initial_pa_nonveterans_aux_2012.T
initial_pa_nonveterans_aux_2012.head()


13              14  \
Unnamed: 0                      18 to 34 years  35 to 54 years   
Adams County, Pennsylvania               27.9%           35.7%   
Allegheny County, Pennsylvania           31.8%           33.5%   
Armstrong County, Pennsylvania           24.1%           37.3%   
Beaver County, Pennsylvania              26.3%           35.0%   

                                            15              16  \
Unnamed: 0                      55 to 64 years  65 to 74 years   
Adams County, Pennsylvania               17.9%           10.4%   
Allegheny County, Pennsylvania           17.0%            9.1%   
Armstrong County, Pennsylvania           18.3%           10.8%   
Beaver County, Pennsylvania              18.2%           10.9%   

                                               17  \
Unnamed: 0                      75 years and over   
Adams County, Pennsylvania                   8.1%   
Allegheny County, Pennsylvania               8.6%   
Armstrong County, Pennsylvania               9.5%   
Beaver County, Pennsylvania                  9.6%   

                                                            41  \
Unnamed: 0                      Labor force participation rate   
Adams County, Pennsylvania                               80.1%   
Allegheny County, Pennsylvania                           78.3%   
Armstrong County, Pennsylvania                           75.0%   
Beaver County, Pennsylvania                              78.6%   

                                               43  \
Unnamed: 0                      Unemployment rate   
Adams County, Pennsylvania                   5.5%   
Allegheny County, Pennsylvania               7.4%   
Armstrong County, Pennsylvania               8.5%   
Beaver County, Pennsylvania                  8.3%   

                                                                 46  \
Unnamed: 0                      Below poverty in the past 12 months   
Adams County, Pennsylvania                                     8.6%   
Allegheny County, Pennsylvania                                11.8%   
Armstrong County, Pennsylvania                                12.2%   
Beaver County, Pennsylvania                                   10.0%   

                                                 49  
Unnamed: 0                      With any disability  
Adams County, Pennsylvania                    15.1%  
Allegheny County, Pennsylvania                14.1%  
Armstrong County, Pennsylvania                19.2%  
Beaver County, Pennsylvania                   16.2%

In [197]:
# Resetting index and renaming to create a 'County' column
initial_pa_nonveterans_aux_2012 = initial_pa_nonveterans_aux_2012.reset_index()
initial_pa_nonveterans_aux_2012.rename(columns={'index': 'County'}, inplace=True)
initial_pa_nonveterans_aux_2012.head()


County              13              14  \
0                      Unnamed: 0  18 to 34 years  35 to 54 years   
1      Adams County, Pennsylvania           27.9%           35.7%   
2  Allegheny County, Pennsylvania           31.8%           33.5%   
3  Armstrong County, Pennsylvania           24.1%           37.3%   
4     Beaver County, Pennsylvania           26.3%           35.0%   

               15              16                 17  \
0  55 to 64 years  65 to 74 years  75 years and over   
1           17.9%           10.4%               8.1%   
2           17.0%            9.1%               8.6%   
3           18.3%           10.8%               9.5%   
4           18.2%           10.9%               9.6%   

                               41                 43  \
0  Labor force participation rate  Unemployment rate   
1                           80.1%               5.5%   
2                           78.3%               7.4%   
3                           75.0%               8.5%   
4                           78.6%               8.3%   

                                    46                   49  
0  Below poverty in the past 12 months  With any disability  
1                                 8.6%                15.1%  
2                                11.8%                14.1%  
3                                12.2%                19.2%  
4                                10.0%                16.2%

In [198]:
# Confirming column data types prior to renaming
print(initial_pa_nonveterans_aux_2012.columns)


Index(['County', 13, 14, 15, 16, 17, 41, 43, 46, 49], dtype='object')


In [199]:
# Converting column data types from integers to strings for renaming
initial_pa_nonveterans_aux_2012.columns = initial_pa_nonveterans_aux_2012.columns.astype(str)
print(initial_pa_nonveterans_aux_2012.columns)


Index(['County', '13', '14', '15', '16', '17', '41', '43', '46', '49'], dtype='object')


In [200]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_nonveterans_aux_2012.replace('N', np.nan, inplace=True)


In [201]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_nonveterans_aux_2012 = initial_pa_nonveterans_aux_2012.rename(columns={'13': '% Nonveteran Population 18-34 Years Old', '14': '% Nonveteran Population 35-54 Years Old', '15': '% Nonveteran Population 55-64 Years Old',
                                                                         '16': '% Nonveteran Population 65-74 Years Old', '17': '% Nonveteran Population 75 Years Old & Over', '41': 'Nonveteran Labor Force Participation Rate (%)',
                                                                         '43': 'Nonveteran Unemployment Rate (%)', '46': '% Nonveteran Population With Income Below Poverty Level (Past 12 Months)',
                                                                         '49': '% Nonveteran Population With Any Disability'})
initial_pa_nonveterans_aux_2012 = initial_pa_nonveterans_aux_2012.drop(0)
initial_pa_nonveterans_aux_2012 = initial_pa_nonveterans_aux_2012.reset_index(drop=True)
initial_pa_nonveterans_aux_2012['County'] = initial_pa_nonveterans_aux_2012['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_nonveterans_aux_2012['County'] = initial_pa_nonveterans_aux_2012['County'].apply(lambda x: x.upper())
initial_pa_nonveterans_aux_2012.insert(0, 'Year', 2012)
initial_pa_nonveterans_aux_2012['% Nonveteran Population 18-34 Years Old'] = initial_pa_nonveterans_aux_2012['% Nonveteran Population 18-34 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2012['% Nonveteran Population 35-54 Years Old'] = initial_pa_nonveterans_aux_2012['% Nonveteran Population 35-54 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2012['% Nonveteran Population 55-64 Years Old'] = initial_pa_nonveterans_aux_2012['% Nonveteran Population 55-64 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2012['% Nonveteran Population 65-74 Years Old'] = initial_pa_nonveterans_aux_2012['% Nonveteran Population 65-74 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2012['% Nonveteran Population 75 Years Old & Over'] = initial_pa_nonveterans_aux_2012['% Nonveteran Population 75 Years Old & Over'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2012['Nonveteran Labor Force Participation Rate (%)'] = initial_pa_nonveterans_aux_2012['Nonveteran Labor Force Participation Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2012['Nonveteran Unemployment Rate (%)'] = initial_pa_nonveterans_aux_2012['Nonveteran Unemployment Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2012['% Nonveteran Population With Income Below Poverty Level (Past 12 Months)'] = initial_pa_nonveterans_aux_2012['% Nonveteran Population With Income Below Poverty Level (Past 12 Months)'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2012['% Nonveteran Population With Any Disability'] = initial_pa_nonveterans_aux_2012['% Nonveteran Population With Any Disability'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2012


Year          County  % Nonveteran Population 18-34 Years Old  \
0   2012           ADAMS                                    0.279   
1   2012       ALLEGHENY                                    0.318   
2   2012       ARMSTRONG                                    0.241   
3   2012          BEAVER                                    0.263   
4   2012           BERKS                                    0.304   
5   2012           BLAIR                                    0.284   
6   2012           BUCKS                                    0.258   
7   2012          BUTLER                                    0.278   
8   2012         CAMBRIA                                    0.274   
9   2012          CARBON                                    0.237   
10  2012          CENTRE                                    0.518   
11  2012         CHESTER                                    0.283   
12  2012      CLEARFIELD                                    0.264   
13  2012        COLUMBIA                                    0.343   
14  2012        CRAWFORD                                    0.286   
15  2012      CUMBERLAND                                    0.314   
16  2012         DAUPHIN                                    0.307   
17  2012        DELAWARE                                    0.316   
18  2012            ERIE                                    0.331   
19  2012         FAYETTE                                    0.262   
20  2012        FRANKLIN                                    0.287   
21  2012         INDIANA                                    0.369   
22  2012      LACKAWANNA                                    0.303   
23  2012       LANCASTER                                    0.311   
24  2012        LAWRENCE                                    0.259   
25  2012         LEBANON                                    0.282   
26  2012          LEHIGH                                    0.298   
27  2012         LUZERNE                                    0.285   
28  2012        LYCOMING                                    0.314   
29  2012          MERCER                                    0.275   
30  2012          MONROE                                    0.297   
31  2012      MONTGOMERY                                    0.277   
32  2012     NORTHAMPTON                                    0.295   
33  2012  NORTHUMBERLAND                                    0.271   
34  2012    PHILADELPHIA                                    0.401   
35  2012      SCHUYLKILL                                    0.252   
36  2012        SOMERSET                                    0.253   
37  2012      WASHINGTON                                    0.261   
38  2012    WESTMORELAND                                    0.244   
39  2012            YORK                                    0.282   

    % Nonveteran Population 35-54 Years Old  \
0                                     0.357   
1                                     0.335   
2                                     0.373   
3                                     0.350   
4                                     0.370   
5                                     0.341   
6                                     0.397   
7                                     0.380   
8                                     0.337   
9                                     0.378   
10                                    0.252   
11                                    0.400   
12                                    0.370   
13                                    0.316   
14                                    0.347   
15                                    0.347   
16                                    0.359   
17                                    0.361   
18                                    0.341   
19                                    0.355   
20                                    0.361   
21                                    0.300   
22                                    0.337   
23                                    0.349   

**2016**
-

In [202]:
# Reading in 2016 U.S. Census Bureau auxillary (Nonveterans) dataset
initial_pa_nonveterans_aux_2016 = pd.read_excel("Resources/PA_Nonveterans_Auxillary_2016.xlsx")
initial_pa_nonveterans_aux_2016.head(60)


Unnamed: 0  \
0                                                 NaN   
1                                               Label   
2               Civilian population 18 years and over   
3                                   PERIOD OF SERVICE   
4                 Gulf War (9/2001 or later) veterans   
5                Gulf War (8/1990 to 8/2001) veterans   
6                                Vietnam era veterans   
7                                 Korean War veterans   
8                               World War II veterans   
9                                                 SEX   
10                                               Male   
11                                             Female   
12                                                AGE   
13                                     18 to 34 years   
14                                     35 to 54 years   
15                                     55 to 64 years   
16                                     65 to 74 years   
17                                  75 years and over   
18                 RACE AND HISPANIC OR LATINO ORIGIN   
19                                        White alone   
20                    Black or African American alone   
21            American Indian and Alaska Native alone   
22                                        Asian alone   
23   Native Hawaiian and Other Pacific Islander alone   
24                              Some other race alone   
25                                  Two or more races   
26                   Hispanic or Latino (of any race)   
27                White alone, not Hispanic or Latino   
28  MEDIAN INCOME IN THE PAST 12 MONTHS (IN 2016 I...   
29  Civilian population 18 years and over with income   
30                                               Male   
31                                             Female   
32                             EDUCATIONAL ATTAINMENT   
33              Civilian population 25 years and over   
34                     Less than high school graduate   
35        High school graduate (includes equivalency)   
36                 Some college or associate's degree   
37                        Bachelor's degree or higher   
38                                  EMPLOYMENT STATUS   
39                 Civilian population 18 to 64 years   
40                     Labor force participation rate   
41                Civilian labor force 18 to 64 years   
42                                  Unemployment rate   
43               POVERTY STATUS IN THE PAST 12 MONTHS   
44  Civilian population 18 years and over for whom...   
45   Income in the past 12 months below poverty level   
46  Income in the past 12 months at or above pover...   
47                                  DISABILITY STATUS   
48  Civilian population 18 years and over for whom...   
49                                With any disability   
50                               Without a disability   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
0                     Percent                        Percent   
1                    Estimate                       Estimate   
2                       89.3%                          92.2%   
3                         NaN                            NaN   
4                         (X)                            (X)   
5                         (X)                            (X)   
6                         (X)                            (X)   
7                         (X)                            (X)   
8                         (X)                            (X)   
9                         NaN                            NaN   
10                      44.0%                          43.8%   
11                      56.0%                          56.2%   
12                        NaN                            NaN   
13                      27.4%                          31.7%   
14                      32.9%                          30.7%   
15                      17.5%                         

In [203]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Three groupings = Total Population, Veteran Population, Nonveteran Population
# % of population groups above that fall into these age categories: 18 to 34, 35 to 54, 55 to 64, 65 to 74 and 75 & Over
# Labor force participation rate
# Unemployment rate
# % of Population group with income below poverty level in the past 12 months
# % of Population group with any disability
initial_pa_nonveterans_aux_2016 = initial_pa_nonveterans_aux_2016.iloc[[13, 14, 15, 16, 17, 40, 42, 45, 49], :]
initial_pa_nonveterans_aux_2016


Unnamed: 0  \
13                                    18 to 34 years   
14                                    35 to 54 years   
15                                    55 to 64 years   
16                                    65 to 74 years   
17                                 75 years and over   
40                    Labor force participation rate   
42                                 Unemployment rate   
45  Income in the past 12 months below poverty level   
49                               With any disability   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
13                      27.4%                          31.7%   
14                      32.9%                          30.7%   
15                      17.5%                          18.4%   
16                      12.6%                          10.7%   
17                       9.6%                           8.5%   
40                      79.1%                          80.1%   
42                       5.2%                           5.2%   
45                       8.2%                          11.2%   
49                      16.1%                          15.0%   

   Armstrong County, Pennsylvania Beaver County, Pennsylvania  \
13                          23.8%                       25.9%   
14                          32.9%                       32.1%   
15                          20.5%                       20.2%   
16                          13.0%                       12.2%   
17                           9.9%                        9.6%   
40                          71.4%                       77.8%   
42                           5.8%                        4.4%   
45                          12.4%                        7.3%   
49                          21.8%                       16.2%   

   Berks County, Pennsylvania Blair County, Pennsylvania  \
13                      30.1%                      26.9%   
14                      33.9%                      32.2%   
15                      17.7%                      18.6%   
16                      10.3%                      12.3%   
17                       8.0%                      10.0%   
40                      78.4%                      74.4%   
42                       6.0%                       4.6%   
45                      11.7%                      11.6%   
49                      15.4%                      19.7%   

   Bucks County, Pennsylvania Butler County, Pennsylvania  \
13                      25.3%                       26.9%   
14                      35.1%                       34.3%   
15                      20.2%                       19.5%   
16                      11.3%                       11.2%   
17                       8.0%                        8.1%   
40                      80.3%                       76.8%   
42                       3.7%                        3.5%   
45                       6.3%                        6.6%   
49                      13.0%                       13.7%   

   Cambria County, Pennsylvania  ... Monroe County, Pennsylvania  \
13                        26.4%  ...                       29.6%   
14                        30.6%  ...                       33.9%   
15                        19.4%  ...                       19.3%   
16                        13.2%  ...                       11.4%   
17                        10.4%  ...                        5.8%   
40                        71.4%  ...                       73.0%   
42                         7.8%  ...                        7.7%   
45                        14.4%  ...                       10.1%   
49                        19.3%  ...                       16.6%   

   Montgomery County, Pennsylvania Northampton County, Pennsylvania  \
13                           27.5%                            29.0%   
14                           35.0%                            33.2%   
15                           18.2%                            18.4%   
16          

In [204]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_nonveterans_aux_2016 = initial_pa_nonveterans_aux_2016.T
initial_pa_nonveterans_aux_2016.head()


13              14  \
Unnamed: 0                      18 to 34 years  35 to 54 years   
Adams County, Pennsylvania               27.4%           32.9%   
Allegheny County, Pennsylvania           31.7%           30.7%   
Armstrong County, Pennsylvania           23.8%           32.9%   
Beaver County, Pennsylvania              25.9%           32.1%   

                                            15              16  \
Unnamed: 0                      55 to 64 years  65 to 74 years   
Adams County, Pennsylvania               17.5%           12.6%   
Allegheny County, Pennsylvania           18.4%           10.7%   
Armstrong County, Pennsylvania           20.5%           13.0%   
Beaver County, Pennsylvania              20.2%           12.2%   

                                               17  \
Unnamed: 0                      75 years and over   
Adams County, Pennsylvania                   9.6%   
Allegheny County, Pennsylvania               8.5%   
Armstrong County, Pennsylvania               9.9%   
Beaver County, Pennsylvania                  9.6%   

                                                            40  \
Unnamed: 0                      Labor force participation rate   
Adams County, Pennsylvania                               79.1%   
Allegheny County, Pennsylvania                           80.1%   
Armstrong County, Pennsylvania                           71.4%   
Beaver County, Pennsylvania                              77.8%   

                                               42  \
Unnamed: 0                      Unemployment rate   
Adams County, Pennsylvania                   5.2%   
Allegheny County, Pennsylvania               5.2%   
Armstrong County, Pennsylvania               5.8%   
Beaver County, Pennsylvania                  4.4%   

                                                                              45  \
Unnamed: 0                      Income in the past 12 months below poverty level   
Adams County, Pennsylvania                                                  8.2%   
Allegheny County, Pennsylvania                                             11.2%   
Armstrong County, Pennsylvania                                             12.4%   
Beaver County, Pennsylvania                                                 7.3%   

                                                 49  
Unnamed: 0                      With any disability  
Adams County, Pennsylvania                    16.1%  
Allegheny County, Pennsylvania                15.0%  
Armstrong County, Pennsylvania                21.8%  
Beaver County, Pennsylvania                   16.2%

In [205]:
# Resetting index and renaming to create a 'County' column
initial_pa_nonveterans_aux_2016 = initial_pa_nonveterans_aux_2016.reset_index()
initial_pa_nonveterans_aux_2016.rename(columns={'index': 'County'}, inplace=True)
initial_pa_nonveterans_aux_2016.head()


County              13              14  \
0                      Unnamed: 0  18 to 34 years  35 to 54 years   
1      Adams County, Pennsylvania           27.4%           32.9%   
2  Allegheny County, Pennsylvania           31.7%           30.7%   
3  Armstrong County, Pennsylvania           23.8%           32.9%   
4     Beaver County, Pennsylvania           25.9%           32.1%   

               15              16                 17  \
0  55 to 64 years  65 to 74 years  75 years and over   
1           17.5%           12.6%               9.6%   
2           18.4%           10.7%               8.5%   
3           20.5%           13.0%               9.9%   
4           20.2%           12.2%               9.6%   

                               40                 42  \
0  Labor force participation rate  Unemployment rate   
1                           79.1%               5.2%   
2                           80.1%               5.2%   
3                           71.4%               5.8%   
4                           77.8%               4.4%   

                                                 45                   49  
0  Income in the past 12 months below poverty level  With any disability  
1                                              8.2%                16.1%  
2                                             11.2%                15.0%  
3                                             12.4%                21.8%  
4                                              7.3%                16.2%

In [206]:
# Confirming column data types prior to renaming
print(initial_pa_nonveterans_aux_2016.columns)


Index(['County', 13, 14, 15, 16, 17, 40, 42, 45, 49], dtype='object')


In [207]:
# Converting column data types from integers to strings for renaming
initial_pa_nonveterans_aux_2016.columns = initial_pa_nonveterans_aux_2016.columns.astype(str)
print(initial_pa_nonveterans_aux_2016.columns)


Index(['County', '13', '14', '15', '16', '17', '40', '42', '45', '49'], dtype='object')


In [208]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_nonveterans_aux_2016.replace('N', np.nan, inplace=True)


In [209]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_nonveterans_aux_2016 = initial_pa_nonveterans_aux_2016.rename(columns={'13': '% Nonveteran Population 18-34 Years Old', '14': '% Nonveteran Population 35-54 Years Old', '15': '% Nonveteran Population 55-64 Years Old',
                                                                         '16': '% Nonveteran Population 65-74 Years Old', '17': '% Nonveteran Population 75 Years Old & Over', '40': 'Nonveteran Labor Force Participation Rate (%)',
                                                                         '42': 'Nonveteran Unemployment Rate (%)', '45': '% Nonveteran Population With Income Below Poverty Level (Past 12 Months)',
                                                                         '49': '% Nonveteran Population With Any Disability'})
initial_pa_nonveterans_aux_2016 = initial_pa_nonveterans_aux_2016.drop(0)
initial_pa_nonveterans_aux_2016 = initial_pa_nonveterans_aux_2016.reset_index(drop=True)
initial_pa_nonveterans_aux_2016['County'] = initial_pa_nonveterans_aux_2016['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_nonveterans_aux_2016['County'] = initial_pa_nonveterans_aux_2016['County'].apply(lambda x: x.upper())
initial_pa_nonveterans_aux_2016.insert(0, 'Year', 2016)
initial_pa_nonveterans_aux_2016['% Nonveteran Population 18-34 Years Old'] = initial_pa_nonveterans_aux_2016['% Nonveteran Population 18-34 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2016['% Nonveteran Population 35-54 Years Old'] = initial_pa_nonveterans_aux_2016['% Nonveteran Population 35-54 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2016['% Nonveteran Population 55-64 Years Old'] = initial_pa_nonveterans_aux_2016['% Nonveteran Population 55-64 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2016['% Nonveteran Population 65-74 Years Old'] = initial_pa_nonveterans_aux_2016['% Nonveteran Population 65-74 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2016['% Nonveteran Population 75 Years Old & Over'] = initial_pa_nonveterans_aux_2016['% Nonveteran Population 75 Years Old & Over'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2016['Nonveteran Labor Force Participation Rate (%)'] = initial_pa_nonveterans_aux_2016['Nonveteran Labor Force Participation Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2016['Nonveteran Unemployment Rate (%)'] = initial_pa_nonveterans_aux_2016['Nonveteran Unemployment Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2016['% Nonveteran Population With Income Below Poverty Level (Past 12 Months)'] = initial_pa_nonveterans_aux_2016['% Nonveteran Population With Income Below Poverty Level (Past 12 Months)'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2016['% Nonveteran Population With Any Disability'] = initial_pa_nonveterans_aux_2016['% Nonveteran Population With Any Disability'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2016


Year          County  % Nonveteran Population 18-34 Years Old  \
0   2016           ADAMS                                    0.274   
1   2016       ALLEGHENY                                    0.317   
2   2016       ARMSTRONG                                    0.238   
3   2016          BEAVER                                    0.259   
4   2016           BERKS                                    0.301   
5   2016           BLAIR                                    0.269   
6   2016           BUCKS                                    0.253   
7   2016          BUTLER                                    0.269   
8   2016         CAMBRIA                                    0.264   
9   2016          CARBON                                    0.234   
10  2016          CENTRE                                    0.474   
11  2016         CHESTER                                    0.280   
12  2016      CLEARFIELD                                    0.254   
13  2016        COLUMBIA                                    0.349   
14  2016        CRAWFORD                                    0.280   
15  2016      CUMBERLAND                                    0.310   
16  2016         DAUPHIN                                    0.302   
17  2016        DELAWARE                                    0.311   
18  2016            ERIE                                    0.318   
19  2016         FAYETTE                                    0.252   
20  2016        FRANKLIN                                    0.268   
21  2016         INDIANA                                    0.354   
22  2016      LACKAWANNA                                    0.295   
23  2016       LANCASTER                                    0.307   
24  2016        LAWRENCE                                    0.256   
25  2016         LEBANON                                    0.286   
26  2016          LEHIGH                                    0.300   
27  2016         LUZERNE                                    0.284   
28  2016        LYCOMING                                    0.309   
29  2016          MERCER                                    0.272   
30  2016          MONROE                                    0.296   
31  2016      MONTGOMERY                                    0.275   
32  2016     NORTHAMPTON                                    0.290   
33  2016  NORTHUMBERLAND                                    0.248   
34  2016    PHILADELPHIA                                    0.392   
35  2016      SCHUYLKILL                                    0.255   
36  2016        SOMERSET                                    0.259   
37  2016      WASHINGTON                                    0.264   
38  2016    WESTMORELAND                                    0.238   
39  2016            YORK                                    0.283   

    % Nonveteran Population 35-54 Years Old  \
0                                     0.329   
1                                     0.307   
2                                     0.329   
3                                     0.321   
4                                     0.339   
5                                     0.322   
6                                     0.351   
7                                     0.343   
8                                     0.306   
9                                     0.344   
10                                    0.261   
11                                    0.363   
12                                    0.341   
13                                    0.287   
14                                    0.313   
15                                    0.330   
16                                    0.336   
17                                    0.335   
18                                    0.322   
19                                    0.329   
20                                    0.345   
21                                    0.266   
22                                    0.319   
23                                    0.326   

**2019**
-
Please note: 2020 United States Census Bureau was unavailable and as such the closest year prior to the election (2019) was utilized


In [210]:
# Reading in 2019 U.S. Census Bureau auxillary (Nonveterans) dataset
initial_pa_nonveterans_aux_2019 = pd.read_excel("Resources/PA_Nonveterans_Auxillary_2019.xlsx")
initial_pa_nonveterans_aux_2019.head(60)


Unnamed: 0  \
0                                                 NaN   
1                                               Label   
2               Civilian population 18 years and over   
3                                   PERIOD OF SERVICE   
4                 Gulf War (9/2001 or later) veterans   
5                Gulf War (8/1990 to 8/2001) veterans   
6                                Vietnam era veterans   
7                                 Korean War veterans   
8                               World War II veterans   
9                                                 SEX   
10                                               Male   
11                                             Female   
12                                                AGE   
13                                     18 to 34 years   
14                                     35 to 54 years   
15                                     55 to 64 years   
16                                     65 to 74 years   
17                                  75 years and over   
18                 RACE AND HISPANIC OR LATINO ORIGIN   
19                                        White alone   
20                    Black or African American alone   
21            American Indian and Alaska Native alone   
22                                        Asian alone   
23   Native Hawaiian and Other Pacific Islander alone   
24                              Some other race alone   
25                                  Two or more races   
26                   Hispanic or Latino (of any race)   
27                White alone, not Hispanic or Latino   
28  MEDIAN INCOME IN THE PAST 12 MONTHS (IN 2019 I...   
29  Civilian population 18 years and over with income   
30                                               Male   
31                                             Female   
32                             EDUCATIONAL ATTAINMENT   
33              Civilian population 25 years and over   
34                     Less than high school graduate   
35        High school graduate (includes equivalency)   
36                 Some college or associate's degree   
37                        Bachelor's degree or higher   
38                                  EMPLOYMENT STATUS   
39                 Civilian population 18 to 64 years   
40                     Labor force participation rate   
41                Civilian labor force 18 to 64 years   
42                                  Unemployment rate   
43               POVERTY STATUS IN THE PAST 12 MONTHS   
44  Civilian population 18 years and over for whom...   
45   Income in the past 12 months below poverty level   
46  Income in the past 12 months at or above pover...   
47                                  DISABILITY STATUS   
48  Civilian population 18 years and over for whom...   
49                                With any disability   
50                               Without a disability   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
0         Percent Nonveterans            Percent Nonveterans   
1                    Estimate                       Estimate   
2                       91.7%                          93.2%   
3                         NaN                            NaN   
4                         (X)                            (X)   
5                         (X)                            (X)   
6                         (X)                            (X)   
7                         (X)                            (X)   
8                         (X)                            (X)   
9                         NaN                            NaN   
10                      44.5%                          44.4%   
11                      55.5%                          55.6%   
12                        NaN                            NaN   
13                      27.3%                          31.4%   
14                      30.9%                          29.8%   
15                      18.1%                         

In [211]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Three groupings = Total Population, Veteran Population, Nonveteran Population
# % of population groups above that fall into these age categories: 18 to 34, 35 to 54, 55 to 64, 65 to 74 and 75 & Over
# Labor force participation rate
# Unemployment rate
# % of Population group with income below poverty level in the past 12 months
# % of Population group with any disability
initial_pa_nonveterans_aux_2019 = initial_pa_nonveterans_aux_2019.iloc[[13, 14, 15, 16, 17, 40, 42, 45, 49], :]
initial_pa_nonveterans_aux_2019


Unnamed: 0  \
13                                    18 to 34 years   
14                                    35 to 54 years   
15                                    55 to 64 years   
16                                    65 to 74 years   
17                                 75 years and over   
40                    Labor force participation rate   
42                                 Unemployment rate   
45  Income in the past 12 months below poverty level   
49                               With any disability   

   Adams County, Pennsylvania Allegheny County, Pennsylvania  \
13                      27.3%                          31.4%   
14                      30.9%                          29.8%   
15                      18.1%                          17.5%   
16                      14.2%                          12.5%   
17                       9.5%                           8.8%   
40                      78.9%                          80.6%   
42                       1.8%                           4.0%   
45                       6.9%                          10.3%   
49                      15.7%                          14.8%   

   Armstrong County, Pennsylvania Beaver County, Pennsylvania  \
13                          22.6%                       25.5%   
14                          30.5%                       30.3%   
15                          21.2%                       19.2%   
16                          14.7%                       14.5%   
17                          11.1%                       10.4%   
40                          78.5%                       79.6%   
42                           3.1%                        4.1%   
45                           9.3%                        9.9%   
49                          17.8%                       18.8%   

   Berks County, Pennsylvania Blair County, Pennsylvania  \
13                      29.7%                      27.3%   
14                      32.4%                      30.8%   
15                      17.7%                      17.9%   
16                      11.6%                      13.6%   
17                       8.6%                      10.4%   
40                      80.9%                      78.6%   
42                       4.9%                       4.1%   
45                       8.5%                      13.6%   
49                      15.1%                      17.4%   

   Bucks County, Pennsylvania Butler County, Pennsylvania  \
13                      24.6%                       26.7%   
14                      33.2%                       32.6%   
15                      20.6%                       19.4%   
16                      12.8%                       12.7%   
17                       8.7%                        8.7%   
40                      82.9%                       76.6%   
42                       3.8%                        3.6%   
45                       5.2%                        7.7%   
49                      11.3%                       14.5%   

   Cambria County, Pennsylvania  ... Monroe County, Pennsylvania  \
13                        25.4%  ...                       29.0%   
14                        29.5%  ...                       30.9%   
15                        19.1%  ...                       20.0%   
16                        14.9%  ...                       12.6%   
17                        11.0%  ...                        7.4%   
40                        72.2%  ...                       74.6%   
42                         4.0%  ...                        3.2%   
45                        12.8%  ...                       11.4%   
49                        20.6%  ...                       15.3%   

   Montgomery County, Pennsylvania Northampton County, Pennsylvania  \
13                           27.1%                            29.3%   
14                           33.8%                            31.5%   
15                           18.3%                            17.1%   
16          

In [212]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_nonveterans_aux_2019 = initial_pa_nonveterans_aux_2019.T
initial_pa_nonveterans_aux_2019.head()


13              14  \
Unnamed: 0                      18 to 34 years  35 to 54 years   
Adams County, Pennsylvania               27.3%           30.9%   
Allegheny County, Pennsylvania           31.4%           29.8%   
Armstrong County, Pennsylvania           22.6%           30.5%   
Beaver County, Pennsylvania              25.5%           30.3%   

                                            15              16  \
Unnamed: 0                      55 to 64 years  65 to 74 years   
Adams County, Pennsylvania               18.1%           14.2%   
Allegheny County, Pennsylvania           17.5%           12.5%   
Armstrong County, Pennsylvania           21.2%           14.7%   
Beaver County, Pennsylvania              19.2%           14.5%   

                                               17  \
Unnamed: 0                      75 years and over   
Adams County, Pennsylvania                   9.5%   
Allegheny County, Pennsylvania               8.8%   
Armstrong County, Pennsylvania              11.1%   
Beaver County, Pennsylvania                 10.4%   

                                                            40  \
Unnamed: 0                      Labor force participation rate   
Adams County, Pennsylvania                               78.9%   
Allegheny County, Pennsylvania                           80.6%   
Armstrong County, Pennsylvania                           78.5%   
Beaver County, Pennsylvania                              79.6%   

                                               42  \
Unnamed: 0                      Unemployment rate   
Adams County, Pennsylvania                   1.8%   
Allegheny County, Pennsylvania               4.0%   
Armstrong County, Pennsylvania               3.1%   
Beaver County, Pennsylvania                  4.1%   

                                                                              45  \
Unnamed: 0                      Income in the past 12 months below poverty level   
Adams County, Pennsylvania                                                  6.9%   
Allegheny County, Pennsylvania                                             10.3%   
Armstrong County, Pennsylvania                                              9.3%   
Beaver County, Pennsylvania                                                 9.9%   

                                                 49  
Unnamed: 0                      With any disability  
Adams County, Pennsylvania                    15.7%  
Allegheny County, Pennsylvania                14.8%  
Armstrong County, Pennsylvania                17.8%  
Beaver County, Pennsylvania                   18.8%

In [213]:
# Resetting index and renaming to create a 'County' column
initial_pa_nonveterans_aux_2019 = initial_pa_nonveterans_aux_2019.reset_index()
initial_pa_nonveterans_aux_2019.rename(columns={'index': 'County'}, inplace=True)
initial_pa_nonveterans_aux_2019.head()


County              13              14  \
0                      Unnamed: 0  18 to 34 years  35 to 54 years   
1      Adams County, Pennsylvania           27.3%           30.9%   
2  Allegheny County, Pennsylvania           31.4%           29.8%   
3  Armstrong County, Pennsylvania           22.6%           30.5%   
4     Beaver County, Pennsylvania           25.5%           30.3%   

               15              16                 17  \
0  55 to 64 years  65 to 74 years  75 years and over   
1           18.1%           14.2%               9.5%   
2           17.5%           12.5%               8.8%   
3           21.2%           14.7%              11.1%   
4           19.2%           14.5%              10.4%   

                               40                 42  \
0  Labor force participation rate  Unemployment rate   
1                           78.9%               1.8%   
2                           80.6%               4.0%   
3                           78.5%               3.1%   
4                           79.6%               4.1%   

                                                 45                   49  
0  Income in the past 12 months below poverty level  With any disability  
1                                              6.9%                15.7%  
2                                             10.3%                14.8%  
3                                              9.3%                17.8%  
4                                              9.9%                18.8%

In [214]:
# Confirming column data types prior to renaming
print(initial_pa_nonveterans_aux_2019.columns)


Index(['County', 13, 14, 15, 16, 17, 40, 42, 45, 49], dtype='object')


In [215]:
# Converting column data types from integers to strings for renaming
initial_pa_nonveterans_aux_2019.columns = initial_pa_nonveterans_aux_2019.columns.astype(str)
print(initial_pa_nonveterans_aux_2019.columns)


Index(['County', '13', '14', '15', '16', '17', '40', '42', '45', '49'], dtype='object')


In [216]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_nonveterans_aux_2019.replace('N', np.nan, inplace=True)


In [217]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges and all % data types are coverted to floats
initial_pa_nonveterans_aux_2019 = initial_pa_nonveterans_aux_2019.rename(columns={'13': '% Nonveteran Population 18-34 Years Old', '14': '% Nonveteran Population 35-54 Years Old', '15': '% Nonveteran Population 55-64 Years Old',
                                                                         '16': '% Nonveteran Population 65-74 Years Old', '17': '% Nonveteran Population 75 Years Old & Over', '40': 'Nonveteran Labor Force Participation Rate (%)',
                                                                         '42': 'Nonveteran Unemployment Rate (%)', '45': '% Nonveteran Population With Income Below Poverty Level (Past 12 Months)',
                                                                         '49': '% Nonveteran Population With Any Disability'})
initial_pa_nonveterans_aux_2019 = initial_pa_nonveterans_aux_2019.drop(0)
initial_pa_nonveterans_aux_2019 = initial_pa_nonveterans_aux_2019.reset_index(drop=True)
initial_pa_nonveterans_aux_2019['County'] = initial_pa_nonveterans_aux_2019['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_nonveterans_aux_2019['County'] = initial_pa_nonveterans_aux_2019['County'].apply(lambda x: x.upper())
initial_pa_nonveterans_aux_2019.insert(0, 'Year', 2020)
initial_pa_nonveterans_aux_2019['% Nonveteran Population 18-34 Years Old'] = initial_pa_nonveterans_aux_2019['% Nonveteran Population 18-34 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2019['% Nonveteran Population 35-54 Years Old'] = initial_pa_nonveterans_aux_2019['% Nonveteran Population 35-54 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2019['% Nonveteran Population 55-64 Years Old'] = initial_pa_nonveterans_aux_2019['% Nonveteran Population 55-64 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2019['% Nonveteran Population 65-74 Years Old'] = initial_pa_nonveterans_aux_2019['% Nonveteran Population 65-74 Years Old'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2019['% Nonveteran Population 75 Years Old & Over'] = initial_pa_nonveterans_aux_2019['% Nonveteran Population 75 Years Old & Over'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2019['Nonveteran Labor Force Participation Rate (%)'] = initial_pa_nonveterans_aux_2019['Nonveteran Labor Force Participation Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2019['Nonveteran Unemployment Rate (%)'] = initial_pa_nonveterans_aux_2019['Nonveteran Unemployment Rate (%)'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2019['% Nonveteran Population With Income Below Poverty Level (Past 12 Months)'] = initial_pa_nonveterans_aux_2019['% Nonveteran Population With Income Below Poverty Level (Past 12 Months)'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2019['% Nonveteran Population With Any Disability'] = initial_pa_nonveterans_aux_2019['% Nonveteran Population With Any Disability'].str.rstrip('%').astype(float) / 100
initial_pa_nonveterans_aux_2019


Year          County  % Nonveteran Population 18-34 Years Old  \
0   2020           ADAMS                                    0.273   
1   2020       ALLEGHENY                                    0.314   
2   2020       ARMSTRONG                                    0.226   
3   2020          BEAVER                                    0.255   
4   2020           BERKS                                    0.297   
5   2020           BLAIR                                    0.273   
6   2020           BUCKS                                    0.246   
7   2020          BUTLER                                    0.267   
8   2020         CAMBRIA                                    0.254   
9   2020          CARBON                                    0.234   
10  2020          CENTRE                                    0.456   
11  2020         CHESTER                                    0.278   
12  2020      CLEARFIELD                                    0.250   
13  2020        COLUMBIA                                    0.320   
14  2020        CRAWFORD                                    0.272   
15  2020      CUMBERLAND                                    0.301   
16  2020         DAUPHIN                                    0.297   
17  2020        DELAWARE                                    0.304   
18  2020            ERIE                                    0.304   
19  2020         FAYETTE                                    0.250   
20  2020        FRANKLIN                                    0.256   
21  2020         INDIANA                                    0.346   
22  2020      LACKAWANNA                                    0.278   
23  2020       LANCASTER                                    0.302   
24  2020        LAWRENCE                                    0.257   
25  2020         LEBANON                                    0.286   
26  2020          LEHIGH                                    0.299   
27  2020         LUZERNE                                    0.285   
28  2020        LYCOMING                                    0.290   
29  2020          MERCER                                    0.260   
30  2020          MONROE                                    0.290   
31  2020      MONTGOMERY                                    0.271   
32  2020     NORTHAMPTON                                    0.293   
33  2020  NORTHUMBERLAND                                    0.272   
34  2020    PHILADELPHIA                                    0.382   
35  2020      SCHUYLKILL                                    0.253   
36  2020        SOMERSET                                    0.239   
37  2020      WASHINGTON                                    0.255   
38  2020    WESTMORELAND                                    0.236   
39  2020            YORK                                    0.277   

    % Nonveteran Population 35-54 Years Old  \
0                                     0.309   
1                                     0.298   
2                                     0.305   
3                                     0.303   
4                                     0.324   
5                                     0.308   
6                                     0.332   
7                                     0.326   
8                                     0.295   
9                                     0.345   
10                                    0.254   
11                                    0.343   
12                                    0.331   
13                                    0.294   
14                                    0.311   
15                                    0.323   
16                                    0.329   
17                                    0.323   
18                                    0.309   
19                                    0.306   
20                                    0.341   
21                                    0.259   
22                                    0.315   
23                                    0.310   

**Fertility & Income Assistance Data Extraction, Transformation & Loading (2012, 2016 & 2019)**
-
-----------

**2012**
-

In [218]:
# Reading in 2012 U.S. Census Bureau Fertility & Income Assistance dataset
initial_pa_fertility_2012 = pd.read_excel("Resources/PA_Fertility_2012.xlsx")
initial_pa_fertility_2012.head(60)


Unnamed: 0  \
0                                                 NaN   
1                                                 NaN   
2                                               Label   
3                                Women 15 to 50 years   
4                                      15 to 19 years   
5                                      20 to 34 years   
6                                      35 to 50 years   
7                  RACE AND HISPANIC OR LATINO ORIGIN   
8                                            One race   
9                                               White   
10                          Black or African American   
11                  American Indian and Alaska Native   
12                                              Asian   
13         Native Hawaiian and Other Pacific Islander   
14                                    Some other race   
15                                  Two or more races   
16            Hispanic or Latino origin (of any race)   
17                White alone, not Hispanic or Latino   
18                                           NATIVITY   
19                                             Native   
20                                       Foreign born   
21                             EDUCATIONAL ATTAINMENT   
22                     Less than high school graduate   
23        High school graduate (includes equivalency)   
24                 Some college or associate's degree   
25                                  Bachelor's degree   
26                    Graduate or professional degree   
27               POVERTY STATUS IN THE PAST 12 MONTHS   
28  Women 15 to 50 years for whom poverty status i...   
29                 Below 100 percent of poverty level   
30                100 to 199 percent of poverty level   
31            200 percent or more above poverty level   
32                                 LABOR FORCE STATUS   
33                               Women 16 to 50 years   
34                                     In labor force   
35     PUBLIC ASSISTANCE INCOME IN THE PAST 12 MONTHS   
36                               Women 15 to 50 years   
37                  Received public assistance income   
38           Did not receive public assistance income   
39                                    PERCENT IMPUTED   
40                                     Marital status   
41                                          Fertility   

                  Adams County, Pennsylvania  \
0   Women with births in the past 12 months    
1                       Rate per 1,000 women   
2                                   Estimate   
3                                         57   
4                                         82   
5                                        100   
6                                         14   
7                                        NaN   
8                                          N   
9                                         58   
10                                         N   
11                                         N   
12                                         N   
13                                         N   
14                                         N   
15                                         N   
16                                        10   
17                                        59   
18                                       NaN   
19                                        55   
20                                        89   
21                                       NaN   
22                                        80   
23                                        24   
24                                        44   
25                                       144   
26                                        70   
27                                       NaN   
28                                        61   
29                                        76   
30                                        10   
31                                        68   
32     

In [219]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Primary grouping = Population of women with births in the past 12 months:
# Rate per 1,000 Women (within above group) in the following age categories: 15-19 Years Old, 20-34 Years Old, 35-50 Years Old 
# Rate per 1,000 Women (within above group) Received Public Assistance Income
initial_pa_fertility_2012 = initial_pa_fertility_2012.iloc[[4, 5, 6, 37], :]
initial_pa_fertility_2012


Unnamed: 0 Adams County, Pennsylvania  \
4                      15 to 19 years                         82   
5                      20 to 34 years                        100   
6                      35 to 50 years                         14   
37  Received public assistance income                         99   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
4                              11                             38   
5                              83                             90   
6                              19                              5   
37                            184                            155   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
4                           40                         13   
5                          121                        109   
6                           15                         20   
37                          26                        174   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
4                          35                          2   
5                         115                         98   
6                          22                         23   
37                         84                         53   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
4                           48                           32  ...   
5                           90                          111  ...   
6                           32                           12  ...   
37                         176                          378  ...   

   Monroe County, Pennsylvania Montgomery County, Pennsylvania  \
4                            0                               5   
5                          111                              75   
6                            6                              32   
37                          88                             128   

   Northampton County, Pennsylvania Northumberland County, Pennsylvania  \
4                                11                                   0   
5                                79                                 134   
6                                35                                   6   
37                               79                                 121   

   Philadelphia County, Pennsylvania Schuylkill County, Pennsylvania  \
4                                 48                              17   
5                                 73                              84   
6                                 29                              31   
37                               107                             122   

   Somerset County, Pennsylvania Washington County, Pennsylvania  \
4                             41                              20   
5                            131                              97   
6                              5                              11   
37                           390                              57   

   Westmoreland County, Pennsylvania York County, Pennsylvania  
4                                  4                        30  
5                                 74                        76  
6                                 11                        16  
37                                62                       157  

[4 rows x 41 columns]

In [220]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_fertility_2012 = initial_pa_fertility_2012.T
initial_pa_fertility_2012.head()


4               5   \
Unnamed: 0                      15 to 19 years  20 to 34 years   
Adams County, Pennsylvania                  82             100   
Allegheny County, Pennsylvania              11              83   
Armstrong County, Pennsylvania              38              90   
Beaver County, Pennsylvania                 40             121   

                                            6   \
Unnamed: 0                      35 to 50 years   
Adams County, Pennsylvania                  14   
Allegheny County, Pennsylvania              19   
Armstrong County, Pennsylvania               5   
Beaver County, Pennsylvania                 15   

                                                               37  
Unnamed: 0                      Received public assistance income  
Adams County, Pennsylvania                                     99  
Allegheny County, Pennsylvania                                184  
Armstrong County, Pennsylvania                                155  
Beaver County, Pennsylvania                                    26

In [221]:
# Resetting index and renaming to create a 'County' column
initial_pa_fertility_2012 = initial_pa_fertility_2012.reset_index()
initial_pa_fertility_2012.rename(columns={'index': 'County'}, inplace=True)
initial_pa_fertility_2012.head()


County               4               5  \
0                      Unnamed: 0  15 to 19 years  20 to 34 years   
1      Adams County, Pennsylvania              82             100   
2  Allegheny County, Pennsylvania              11              83   
3  Armstrong County, Pennsylvania              38              90   
4     Beaver County, Pennsylvania              40             121   

                6                                 37  
0  35 to 50 years  Received public assistance income  
1              14                                 99  
2              19                                184  
3               5                                155  
4              15                                 26

In [222]:
# Confirming column data types prior to renaming
print(initial_pa_fertility_2012.columns)


Index(['County', 4, 5, 6, 37], dtype='object')


In [223]:
# Converting column data types from integers to strings for renaming
initial_pa_fertility_2012.columns = initial_pa_fertility_2012.columns.astype(str)
print(initial_pa_fertility_2012.columns)


Index(['County', '4', '5', '6', '37'], dtype='object')


In [224]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_fertility_2012.replace('N', np.nan, inplace=True)


In [225]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges
# Converting all values to floats as well
initial_pa_fertility_2012 = initial_pa_fertility_2012.rename(columns={'4': 'Birth Rate Per 1000 Women (15-19 Years Old)', '5': 'Birth Rate Per 1000 Women (20-34 Years Old)', '6': 'Birth Rate Per 1000 Women (35-50 Years Old)',
                                                                         '37': 'Received Public Assistance Income Rate Per 1000 Women (Past 12 Months)'})
initial_pa_fertility_2012 = initial_pa_fertility_2012.drop(0)
initial_pa_fertility_2012 = initial_pa_fertility_2012.reset_index(drop=True)
initial_pa_fertility_2012['County'] = initial_pa_fertility_2012['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_fertility_2012['County'] = initial_pa_fertility_2012['County'].apply(lambda x: x.upper())
initial_pa_fertility_2012.insert(0, 'Year', 2012)
columns_to_floats = ['Birth Rate Per 1000 Women (15-19 Years Old)', 'Birth Rate Per 1000 Women (20-34 Years Old)',
                     'Birth Rate Per 1000 Women (35-50 Years Old)', 'Received Public Assistance Income Rate Per 1000 Women (Past 12 Months)']
initial_pa_fertility_2012[columns_to_floats] = initial_pa_fertility_2012[columns_to_floats].astype(float)
initial_pa_fertility_2012


Year          County  Birth Rate Per 1000 Women (15-19 Years Old)  \
0   2012           ADAMS                                         82.0   
1   2012       ALLEGHENY                                         11.0   
2   2012       ARMSTRONG                                         38.0   
3   2012          BEAVER                                         40.0   
4   2012           BERKS                                         13.0   
5   2012           BLAIR                                         35.0   
6   2012           BUCKS                                          2.0   
7   2012          BUTLER                                         48.0   
8   2012         CAMBRIA                                         32.0   
9   2012          CARBON                                          NaN   
10  2012          CENTRE                                         12.0   
11  2012         CHESTER                                         13.0   
12  2012      CLEARFIELD                                          7.0   
13  2012        COLUMBIA                                          3.0   
14  2012        CRAWFORD                                          7.0   
15  2012      CUMBERLAND                                          3.0   
16  2012         DAUPHIN                                         26.0   
17  2012        DELAWARE                                         24.0   
18  2012            ERIE                                          0.0   
19  2012         FAYETTE                                          7.0   
20  2012        FRANKLIN                                          0.0   
21  2012         INDIANA                                          3.0   
22  2012      LACKAWANNA                                         12.0   
23  2012       LANCASTER                                         27.0   
24  2012        LAWRENCE                                         35.0   
25  2012         LEBANON                                         29.0   
26  2012          LEHIGH                                         24.0   
27  2012         LUZERNE                                         15.0   
28  2012        LYCOMING                                          0.0   
29  2012          MERCER                                          0.0   
30  2012          MONROE                                          0.0   
31  2012      MONTGOMERY                                          5.0   
32  2012     NORTHAMPTON                                         11.0   
33  2012  NORTHUMBERLAND                                          0.0   
34  2012    PHILADELPHIA                                         48.0   
35  2012      SCHUYLKILL                                         17.0   
36  2012        SOMERSET                                         41.0   
37  2012      WASHINGTON                                         20.0   
38  2012    WESTMORELAND                                          4.0   
39  2012            YORK                                         30.0   

    Birth Rate Per 1000 Women (20-34 Years Old)  \
0                                         100.0   
1                                          83.0   
2                                          90.0   
3                                         121.0   
4                                         109.0   
5                                         115.0   
6                                          98.0   
7                                          90.0   
8                                         111.0   
9                                           NaN   
10                                         35.0   
11                                        114.0   
12                                         76.0   
13                                         75.0   
14                                         89.0   
15                                         94.0   
16                                         94.0   
17                                         96.0   
18                                       

**2016**
-

In [226]:
# Reading in 2016 U.S. Census Bureau Fertility & Income Assistance dataset
initial_pa_fertility_2016 = pd.read_excel("Resources/PA_Fertility_2016.xlsx")
initial_pa_fertility_2016.head(60)


Unnamed: 0  \
0                                                 NaN   
1                                                 NaN   
2                                               Label   
3                                Women 15 to 50 years   
4                                      15 to 19 years   
5                                      20 to 34 years   
6                                      35 to 50 years   
7                  RACE AND HISPANIC OR LATINO ORIGIN   
8                                            One race   
9                                               White   
10                          Black or African American   
11                  American Indian and Alaska Native   
12                                              Asian   
13         Native Hawaiian and Other Pacific Islander   
14                                    Some other race   
15                                  Two or more races   
16            Hispanic or Latino origin (of any race)   
17                White alone, not Hispanic or Latino   
18                                           NATIVITY   
19                                             Native   
20                                       Foreign born   
21                             EDUCATIONAL ATTAINMENT   
22                     Less than high school graduate   
23        High school graduate (includes equivalency)   
24                 Some college or associate's degree   
25                                  Bachelor's degree   
26                    Graduate or professional degree   
27               POVERTY STATUS IN THE PAST 12 MONTHS   
28  Women 15 to 50 years for whom poverty status i...   
29                 Below 100 percent of poverty level   
30                100 to 199 percent of poverty level   
31            200 percent or more above poverty level   
32                                 LABOR FORCE STATUS   
33                               Women 16 to 50 years   
34                                     In labor force   
35     PUBLIC ASSISTANCE INCOME IN THE PAST 12 MONTHS   
36                               Women 15 to 50 years   
37                  Received public assistance income   
38           Did not receive public assistance income   
39                                  PERCENT ALLOCATED   
40                                     Marital status   
41                                          Fertility   

                  Adams County, Pennsylvania  \
0   Women with births in the past 12 months    
1                       Rate per 1,000 women   
2                                   Estimate   
3                                         62   
4                                          0   
5                                        139   
6                                         19   
7                                        NaN   
8                                          N   
9                                         57   
10                                         N   
11                                         N   
12                                         N   
13                                         N   
14                                         N   
15                                         N   
16                                       136   
17                                        57   
18                                       NaN   
19                                        54   
20                                       185   
21                                       NaN   
22                                        88   
23                                        41   
24                                        23   
25                                       149   
26                                        52   
27                                       NaN   
28                                        66   
29                                        77   
30                                       119   
31                                        51   
32     

In [227]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Primary grouping = Population of women with births in the past 12 months:
# Rate per 1,000 Women (within above group) in the following age categories: 15-19 Years Old, 20-34 Years Old, 35-50 Years Old 
# Rate per 1,000 Women (within above group) Received Public Assistance Income
initial_pa_fertility_2016 = initial_pa_fertility_2016.iloc[[4, 5, 6, 37], :]
initial_pa_fertility_2016


Unnamed: 0 Adams County, Pennsylvania  \
4                      15 to 19 years                          0   
5                      20 to 34 years                        139   
6                      35 to 50 years                         19   
37  Received public assistance income                          0   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
4                               2                              0   
5                              83                             89   
6                              32                             16   
37                            133                            200   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
4                            0                         18   
5                          117                        107   
6                           19                         18   
37                         238                         43   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
4                          38                         10   
5                         138                         92   
6                          34                         29   
37                        220                        214   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
4                            0                            0  ...   
5                          123                          106  ...   
6                           21                           31  ...   
37                           3                          193  ...   

   Monroe County, Pennsylvania Montgomery County, Pennsylvania  \
4                            0                               0   
5                           53                              90   
6                           22                              33   
37                         120                              54   

   Northampton County, Pennsylvania Northumberland County, Pennsylvania  \
4                                 0                                   0   
5                                75                                 165   
6                                26                                  27   
37                               35                                 176   

   Philadelphia County, Pennsylvania Schuylkill County, Pennsylvania  \
4                                 25                               0   
5                                 74                             106   
6                                 36                              12   
37                               158                              56   

   Somerset County, Pennsylvania Washington County, Pennsylvania  \
4                             26                              20   
5                            103                              79   
6                             45                              25   
37                           597                             178   

   Westmoreland County, Pennsylvania York County, Pennsylvania  
4                                  0                         7  
5                                 76                       105  
6                                 30                        18  
37                                49                        53  

[4 rows x 41 columns]

In [228]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_fertility_2016 = initial_pa_fertility_2016.T
initial_pa_fertility_2016.head()


4               5   \
Unnamed: 0                      15 to 19 years  20 to 34 years   
Adams County, Pennsylvania                   0             139   
Allegheny County, Pennsylvania               2              83   
Armstrong County, Pennsylvania               0              89   
Beaver County, Pennsylvania                  0             117   

                                            6   \
Unnamed: 0                      35 to 50 years   
Adams County, Pennsylvania                  19   
Allegheny County, Pennsylvania              32   
Armstrong County, Pennsylvania              16   
Beaver County, Pennsylvania                 19   

                                                               37  
Unnamed: 0                      Received public assistance income  
Adams County, Pennsylvania                                      0  
Allegheny County, Pennsylvania                                133  
Armstrong County, Pennsylvania                                200  
Beaver County, Pennsylvania                                   238

In [229]:
# Resetting index and renaming to create a 'County' column
initial_pa_fertility_2016 = initial_pa_fertility_2016.reset_index()
initial_pa_fertility_2016.rename(columns={'index': 'County'}, inplace=True)
initial_pa_fertility_2016.head()


County               4               5  \
0                      Unnamed: 0  15 to 19 years  20 to 34 years   
1      Adams County, Pennsylvania               0             139   
2  Allegheny County, Pennsylvania               2              83   
3  Armstrong County, Pennsylvania               0              89   
4     Beaver County, Pennsylvania               0             117   

                6                                 37  
0  35 to 50 years  Received public assistance income  
1              19                                  0  
2              32                                133  
3              16                                200  
4              19                                238

In [230]:
# Confirming column data types prior to renaming
print(initial_pa_fertility_2016.columns)


Index(['County', 4, 5, 6, 37], dtype='object')


In [231]:
# Converting column data types from integers to strings for renaming
initial_pa_fertility_2016.columns = initial_pa_fertility_2016.columns.astype(str)
print(initial_pa_fertility_2016.columns)


Index(['County', '4', '5', '6', '37'], dtype='object')


In [232]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_fertility_2016.replace('N', np.nan, inplace=True)


In [233]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges
# Converting all values to floats as well
initial_pa_fertility_2016 = initial_pa_fertility_2016.rename(columns={'4': 'Birth Rate Per 1000 Women (15-19 Years Old)', '5': 'Birth Rate Per 1000 Women (20-34 Years Old)', '6': 'Birth Rate Per 1000 Women (35-50 Years Old)',
                                                                         '37': 'Received Public Assistance Income Rate Per 1000 Women (Past 12 Months)'})
initial_pa_fertility_2016 = initial_pa_fertility_2016.drop(0)
initial_pa_fertility_2016 = initial_pa_fertility_2016.reset_index(drop=True)
initial_pa_fertility_2016['County'] = initial_pa_fertility_2016['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_fertility_2016['County'] = initial_pa_fertility_2016['County'].apply(lambda x: x.upper())
initial_pa_fertility_2016.insert(0, 'Year', 2016)
columns_to_floats = ['Birth Rate Per 1000 Women (15-19 Years Old)', 'Birth Rate Per 1000 Women (20-34 Years Old)',
                     'Birth Rate Per 1000 Women (35-50 Years Old)', 'Received Public Assistance Income Rate Per 1000 Women (Past 12 Months)']
initial_pa_fertility_2016[columns_to_floats] = initial_pa_fertility_2016[columns_to_floats].astype(float)
initial_pa_fertility_2016


Year          County  Birth Rate Per 1000 Women (15-19 Years Old)  \
0   2016           ADAMS                                          0.0   
1   2016       ALLEGHENY                                          2.0   
2   2016       ARMSTRONG                                          0.0   
3   2016          BEAVER                                          0.0   
4   2016           BERKS                                         18.0   
5   2016           BLAIR                                         38.0   
6   2016           BUCKS                                         10.0   
7   2016          BUTLER                                          0.0   
8   2016         CAMBRIA                                          0.0   
9   2016          CARBON                                        126.0   
10  2016          CENTRE                                          0.0   
11  2016         CHESTER                                          0.0   
12  2016      CLEARFIELD                                          0.0   
13  2016        COLUMBIA                                          4.0   
14  2016        CRAWFORD                                          0.0   
15  2016      CUMBERLAND                                          4.0   
16  2016         DAUPHIN                                         10.0   
17  2016        DELAWARE                                         12.0   
18  2016            ERIE                                          0.0   
19  2016         FAYETTE                                          0.0   
20  2016        FRANKLIN                                         20.0   
21  2016         INDIANA                                          0.0   
22  2016      LACKAWANNA                                         15.0   
23  2016       LANCASTER                                         10.0   
24  2016        LAWRENCE                                          0.0   
25  2016         LEBANON                                         18.0   
26  2016          LEHIGH                                         12.0   
27  2016         LUZERNE                                         14.0   
28  2016        LYCOMING                                          0.0   
29  2016          MERCER                                         33.0   
30  2016          MONROE                                          0.0   
31  2016      MONTGOMERY                                          0.0   
32  2016     NORTHAMPTON                                          0.0   
33  2016  NORTHUMBERLAND                                          0.0   
34  2016    PHILADELPHIA                                         25.0   
35  2016      SCHUYLKILL                                          0.0   
36  2016        SOMERSET                                         26.0   
37  2016      WASHINGTON                                         20.0   
38  2016    WESTMORELAND                                          0.0   
39  2016            YORK                                          7.0   

    Birth Rate Per 1000 Women (20-34 Years Old)  \
0                                         139.0   
1                                          83.0   
2                                          89.0   
3                                         117.0   
4                                         107.0   
5                                         138.0   
6                                          92.0   
7                                         123.0   
8                                         106.0   
9                                          46.0   
10                                         45.0   
11                                         80.0   
12                                         82.0   
13                                         75.0   
14                                         59.0   
15                                         80.0   
16                                        108.0   
17                                         70.0   
18                                       

**2019**
-
Please note: 2020 United States Census Bureau was unavailable and as such the closest year prior to the election (2019) was utilized


In [234]:
# Reading in 2019 U.S. Census Bureau Fertility & Income Assistance dataset
initial_pa_fertility_2019 = pd.read_excel("Resources/PA_Fertility_2019.xlsx")
initial_pa_fertility_2019.head(60)


Unnamed: 0  \
0                                                 NaN   
1                                                 NaN   
2                                               Label   
3                                Women 15 to 50 years   
4                                      15 to 19 years   
5                                      20 to 34 years   
6                                      35 to 50 years   
7                  RACE AND HISPANIC OR LATINO ORIGIN   
8                                            One race   
9                                               White   
10                          Black or African American   
11                  American Indian and Alaska Native   
12                                              Asian   
13         Native Hawaiian and Other Pacific Islander   
14                                    Some other race   
15                                  Two or more races   
16            Hispanic or Latino origin (of any race)   
17                White alone, not Hispanic or Latino   
18                                           NATIVITY   
19                                             Native   
20                                       Foreign born   
21                             EDUCATIONAL ATTAINMENT   
22                     Less than high school graduate   
23        High school graduate (includes equivalency)   
24                 Some college or associate's degree   
25                                  Bachelor's degree   
26                    Graduate or professional degree   
27               POVERTY STATUS IN THE PAST 12 MONTHS   
28  Women 15 to 50 years for whom poverty status i...   
29                 Below 100 percent of poverty level   
30                100 to 199 percent of poverty level   
31            200 percent or more above poverty level   
32                                 LABOR FORCE STATUS   
33                               Women 16 to 50 years   
34                                     In labor force   
35     PUBLIC ASSISTANCE INCOME IN THE PAST 12 MONTHS   
36                               Women 15 to 50 years   
37                  Received public assistance income   
38           Did not receive public assistance income   
39                                  PERCENT ALLOCATED   
40                                     Marital status   
41                                          Fertility   

                 Adams County, Pennsylvania  \
0   Women with births in the past 12 months   
1                      Rate per 1,000 women   
2                                  Estimate   
3                                        44   
4                                         2   
5                                       105   
6                                         3   
7                                       NaN   
8                                         N   
9                                        47   
10                                        N   
11                                        N   
12                                        N   
13                                        N   
14                                       55   
15                                        N   
16                                       23   
17                                       49   
18                                      NaN   
19                                       41   
20                                       95   
21                                      NaN   
22                                       66   
23                                       33   
24                                       18   
25                                       98   
26                                       51   
27                                      NaN   
28                                       46   
29                                       37   
30                                       83   
31                                       41   
32                                      

In [235]:
# Retrieving only rows that contain the desired county summary demographic statistics
# Primary grouping = Population of women with births in the past 12 months:
# Rate per 1,000 Women (within above group) in the following age categories: 15-19 Years Old, 20-34 Years Old, 35-50 Years Old 
# Rate per 1,000 Women (within above group) Received Public Assistance Income
initial_pa_fertility_2019 = initial_pa_fertility_2019.iloc[[4, 5, 6, 37], :]
initial_pa_fertility_2019


Unnamed: 0 Adams County, Pennsylvania  \
4                      15 to 19 years                          2   
5                      20 to 34 years                        105   
6                      35 to 50 years                          3   
37  Received public assistance income                         80   

   Allegheny County, Pennsylvania Armstrong County, Pennsylvania  \
4                              13                              0   
5                              75                             90   
6                              33                              1   
37                            148                              0   

   Beaver County, Pennsylvania Berks County, Pennsylvania  \
4                           10                         16   
5                           89                         92   
6                           11                         20   
37                         134                        146   

   Blair County, Pennsylvania Bucks County, Pennsylvania  \
4                           0                          6   
5                          87                         75   
6                          55                         32   
37                        202                        108   

   Butler County, Pennsylvania Cambria County, Pennsylvania  ...  \
4                            3                            0  ...   
5                          119                          100  ...   
6                           22                           10  ...   
37                           0                          273  ...   

   Monroe County, Pennsylvania Montgomery County, Pennsylvania  \
4                            0                               8   
5                           43                              67   
6                           46                              38   
37                           0                              64   

   Northampton County, Pennsylvania Northumberland County, Pennsylvania  \
4                                 0                                   6   
5                                31                                 141   
6                                37                                  16   
37                               38                                 100   

   Philadelphia County, Pennsylvania Schuylkill County, Pennsylvania  \
4                                 10                               9   
5                                 78                             159   
6                                 31                              25   
37                               136                              64   

   Somerset County, Pennsylvania Washington County, Pennsylvania  \
4                            113                               0   
5                            162                              97   
6                             44                               7   
37                           102                             110   

   Westmoreland County, Pennsylvania York County, Pennsylvania  
4                                 13                         8  
5                                 98                        84  
6                                 31                        25  
37                                17                       162  

[4 rows x 41 columns]

In [236]:
# Transposing the DataFrame's format for process integrity and future merging simplicity
initial_pa_fertility_2019 = initial_pa_fertility_2019.T
initial_pa_fertility_2019.head()


4               5   \
Unnamed: 0                      15 to 19 years  20 to 34 years   
Adams County, Pennsylvania                   2             105   
Allegheny County, Pennsylvania              13              75   
Armstrong County, Pennsylvania               0              90   
Beaver County, Pennsylvania                 10              89   

                                            6   \
Unnamed: 0                      35 to 50 years   
Adams County, Pennsylvania                   3   
Allegheny County, Pennsylvania              33   
Armstrong County, Pennsylvania               1   
Beaver County, Pennsylvania                 11   

                                                               37  
Unnamed: 0                      Received public assistance income  
Adams County, Pennsylvania                                     80  
Allegheny County, Pennsylvania                                148  
Armstrong County, Pennsylvania                                  0  
Beaver County, Pennsylvania                                   134

In [237]:
# Resetting index and renaming to create a 'County' column
initial_pa_fertility_2019 = initial_pa_fertility_2019.reset_index()
initial_pa_fertility_2019.rename(columns={'index': 'County'}, inplace=True)
initial_pa_fertility_2019.head()


County               4               5  \
0                      Unnamed: 0  15 to 19 years  20 to 34 years   
1      Adams County, Pennsylvania               2             105   
2  Allegheny County, Pennsylvania              13              75   
3  Armstrong County, Pennsylvania               0              90   
4     Beaver County, Pennsylvania              10              89   

                6                                 37  
0  35 to 50 years  Received public assistance income  
1               3                                 80  
2              33                                148  
3               1                                  0  
4              11                                134

In [238]:
# Confirming column data types prior to renaming
print(initial_pa_fertility_2019.columns)


Index(['County', 4, 5, 6, 37], dtype='object')


In [239]:
# Converting column data types from integers to strings for renaming
initial_pa_fertility_2019.columns = initial_pa_fertility_2019.columns.astype(str)
print(initial_pa_fertility_2019.columns)


Index(['County', '4', '5', '6', '37'], dtype='object')


In [240]:
# Finding and replacing all 'N' values with 'NaN' across the entire DataFrame for future manipulation
initial_pa_fertility_2019.replace('N', np.nan, inplace=True)


In [241]:
# Further DataFrame cleaning including execution of column renaming, dropping obselete (0) index row and subsequent resetting,
# as well as converting 'County' values to uppercase county names only (removing ' County, Pennsylvania')
# A corresponding year column is also included for future merges
# Converting all values to floats as well
initial_pa_fertility_2019 = initial_pa_fertility_2019.rename(columns={'4': 'Birth Rate Per 1000 Women (15-19 Years Old)', '5': 'Birth Rate Per 1000 Women (20-34 Years Old)', '6': 'Birth Rate Per 1000 Women (35-50 Years Old)',
                                                                         '37': 'Received Public Assistance Income Rate Per 1000 Women (Past 12 Months)'})
initial_pa_fertility_2019 = initial_pa_fertility_2019.drop(0)
initial_pa_fertility_2019 = initial_pa_fertility_2019.reset_index(drop=True)
initial_pa_fertility_2019['County'] = initial_pa_fertility_2019['County'].str.replace(' County, Pennsylvania', '', regex=False)
initial_pa_fertility_2019['County'] = initial_pa_fertility_2019['County'].apply(lambda x: x.upper())
initial_pa_fertility_2019.insert(0, 'Year', 2020)
columns_to_floats = ['Birth Rate Per 1000 Women (15-19 Years Old)', 'Birth Rate Per 1000 Women (20-34 Years Old)',
                     'Birth Rate Per 1000 Women (35-50 Years Old)', 'Received Public Assistance Income Rate Per 1000 Women (Past 12 Months)']
initial_pa_fertility_2019[columns_to_floats] = initial_pa_fertility_2019[columns_to_floats].astype(float)
initial_pa_fertility_2019


Year          County  Birth Rate Per 1000 Women (15-19 Years Old)  \
0   2020           ADAMS                                          2.0   
1   2020       ALLEGHENY                                         13.0   
2   2020       ARMSTRONG                                          0.0   
3   2020          BEAVER                                         10.0   
4   2020           BERKS                                         16.0   
5   2020           BLAIR                                          0.0   
6   2020           BUCKS                                          6.0   
7   2020          BUTLER                                          3.0   
8   2020         CAMBRIA                                          0.0   
9   2020          CARBON                                          0.0   
10  2020          CENTRE                                          0.0   
11  2020         CHESTER                                          0.0   
12  2020      CLEARFIELD                                          0.0   
13  2020        COLUMBIA                                          0.0   
14  2020        CRAWFORD                                          3.0   
15  2020      CUMBERLAND                                          0.0   
16  2020         DAUPHIN                                          0.0   
17  2020        DELAWARE                                          0.0   
18  2020            ERIE                                         10.0   
19  2020         FAYETTE                                         31.0   
20  2020        FRANKLIN                                          0.0   
21  2020         INDIANA                                          0.0   
22  2020      LACKAWANNA                                          6.0   
23  2020       LANCASTER                                         39.0   
24  2020        LAWRENCE                                         33.0   
25  2020         LEBANON                                         15.0   
26  2020          LEHIGH                                          0.0   
27  2020         LUZERNE                                          3.0   
28  2020        LYCOMING                                         22.0   
29  2020          MERCER                                         17.0   
30  2020          MONROE                                          0.0   
31  2020      MONTGOMERY                                          8.0   
32  2020     NORTHAMPTON                                          0.0   
33  2020  NORTHUMBERLAND                                          6.0   
34  2020    PHILADELPHIA                                         10.0   
35  2020      SCHUYLKILL                                          9.0   
36  2020        SOMERSET                                        113.0   
37  2020      WASHINGTON                                          0.0   
38  2020    WESTMORELAND                                         13.0   
39  2020            YORK                                          8.0   

    Birth Rate Per 1000 Women (20-34 Years Old)  \
0                                         105.0   
1                                          75.0   
2                                          90.0   
3                                          89.0   
4                                          92.0   
5                                          87.0   
6                                          75.0   
7                                         119.0   
8                                         100.0   
9                                         109.0   
10                                         61.0   
11                                         68.0   
12                                        176.0   
13                                        135.0   
14                                        116.0   
15                                         82.0   
16                                         91.0   
17                                         87.0   
18                                       

**Combining All Derived Datasets/DataFrames for County Level Attribute Aggregation**
-
-----------

In [242]:
# Due to all County attribute DataFrames having the same index, we can simply outer merge all DataFrames
# from the same year on 'County' and 'Year' sequentially. This will produce a master DataFrame for each year
# (2012, 2016, & 2019). Finally we can concatenate all three vertically with axis = 0 (default)
dfs_2012 = [initial_pa_demographic_2012, initial_pa_education_2012, initial_pa_households_2012, initial_pa_families_2012,
            initial_pa_mc_families_2012, initial_pa_nonfamily_2012, initial_pa_total_aux_2012, initial_pa_veterans_aux_2012,
            initial_pa_nonveterans_aux_2012, initial_pa_fertility_2012]

dfs_2016 = [initial_pa_demographic_2016, initial_pa_education_2016, initial_pa_households_2016, initial_pa_families_2016,
            initial_pa_mc_families_2016, initial_pa_nonfamily_2016, initial_pa_total_aux_2016, initial_pa_veterans_aux_2016,
            initial_pa_nonveterans_aux_2016, initial_pa_fertility_2016]

dfs_2019 = [initial_pa_demographic_2019, initial_pa_education_2019, initial_pa_households_2019, initial_pa_families_2019,
            initial_pa_mc_families_2019, initial_pa_nonfamily_2019, initial_pa_total_aux_2019, initial_pa_veterans_aux_2019,
            initial_pa_nonveterans_aux_2019, initial_pa_fertility_2019]


In [243]:
# 2012 DataFrame merging

# Start with the first DataFrame
merged_dfs_2012 = dfs_2012[0]

# Iteratively merge the remaining DataFrames
for df in dfs_2012[1:]:
    merged_dfs_2012 = pd.merge(merged_dfs_2012, df, on=['County', 'Year'], how='outer')

# Display the final resulting 2012 DataFrame
merged_dfs_2012


Year          County  % Male  % Female  % Male > 18 Years Old  \
0   2012           ADAMS   0.492     0.508                  0.486   
1   2012       ALLEGHENY   0.480     0.520                  0.473   
2   2012       ARMSTRONG   0.496     0.504                  0.493   
3   2012          BEAVER   0.483     0.517                  0.477   
4   2012           BERKS   0.491     0.509                  0.484   
5   2012           BLAIR   0.488     0.512                  0.480   
6   2012           BUCKS   0.490     0.510                  0.484   
7   2012          BUTLER   0.496     0.504                  0.488   
8   2012         CAMBRIA   0.496     0.504                  0.492   
9   2012          CARBON   0.489     0.511                  0.481   
10  2012          CENTRE   0.518     0.482                  0.521   
11  2012         CHESTER   0.491     0.509                  0.485   
12  2012      CLEARFIELD   0.516     0.484                  0.513   
13  2012        COLUMBIA   0.478     0.522                  0.474   
14  2012        CRAWFORD   0.487     0.513                  0.479   
15  2012      CUMBERLAND   0.497     0.503                  0.489   
16  2012         DAUPHIN   0.483     0.517                  0.475   
17  2012        DELAWARE   0.480     0.520                  0.471   
18  2012            ERIE   0.491     0.509                  0.486   
19  2012         FAYETTE   0.494     0.506                  0.490   
20  2012        FRANKLIN   0.487     0.513                  0.481   
21  2012         INDIANA   0.499     0.501                  0.495   
22  2012      LACKAWANNA   0.480     0.520                  0.473   
23  2012       LANCASTER   0.489     0.511                  0.482   
24  2012        LAWRENCE   0.485     0.515                  0.476   
25  2012         LEBANON   0.484     0.516                  0.479   
26  2012          LEHIGH   0.484     0.516                  0.475   
27  2012         LUZERNE   0.493     0.507                  0.486   
28  2012        LYCOMING   0.488     0.512                  0.485   
29  2012          MERCER   0.491     0.509                  0.482   
30  2012          MONROE   0.490     0.510                  0.489   
31  2012      MONTGOMERY   0.485     0.515                  0.478   
32  2012     NORTHAMPTON   0.492     0.508                  0.484   
33  2012  NORTHUMBERLAND   0.510     0.490                  0.507   
34  2012    PHILADELPHIA   0.473     0.527                  0.462   
35  2012      SCHUYLKILL   0.505     0.495                  0.505   
36  2012        SOMERSET   0.517     0.483                  0.518   
37  2012      WASHINGTON   0.488     0.512                  0.483   
38  2012    WESTMORELAND   0.488     0.512                  0.484   
39  2012            YORK   0.493     0.507                  0.488   

    % Female > 18 Years Old  % White  % Black or African American  \
0                     0.514    0.944                        0.020   
1                     0.527    0.831                        0.145   
2                     0.507    0.986                        0.014   
3                     0.523    0.927                        0.076   
4                     0.516    0.875                        0.061   
5                     0.520    0.977                        0.024   
6                     0.516    0.909                        0.045   
7                     0.512    0.976                        0.017   
8                     0.508    0.957                        0.038   
9                     0.519    0.968                        0.030   
10                    0.479    0.907                        0.044   
11                    0.515    0.886                        0.070   
12                    0.487    0.968                        0.027   
13                    0.526    0.976                        0.019   
14                    0.521    0.974                        0.027   
15                    0.511    0.917                        0.044   
1

In [244]:
# 2016 DataFrame merging

# Start with the first DataFrame
merged_dfs_2016 = dfs_2016[0]

# Iteratively merge the remaining DataFrames
for df in dfs_2016[1:]:
    merged_dfs_2016 = pd.merge(merged_dfs_2016, df, on=['County', 'Year'], how='outer')

# Display the final resulting 2016 DataFrame
merged_dfs_2016


Year          County  % Male  % Female  % Male > 18 Years Old  \
0   2016           ADAMS   0.493     0.507                  0.490   
1   2016       ALLEGHENY   0.483     0.517                  0.477   
2   2016       ARMSTRONG   0.497     0.503                  0.493   
3   2016          BEAVER   0.487     0.513                  0.482   
4   2016           BERKS   0.493     0.507                  0.486   
5   2016           BLAIR   0.490     0.510                  0.480   
6   2016           BUCKS   0.491     0.509                  0.485   
7   2016          BUTLER   0.497     0.503                  0.490   
8   2016         CAMBRIA   0.491     0.509                  0.486   
9   2016          CARBON   0.505     0.495                  0.500   
10  2016          CENTRE   0.528     0.472                  0.535   
11  2016         CHESTER   0.492     0.508                  0.487   
12  2016      CLEARFIELD   0.524     0.476                  0.526   
13  2016        COLUMBIA   0.477     0.523                  0.470   
14  2016        CRAWFORD   0.488     0.512                  0.483   
15  2016      CUMBERLAND   0.495     0.505                  0.489   
16  2016         DAUPHIN   0.482     0.518                  0.475   
17  2016        DELAWARE   0.481     0.519                  0.472   
18  2016            ERIE   0.494     0.506                  0.489   
19  2016         FAYETTE   0.493     0.507                  0.488   
20  2016        FRANKLIN   0.498     0.502                  0.487   
21  2016         INDIANA   0.505     0.495                  0.505   
22  2016      LACKAWANNA   0.482     0.518                  0.477   
23  2016       LANCASTER   0.490     0.510                  0.483   
24  2016        LAWRENCE   0.490     0.510                  0.482   
25  2016         LEBANON   0.487     0.513                  0.479   
26  2016          LEHIGH   0.489     0.511                  0.480   
27  2016         LUZERNE   0.491     0.509                  0.489   
28  2016        LYCOMING   0.488     0.512                  0.481   
29  2016          MERCER   0.493     0.507                  0.492   
30  2016          MONROE   0.496     0.504                  0.490   
31  2016      MONTGOMERY   0.486     0.514                  0.479   
32  2016     NORTHAMPTON   0.494     0.506                  0.486   
33  2016  NORTHUMBERLAND   0.511     0.489                  0.507   
34  2016    PHILADELPHIA   0.474     0.526                  0.463   
35  2016      SCHUYLKILL   0.512     0.488                  0.513   
36  2016        SOMERSET   0.516     0.484                  0.519   
37  2016      WASHINGTON   0.489     0.511                  0.483   
38  2016    WESTMORELAND   0.488     0.512                  0.483   
39  2016            YORK   0.493     0.507                  0.488   

    % Female > 18 Years Old  % White  % Black or African American  \
0                     0.510    0.948                        0.019   
1                     0.523    0.828                        0.147   
2                     0.507    0.988                        0.005   
3                     0.518    0.935                        0.074   
4                     0.514    0.892                        0.086   
5                     0.520    0.968                        0.026   
6                     0.515    0.900                        0.049   
7                     0.510    0.969                        0.016   
8                     0.514    0.964                        0.040   
9                     0.500    0.963                        0.031   
10                    0.465    0.898                        0.042   
11                    0.513    0.875                        0.069   
12                    0.474    0.953                        0.034   
13                    0.530    0.951                        0.027   
14                    0.517    0.972                        0.025   
15                    0.511    0.897                        0.049   
1

In [245]:
# 2019 DataFrame merging

# Start with the first DataFrame
merged_dfs_2019 = dfs_2019[0]

# Iteratively merge the remaining DataFrames
for df in dfs_2019[1:]:
    merged_dfs_2019 = pd.merge(merged_dfs_2019, df, on=['County', 'Year'], how='outer')

# Display the final resulting 2019 DataFrame
merged_dfs_2019


Year          County  % Male  % Female  % Male > 18 Years Old  \
0   2020           ADAMS   0.494     0.506                  0.487   
1   2020       ALLEGHENY   0.484     0.516                  0.478   
2   2020       ARMSTRONG   0.501     0.499                  0.498   
3   2020          BEAVER   0.483     0.517                  0.479   
4   2020           BERKS   0.492     0.508                  0.487   
5   2020           BLAIR   0.491     0.509                  0.482   
6   2020           BUCKS   0.491     0.509                  0.486   
7   2020          BUTLER   0.491     0.509                  0.486   
8   2020         CAMBRIA   0.490     0.510                  0.484   
9   2020          CARBON   0.499     0.501                  0.498   
10  2020          CENTRE   0.523     0.477                  0.525   
11  2020         CHESTER   0.494     0.506                  0.488   
12  2020      CLEARFIELD   0.532     0.468                  0.534   
13  2020        COLUMBIA   0.484     0.516                  0.479   
14  2020        CRAWFORD   0.486     0.514                  0.479   
15  2020      CUMBERLAND   0.495     0.505                  0.491   
16  2020         DAUPHIN   0.487     0.513                  0.478   
17  2020        DELAWARE   0.482     0.518                  0.473   
18  2020            ERIE   0.489     0.511                  0.487   
19  2020         FAYETTE   0.493     0.507                  0.494   
20  2020        FRANKLIN   0.492     0.508                  0.485   
21  2020         INDIANA   0.500     0.500                  0.498   
22  2020      LACKAWANNA   0.485     0.515                  0.478   
23  2020       LANCASTER   0.489     0.511                  0.483   
24  2020        LAWRENCE   0.486     0.514                  0.483   
25  2020         LEBANON   0.493     0.507                  0.489   
26  2020          LEHIGH   0.490     0.510                  0.483   
27  2020         LUZERNE   0.494     0.506                  0.491   
28  2020        LYCOMING   0.493     0.507                  0.487   
29  2020          MERCER   0.490     0.510                  0.483   
30  2020          MONROE   0.495     0.505                  0.492   
31  2020      MONTGOMERY   0.486     0.514                  0.480   
32  2020     NORTHAMPTON   0.493     0.507                  0.486   
33  2020  NORTHUMBERLAND   0.506     0.494                  0.504   
34  2020    PHILADELPHIA   0.473     0.527                  0.463   
35  2020      SCHUYLKILL   0.515     0.485                  0.513   
36  2020        SOMERSET   0.522     0.478                  0.524   
37  2020      WASHINGTON   0.491     0.509                  0.486   
38  2020    WESTMORELAND   0.491     0.509                  0.485   
39  2020            YORK   0.496     0.504                  0.488   

    % Female > 18 Years Old  % White  % Black or African American  \
0                     0.513    0.944                        0.030   
1                     0.522    0.821                        0.147   
2                     0.502    0.981                        0.021   
3                     0.521    0.929                        0.084   
4                     0.513    0.824                        0.075   
5                     0.518    0.975                        0.033   
6                     0.514    0.886                        0.051   
7                     0.514    0.976                        0.017   
8                     0.516    0.949                        0.054   
9                     0.502    0.942                        0.029   
10                    0.475    0.898                        0.044   
11                    0.512    0.851                        0.072   
12                    0.466    0.945                        0.039   
13                    0.521    0.960                        0.014   
14                    0.521    0.968                        0.026   
15                    0.509    0.894                        0.061   
1

In [246]:
# Concatenating the resulting 2012, 2016 & 2019 master DataFrames vertically into a single county attribute DataFrame
combined_county_attributes = pd.concat([merged_dfs_2012, merged_dfs_2016, merged_dfs_2019], ignore_index=True)
combined_county_attributes


Year        County  % Male  % Female  % Male > 18 Years Old  \
0    2012         ADAMS   0.492     0.508                  0.486   
1    2012     ALLEGHENY   0.480     0.520                  0.473   
2    2012     ARMSTRONG   0.496     0.504                  0.493   
3    2012        BEAVER   0.483     0.517                  0.477   
4    2012         BERKS   0.491     0.509                  0.484   
..    ...           ...     ...       ...                    ...   
115  2020    SCHUYLKILL   0.515     0.485                  0.513   
116  2020      SOMERSET   0.522     0.478                  0.524   
117  2020    WASHINGTON   0.491     0.509                  0.486   
118  2020  WESTMORELAND   0.491     0.509                  0.485   
119  2020          YORK   0.496     0.504                  0.488   

     % Female > 18 Years Old  % White  % Black or African American  \
0                      0.514    0.944                        0.020   
1                      0.527    0.831                        0.145   
2                      0.507    0.986                        0.014   
3                      0.523    0.927                        0.076   
4                      0.516    0.875                        0.061   
..                       ...      ...                          ...   
115                    0.487    0.954                        0.040   
116                    0.476    0.968                        0.033   
117                    0.514    0.954                        0.048   
118                    0.515    0.963                        0.036   
119                    0.512    0.906                        0.080   

     % American Indian and Alaska Native  % Asian  ...  \
0                                  0.005    0.010  ...   
1                                  0.007    0.036  ...   
2                                  0.006    0.003  ...   
3                                  0.005    0.007  ...   
4                                  0.010    0.018  ...   
..                                   ...      ...  ...   
115                                0.006    0.008  ...   
116                                0.009    0.007  ...   
117                                0.004    0.015  ...   
118                                0.004    0.013  ...   
119                                0.008    0.019  ...   

     % Nonveteran Population 65-74 Years Old  \
0                                      0.104   
1                                      0.091   
2                                      0.108   
3                                      0.109   
4                                      0.089   
..                                       ...   
115                                    0.133   
116                                    0.151   
117                                    0.137   
118                                    0.152   
119                                    0.126   

     % Nonveteran Population 75 Years Old & Over  \
0                                          0.081   
1                                          0.086   
2                                          0.095   
3                                          0.096   
4                                          0.077   
..                                           ...   
115                                        0.094   
116                                        0.111   
117                                        0.101   
118                                        0.100   
119                                        0.083   

     Nonveteran Labor Force Participation Rate (%)  \
0                                            0.801   
1                                            0.783   
2                                            0.750   
3                                            0.786   
4                                            0.796   
..                                             ...   
115                                          0.726   
116             

In [247]:
# Confirming Data Types for our combined county attribute DataFrame
combined_county_attributes.dtypes

Year                                                                        int64
County                                                                     object
% Male                                                                    float64
% Female                                                                  float64
% Male > 18 Years Old                                                     float64
                                                                           ...   
% Nonveteran Population With Any Disability                               float64
Birth Rate Per 1000 Women (15-19 Years Old)                               float64
Birth Rate Per 1000 Women (20-34 Years Old)                               float64
Birth Rate Per 1000 Women (35-50 Years Old)                               float64
Received Public Assistance Income Rate Per 1000 Women (Past 12 Months)    float64
Length: 103, dtype: object

In [248]:
# Confirming Data Types for our combined county attribute DataFrame
combined_county_attributes.dtypes.tolist()


[dtype('int64'),
 dtype('O'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 dtype('float64'),
 

**Combined County Attribute Table Preprocessing and Data Imputation**
-
-----------

In [249]:
# First, exploring DataFrame for missing/'NaN'/Null values
non_null_counts = combined_county_attributes.count()
non_null_counts


Year                                                                      120
County                                                                    120
% Male                                                                    120
% Female                                                                  120
% Male > 18 Years Old                                                     120
                                                                         ... 
% Nonveteran Population With Any Disability                               120
Birth Rate Per 1000 Women (15-19 Years Old)                               119
Birth Rate Per 1000 Women (20-34 Years Old)                               119
Birth Rate Per 1000 Women (35-50 Years Old)                               119
Received Public Assistance Income Rate Per 1000 Women (Past 12 Months)    116
Length: 103, dtype: int64

In [250]:
# Describing our DataFrame regarding missing values
columns_without_120_values = non_null_counts[non_null_counts != 120]
count_columns_without_120_values = len(columns_without_120_values)


print(f"Columns without 120 non-null values: ({count_columns_without_120_values} Total)")
print("------------------------------------------")
for column, count in columns_without_120_values.items():
    print(f"{column}: {count}")


Columns without 120 non-null values: (18 Total)
------------------------------------------
% American Indian and Alaska Native: 113
% Asian: 116
# of Married Couple Families: 101
% Married Couple Families <$10,000: 101
% Married Couple Families $10,000-$14,999: 101
% Married Couple Families $15,000-$24,999: 101
% Married Couple Families $25,000-$34,999: 101
% Married Couple Families $35,000-$49,999: 101
% Married Couple Families $50,000-$74,999: 101
% Married Couple Families $75,000-$99,999: 101
% Married Couple Families $100,000-$149,999: 101
% Married Couple Families $150,000-$199,999: 101
% Married Couple Families $200,000 or More: 101
Mean Married Couple Families Income ($): 43
Birth Rate Per 1000 Women (15-19 Years Old): 119
Birth Rate Per 1000 Women (20-34 Years Old): 119
Birth Rate Per 1000 Women (35-50 Years Old): 119
Received Public Assistance Income Rate Per 1000 Women (Past 12 Months): 116


---

It is important to note that this calculation indicates across our dataset/DataFrame, we have (18) columns/county level attributes that possess 1 or more 'NaN' or Null values. Futhermore, from the list of columns/attributes above that fall into this category - we are able to determine how many values are missing respectively and from which original datasets the missing information is derived from:

**-DPO5: % American Indian and Alaska Native & % Asian metrics as part of the baseline population demographic data**

- As these metrics are a small part of an important dataset that contains demographic data for all counties within this study AND the above output determines only (7) values are missing from the % American Indian and Alaska Native column and only (4) from the % Asian  column, we will impute these (11) missing values via Sklearn SimpleImputer with a mean strategy. We will then normalize the associated percentage columns.
    
**-S1901: 'Married Couple Families' data**

- While this table within the above mentioned dataset proves to have the most 'NaN'/Null values contained, the majority of columns missing data are only missing (19) county values (across 120) in regards to the % of Married Couple Families falling into the predefined income brackets. As the entire dataset contains referential data from other counties AND the potential for reference from the same county via a different year (2012, 2016, or 2019), we will impute the (19) missing values with Sklearn SimpleImputer and a mean strategy for each column. Although our model will already inlcude these metrics for Families, Households and Nonfamily Households, by maintaining/keeping data that represents an entire population segement surveyed by the U.S. Census Bureau (Married Couple Families), we hope to achieve a more representative county sample size. We will also normalize the associated percentage columns.

- The most significant number of 'NaN'/Null values of (77) comes from the 'Mean Married Couple Familes Income ($)' column via this same dataset table. As (77) missing values represents missing data from (77) out of (120) counties AND a mean income metric is included from the other three aforementioned surveyed groups, we will remove this column completely from our dataset/Dataframe rather than imputing (77) values.

- We will also Impute the (19) missing values for the '# of Married Couple Families' column via Sklearn SimpleImputer with a mean strategy. Associated column normalization is not required here as values aren't represented as percentages.

**-S1301: 'Fertility & Income Assistance' data**

- The above output shows the final four columns contaning 'NaN'/Null values are 'Birth Rate Per 1000 Women (15-19 Years Old)', 'Birth Rate Per 1000 Women (20-34 Years Old)', 'Birth Rate Per 1000 Women (35-50 Years Old)' & 'Received Public Assistance Income Rate Per 1000 Women (Past 12 Months)' from the Fertility and Income Assistance dataset. Each column contains (1), (1), (1) and (4) missing values for counties respectively. As this is the primary attribute data associated with healthcare AND there's a very miniscule number of missing values, we will Impute via Sklearn SimpleImputer with a mean strategy here as well. Associated column normalization is not required here as values aren't represented as percentages.


In [251]:
# DP05 Imputation % columns
demographic_columns_to_impute = ['% American Indian and Alaska Native', '% Asian']

demographic_percentage_imputer = SimpleImputer(strategy='mean')
combined_county_attributes[demographic_columns_to_impute] = demographic_percentage_imputer.fit_transform(combined_county_attributes[demographic_columns_to_impute])

# Subsequent Normalization for all % Race Population associated columns
demographic_percentage_columns_to_normalize = ['% White', '% Black or African American', '% American Indian and Alaska Native', '% Asian']
combined_county_attributes[demographic_percentage_columns_to_normalize] = combined_county_attributes[demographic_percentage_columns_to_normalize].div(combined_county_attributes[demographic_percentage_columns_to_normalize].sum(axis=1), axis=0)

# Display
combined_county_attributes


Year        County  % Male  % Female  % Male > 18 Years Old  \
0    2012         ADAMS   0.492     0.508                  0.486   
1    2012     ALLEGHENY   0.480     0.520                  0.473   
2    2012     ARMSTRONG   0.496     0.504                  0.493   
3    2012        BEAVER   0.483     0.517                  0.477   
4    2012         BERKS   0.491     0.509                  0.484   
..    ...           ...     ...       ...                    ...   
115  2020    SCHUYLKILL   0.515     0.485                  0.513   
116  2020      SOMERSET   0.522     0.478                  0.524   
117  2020    WASHINGTON   0.491     0.509                  0.486   
118  2020  WESTMORELAND   0.491     0.509                  0.485   
119  2020          YORK   0.496     0.504                  0.488   

     % Female > 18 Years Old   % White  % Black or African American  \
0                      0.514  0.964249                     0.020429   
1                      0.527  0.815505                     0.142296   
2                      0.507  0.977205                     0.013875   
3                      0.523  0.913300                     0.074877   
4                      0.516  0.907676                     0.063278   
..                       ...       ...                          ...   
115                    0.487  0.946429                     0.039683   
116                    0.476  0.951819                     0.032448   
117                    0.514  0.934378                     0.047013   
118                    0.515  0.947835                     0.035433   
119                    0.512  0.894373                     0.078973   

     % American Indian and Alaska Native   % Asian  ...  \
0                               0.005107  0.010215  ...   
1                               0.006869  0.035329  ...   
2                               0.005946  0.002973  ...   
3                               0.004926  0.006897  ...   
4                               0.010373  0.018672  ...   
..                                   ...       ...  ...   
115                             0.005952  0.007937  ...   
116                             0.008850  0.006883  ...   
117                             0.003918  0.014691  ...   
118                             0.003937  0.012795  ...   
119                             0.007897  0.018756  ...   

     % Nonveteran Population 65-74 Years Old  \
0                                      0.104   
1                                      0.091   
2                                      0.108   
3                                      0.109   
4                                      0.089   
..                                       ...   
115                                    0.133   
116                                    0.151   
117                                    0.137   
118                                    0.152   
119                                    0.126   

     % Nonveteran Population 75 Years Old & Over  \
0                                          0.081   
1                                          0.086   
2                                          0.095   
3                                          0.096   
4                                          0.077   
..                                           ...   
115                                        0.094   
116                                        0.111   
117                                        0.101   
118                                        0.100   
119                                        0.083   

     Nonveteran Labor Force Participation Rate (%)  \
0                                            0.801   
1                                            0.783   
2                                            0.750   
3                                            0.786   
4                                            0.796   
..                                             ...   
115                                          0

In [252]:
# S1901 Imputation % columns
economic_columns_to_impute = ['% Married Couple Families <$10,000', '% Married Couple Families $10,000-$14,999',
                             '% Married Couple Families $15,000-$24,999', '% Married Couple Families $25,000-$34,999',
                             '% Married Couple Families $35,000-$49,999', '% Married Couple Families $50,000-$74,999',
                              '% Married Couple Families $75,000-$99,999', '% Married Couple Families $100,000-$149,999',
                              '% Married Couple Families $150,000-$199,999', '% Married Couple Families $200,000 or More'
                             ]

econmic_percentage_imputer = SimpleImputer(strategy='mean')
combined_county_attributes[economic_columns_to_impute] = econmic_percentage_imputer.fit_transform(combined_county_attributes[economic_columns_to_impute])

# Subsequent Normalization for all income bracket % associated columns for Married Couple Families
combined_county_attributes[economic_columns_to_impute] = combined_county_attributes[economic_columns_to_impute].div(combined_county_attributes[economic_columns_to_impute].sum(axis=1), axis=0)

# Display
combined_county_attributes


Year        County  % Male  % Female  % Male > 18 Years Old  \
0    2012         ADAMS   0.492     0.508                  0.486   
1    2012     ALLEGHENY   0.480     0.520                  0.473   
2    2012     ARMSTRONG   0.496     0.504                  0.493   
3    2012        BEAVER   0.483     0.517                  0.477   
4    2012         BERKS   0.491     0.509                  0.484   
..    ...           ...     ...       ...                    ...   
115  2020    SCHUYLKILL   0.515     0.485                  0.513   
116  2020      SOMERSET   0.522     0.478                  0.524   
117  2020    WASHINGTON   0.491     0.509                  0.486   
118  2020  WESTMORELAND   0.491     0.509                  0.485   
119  2020          YORK   0.496     0.504                  0.488   

     % Female > 18 Years Old   % White  % Black or African American  \
0                      0.514  0.964249                     0.020429   
1                      0.527  0.815505                     0.142296   
2                      0.507  0.977205                     0.013875   
3                      0.523  0.913300                     0.074877   
4                      0.516  0.907676                     0.063278   
..                       ...       ...                          ...   
115                    0.487  0.946429                     0.039683   
116                    0.476  0.951819                     0.032448   
117                    0.514  0.934378                     0.047013   
118                    0.515  0.947835                     0.035433   
119                    0.512  0.894373                     0.078973   

     % American Indian and Alaska Native   % Asian  ...  \
0                               0.005107  0.010215  ...   
1                               0.006869  0.035329  ...   
2                               0.005946  0.002973  ...   
3                               0.004926  0.006897  ...   
4                               0.010373  0.018672  ...   
..                                   ...       ...  ...   
115                             0.005952  0.007937  ...   
116                             0.008850  0.006883  ...   
117                             0.003918  0.014691  ...   
118                             0.003937  0.012795  ...   
119                             0.007897  0.018756  ...   

     % Nonveteran Population 65-74 Years Old  \
0                                      0.104   
1                                      0.091   
2                                      0.108   
3                                      0.109   
4                                      0.089   
..                                       ...   
115                                    0.133   
116                                    0.151   
117                                    0.137   
118                                    0.152   
119                                    0.126   

     % Nonveteran Population 75 Years Old & Over  \
0                                          0.081   
1                                          0.086   
2                                          0.095   
3                                          0.096   
4                                          0.077   
..                                           ...   
115                                        0.094   
116                                        0.111   
117                                        0.101   
118                                        0.100   
119                                        0.083   

     Nonveteran Labor Force Participation Rate (%)  \
0                                            0.801   
1                                            0.783   
2                                            0.750   
3                                            0.786   
4                                            0.796   
..                                             ...   
115                                          0

In [253]:
# S1901 and S1301 Imputation for numerical columns
numerical_columns_to_impute = ['# of Married Couple Families', 'Birth Rate Per 1000 Women (15-19 Years Old)',
                               'Birth Rate Per 1000 Women (20-34 Years Old)', 'Birth Rate Per 1000 Women (35-50 Years Old)',
                               'Received Public Assistance Income Rate Per 1000 Women (Past 12 Months)']

numerical_imputer = SimpleImputer(strategy='mean')
combined_county_attributes[numerical_columns_to_impute] = numerical_imputer.fit_transform(combined_county_attributes[numerical_columns_to_impute])

# Display
combined_county_attributes


Year        County  % Male  % Female  % Male > 18 Years Old  \
0    2012         ADAMS   0.492     0.508                  0.486   
1    2012     ALLEGHENY   0.480     0.520                  0.473   
2    2012     ARMSTRONG   0.496     0.504                  0.493   
3    2012        BEAVER   0.483     0.517                  0.477   
4    2012         BERKS   0.491     0.509                  0.484   
..    ...           ...     ...       ...                    ...   
115  2020    SCHUYLKILL   0.515     0.485                  0.513   
116  2020      SOMERSET   0.522     0.478                  0.524   
117  2020    WASHINGTON   0.491     0.509                  0.486   
118  2020  WESTMORELAND   0.491     0.509                  0.485   
119  2020          YORK   0.496     0.504                  0.488   

     % Female > 18 Years Old   % White  % Black or African American  \
0                      0.514  0.964249                     0.020429   
1                      0.527  0.815505                     0.142296   
2                      0.507  0.977205                     0.013875   
3                      0.523  0.913300                     0.074877   
4                      0.516  0.907676                     0.063278   
..                       ...       ...                          ...   
115                    0.487  0.946429                     0.039683   
116                    0.476  0.951819                     0.032448   
117                    0.514  0.934378                     0.047013   
118                    0.515  0.947835                     0.035433   
119                    0.512  0.894373                     0.078973   

     % American Indian and Alaska Native   % Asian  ...  \
0                               0.005107  0.010215  ...   
1                               0.006869  0.035329  ...   
2                               0.005946  0.002973  ...   
3                               0.004926  0.006897  ...   
4                               0.010373  0.018672  ...   
..                                   ...       ...  ...   
115                             0.005952  0.007937  ...   
116                             0.008850  0.006883  ...   
117                             0.003918  0.014691  ...   
118                             0.003937  0.012795  ...   
119                             0.007897  0.018756  ...   

     % Nonveteran Population 65-74 Years Old  \
0                                      0.104   
1                                      0.091   
2                                      0.108   
3                                      0.109   
4                                      0.089   
..                                       ...   
115                                    0.133   
116                                    0.151   
117                                    0.137   
118                                    0.152   
119                                    0.126   

     % Nonveteran Population 75 Years Old & Over  \
0                                          0.081   
1                                          0.086   
2                                          0.095   
3                                          0.096   
4                                          0.077   
..                                           ...   
115                                        0.094   
116                                        0.111   
117                                        0.101   
118                                        0.100   
119                                        0.083   

     Nonveteran Labor Force Participation Rate (%)  \
0                                            0.801   
1                                            0.783   
2                                            0.750   
3                                            0.786   
4                                            0.796   
..                                             ...   
115                                          0

In [254]:
# Dropping the underepresented 'Mean Married Couple Families Income ($)' columns with only (77) non-null values
final_imputed_county_attributes = combined_county_attributes.drop(columns='Mean Married Couple Families Income ($)')
final_imputed_county_attributes


Year        County  % Male  % Female  % Male > 18 Years Old  \
0    2012         ADAMS   0.492     0.508                  0.486   
1    2012     ALLEGHENY   0.480     0.520                  0.473   
2    2012     ARMSTRONG   0.496     0.504                  0.493   
3    2012        BEAVER   0.483     0.517                  0.477   
4    2012         BERKS   0.491     0.509                  0.484   
..    ...           ...     ...       ...                    ...   
115  2020    SCHUYLKILL   0.515     0.485                  0.513   
116  2020      SOMERSET   0.522     0.478                  0.524   
117  2020    WASHINGTON   0.491     0.509                  0.486   
118  2020  WESTMORELAND   0.491     0.509                  0.485   
119  2020          YORK   0.496     0.504                  0.488   

     % Female > 18 Years Old   % White  % Black or African American  \
0                      0.514  0.964249                     0.020429   
1                      0.527  0.815505                     0.142296   
2                      0.507  0.977205                     0.013875   
3                      0.523  0.913300                     0.074877   
4                      0.516  0.907676                     0.063278   
..                       ...       ...                          ...   
115                    0.487  0.946429                     0.039683   
116                    0.476  0.951819                     0.032448   
117                    0.514  0.934378                     0.047013   
118                    0.515  0.947835                     0.035433   
119                    0.512  0.894373                     0.078973   

     % American Indian and Alaska Native   % Asian  ...  \
0                               0.005107  0.010215  ...   
1                               0.006869  0.035329  ...   
2                               0.005946  0.002973  ...   
3                               0.004926  0.006897  ...   
4                               0.010373  0.018672  ...   
..                                   ...       ...  ...   
115                             0.005952  0.007937  ...   
116                             0.008850  0.006883  ...   
117                             0.003918  0.014691  ...   
118                             0.003937  0.012795  ...   
119                             0.007897  0.018756  ...   

     % Nonveteran Population 65-74 Years Old  \
0                                      0.104   
1                                      0.091   
2                                      0.108   
3                                      0.109   
4                                      0.089   
..                                       ...   
115                                    0.133   
116                                    0.151   
117                                    0.137   
118                                    0.152   
119                                    0.126   

     % Nonveteran Population 75 Years Old & Over  \
0                                          0.081   
1                                          0.086   
2                                          0.095   
3                                          0.096   
4                                          0.077   
..                                           ...   
115                                        0.094   
116                                        0.111   
117                                        0.101   
118                                        0.100   
119                                        0.083   

     Nonveteran Labor Force Participation Rate (%)  \
0                                            0.801   
1                                            0.783   
2                                            0.750   
3                                            0.786   
4                                            0.796   
..                                             ...   
115                                          0

In [255]:
# Finally, confirm impuation process via value counts (all columns should = 120)
final_imputed_county_attributes.count()


Year                                                                      120
County                                                                    120
% Male                                                                    120
% Female                                                                  120
% Male > 18 Years Old                                                     120
                                                                         ... 
% Nonveteran Population With Any Disability                               120
Birth Rate Per 1000 Women (15-19 Years Old)                               120
Birth Rate Per 1000 Women (20-34 Years Old)                               120
Birth Rate Per 1000 Women (35-50 Years Old)                               120
Received Public Assistance Income Rate Per 1000 Women (Past 12 Months)    120
Length: 102, dtype: int64

In [256]:
# Finally, confirm impuation process via value counts (all columns should = 120)
final_imputed_county_attributes.count().tolist()


[120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120,
 120]

In [257]:
# Exporting dataset to CSV
final_imputed_county_attributes.to_csv('Resources/County_Final.csv', index=False)


**Joining County Outcome Table with County Attributes Table**
-
-----------

In [258]:
# Reading in cleaned county election party outcome table ('combined_county_results_clean.csv')
county_party_coutcomes = pd.read_csv('Resources/combined_county_results_clean.csv')
county_party_coutcomes


Year        County  winning_party D:0 R:1
0    2012         ADAMS                      1
1    2012     ALLEGHENY                      0
2    2012     ARMSTRONG                      1
3    2012        BEAVER                      1
4    2012         BERKS                      1
..    ...           ...                    ...
115  2020    SCHUYLKILL                      1
116  2020      SOMERSET                      1
117  2020    WASHINGTON                      1
118  2020  WESTMORELAND                      1
119  2020          YORK                      1

[120 rows x 3 columns]

In [259]:
# Joining county party outcome table with county attributes table
county_joined_with_outcomes = pd.merge(final_imputed_county_attributes, county_party_coutcomes, on=['County', 'Year'], how='outer')
county_joined_with_outcomes


Year        County  % Male  % Female  % Male > 18 Years Old  \
0    2012         ADAMS   0.492     0.508                  0.486   
1    2012     ALLEGHENY   0.480     0.520                  0.473   
2    2012     ARMSTRONG   0.496     0.504                  0.493   
3    2012        BEAVER   0.483     0.517                  0.477   
4    2012         BERKS   0.491     0.509                  0.484   
..    ...           ...     ...       ...                    ...   
115  2020    SCHUYLKILL   0.515     0.485                  0.513   
116  2020      SOMERSET   0.522     0.478                  0.524   
117  2020    WASHINGTON   0.491     0.509                  0.486   
118  2020  WESTMORELAND   0.491     0.509                  0.485   
119  2020          YORK   0.496     0.504                  0.488   

     % Female > 18 Years Old   % White  % Black or African American  \
0                      0.514  0.964249                     0.020429   
1                      0.527  0.815505                     0.142296   
2                      0.507  0.977205                     0.013875   
3                      0.523  0.913300                     0.074877   
4                      0.516  0.907676                     0.063278   
..                       ...       ...                          ...   
115                    0.487  0.946429                     0.039683   
116                    0.476  0.951819                     0.032448   
117                    0.514  0.934378                     0.047013   
118                    0.515  0.947835                     0.035433   
119                    0.512  0.894373                     0.078973   

     % American Indian and Alaska Native   % Asian  ...  \
0                               0.005107  0.010215  ...   
1                               0.006869  0.035329  ...   
2                               0.005946  0.002973  ...   
3                               0.004926  0.006897  ...   
4                               0.010373  0.018672  ...   
..                                   ...       ...  ...   
115                             0.005952  0.007937  ...   
116                             0.008850  0.006883  ...   
117                             0.003918  0.014691  ...   
118                             0.003937  0.012795  ...   
119                             0.007897  0.018756  ...   

     % Nonveteran Population 75 Years Old & Over  \
0                                          0.081   
1                                          0.086   
2                                          0.095   
3                                          0.096   
4                                          0.077   
..                                           ...   
115                                        0.094   
116                                        0.111   
117                                        0.101   
118                                        0.100   
119                                        0.083   

     Nonveteran Labor Force Participation Rate (%)  \
0                                            0.801   
1                                            0.783   
2                                            0.750   
3                                            0.786   
4                                            0.796   
..                                             ...   
115                                          0.726   
116                                          0.702   
117                                          0.774   
118                                          0.786   
119                                          0.799   

     Nonveteran Unemployment Rate (%)  \
0                               0.055   
1                               0.074   
2                               0.085   
3                               0.083   
4                               0.095   
..                                ...   
115                             0.048   
116                     

In [260]:
# Exporting final version of complete county data prior to any scaling via Unsupervised/Supervised Machine Learning
county_joined_with_outcomes.to_csv('Resources/County_Final_With_Outcomes.csv', index=False)


**Unsupervised Learning Segmentation & Dataset Enrichment**
-
-----------

In [261]:
# Scaling the final county attribute table WITHOUT the target/outcome variable (Winning Party - Democrat: 0 Republican: 1)
# Also must remove the 'County' column as it represents  string categorical values
final_imputed_county_attributes_no_county = final_imputed_county_attributes.drop(columns=['County'])
final_imputed_county_attributes_no_county


Year  % Male  % Female  % Male > 18 Years Old  % Female > 18 Years Old  \
0    2012   0.492     0.508                  0.486                    0.514   
1    2012   0.480     0.520                  0.473                    0.527   
2    2012   0.496     0.504                  0.493                    0.507   
3    2012   0.483     0.517                  0.477                    0.523   
4    2012   0.491     0.509                  0.484                    0.516   
..    ...     ...       ...                    ...                      ...   
115  2020   0.515     0.485                  0.513                    0.487   
116  2020   0.522     0.478                  0.524                    0.476   
117  2020   0.491     0.509                  0.486                    0.514   
118  2020   0.491     0.509                  0.485                    0.515   
119  2020   0.496     0.504                  0.488                    0.512   

      % White  % Black or African American  \
0    0.964249                     0.020429   
1    0.815505                     0.142296   
2    0.977205                     0.013875   
3    0.913300                     0.074877   
4    0.907676                     0.063278   
..        ...                          ...   
115  0.946429                     0.039683   
116  0.951819                     0.032448   
117  0.934378                     0.047013   
118  0.947835                     0.035433   
119  0.894373                     0.078973   

     % American Indian and Alaska Native   % Asian  \
0                               0.005107  0.010215   
1                               0.006869  0.035329   
2                               0.005946  0.002973   
3                               0.004926  0.006897   
4                               0.010373  0.018672   
..                                   ...       ...   
115                             0.005952  0.007937   
116                             0.008850  0.006883   
117                             0.003918  0.014691   
118                             0.003937  0.012795   
119                             0.007897  0.018756   

     % High School Graduate (18-24)  ...  \
0                             0.361  ...   
1                             0.257  ...   
2                             0.479  ...   
3                             0.291  ...   
4                             0.367  ...   
..                              ...  ...   
115                           0.427  ...   
116                           0.520  ...   
117                           0.378  ...   
118                           0.326  ...   
119                           0.384  ...   

     % Nonveteran Population 65-74 Years Old  \
0                                      0.104   
1                                      0.091   
2                                      0.108   
3                                      0.109   
4                                      0.089   
..                                       ...   
115                                    0.133   
116                                    0.151   
117                                    0.137   
118                                    0.152   
119                                    0.126   

     % Nonveteran Population 75 Years Old & Over  \
0                                          0.081   
1                                          0.086   
2                                          0.095   
3                                          0.096   
4                                          0.077   
..                                           ...   
115                                        0.094   
116                                        0.111   
117                                        0.101   
118                                        0.100   
119                                        0.083   

     Nonveteran Labor Force Participation Rate (%)  \
0                                            0.801   
1              

In [262]:
# Scaling the final county attribute table WITHOUT the target/outcome variable (Winning Party - Democrat: 0 Republican: 1)
scaler = StandardScaler()
scaled_final_imputed_county_attributes_no_county = scaler.fit_transform(final_imputed_county_attributes_no_county)
scaled_final_imputed_county_attributes_no_county


array([[-1.22474487, -0.09955146,  0.09955146, ...,  0.1365429 ,
        -0.77104402, -0.22365943],
       [-1.22474487, -1.19385758,  1.19385758, ..., -0.48982056,
        -0.38356835,  0.63912695],
       [-1.22474487,  0.26521725, -0.26521725, ..., -0.2319062 ,
        -1.46850023,  0.34476454],
       ...,
       [ 1.22474487, -0.19074364,  0.19074364, ...,  0.02600817,
        -1.31350996, -0.11200472],
       [ 1.22474487, -0.19074364,  0.19074364, ...,  0.06285308,
         0.54637326, -1.05599453],
       [ 1.22474487,  0.26521725, -0.26521725, ..., -0.45297565,
         0.08140245,  0.41581753]])

In [263]:
# Creating a DataFrame with the scaled data
scaled_final_imputed_county_attributes_no_county_df = pd.DataFrame(scaled_final_imputed_county_attributes_no_county,
                                                                   columns=final_imputed_county_attributes_no_county.columns)
scaled_final_imputed_county_attributes_no_county_df


Year    % Male  % Female  % Male > 18 Years Old  \
0   -1.224745 -0.099551  0.099551              -0.144893   
1   -1.224745 -1.193858  1.193858              -1.102662   
2   -1.224745  0.265217 -0.265217               0.370828   
3   -1.224745 -0.920281  0.920281              -0.807964   
4   -1.224745 -0.190744  0.190744              -0.292242   
..        ...       ...       ...                    ...   
115  1.224745  1.997869 -1.997869               1.844318   
116  1.224745  2.636214 -2.636214               2.654738   
117  1.224745 -0.190744  0.190744              -0.144893   
118  1.224745 -0.190744  0.190744              -0.218568   
119  1.224745  0.265217 -0.265217               0.002456   

     % Female > 18 Years Old   % White  % Black or African American  \
0                   0.144893  0.737739                    -0.676706   
1                   1.102662 -0.845226                     0.885859   
2                  -0.370828  0.875619                    -0.760739   
3                   0.807964  0.195531                     0.021416   
4                   0.292242  0.135678                    -0.127303   
..                       ...       ...                          ...   
115                -1.844318  0.548088                    -0.429840   
116                -2.654738  0.605455                    -0.522596   
117                 0.144893  0.419843                    -0.335854   
118                 0.218568  0.563051                    -0.484327   
119                -0.002456 -0.005898                     0.073941   

     % American Indian and Alaska Native   % Asian  \
0                              -0.391053 -0.698111   
1                               0.042635  0.474216   
2                              -0.184517 -1.036131   
3                              -0.435633 -0.852992   
4                               0.904968 -0.303308   
..                                   ...       ...   
115                            -0.183065 -0.804447   
116                             0.529937 -0.853625   
117                            -0.683798 -0.489127   
118                            -0.679053 -0.577641   
119                             0.295592 -0.299388   

     % High School Graduate (18-24)  ...  \
0                         -0.028583  ...   
1                         -1.250192  ...   
2                          1.357474  ...   
3                         -0.850820  ...   
4                          0.041895  ...   
..                              ...  ...   
115                        0.746670  ...   
116                        1.839070  ...   
117                        0.171104  ...   
118                       -0.439701  ...   
119                        0.241581  ...   

     % Nonveteran Population 65-74 Years Old  \
0                                  -0.538015   
1                                  -1.262802   
2                                  -0.315004   
3                                  -0.259251   
4                                  -1.374308   
..                                       ...   
115                                 1.078818   
116                                 2.082369   
117                                 1.301829   
118                                 2.138122   
119                                 0.688548   

     % Nonveteran Population 75 Years Old & Over  \
0                                      -0.528495   
1                                      -0.135074   
2                                       0.573083   
3                                       0.651767   
4                                      -0.843232   
..                                           ...   
115                                     0.494399   
116                                     1.832029   
117                                     1.045188   
118                                     0.966504   
119                                    -0.371127   

     Nonveteran Labor Force Participation Rate (%)  \
0

In [264]:
# Principal Component Analysis for dimensionality reduction of scaled data (30 components results in ~>95% explained variance ratio)
pca = PCA(n_components=30, random_state=0)
scaled_pca_data = pca.fit_transform(scaled_final_imputed_county_attributes_no_county_df)
print(f'Explained Variance Ratio: {sum(pca.explained_variance_ratio_)}')


Explained Variance Ratio: 0.9530723089750718


In [265]:
# Creating a new DataFrame with PCA data
scaled_pca_df = pd.DataFrame(scaled_pca_data, columns=["PCA1", "PCA2", "PCA3", "PCA4", "PCA5", "PCA6", "PCA7",
                                                       "PCA8", "PCA9", "PCA10", "PCA11", "PCA12", "PCA13", "PCA14", 
                                                       "PCA15", "PCA16", "PCA17", "PCA18", "PCA19", "PCA20", "PCA21", 
                                                       "PCA22", "PCA23", "PCA24", "PCA25", "PCA26", "PCA27", "PCA28", 
                                                       "PCA29", "PCA30"])
scaled_pca_df


PCA1      PCA2      PCA3      PCA4      PCA5      PCA6      PCA7  \
0   -1.220543 -2.650239 -4.226980  2.832132  2.844367 -0.088180 -0.363029   
1    2.658206  5.462741 -1.965351 -2.013644 -1.300384 -2.486122  1.828332   
2   -8.958764  0.423010 -1.356897 -1.365840 -3.561745  0.582613  2.006504   
3   -4.223753 -0.674939 -2.936526 -0.686120 -1.616674 -2.473770  0.616003   
4   -2.730467  2.469756 -4.297313  1.787232  1.239753  1.029241  0.982666   
..        ...       ...       ...       ...       ...       ...       ...   
115 -2.282243 -4.969901  2.059689  0.572913  1.143632  1.710334  1.016356   
116 -5.347174 -5.195419  4.089941 -0.096863  0.074844  4.382755  3.432463   
117  5.511346 -2.518372  2.030535 -2.766796 -0.902097 -0.214796 -1.906393   
118  3.375545 -3.823598  1.693324 -2.719202  0.088765 -2.393045  0.494310   
119  5.740954 -2.182621 -0.327173  0.914296  1.670997  1.098430 -1.253818   

         PCA8      PCA9     PCA10  ...     PCA21     PCA22     PCA23  \
0   -0.541284 -0.588251  2.020962  ...  0.018784 -1.806501 -0.225332   
1    3.548256 -2.624384 -0.521557  ... -0.572935 -0.117636 -0.580654   
2   -2.813614  0.624405 -0.885881  ... -0.695176  0.201331  0.335493   
3   -0.086681 -1.149728  0.265770  ... -0.331090  0.126415 -0.848719   
4    0.216882  0.024914  0.897717  ... -0.343778  0.401807  0.487343   
..        ...       ...       ...  ...       ...       ...       ...   
115  0.799515  0.759724  1.956680  ... -0.564521  0.954424  0.861859   
116  1.938479 -1.681425  1.155796  ... -1.204209 -0.433852  0.512079   
117 -0.973719  0.607461  0.631745  ... -1.707474 -1.185151 -0.044671   
118  1.407597 -1.385893  0.546170  ... -1.499379  0.685008  0.012629   
119  1.364035 -0.242867 -0.929259  ... -1.262103 -0.245583  0.983564   

        PCA24     PCA25     PCA26     PCA27     PCA28     PCA29     PCA30  
0   -0.831585  1.523588 -0.618654  1.341579  0.023301  0.137271  0.660737  
1   -0.440109  0.530133  0.822689  0.229181 -0.195736 -0.317751  0.400293  
2   -0.985781  0.492323  0.003082 -1.340281 -0.380461  0.792108 -0.441984  
3   -0.352324 -0.070065 -0.841973  0.944907 -0.469644  0.117054 -0.918419  
4    0.481445  0.185756  0.070464  0.190350  0.332882  0.519049 -0.077251  
..        ...       ...       ...       ...       ...       ...       ...  
115 -0.178525 -0.474849 -0.741148  0.171595  0.140371  1.309219 -0.352059  
116 -2.150850 -0.390801  0.575654 -0.727950 -0.879708  0.141714 -0.637493  
117  0.224726  1.946552  0.393153 -0.633717  0.103932  0.531512 -0.035536  
118  1.204141  1.003089  0.117718  0.974957  0.156658  0.437216  0.741619  
119 -0.727889 -0.569303  0.224882  0.300549  1.274374 -0.421791  0.076689  

[120 rows x 30 columns]

In [266]:
# Finding best value for K in Kmeans via elbow method
k = list(range(1, 11))
inertia = []
for i in k:
    model = KMeans(n_clusters=i, random_state=0)
    model.fit(scaled_pca_df)
    inertia.append(model.inertia_)

elbow_data_pca = {
    "k": k,
    "inertia": inertia
}

df_elbow_data_pca = pd.DataFrame(elbow_data_pca)
df_elbow_data_pca


/Applications/anaconda3/envs/Eclipse/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1412: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/Applications/anaconda3/envs/Eclipse/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1412: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/Applications/anaconda3/envs/Eclipse/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1412: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/Applications/anaconda3/envs/Eclipse/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1412: FutureW

k       inertia
0   1  11551.236385
1   2   8559.832737
2   3   7458.897082
3   4   6472.896299
4   5   5991.340623
5   6   5360.024405
6   7   4945.464106
7   8   4714.697602
8   9   4414.210502
9  10   4295.491462

In [267]:
# Visualize Elbow data (shows optimal value of k = 4)
elbow_plot_pca = df_elbow_data_pca.hvplot.line(x="k", y="inertia", title="Elbow Curve Using PCA(30) w/ Scaled Data", xticks=k)
elbow_plot_pca


:Curve   [k]   (inertia)

In [268]:
# Segment data with the determined number of clusters (k) = 4
model = KMeans(n_clusters=4, random_state=0)
model.fit(scaled_pca_df)
segment_predictions = model.predict(scaled_pca_df)
print(segment_predictions)


/Applications/anaconda3/envs/Eclipse/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1412: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)


[1 1 0 0 0 0 2 1 0 0 1 2 0 0 0 1 1 1 0 0 0 0 0 1 0 0 1 0 0 0 1 2 1 0 3 0 0
 1 0 1 1 1 0 1 1 0 2 1 0 0 1 2 0 1 0 1 1 2 0 0 1 0 0 1 0 1 1 0 0 0 1 2 1 0
 3 0 0 1 1 1 1 2 1 1 1 1 2 2 0 1 1 2 0 1 0 2 1 2 1 0 1 1 1 1 0 1 1 1 1 1 1
 2 2 0 3 0 0 1 1 1]


In [269]:
# Enrich master county dataset that has target/label outcomes included with segment predictions
ultimate_county_df = county_joined_with_outcomes.copy()
ultimate_county_df['Segment'] = segment_predictions
ultimate_county_df


Year        County  % Male  % Female  % Male > 18 Years Old  \
0    2012         ADAMS   0.492     0.508                  0.486   
1    2012     ALLEGHENY   0.480     0.520                  0.473   
2    2012     ARMSTRONG   0.496     0.504                  0.493   
3    2012        BEAVER   0.483     0.517                  0.477   
4    2012         BERKS   0.491     0.509                  0.484   
..    ...           ...     ...       ...                    ...   
115  2020    SCHUYLKILL   0.515     0.485                  0.513   
116  2020      SOMERSET   0.522     0.478                  0.524   
117  2020    WASHINGTON   0.491     0.509                  0.486   
118  2020  WESTMORELAND   0.491     0.509                  0.485   
119  2020          YORK   0.496     0.504                  0.488   

     % Female > 18 Years Old   % White  % Black or African American  \
0                      0.514  0.964249                     0.020429   
1                      0.527  0.815505                     0.142296   
2                      0.507  0.977205                     0.013875   
3                      0.523  0.913300                     0.074877   
4                      0.516  0.907676                     0.063278   
..                       ...       ...                          ...   
115                    0.487  0.946429                     0.039683   
116                    0.476  0.951819                     0.032448   
117                    0.514  0.934378                     0.047013   
118                    0.515  0.947835                     0.035433   
119                    0.512  0.894373                     0.078973   

     % American Indian and Alaska Native   % Asian  ...  \
0                               0.005107  0.010215  ...   
1                               0.006869  0.035329  ...   
2                               0.005946  0.002973  ...   
3                               0.004926  0.006897  ...   
4                               0.010373  0.018672  ...   
..                                   ...       ...  ...   
115                             0.005952  0.007937  ...   
116                             0.008850  0.006883  ...   
117                             0.003918  0.014691  ...   
118                             0.003937  0.012795  ...   
119                             0.007897  0.018756  ...   

     Nonveteran Labor Force Participation Rate (%)  \
0                                            0.801   
1                                            0.783   
2                                            0.750   
3                                            0.786   
4                                            0.796   
..                                             ...   
115                                          0.726   
116                                          0.702   
117                                          0.774   
118                                          0.786   
119                                          0.799   

     Nonveteran Unemployment Rate (%)  \
0                               0.055   
1                               0.074   
2                               0.085   
3                               0.083   
4                               0.095   
..                                ...   
115                             0.048   
116                             0.026   
117                             0.049   
118                             0.042   
119                             0.037   

     % Nonveteran Population With Income Below Poverty Level (Past 12 Months)  \
0                                                0.086                          
1                                                0.118                          
2                                                0.122                          
3                                                0.100                          
4                                                0.127                         

In [270]:
# Export final county dataset with segmentation column included for model training (executed in another notebook)
ultimate_county_df.to_csv('Resources/County_Final_With_Outcomes_And_Segments.csv', index=False)
